In [35]:
!pip install yfinance

  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 949.2/949.2 kB 24.6 MB/s  0:00:00
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.0/3.0 MB 38.2 MB/s  0:00:00
  DEPRECATION: Building 'multitasking' using the legacy setup.py bdist_wheel mechanism, which will be removed in a future version. pip 25.3 will enforce this behaviour change. A possible replacement is to use the standardized build interface by setting the `--use-pep517` option, (possibly combined with `--no-build-isolation`), or adding a `pyproject.toml` file to the source tree of 'multitasking'. Discussion can be found at https://github.com/pypa/pip/issues/6334
  Created wheel for multitasking: filename=multitasking-0.0.12-py3-none-any.whl size=15548 sha256=963aff327d554007f15adc9f6a1352a427cfa09144f0933e5e539ebd98ce4a75
  Stored in directory: /Users/w/Library

# Data

In [16]:
import requests
import pandas as pd
from bs4 import BeautifulSoup
from datetime import datetime
import re

def fetch_sp500_data():
    """
    Fetches and combines S&P 500 company data from Wikipedia tables.
    Returns a comprehensive DataFrame with company details and date removed info.
    """
    
    # URL of the Wikipedia page
    url = "https://en.wikipedia.org/wiki/List_of_S%26P_500_companies"
    
    try:
        # Fetch the page
        response = requests.get(url)
        response.raise_for_status()
        
        # Parse HTML
        soup = BeautifulSoup(response.content, 'html.parser')
        
        # Find all tables on the page
        tables = soup.find_all('table', class_='wikitable')
        
        if len(tables) < 2:
            print("Warning: Expected at least 2 tables, found", len(tables))
        
        # The first table contains the main S&P 500 companies list
        main_table = tables[0]
        
        # Extract main company data
        main_data = []
        rows = main_table.find_all('tr')[1:]  # Skip header row
        
        for row in rows:
            cols = row.find_all(['td', 'th'])
            if len(cols) >= 7:  # Ensure we have enough columns
                # Extract text and clean it
                row_data = []
                for col in cols:
                    text = col.get_text().strip()
                    # Remove citations like [1], [2] etc.
                    text = re.sub(r'\[\d+\]', '', text)
                    row_data.append(text)
                
                # Only add if we have enough data
                if len(row_data) >= 7:
                    main_data.append({
                        'Symbol': row_data[0],
                        'Security': row_data[1],
                        'GICS_Sector': row_data[2],
                        'GICS_Sub_Industry': row_data[3],
                        'Headquarters_Location': row_data[4],
                        'Date_Added': row_data[5],
                        'CIK': row_data[6],
                        'Founded': row_data[7] if len(row_data) > 7 else 'N/A'
                    })
        
        # Create DataFrame for main data
        main_df = pd.DataFrame(main_data)
        
        # The second table contains changes/removals
        changes_data = []
        if len(tables) > 1:
            changes_table = tables[1]
            changes_rows = changes_table.find_all('tr')[1:]  # Skip header
            
            for row in changes_rows:
                cols = row.find_all(['td', 'th'])
                if len(cols) >= 5:  # Date, Added (ticker & security), Removed (ticker & security), Reason
                    row_data = []
                    for col in cols:
                        text = col.get_text().strip()
                        text = re.sub(r'\[\d+\]', '', text)  # Remove citations
                        row_data.append(text)
                    
                    if len(row_data) >= 5:
                        # Extract removed company ticker if available
                        removed_ticker = row_data[3] if len(row_data) > 3 else ''
                        if removed_ticker and removed_ticker != '—':
                            changes_data.append({
                                'Date_Removed': row_data[0],
                                'Symbol': removed_ticker,
                                'Reason_for_Removal': row_data[4] if len(row_data) > 4 else 'N/A'
                            })
        
        # Create DataFrame for changes
        changes_df = pd.DataFrame(changes_data)
        
        # Merge the dataframes on Symbol to get removal dates
        if not changes_df.empty:
            # Left join to keep all companies, adding removal info where available
            combined_df = main_df.merge(changes_df[['Symbol', 'Date_Removed', 'Reason_for_Removal']], 
                                      on='Symbol', how='left')
        else:
            # If no changes data, add empty columns
            combined_df = main_df.copy()
            combined_df['Date_Removed'] = None
            combined_df['Reason_for_Removal'] = None
        
        # Reorder columns as requested
        column_order = [
            'Symbol', 'Security', 'GICS_Sector', 'GICS_Sub_Industry', 
            'CIK', 'Founded', 'Date_Added', 'Date_Removed', 'Reason_for_Removal'
        ]
        
        # Only include columns that exist
        available_columns = [col for col in column_order if col in combined_df.columns]
        combined_df = combined_df[available_columns]
        
        return combined_df
        
    except Exception as e:
        print(f"Error fetching data: {e}")
        return None

fetch_sp500_data()

Error fetching data: HTTPSConnectionPool(host='en.wikipedia.org', port=443): Read timed out. (read timeout=None)


In [30]:
import pandas as pd
from bs4 import BeautifulSoup
import re

# HTML table data (the provided HTML content)
html_content = """<table class="wikitable sortable mw-collapsible sticky-header jquery-tablesorter mw-made-collapsible" id="constituents">

<thead><tr>
<th class="headerSort" tabindex="0" role="columnheader button" title="Sort ascending"><a href="/wiki/Ticker_symbol" title="Ticker symbol">Symbol</a>
</th>
<th class="headerSort" tabindex="0" role="columnheader button" title="Sort ascending">Security</th>
<th class="headerSort" tabindex="0" role="columnheader button" title="Sort ascending"><a href="/wiki/Global_Industry_Classification_Standard" title="Global Industry Classification Standard">GICS</a> Sector</th>
<th class="headerSort" tabindex="0" role="columnheader button" title="Sort ascending">GICS Sub-Industry</th>
<th class="headerSort" tabindex="0" role="columnheader button" title="Sort ascending">Headquarters Location</th>
<th class="headerSort" tabindex="0" role="columnheader button" title="Sort ascending">Date added</th>
<th class="headerSort" tabindex="0" role="columnheader button" title="Sort ascending"><a href="/wiki/Central_Index_Key" title="Central Index Key">CIK</a></th>
<th class="headerSort" tabindex="0" role="columnheader button" title="Sort ascending"><button type="button" class="mw-collapsible-toggle mw-collapsible-toggle-default" aria-expanded="true" tabindex="0"><span class="mw-collapsible-text">hide</span></button>Founded
</th></tr></thead><tbody>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:MMM">MMM</a>
</td>
<td><a href="/wiki/3M" title="3M">3M</a></td>
<td>Industrials</td>
<td>Industrial Conglomerates</td>
<td><a href="/wiki/Saint_Paul,_Minnesota" title="Saint Paul, Minnesota">Saint Paul, Minnesota</a></td>
<td>1957-03-04</td>
<td>0000066740</td>
<td>1902
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:AOS">AOS</a>
</td>
<td><a href="/wiki/A._O._Smith" title="A. O. Smith">A. O. Smith</a></td>
<td>Industrials</td>
<td>Building Products</td>
<td><a href="/wiki/Milwaukee" title="Milwaukee">Milwaukee</a>, Wisconsin</td>
<td>2017-07-26</td>
<td>0000091142</td>
<td>1916
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:ABT">ABT</a>
</td>
<td><a href="/wiki/Abbott_Laboratories" title="Abbott Laboratories">Abbott Laboratories</a></td>
<td>Health Care</td>
<td>Health Care Equipment</td>
<td><a href="/wiki/North_Chicago,_Illinois" title="North Chicago, Illinois">North Chicago, Illinois</a></td>
<td>1957-03-04</td>
<td>0000001800</td>
<td>1888
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:ABBV">ABBV</a>
</td>
<td><a href="/wiki/AbbVie" title="AbbVie">AbbVie</a></td>
<td>Health Care</td>
<td>Biotechnology</td>
<td><a href="/wiki/North_Chicago,_Illinois" title="North Chicago, Illinois">North Chicago, Illinois</a></td>
<td>2012-12-31</td>
<td>0001551152</td>
<td>2013 (1888)
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:ACN">ACN</a>
</td>
<td><a href="/wiki/Accenture" title="Accenture">Accenture</a></td>
<td>Information Technology</td>
<td>IT Consulting &amp; Other Services</td>
<td><a href="/wiki/Dublin" title="Dublin">Dublin</a>, Ireland</td>
<td>2011-07-06</td>
<td>0001467373</td>
<td>1989
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/adbe">ADBE</a>
</td>
<td><a href="/wiki/Adobe_Inc." title="Adobe Inc.">Adobe Inc.</a></td>
<td>Information Technology</td>
<td>Application Software</td>
<td><a href="/wiki/San_Jose,_California" title="San Jose, California">San Jose, California</a></td>
<td>1997-05-05</td>
<td>0000796343</td>
<td>1982
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/amd">AMD</a>
</td>
<td><a href="/wiki/AMD" title="AMD">Advanced Micro Devices</a></td>
<td>Information Technology</td>
<td>Semiconductors</td>
<td><a href="/wiki/Santa_Clara,_California" title="Santa Clara, California">Santa Clara, California</a></td>
<td>2017-03-20</td>
<td>0000002488</td>
<td>1969
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:AES">AES</a>
</td>
<td><a href="/wiki/AES_Corporation" title="AES Corporation">AES Corporation</a></td>
<td>Utilities</td>
<td>Independent Power Producers &amp; Energy Traders</td>
<td><a href="/wiki/Arlington,_Virginia" class="mw-redirect" title="Arlington, Virginia">Arlington, Virginia</a></td>
<td>1998-10-02</td>
<td>0000874761</td>
<td>1981
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:AFL">AFL</a>
</td>
<td><a href="/wiki/Aflac" title="Aflac">Aflac</a></td>
<td>Financials</td>
<td>Life &amp; Health Insurance</td>
<td><a href="/wiki/Columbus,_Georgia" title="Columbus, Georgia">Columbus, Georgia</a></td>
<td>1999-05-28</td>
<td>0000004977</td>
<td>1955
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:A">A</a>
</td>
<td><a href="/wiki/Agilent_Technologies" title="Agilent Technologies">Agilent Technologies</a></td>
<td>Health Care</td>
<td>Life Sciences Tools &amp; Services</td>
<td><a href="/wiki/Santa_Clara,_California" title="Santa Clara, California">Santa Clara, California</a></td>
<td>2000-06-05</td>
<td>0001090872</td>
<td>1999
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:APD">APD</a>
</td>
<td><a href="/wiki/Air_Products" title="Air Products">Air Products</a></td>
<td>Materials</td>
<td>Industrial Gases</td>
<td><a href="/wiki/Upper_Macungie_Township,_Pennsylvania" title="Upper Macungie Township, Pennsylvania">Upper Macungie Township, Pennsylvania</a></td>
<td>1985-04-30</td>
<td>0000002969</td>
<td>1940
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/abnb">ABNB</a>
</td>
<td><a href="/wiki/Airbnb" title="Airbnb">Airbnb</a></td>
<td>Consumer Discretionary</td>
<td>Hotels, Resorts &amp; Cruise Lines</td>
<td><a href="/wiki/San_Francisco" title="San Francisco">San Francisco</a>, California</td>
<td>2023-09-18</td>
<td>0001559720</td>
<td>2008
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/akam">AKAM</a>
</td>
<td><a href="/wiki/Akamai_Technologies" title="Akamai Technologies">Akamai Technologies</a></td>
<td>Information Technology</td>
<td>Internet Services &amp; Infrastructure</td>
<td><a href="/wiki/Cambridge,_Massachusetts" title="Cambridge, Massachusetts">Cambridge, Massachusetts</a></td>
<td>2007-07-12</td>
<td>0001086222</td>
<td>1998
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:ALB">ALB</a>
</td>
<td><a href="/wiki/Albemarle_Corporation" title="Albemarle Corporation">Albemarle Corporation</a></td>
<td>Materials</td>
<td>Specialty Chemicals</td>
<td><a href="/wiki/Charlotte,_North_Carolina" title="Charlotte, North Carolina">Charlotte, North Carolina</a></td>
<td>2016-07-01</td>
<td>0000915913</td>
<td>1994
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:ARE">ARE</a>
</td>
<td><a href="/wiki/Alexandria_Real_Estate_Equities" title="Alexandria Real Estate Equities">Alexandria Real Estate Equities</a></td>
<td>Real Estate</td>
<td>Office REITs</td>
<td><a href="/wiki/Pasadena,_California" title="Pasadena, California">Pasadena, California</a></td>
<td>2017-03-20</td>
<td>0001035443</td>
<td>1994
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/algn">ALGN</a>
</td>
<td><a href="/wiki/Align_Technology" title="Align Technology">Align Technology</a></td>
<td>Health Care</td>
<td>Health Care Supplies</td>
<td><a href="/wiki/Tempe,_Arizona" title="Tempe, Arizona">Tempe, Arizona</a></td>
<td>2017-06-19</td>
<td>0001097149</td>
<td>1997
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:ALLE">ALLE</a>
</td>
<td><a href="/wiki/Allegion" title="Allegion">Allegion</a></td>
<td>Industrials</td>
<td>Building Products</td>
<td><a href="/wiki/Dublin" title="Dublin">Dublin</a>, Ireland</td>
<td>2013-12-02</td>
<td>0001579241</td>
<td>1908
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/lnt">LNT</a>
</td>
<td><a href="/wiki/Alliant_Energy" title="Alliant Energy">Alliant Energy</a></td>
<td>Utilities</td>
<td>Electric Utilities</td>
<td><a href="/wiki/Madison,_Wisconsin" title="Madison, Wisconsin">Madison, Wisconsin</a></td>
<td>2016-07-01</td>
<td>0000352541</td>
<td>1917
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:ALL">ALL</a>
</td>
<td><a href="/wiki/Allstate" title="Allstate">Allstate</a></td>
<td>Financials</td>
<td>Property &amp; Casualty Insurance</td>
<td><a href="/wiki/Northbrook,_Illinois" title="Northbrook, Illinois">Northbrook, Illinois</a></td>
<td>1995-07-13</td>
<td>0000899051</td>
<td>1931
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/googl">GOOGL</a>
</td>
<td><a href="/wiki/Alphabet_Inc." title="Alphabet Inc.">Alphabet Inc.</a> (Class A)</td>
<td>Communication Services</td>
<td>Interactive Media &amp; Services</td>
<td><a href="/wiki/Mountain_View,_California" title="Mountain View, California">Mountain View, California</a></td>
<td>2014-04-03</td>
<td>0001652044</td>
<td>1998
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/goog">GOOG</a>
</td>
<td><a href="/wiki/Alphabet_Inc." title="Alphabet Inc.">Alphabet Inc.</a> (Class C)</td>
<td>Communication Services</td>
<td>Interactive Media &amp; Services</td>
<td><a href="/wiki/Mountain_View,_California" title="Mountain View, California">Mountain View, California</a></td>
<td>2006-04-03</td>
<td>0001652044</td>
<td>1998
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:MO">MO</a>
</td>
<td><a href="/wiki/Altria" title="Altria">Altria</a></td>
<td>Consumer Staples</td>
<td>Tobacco</td>
<td><a href="/wiki/Richmond,_Virginia" title="Richmond, Virginia">Richmond, Virginia</a></td>
<td>1957-03-04</td>
<td>0000764180</td>
<td>1985
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/amzn">AMZN</a>
</td>
<td><a href="/wiki/Amazon_(company)" title="Amazon (company)">Amazon</a></td>
<td>Consumer Discretionary</td>
<td>Broadline Retail</td>
<td><a href="/wiki/Seattle" title="Seattle">Seattle</a>, Washington</td>
<td>2005-11-18</td>
<td>0001018724</td>
<td>1994
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:AMCR">AMCR</a>
</td>
<td><a href="/wiki/Amcor" title="Amcor">Amcor</a></td>
<td>Materials</td>
<td>Paper &amp; Plastic Packaging Products &amp; Materials</td>
<td><a href="/wiki/Warmley" title="Warmley">Warmley</a>, <a href="/wiki/Bristol" title="Bristol">Bristol</a>, United Kingdom</td>
<td>2019-06-07</td>
<td>0001748790</td>
<td>2019 (1860)
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:AEE">AEE</a>
</td>
<td><a href="/wiki/Ameren" title="Ameren">Ameren</a></td>
<td>Utilities</td>
<td>Multi-Utilities</td>
<td><a href="/wiki/St._Louis" title="St. Louis">St. Louis</a>, Missouri</td>
<td>1991-09-19</td>
<td>0001002910</td>
<td>1902
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/aep">AEP</a>
</td>
<td><a href="/wiki/American_Electric_Power" title="American Electric Power">American Electric Power</a></td>
<td>Utilities</td>
<td>Electric Utilities</td>
<td><a href="/wiki/Columbus,_Ohio" title="Columbus, Ohio">Columbus, Ohio</a></td>
<td>1957-03-04</td>
<td>0000004904</td>
<td>1906
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:AXP">AXP</a>
</td>
<td><a href="/wiki/American_Express" title="American Express">American Express</a></td>
<td>Financials</td>
<td>Consumer Finance</td>
<td><a href="/wiki/New_York_City" title="New York City">New York City</a>, New York</td>
<td>1976-06-30</td>
<td>0000004962</td>
<td>1850
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:AIG">AIG</a>
</td>
<td><a href="/wiki/American_International_Group" title="American International Group">American International Group</a></td>
<td>Financials</td>
<td>Multi-line Insurance</td>
<td><a href="/wiki/New_York_City" title="New York City">New York City</a>, New York</td>
<td>1980-03-31</td>
<td>0000005272</td>
<td>1919
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:AMT">AMT</a>
</td>
<td><a href="/wiki/American_Tower" title="American Tower">American Tower</a></td>
<td>Real Estate</td>
<td>Telecom Tower REITs</td>
<td><a href="/wiki/Boston" title="Boston">Boston</a>, Massachusetts</td>
<td>2007-11-19</td>
<td>0001053507</td>
<td>1995
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:AWK">AWK</a>
</td>
<td><a href="/wiki/American_Water_Works" title="American Water Works">American Water Works</a></td>
<td>Utilities</td>
<td>Water Utilities</td>
<td><a href="/wiki/Camden,_New_Jersey" title="Camden, New Jersey">Camden, New Jersey</a></td>
<td>2016-03-04</td>
<td>0001410636</td>
<td>1886
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:AMP">AMP</a>
</td>
<td><a href="/wiki/Ameriprise_Financial" title="Ameriprise Financial">Ameriprise Financial</a></td>
<td>Financials</td>
<td>Asset Management &amp; Custody Banks</td>
<td><a href="/wiki/Minneapolis" title="Minneapolis">Minneapolis</a>, Minnesota</td>
<td>2005-10-03</td>
<td>0000820027
</td>
<td>1894
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:AME">AME</a>
</td>
<td><a href="/wiki/Ametek" title="Ametek">Ametek</a></td>
<td>Industrials</td>
<td>Electrical Components &amp; Equipment</td>
<td><a href="/wiki/Berwyn,_Pennsylvania" title="Berwyn, Pennsylvania">Berwyn, Pennsylvania</a></td>
<td>2013-09-23</td>
<td>0001037868
</td>
<td>1930
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/amgn">AMGN</a>
</td>
<td><a href="/wiki/Amgen" title="Amgen">Amgen</a></td>
<td>Health Care</td>
<td>Biotechnology</td>
<td><a href="/wiki/Thousand_Oaks,_California" title="Thousand Oaks, California">Thousand Oaks, California</a></td>
<td>1992-01-02</td>
<td>0000318154
</td>
<td>1980
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:APH">APH</a>
</td>
<td><a href="/wiki/Amphenol" title="Amphenol">Amphenol</a></td>
<td>Information Technology</td>
<td>Electronic Components</td>
<td><a href="/wiki/Wallingford,_Connecticut" title="Wallingford, Connecticut">Wallingford, Connecticut</a></td>
<td>2008-09-30</td>
<td>0000820313</td>
<td>1932
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/adi">ADI</a>
</td>
<td><a href="/wiki/Analog_Devices" title="Analog Devices">Analog Devices</a></td>
<td>Information Technology</td>
<td>Semiconductors</td>
<td><a href="/wiki/Wilmington,_Massachusetts" title="Wilmington, Massachusetts">Wilmington, Massachusetts</a></td>
<td>1999-10-12</td>
<td>0000006281
</td>
<td>1965
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:AON">AON</a>
</td>
<td><a href="/wiki/Aon_(company)" title="Aon (company)">Aon plc</a></td>
<td>Financials</td>
<td>Insurance Brokers</td>
<td><a href="/wiki/London" title="London">London</a>, United Kingdom</td>
<td>1996-04-23</td>
<td>0000315293</td>
<td>1982 (1919)
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/apa">APA</a>
</td>
<td><a href="/wiki/APA_Corporation" title="APA Corporation">APA Corporation</a></td>
<td>Energy</td>
<td>Oil &amp; Gas Exploration &amp; Production</td>
<td><a href="/wiki/Houston" title="Houston">Houston</a>, Texas</td>
<td>1997-07-28</td>
<td>0001841666</td>
<td>1954
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:APO">APO</a>
</td>
<td><a href="/wiki/Apollo_Global_Management" title="Apollo Global Management">Apollo Global Management</a></td>
<td>Financials</td>
<td>Asset Management &amp; Custody Banks</td>
<td><a href="/wiki/New_York_City" title="New York City">New York City</a>, New York</td>
<td>2024-12-23</td>
<td>0001858681</td>
<td>1990
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/aapl">AAPL</a>
</td>
<td><a href="/wiki/Apple_Inc." title="Apple Inc.">Apple Inc.</a></td>
<td>Information Technology</td>
<td>Technology Hardware, Storage &amp; Peripherals</td>
<td><a href="/wiki/Cupertino,_California" title="Cupertino, California">Cupertino, California</a></td>
<td>1982-11-30</td>
<td>0000320193
</td>
<td>1977
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/amat">AMAT</a>
</td>
<td><a href="/wiki/Applied_Materials" title="Applied Materials">Applied Materials</a></td>
<td>Information Technology</td>
<td>Semiconductor Materials &amp; Equipment</td>
<td><a href="/wiki/Santa_Clara,_California" title="Santa Clara, California">Santa Clara, California</a></td>
<td>1995-03-16</td>
<td>0000006951
</td>
<td>1967
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:APTV">APTV</a>
</td>
<td><a href="/wiki/Aptiv" title="Aptiv">Aptiv</a></td>
<td>Consumer Discretionary</td>
<td>Automotive Parts &amp; Equipment</td>
<td><a href="/wiki/Dublin" title="Dublin">Dublin</a>, Ireland</td>
<td>2012-12-24</td>
<td>0001521332
</td>
<td>1994
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/acgl">ACGL</a>
</td>
<td><a href="/wiki/Arch_Capital_Group" title="Arch Capital Group">Arch Capital Group</a></td>
<td>Financials</td>
<td>Property &amp; Casualty Insurance</td>
<td><a href="/wiki/Hamilton,_Bermuda" title="Hamilton, Bermuda">Hamilton, Bermuda</a></td>
<td>2022-11-01</td>
<td>0000947484</td>
<td>1995
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:ADM">ADM</a>
</td>
<td><a href="/wiki/Archer_Daniels_Midland" title="Archer Daniels Midland">Archer Daniels Midland</a></td>
<td>Consumer Staples</td>
<td>Agricultural Products &amp; Services</td>
<td><a href="/wiki/Chicago" title="Chicago">Chicago</a>, Illinois</td>
<td>1957-03-04</td>
<td>0000007084
</td>
<td>1902
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:ANET">ANET</a>
</td>
<td><a href="/wiki/Arista_Networks" title="Arista Networks">Arista Networks</a></td>
<td>Information Technology</td>
<td>Communications Equipment</td>
<td><a href="/wiki/Santa_Clara,_California" title="Santa Clara, California">Santa Clara, California</a></td>
<td>2018-08-28</td>
<td>0001596532</td>
<td>2004
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:AJG">AJG</a>
</td>
<td><a href="/wiki/Arthur_J._Gallagher_%26_Co." title="Arthur J. Gallagher &amp; Co.">Arthur J. Gallagher &amp; Co.</a></td>
<td>Financials</td>
<td>Insurance Brokers</td>
<td><a href="/wiki/Rolling_Meadows,_Illinois" title="Rolling Meadows, Illinois">Rolling Meadows, Illinois</a></td>
<td>2016-05-31</td>
<td>0000354190
</td>
<td>1927
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:AIZ">AIZ</a>
</td>
<td><a href="/wiki/Assurant" title="Assurant">Assurant</a></td>
<td>Financials</td>
<td>Multi-line Insurance</td>
<td><a href="/wiki/Atlanta" title="Atlanta">Atlanta</a>, Georgia</td>
<td>2007-04-10</td>
<td>0001267238</td>
<td>1892
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:T">T</a>
</td>
<td><a href="/wiki/AT%26T" title="AT&amp;T">AT&amp;T</a></td>
<td>Communication Services</td>
<td>Integrated Telecommunication Services</td>
<td><a href="/wiki/Dallas" title="Dallas">Dallas</a>, Texas</td>
<td>1983-11-30</td>
<td>0000732717</td>
<td>1983 (1885)
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:ATO">ATO</a>
</td>
<td><a href="/wiki/Atmos_Energy" title="Atmos Energy">Atmos Energy</a></td>
<td>Utilities</td>
<td>Gas Utilities</td>
<td><a href="/wiki/Dallas" title="Dallas">Dallas</a>, Texas</td>
<td>2019-02-15</td>
<td>0000731802</td>
<td>1906
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/adsk">ADSK</a>
</td>
<td><a href="/wiki/Autodesk" title="Autodesk">Autodesk</a></td>
<td>Information Technology</td>
<td>Application Software</td>
<td><a href="/wiki/San_Francisco" title="San Francisco">San Francisco</a>, California</td>
<td>1989-12-01</td>
<td>0000769397
</td>
<td>1982
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/adp">ADP</a>
</td>
<td><a href="/wiki/ADP_(company)" title="ADP (company)">Automatic Data Processing</a></td>
<td>Industrials</td>
<td>Human Resource &amp; Employment Services</td>
<td><a href="/wiki/Roseland,_New_Jersey" title="Roseland, New Jersey">Roseland, New Jersey</a></td>
<td>1981-03-31</td>
<td>0000008670
</td>
<td>1949
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:AZO">AZO</a>
</td>
<td><a href="/wiki/AutoZone" title="AutoZone">AutoZone</a></td>
<td>Consumer Discretionary</td>
<td>Automotive Retail</td>
<td><a href="/wiki/Memphis,_Tennessee" title="Memphis, Tennessee">Memphis, Tennessee</a></td>
<td>1997-01-02</td>
<td>0000866787
</td>
<td>1979
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:AVB">AVB</a>
</td>
<td><a href="/wiki/AvalonBay_Communities" title="AvalonBay Communities">AvalonBay Communities</a></td>
<td>Real Estate</td>
<td>Multi-Family Residential REITs</td>
<td><a href="/wiki/Arlington,_Virginia" class="mw-redirect" title="Arlington, Virginia">Arlington, Virginia</a></td>
<td>2007-01-10</td>
<td>0000915912</td>
<td>1978
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:AVY">AVY</a>
</td>
<td><a href="/wiki/Avery_Dennison" title="Avery Dennison">Avery Dennison</a></td>
<td>Materials</td>
<td>Paper &amp; Plastic Packaging Products &amp; Materials</td>
<td><a href="/wiki/Mentor,_Ohio" title="Mentor, Ohio">Mentor, Ohio</a></td>
<td>1987-12-31</td>
<td>0000008818</td>
<td>1935
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/axon">AXON</a>
</td>
<td><a href="/wiki/Axon_Enterprise" title="Axon Enterprise">Axon Enterprise</a></td>
<td>Industrials</td>
<td>Aerospace &amp; Defense</td>
<td><a href="/wiki/Scottsdale,_Arizona" title="Scottsdale, Arizona">Scottsdale, Arizona</a></td>
<td>2023-05-04</td>
<td>0001069183</td>
<td>1993
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/bkr">BKR</a>
</td>
<td><a href="/wiki/Baker_Hughes" title="Baker Hughes">Baker Hughes</a></td>
<td>Energy</td>
<td>Oil &amp; Gas Equipment &amp; Services</td>
<td><a href="/wiki/Houston" title="Houston">Houston</a>, Texas</td>
<td>2017-07-07</td>
<td>0001701605</td>
<td>2017
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:BALL">BALL</a>
</td>
<td><a href="/wiki/Ball_Corporation" title="Ball Corporation">Ball Corporation</a></td>
<td>Materials</td>
<td>Metal, Glass &amp; Plastic Containers</td>
<td><a href="/wiki/Broomfield,_Colorado" title="Broomfield, Colorado">Broomfield, Colorado</a></td>
<td>1984-10-31</td>
<td>0000009389</td>
<td>1880
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:BAC">BAC</a>
</td>
<td><a href="/wiki/Bank_of_America" title="Bank of America">Bank of America</a></td>
<td>Financials</td>
<td>Diversified Banks</td>
<td><a href="/wiki/Charlotte,_North_Carolina" title="Charlotte, North Carolina">Charlotte, North Carolina</a></td>
<td>1976-06-30</td>
<td>0000070858
</td>
<td>1998 (1923 / 1874)
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:BAX">BAX</a>
</td>
<td><a href="/wiki/Baxter_International" title="Baxter International">Baxter International</a></td>
<td>Health Care</td>
<td>Health Care Equipment</td>
<td><a href="/wiki/Deerfield,_Illinois" title="Deerfield, Illinois">Deerfield, Illinois</a></td>
<td>1972-09-30</td>
<td>0000010456</td>
<td>1931
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:BDX">BDX</a>
</td>
<td><a href="/wiki/BD_(company)" title="BD (company)">Becton Dickinson</a></td>
<td>Health Care</td>
<td>Health Care Equipment</td>
<td><a href="/wiki/Franklin_Lakes,_New_Jersey" title="Franklin Lakes, New Jersey">Franklin Lakes, New Jersey</a></td>
<td>1972-09-30</td>
<td>0000010795</td>
<td>1897
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:BRK.B">BRK.B</a>
</td>
<td><a href="/wiki/Berkshire_Hathaway" title="Berkshire Hathaway">Berkshire Hathaway</a></td>
<td>Financials</td>
<td>Multi-Sector Holdings</td>
<td><a href="/wiki/Omaha,_Nebraska" title="Omaha, Nebraska">Omaha, Nebraska</a></td>
<td>2010-02-16</td>
<td>0001067983
</td>
<td>1839
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:BBY">BBY</a>
</td>
<td><a href="/wiki/Best_Buy" title="Best Buy">Best Buy</a></td>
<td>Consumer Discretionary</td>
<td>Computer &amp; Electronics Retail</td>
<td><a href="/wiki/Richfield,_Minnesota" title="Richfield, Minnesota">Richfield, Minnesota</a></td>
<td>1999-06-29</td>
<td>0000764478
</td>
<td>1966
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/tech">TECH</a>
</td>
<td><a href="/wiki/Bio-Techne" title="Bio-Techne">Bio-Techne</a></td>
<td>Health Care</td>
<td>Life Sciences Tools &amp; Services</td>
<td><a href="/wiki/Minneapolis" title="Minneapolis">Minneapolis</a>, Minnesota</td>
<td>2021-08-30</td>
<td>0000842023
</td>
<td>1976
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/biib">BIIB</a>
</td>
<td><a href="/wiki/Biogen" title="Biogen">Biogen</a></td>
<td>Health Care</td>
<td>Biotechnology</td>
<td><a href="/wiki/Cambridge,_Massachusetts" title="Cambridge, Massachusetts">Cambridge, Massachusetts</a></td>
<td>2003-11-13</td>
<td>0000875045
</td>
<td>1978
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:BLK">BLK</a>
</td>
<td><a href="/wiki/BlackRock" title="BlackRock">BlackRock</a></td>
<td>Financials</td>
<td>Asset Management &amp; Custody Banks</td>
<td><a href="/wiki/New_York_City" title="New York City">New York City</a>, New York</td>
<td>2011-04-04</td>
<td>0002012383
</td>
<td>1988
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:BX">BX</a>
</td>
<td><a href="/wiki/Blackstone_Inc." title="Blackstone Inc.">Blackstone Inc.</a></td>
<td>Financials</td>
<td>Asset Management &amp; Custody Banks</td>
<td><a href="/wiki/New_York_City" title="New York City">New York City</a>, New York</td>
<td>2023-09-18</td>
<td>0001393818</td>
<td>1985
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:XYZ">XYZ</a>
</td>
<td><a href="/wiki/Block,_Inc." title="Block, Inc.">Block, Inc.</a></td>
<td>Financials</td>
<td>Transaction &amp; Payment Processing Services</td>
<td>none</td>
<td>2025-07-23</td>
<td>0001512673</td>
<td>2009
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:BK">BK</a>
</td>
<td><a href="/wiki/BNY" title="BNY">BNY Mellon</a></td>
<td>Financials</td>
<td>Asset Management &amp; Custody Banks</td>
<td><a href="/wiki/New_York_City" title="New York City">New York City</a>, New York</td>
<td>1995-03-31</td>
<td>0001390777</td>
<td>1784
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:BA">BA</a>
</td>
<td><a href="/wiki/Boeing" title="Boeing">Boeing</a></td>
<td>Industrials</td>
<td>Aerospace &amp; Defense</td>
<td><a href="/wiki/Arlington,_Virginia" class="mw-redirect" title="Arlington, Virginia">Arlington, Virginia</a></td>
<td>1957-03-04</td>
<td>0000012927</td>
<td>1916
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/bkng">BKNG</a>
</td>
<td><a href="/wiki/Booking_Holdings" title="Booking Holdings">Booking Holdings</a></td>
<td>Consumer Discretionary</td>
<td>Hotels, Resorts &amp; Cruise Lines</td>
<td><a href="/wiki/Norwalk,_Connecticut" title="Norwalk, Connecticut">Norwalk, Connecticut</a></td>
<td>2009-11-06</td>
<td>0001075531</td>
<td>1996
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:BSX">BSX</a>
</td>
<td><a href="/wiki/Boston_Scientific" title="Boston Scientific">Boston Scientific</a></td>
<td>Health Care</td>
<td>Health Care Equipment</td>
<td><a href="/wiki/Marlborough,_Massachusetts" title="Marlborough, Massachusetts">Marlborough, Massachusetts</a></td>
<td>1995-02-24</td>
<td>0000885725
</td>
<td>1979
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:BMY">BMY</a>
</td>
<td><a href="/wiki/Bristol_Myers_Squibb" title="Bristol Myers Squibb">Bristol Myers Squibb</a></td>
<td>Health Care</td>
<td>Pharmaceuticals</td>
<td><a href="/wiki/New_York_City" title="New York City">New York City</a>, New York</td>
<td>1957-03-04</td>
<td>0000014272</td>
<td>1989 (1887)
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/avgo">AVGO</a>
</td>
<td><a href="/wiki/Broadcom" title="Broadcom">Broadcom</a></td>
<td>Information Technology</td>
<td>Semiconductors</td>
<td><a href="/wiki/Palo_Alto,_California" title="Palo Alto, California">Palo Alto, California</a></td>
<td>2014-05-08</td>
<td>0001730168</td>
<td>1961
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:BR">BR</a>
</td>
<td><a href="/wiki/Broadridge_Financial_Solutions" title="Broadridge Financial Solutions">Broadridge Financial Solutions</a></td>
<td>Industrials</td>
<td>Data Processing &amp; Outsourced Services</td>
<td><a href="/wiki/Lake_Success,_New_York" title="Lake Success, New York">Lake Success, New York</a></td>
<td>2018-06-18</td>
<td>0001383312</td>
<td>1962
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:BRO">BRO</a>
</td>
<td><a href="/wiki/Brown_%26_Brown" title="Brown &amp; Brown">Brown &amp; Brown</a></td>
<td>Financials</td>
<td>Insurance Brokers</td>
<td><a href="/wiki/Daytona_Beach,_Florida" title="Daytona Beach, Florida">Daytona Beach, Florida</a></td>
<td>2021-09-20</td>
<td>0000079282</td>
<td>1939
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:BF.B">BF.B</a>
</td>
<td><a href="/wiki/Brown%E2%80%93Forman" class="mw-redirect" title="Brown–Forman">Brown–Forman</a></td>
<td>Consumer Staples</td>
<td>Distillers &amp; Vintners</td>
<td><a href="/wiki/Louisville,_Kentucky" title="Louisville, Kentucky">Louisville, Kentucky</a></td>
<td>1982-10-31</td>
<td>0000014693</td>
<td>1870
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:BLDR">BLDR</a>
</td>
<td><a href="/wiki/Builders_FirstSource" title="Builders FirstSource">Builders FirstSource</a></td>
<td>Industrials</td>
<td>Building Products</td>
<td><a href="/wiki/Irving,_Texas" title="Irving, Texas">Irving, Texas</a></td>
<td>2023-12-18</td>
<td>0001316835</td>
<td>1998
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:BG">BG</a>
</td>
<td><a href="/wiki/Bunge_Global" title="Bunge Global">Bunge Global</a></td>
<td>Consumer Staples</td>
<td>Agricultural Products &amp; Services</td>
<td><a href="/wiki/Chesterfield,_Missouri" title="Chesterfield, Missouri">Chesterfield, Missouri</a></td>
<td>2023-03-15</td>
<td>0001996862</td>
<td>1818
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:BXP">BXP</a>
</td>
<td><a href="/wiki/BXP,_Inc." title="BXP, Inc.">BXP, Inc.</a></td>
<td>Real Estate</td>
<td>Office REITs</td>
<td><a href="/wiki/Boston" title="Boston">Boston</a>, Massachusetts</td>
<td>2006-04-03</td>
<td>0001037540</td>
<td>1970
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/chrw">CHRW</a>
</td>
<td><a href="/wiki/C.H._Robinson" title="C.H. Robinson">C.H. Robinson</a></td>
<td>Industrials</td>
<td>Air Freight &amp; Logistics</td>
<td><a href="/wiki/Eden_Prairie,_Minnesota" title="Eden Prairie, Minnesota">Eden Prairie, Minnesota</a></td>
<td>2007-03-02</td>
<td>0001043277</td>
<td>1905
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/cdns">CDNS</a>
</td>
<td><a href="/wiki/Cadence_Design_Systems" title="Cadence Design Systems">Cadence Design Systems</a></td>
<td>Information Technology</td>
<td>Application Software</td>
<td><a href="/wiki/San_Jose,_California" title="San Jose, California">San Jose, California</a></td>
<td>2017-09-18</td>
<td>0000813672</td>
<td>1988
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/czr">CZR</a>
</td>
<td><a href="/wiki/Caesars_Entertainment" title="Caesars Entertainment">Caesars Entertainment</a></td>
<td>Consumer Discretionary</td>
<td>Casinos &amp; Gaming</td>
<td><a href="/wiki/Reno,_Nevada" title="Reno, Nevada">Reno, Nevada</a></td>
<td>2021-03-22</td>
<td>0001590895</td>
<td>1973
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:CPT">CPT</a>
</td>
<td><a href="/wiki/Camden_Property_Trust" title="Camden Property Trust">Camden Property Trust</a></td>
<td>Real Estate</td>
<td>Multi-Family Residential REITs</td>
<td><a href="/wiki/Houston" title="Houston">Houston</a>, Texas</td>
<td>2022-04-04</td>
<td>0000906345</td>
<td>1981
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:CPB">CPB</a>
</td>
<td><a href="/wiki/Campbell%27s" title="Campbell's">Campbell's Company (The)</a></td>
<td>Consumer Staples</td>
<td>Packaged Foods &amp; Meats</td>
<td><a href="/wiki/Camden,_New_Jersey" title="Camden, New Jersey">Camden, New Jersey</a></td>
<td>1957-03-04</td>
<td>0000016732</td>
<td>1869
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:COF">COF</a>
</td>
<td><a href="/wiki/Capital_One" title="Capital One">Capital One</a></td>
<td>Financials</td>
<td>Consumer Finance</td>
<td><a href="/wiki/Tysons_Corner,_Virginia" class="mw-redirect" title="Tysons Corner, Virginia">Tysons Corner, Virginia</a></td>
<td>1998-07-01</td>
<td>0000927628</td>
<td>1994
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:CAH">CAH</a>
</td>
<td><a href="/wiki/Cardinal_Health" title="Cardinal Health">Cardinal Health</a></td>
<td>Health Care</td>
<td>Health Care Distributors</td>
<td><a href="/wiki/Dublin,_Ohio" title="Dublin, Ohio">Dublin, Ohio</a></td>
<td>1997-05-27</td>
<td>0000721371</td>
<td>1971
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:KMX">KMX</a>
</td>
<td><a href="/wiki/CarMax" title="CarMax">CarMax</a></td>
<td>Consumer Discretionary</td>
<td>Automotive Retail</td>
<td><a href="/wiki/Richmond,_Virginia" title="Richmond, Virginia">Richmond, Virginia</a></td>
<td>2010-06-28</td>
<td>0001170010</td>
<td>1993
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:CCL">CCL</a>
</td>
<td><a href="/wiki/Carnival_Corporation_%26_plc" title="Carnival Corporation &amp; plc">Carnival</a></td>
<td>Consumer Discretionary</td>
<td>Hotels, Resorts &amp; Cruise Lines</td>
<td><a href="/wiki/Miami" title="Miami">Miami</a>, Florida</td>
<td>1998-12-22</td>
<td>0000815097</td>
<td>1972
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:CARR">CARR</a>
</td>
<td><a href="/wiki/Carrier_Global" title="Carrier Global">Carrier Global</a></td>
<td>Industrials</td>
<td>Building Products</td>
<td><a href="/wiki/Palm_Beach_Gardens,_Florida" title="Palm Beach Gardens, Florida">Palm Beach Gardens, Florida</a></td>
<td>2020-04-03</td>
<td>0001783180
</td>
<td>2020 (1915, <a href="/wiki/United_Technologies" title="United Technologies">United Technologies</a> spinoff)
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:CAT">CAT</a>
</td>
<td><a href="/wiki/Caterpillar_Inc." title="Caterpillar Inc.">Caterpillar Inc.</a></td>
<td>Industrials</td>
<td>Construction Machinery &amp; Heavy Transportation Equipment</td>
<td><a href="/wiki/Irving,_Texas" title="Irving, Texas">Irving, Texas</a></td>
<td>1957-03-04</td>
<td>0000018230</td>
<td>1925
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://markets.cboe.com/us/equities/listings/listed_products/symbols/CBOE">CBOE</a>
</td>
<td><a href="/wiki/Cboe_Global_Markets" title="Cboe Global Markets">Cboe Global Markets</a></td>
<td>Financials</td>
<td>Financial Exchanges &amp; Data</td>
<td><a href="/wiki/Chicago" title="Chicago">Chicago</a>, Illinois</td>
<td>2017-03-01</td>
<td>0001374310</td>
<td>1973
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:CBRE">CBRE</a>
</td>
<td><a href="/wiki/CBRE_Group" title="CBRE Group">CBRE Group</a></td>
<td>Real Estate</td>
<td>Real Estate Services</td>
<td><a href="/wiki/Dallas" title="Dallas">Dallas</a>, Texas</td>
<td>2006-11-10</td>
<td>0001138118</td>
<td>1906
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/cdw">CDW</a>
</td>
<td><a href="/wiki/CDW" title="CDW">CDW Corporation</a></td>
<td>Information Technology</td>
<td>Technology Distributors</td>
<td><a href="/wiki/Vernon_Hills,_Illinois" title="Vernon Hills, Illinois">Vernon Hills, Illinois</a></td>
<td>2019-09-23</td>
<td>0001402057</td>
<td>1984
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:COR">COR</a>
</td>
<td><a href="/wiki/Cencora" title="Cencora">Cencora</a></td>
<td>Health Care</td>
<td>Health Care Distributors</td>
<td><a href="/wiki/Conshohocken,_Pennsylvania" title="Conshohocken, Pennsylvania">Conshohocken, Pennsylvania</a></td>
<td>2001-08-30</td>
<td>0001140859</td>
<td>1985
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:CNC">CNC</a>
</td>
<td><a href="/wiki/Centene_Corporation" title="Centene Corporation">Centene Corporation</a></td>
<td>Health Care</td>
<td>Managed Health Care</td>
<td><a href="/wiki/St._Louis" title="St. Louis">St. Louis</a>, Missouri</td>
<td>2016-03-30</td>
<td>0001071739</td>
<td>1984
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:CNP">CNP</a>
</td>
<td><a href="/wiki/CenterPoint_Energy" title="CenterPoint Energy">CenterPoint Energy</a></td>
<td>Utilities</td>
<td>Multi-Utilities</td>
<td><a href="/wiki/Houston" title="Houston">Houston</a>, Texas</td>
<td>1985-07-31</td>
<td>0001130310</td>
<td>1882
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:CF">CF</a>
</td>
<td><a href="/wiki/CF_Industries" title="CF Industries">CF Industries</a></td>
<td>Materials</td>
<td>Fertilizers &amp; Agricultural Chemicals</td>
<td><a href="/wiki/Deerfield,_Illinois" title="Deerfield, Illinois">Deerfield, Illinois</a></td>
<td>2008-08-27</td>
<td>0001324404</td>
<td>1946
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:CRL">CRL</a>
</td>
<td><a href="/wiki/Charles_River_Laboratories" title="Charles River Laboratories">Charles River Laboratories</a></td>
<td>Health Care</td>
<td>Life Sciences Tools &amp; Services</td>
<td><a href="/wiki/Wilmington,_Massachusetts" title="Wilmington, Massachusetts">Wilmington, Massachusetts</a></td>
<td>2021-05-14</td>
<td>0001100682</td>
<td>1947
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:SCHW">SCHW</a>
</td>
<td><a href="/wiki/Charles_Schwab_Corporation" title="Charles Schwab Corporation">Charles Schwab Corporation</a></td>
<td>Financials</td>
<td>Investment Banking &amp; Brokerage</td>
<td><a href="/wiki/Westlake,_Texas" title="Westlake, Texas">Westlake, Texas</a></td>
<td>1997-06-02</td>
<td>0000316709</td>
<td>1971
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/chtr">CHTR</a>
</td>
<td><a href="/wiki/Charter_Communications" title="Charter Communications">Charter Communications</a></td>
<td>Communication Services</td>
<td>Cable &amp; Satellite</td>
<td><a href="/wiki/Stamford,_Connecticut" title="Stamford, Connecticut">Stamford, Connecticut</a></td>
<td>2016-09-08</td>
<td>0001091667</td>
<td>1993
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:CVX">CVX</a>
</td>
<td><a href="/wiki/Chevron_Corporation" title="Chevron Corporation">Chevron Corporation</a></td>
<td>Energy</td>
<td>Integrated Oil &amp; Gas</td>
<td><a href="/wiki/San_Ramon,_California" title="San Ramon, California">San Ramon, California</a></td>
<td>1957-03-04</td>
<td>0000093410</td>
<td>1879
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:CMG">CMG</a>
</td>
<td><a href="/wiki/Chipotle_Mexican_Grill" title="Chipotle Mexican Grill">Chipotle Mexican Grill</a></td>
<td>Consumer Discretionary</td>
<td>Restaurants</td>
<td><a href="/wiki/Newport_Beach,_California" title="Newport Beach, California">Newport Beach, California</a></td>
<td>2011-04-28</td>
<td>0001058090</td>
<td>1993
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:CB">CB</a>
</td>
<td><a href="/wiki/Chubb_Limited" title="Chubb Limited">Chubb Limited</a></td>
<td>Financials</td>
<td>Property &amp; Casualty Insurance</td>
<td><a href="/wiki/Zurich,_Switzerland" class="mw-redirect" title="Zurich, Switzerland">Zurich, Switzerland</a></td>
<td>2010-07-15</td>
<td>0000896159</td>
<td>1985
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:CHD">CHD</a>
</td>
<td><a href="/wiki/Church_%26_Dwight" title="Church &amp; Dwight">Church &amp; Dwight</a></td>
<td>Consumer Staples</td>
<td>Household Products</td>
<td><a href="/wiki/Ewing,_New_Jersey" class="mw-redirect" title="Ewing, New Jersey">Ewing, New Jersey</a></td>
<td>2015-12-29</td>
<td>0000313927</td>
<td>1847
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:CI">CI</a>
</td>
<td><a href="/wiki/Cigna" class="mw-redirect" title="Cigna">Cigna</a></td>
<td>Health Care</td>
<td>Health Care Services</td>
<td><a href="/wiki/Bloomfield,_Connecticut" title="Bloomfield, Connecticut">Bloomfield, Connecticut</a></td>
<td>1976-06-30</td>
<td>0001739940
</td>
<td>1982
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/cinf">CINF</a>
</td>
<td><a href="/wiki/Cincinnati_Financial" title="Cincinnati Financial">Cincinnati Financial</a></td>
<td>Financials</td>
<td>Property &amp; Casualty Insurance</td>
<td><a href="/wiki/Fairfield,_Ohio" title="Fairfield, Ohio">Fairfield, Ohio</a></td>
<td>1997-12-18</td>
<td>0000020286</td>
<td>1950
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/ctas">CTAS</a>
</td>
<td><a href="/wiki/Cintas" title="Cintas">Cintas</a></td>
<td>Industrials</td>
<td>Diversified Support Services</td>
<td><a href="/wiki/Mason,_Ohio" title="Mason, Ohio">Mason, Ohio</a></td>
<td>2001-03-01</td>
<td>0000723254</td>
<td>1929
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/csco">CSCO</a>
</td>
<td><a href="/wiki/Cisco" title="Cisco">Cisco</a></td>
<td>Information Technology</td>
<td>Communications Equipment</td>
<td><a href="/wiki/San_Jose,_California" title="San Jose, California">San Jose, California</a></td>
<td>1993-12-01</td>
<td>0000858877</td>
<td>1984
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:C">C</a>
</td>
<td><a href="/wiki/Citigroup" title="Citigroup">Citigroup</a></td>
<td>Financials</td>
<td>Diversified Banks</td>
<td><a href="/wiki/New_York_City" title="New York City">New York City</a>, New York</td>
<td>1988-05-31</td>
<td>0000831001</td>
<td>1998
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:CFG">CFG</a>
</td>
<td><a href="/wiki/Citizens_Financial_Group" title="Citizens Financial Group">Citizens Financial Group</a></td>
<td>Financials</td>
<td>Regional Banks</td>
<td><a href="/wiki/Providence,_Rhode_Island" title="Providence, Rhode Island">Providence, Rhode Island</a></td>
<td>2016-01-29</td>
<td>0000759944</td>
<td>1828
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:CLX">CLX</a>
</td>
<td><a href="/wiki/Clorox" title="Clorox">Clorox</a></td>
<td>Consumer Staples</td>
<td>Household Products</td>
<td><a href="/wiki/Oakland,_California" title="Oakland, California">Oakland, California</a></td>
<td>1969-03-31</td>
<td>0000021076</td>
<td>1913
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/cme">CME</a>
</td>
<td><a href="/wiki/CME_Group" title="CME Group">CME Group</a></td>
<td>Financials</td>
<td>Financial Exchanges &amp; Data</td>
<td><a href="/wiki/Chicago" title="Chicago">Chicago</a>, Illinois</td>
<td>2006-08-11</td>
<td>0001156375</td>
<td>1848
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:CMS">CMS</a>
</td>
<td><a href="/wiki/CMS_Energy" title="CMS Energy">CMS Energy</a></td>
<td>Utilities</td>
<td>Multi-Utilities</td>
<td><a href="/wiki/Jackson,_Michigan" title="Jackson, Michigan">Jackson, Michigan</a></td>
<td>1957-03-04</td>
<td>0000811156</td>
<td>1886
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:KO">KO</a>
</td>
<td><a href="/wiki/The_Coca-Cola_Company" title="The Coca-Cola Company">Coca-Cola Company (The)</a></td>
<td>Consumer Staples</td>
<td>Soft Drinks &amp; Non-alcoholic Beverages</td>
<td><a href="/wiki/Atlanta" title="Atlanta">Atlanta</a>, Georgia</td>
<td>1957-03-04</td>
<td>0000021344</td>
<td>1886
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/ctsh">CTSH</a>
</td>
<td><a href="/wiki/Cognizant" title="Cognizant">Cognizant</a></td>
<td>Information Technology</td>
<td>IT Consulting &amp; Other Services</td>
<td><a href="/wiki/Teaneck,_New_Jersey" title="Teaneck, New Jersey">Teaneck, New Jersey</a></td>
<td>2006-11-17</td>
<td>0001058290</td>
<td>1994
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/coin">COIN</a>
</td>
<td><a href="/wiki/Coinbase" title="Coinbase">Coinbase</a></td>
<td>Financials</td>
<td>Financial Exchanges &amp; Data</td>
<td><a href="/wiki/New_York_City" title="New York City">New York City</a>, New York</td>
<td>2025-05-19</td>
<td>0001679788</td>
<td>2012
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:CL">CL</a>
</td>
<td><a href="/wiki/Colgate-Palmolive" title="Colgate-Palmolive">Colgate-Palmolive</a></td>
<td>Consumer Staples</td>
<td>Household Products</td>
<td><a href="/wiki/New_York_City" title="New York City">New York City</a>, New York</td>
<td>1957-03-04</td>
<td>0000021665</td>
<td>1806
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/cmcsa">CMCSA</a>
</td>
<td><a href="/wiki/Comcast" title="Comcast">Comcast</a></td>
<td>Communication Services</td>
<td>Cable &amp; Satellite</td>
<td><a href="/wiki/Philadelphia" title="Philadelphia">Philadelphia</a>, Pennsylvania</td>
<td>2002-11-19</td>
<td>0001166691</td>
<td>1963
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:CAG">CAG</a>
</td>
<td><a href="/wiki/Conagra_Brands" title="Conagra Brands">Conagra Brands</a></td>
<td>Consumer Staples</td>
<td>Packaged Foods &amp; Meats</td>
<td><a href="/wiki/Chicago" title="Chicago">Chicago</a>, Illinois</td>
<td>1983-08-31</td>
<td>0000023217
</td>
<td>1919
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:COP">COP</a>
</td>
<td><a href="/wiki/ConocoPhillips" title="ConocoPhillips">ConocoPhillips</a></td>
<td>Energy</td>
<td>Oil &amp; Gas Exploration &amp; Production</td>
<td><a href="/wiki/Houston" title="Houston">Houston</a>, Texas</td>
<td>1957-03-04</td>
<td>0001163165</td>
<td>2002
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:ED">ED</a>
</td>
<td><a href="/wiki/Consolidated_Edison" title="Consolidated Edison">Consolidated Edison</a></td>
<td>Utilities</td>
<td>Multi-Utilities</td>
<td><a href="/wiki/New_York_City" title="New York City">New York City</a>, New York</td>
<td>1957-03-04</td>
<td>0001047862</td>
<td>1823
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:STZ">STZ</a>
</td>
<td><a href="/wiki/Constellation_Brands" title="Constellation Brands">Constellation Brands</a></td>
<td>Consumer Staples</td>
<td>Distillers &amp; Vintners</td>
<td><a href="/wiki/Rochester,_New_York" title="Rochester, New York">Rochester, New York</a></td>
<td>2005-07-01</td>
<td>0000016918</td>
<td>1945
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/ceg">CEG</a>
</td>
<td><a href="/wiki/Constellation_Energy" title="Constellation Energy">Constellation Energy</a></td>
<td>Utilities</td>
<td>Electric Utilities</td>
<td><a href="/wiki/Baltimore" title="Baltimore">Baltimore</a>, Maryland</td>
<td>2022-02-02</td>
<td>0001868275</td>
<td>1999
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/coo">COO</a>
</td>
<td><a href="/wiki/The_Cooper_Companies" title="The Cooper Companies">Cooper Companies (The)</a></td>
<td>Health Care</td>
<td>Health Care Supplies</td>
<td><a href="/wiki/San_Ramon,_California" title="San Ramon, California">San Ramon, California</a></td>
<td>2016-09-23</td>
<td>0000711404</td>
<td>1958
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/cprt">CPRT</a>
</td>
<td><a href="/wiki/Copart" title="Copart">Copart</a></td>
<td>Industrials</td>
<td>Diversified Support Services</td>
<td><a href="/wiki/Dallas" title="Dallas">Dallas</a>, Texas</td>
<td>2018-07-02</td>
<td>0000900075</td>
<td>1982
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:GLW">GLW</a>
</td>
<td><a href="/wiki/Corning_Inc." title="Corning Inc.">Corning Inc.</a></td>
<td>Information Technology</td>
<td>Electronic Components</td>
<td><a href="/wiki/Corning_(city),_New_York" class="mw-redirect" title="Corning (city), New York">Corning, New York</a></td>
<td>1995-02-27</td>
<td>0000024741</td>
<td>1851
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:CPAY">CPAY</a>
</td>
<td><a href="/wiki/Corpay" title="Corpay">Corpay</a></td>
<td>Financials</td>
<td>Transaction &amp; Payment Processing Services</td>
<td><a href="/wiki/Atlanta" title="Atlanta">Atlanta</a>, Georgia</td>
<td>2018-06-20</td>
<td>0001175454</td>
<td>2000
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:CTVA">CTVA</a>
</td>
<td><a href="/wiki/Corteva" title="Corteva">Corteva</a></td>
<td>Materials</td>
<td>Fertilizers &amp; Agricultural Chemicals</td>
<td><a href="/wiki/Indianapolis" title="Indianapolis">Indianapolis</a>, Indiana</td>
<td>2019-06-03</td>
<td>0001755672</td>
<td>2019
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/csgp">CSGP</a>
</td>
<td><a href="/wiki/CoStar_Group" title="CoStar Group">CoStar Group</a></td>
<td>Real Estate</td>
<td>Real Estate Services</td>
<td><a href="/wiki/Washington,_D.C." title="Washington, D.C.">Washington, D.C.</a></td>
<td>2022-09-19</td>
<td>0001057352</td>
<td>1987
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/cost">COST</a>
</td>
<td><a href="/wiki/Costco" title="Costco">Costco</a></td>
<td>Consumer Staples</td>
<td>Consumer Staples Merchandise Retail</td>
<td><a href="/wiki/Issaquah,_Washington" title="Issaquah, Washington">Issaquah, Washington</a></td>
<td>1993-10-01</td>
<td>0000909832</td>
<td>1976
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:CTRA">CTRA</a>
</td>
<td><a href="/wiki/Coterra" title="Coterra">Coterra</a></td>
<td>Energy</td>
<td>Oil &amp; Gas Exploration &amp; Production</td>
<td><a href="/wiki/Houston" title="Houston">Houston</a>, Texas</td>
<td>2008-06-23</td>
<td>0000858470</td>
<td>2021 (1989)
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/crwd">CRWD</a>
</td>
<td><a href="/wiki/CrowdStrike" title="CrowdStrike">CrowdStrike</a></td>
<td>Information Technology</td>
<td>Systems Software</td>
<td><a href="/wiki/Austin,_Texas" title="Austin, Texas">Austin, Texas</a></td>
<td>2024-06-24</td>
<td>0001535527</td>
<td>2011
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:CCI">CCI</a>
</td>
<td><a href="/wiki/Crown_Castle" title="Crown Castle">Crown Castle</a></td>
<td>Real Estate</td>
<td>Telecom Tower REITs</td>
<td><a href="/wiki/Houston" title="Houston">Houston</a>, Texas</td>
<td>2012-03-14</td>
<td>0001051470</td>
<td>1994
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/csx">CSX</a>
</td>
<td><a href="/wiki/CSX_Corporation" title="CSX Corporation">CSX Corporation</a></td>
<td>Industrials</td>
<td>Rail Transportation</td>
<td><a href="/wiki/Jacksonville,_Florida" title="Jacksonville, Florida">Jacksonville, Florida</a></td>
<td>1957-03-04</td>
<td>0000277948</td>
<td>1980
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:CMI">CMI</a>
</td>
<td><a href="/wiki/Cummins" title="Cummins">Cummins</a></td>
<td>Industrials</td>
<td>Construction Machinery &amp; Heavy Transportation Equipment</td>
<td><a href="/wiki/Columbus,_Indiana" title="Columbus, Indiana">Columbus, Indiana</a></td>
<td>1965-03-31</td>
<td>0000026172</td>
<td>1919
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:CVS">CVS</a>
</td>
<td><a href="/wiki/CVS_Health" title="CVS Health">CVS Health</a></td>
<td>Health Care</td>
<td>Health Care Services</td>
<td><a href="/wiki/Woonsocket,_Rhode_Island" title="Woonsocket, Rhode Island">Woonsocket, Rhode Island</a></td>
<td>1957-03-04</td>
<td>0000064803</td>
<td>1996
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:DHR">DHR</a>
</td>
<td><a href="/wiki/Danaher_Corporation" title="Danaher Corporation">Danaher Corporation</a></td>
<td>Health Care</td>
<td>Life Sciences Tools &amp; Services</td>
<td><a href="/wiki/Washington,_D.C." title="Washington, D.C.">Washington, D.C.</a></td>
<td>1998-11-18</td>
<td>0000313616</td>
<td>1969
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:DRI">DRI</a>
</td>
<td><a href="/wiki/Darden_Restaurants" title="Darden Restaurants">Darden Restaurants</a></td>
<td>Consumer Discretionary</td>
<td>Restaurants</td>
<td><a href="/wiki/Orlando,_Florida" title="Orlando, Florida">Orlando, Florida</a></td>
<td>1995-05-31</td>
<td>0000940944</td>
<td>1938
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/ddog">DDOG</a>
</td>
<td><a href="/wiki/Datadog" title="Datadog">Datadog</a></td>
<td>Information Technology</td>
<td>Application Software</td>
<td><a href="/wiki/New_York_City" title="New York City">New York City</a>, New York</td>
<td>2025-07-09</td>
<td>0001561550</td>
<td>2010
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:DVA">DVA</a>
</td>
<td><a href="/wiki/DaVita" title="DaVita">DaVita</a></td>
<td>Health Care</td>
<td>Health Care Services</td>
<td><a href="/wiki/Denver" title="Denver">Denver</a>, Colorado</td>
<td>2008-07-31</td>
<td>0000927066</td>
<td>1979
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:DAY">DAY</a>
</td>
<td><a href="/wiki/Dayforce" title="Dayforce">Dayforce</a></td>
<td>Industrials</td>
<td>Human Resource &amp; Employment Services</td>
<td><a href="/wiki/Minneapolis" title="Minneapolis">Minneapolis</a>, Minnesota</td>
<td>2021-09-20</td>
<td>0001725057</td>
<td>1992
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:DECK">DECK</a>
</td>
<td><a href="/wiki/Deckers_Brands" title="Deckers Brands">Deckers Brands</a></td>
<td>Consumer Discretionary</td>
<td>Footwear</td>
<td><a href="/wiki/Goleta,_California" title="Goleta, California">Goleta, California</a></td>
<td>2024-03-18</td>
<td>0000910521</td>
<td>1973
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:DE">DE</a>
</td>
<td><a href="/wiki/John_Deere" title="John Deere">Deere &amp; Company</a></td>
<td>Industrials</td>
<td>Agricultural &amp; Farm Machinery</td>
<td><a href="/wiki/Moline,_Illinois" title="Moline, Illinois">Moline, Illinois</a></td>
<td>1957-03-04</td>
<td>0000315189</td>
<td>1837
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:DELL">DELL</a>
</td>
<td><a href="/wiki/Dell_Technologies" title="Dell Technologies">Dell Technologies</a></td>
<td>Information Technology</td>
<td>Technology Hardware, Storage &amp; Peripherals</td>
<td><a href="/wiki/Round_Rock,_Texas" title="Round Rock, Texas">Round Rock, Texas</a></td>
<td>2024-09-23</td>
<td>0001571996</td>
<td>2016
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:DAL">DAL</a>
</td>
<td><a href="/wiki/Delta_Air_Lines" title="Delta Air Lines">Delta Air Lines</a></td>
<td>Industrials</td>
<td>Passenger Airlines</td>
<td><a href="/wiki/Atlanta" title="Atlanta">Atlanta</a>, Georgia</td>
<td>2013-09-11</td>
<td>0000027904</td>
<td>1929
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:DVN">DVN</a>
</td>
<td><a href="/wiki/Devon_Energy" title="Devon Energy">Devon Energy</a></td>
<td>Energy</td>
<td>Oil &amp; Gas Exploration &amp; Production</td>
<td><a href="/wiki/Oklahoma_City" title="Oklahoma City">Oklahoma City</a>, Oklahoma</td>
<td>2000-08-30</td>
<td>0001090012</td>
<td>1971
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/dxcm">DXCM</a>
</td>
<td><a href="/wiki/Dexcom" title="Dexcom">Dexcom</a></td>
<td>Health Care</td>
<td>Health Care Equipment</td>
<td><a href="/wiki/San_Diego" title="San Diego">San Diego</a>, California</td>
<td>2020-05-12</td>
<td>0001093557</td>
<td>1999
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/fang">FANG</a>
</td>
<td><a href="/wiki/Diamondback_Energy" title="Diamondback Energy">Diamondback Energy</a></td>
<td>Energy</td>
<td>Oil &amp; Gas Exploration &amp; Production</td>
<td><a href="/wiki/Midland,_Texas" title="Midland, Texas">Midland, Texas</a></td>
<td>2018-12-03</td>
<td>0001539838</td>
<td>2007
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:DLR">DLR</a>
</td>
<td><a href="/wiki/Digital_Realty" title="Digital Realty">Digital Realty</a></td>
<td>Real Estate</td>
<td>Data Center REITs</td>
<td><a href="/wiki/Austin,_Texas" title="Austin, Texas">Austin, Texas</a></td>
<td>2016-05-18</td>
<td>0001297996</td>
<td>2004
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:DG">DG</a>
</td>
<td><a href="/wiki/Dollar_General" title="Dollar General">Dollar General</a></td>
<td>Consumer Staples</td>
<td>Consumer Staples Merchandise Retail</td>
<td><a href="/wiki/Goodlettsville,_Tennessee" title="Goodlettsville, Tennessee">Goodlettsville, Tennessee</a></td>
<td>2012-12-03</td>
<td>0000029534</td>
<td>1939
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/dltr">DLTR</a>
</td>
<td><a href="/wiki/Dollar_Tree" title="Dollar Tree">Dollar Tree</a></td>
<td>Consumer Staples</td>
<td>Consumer Staples Merchandise Retail</td>
<td><a href="/wiki/Chesapeake,_Virginia" title="Chesapeake, Virginia">Chesapeake, Virginia</a></td>
<td>2011-12-19</td>
<td>0000935703</td>
<td>1986
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:D">D</a>
</td>
<td><a href="/wiki/Dominion_Energy" title="Dominion Energy">Dominion Energy</a></td>
<td>Utilities</td>
<td>Multi-Utilities</td>
<td><a href="/wiki/Richmond,_Virginia" title="Richmond, Virginia">Richmond, Virginia</a></td>
<td>2016-11-30</td>
<td>0000715957</td>
<td>1983
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:DPZ">DPZ</a>
</td>
<td><a href="/wiki/Domino%27s" title="Domino's">Domino's</a></td>
<td>Consumer Discretionary</td>
<td>Restaurants</td>
<td><a href="/wiki/Ann_Arbor,_Michigan" title="Ann Arbor, Michigan">Ann Arbor, Michigan</a></td>
<td>2020-05-12</td>
<td>0001286681</td>
<td>1960
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/dash">DASH</a>
</td>
<td><a href="/wiki/DoorDash" title="DoorDash">DoorDash</a></td>
<td>Consumer Discretionary</td>
<td>Specialized Consumer Services</td>
<td><a href="/wiki/San_Francisco" title="San Francisco">San Francisco</a>, California</td>
<td>2025-03-24</td>
<td>0001792789</td>
<td>2012
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:DOV">DOV</a>
</td>
<td><a href="/wiki/Dover_Corporation" title="Dover Corporation">Dover Corporation</a></td>
<td>Industrials</td>
<td>Industrial Machinery &amp; Supplies &amp; Components</td>
<td><a href="/wiki/Downers_Grove,_Illinois" title="Downers Grove, Illinois">Downers Grove, Illinois</a></td>
<td>1985-10-31</td>
<td>0000029905</td>
<td>1955
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:DOW">DOW</a>
</td>
<td><a href="/wiki/Dow_Chemical_Company" title="Dow Chemical Company">Dow Inc.</a></td>
<td>Materials</td>
<td>Commodity Chemicals</td>
<td><a href="/wiki/Midland,_Michigan" title="Midland, Michigan">Midland, Michigan</a></td>
<td>2019-04-01</td>
<td>0001751788</td>
<td>2019 (1897)
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:DHI">DHI</a>
</td>
<td><a href="/wiki/D._R._Horton" title="D. R. Horton">D. R. Horton</a></td>
<td>Consumer Discretionary</td>
<td>Homebuilding</td>
<td><a href="/wiki/Arlington,_Texas" title="Arlington, Texas">Arlington, Texas</a></td>
<td>2005-06-22</td>
<td>0000882184</td>
<td>1978
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:DTE">DTE</a>
</td>
<td><a href="/wiki/DTE_Energy" title="DTE Energy">DTE Energy</a></td>
<td>Utilities</td>
<td>Multi-Utilities</td>
<td><a href="/wiki/Detroit" title="Detroit">Detroit</a>, Michigan</td>
<td>1957-03-04</td>
<td>0000936340</td>
<td>1995
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:DUK">DUK</a>
</td>
<td><a href="/wiki/Duke_Energy" title="Duke Energy">Duke Energy</a></td>
<td>Utilities</td>
<td>Electric Utilities</td>
<td><a href="/wiki/Charlotte,_North_Carolina" title="Charlotte, North Carolina">Charlotte, North Carolina</a></td>
<td>1976-06-30</td>
<td>0001326160
</td>
<td>1904
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:DD">DD</a>
</td>
<td><a href="/wiki/DuPont" title="DuPont">DuPont</a></td>
<td>Materials</td>
<td>Specialty Chemicals</td>
<td><a href="/wiki/Wilmington,_Delaware" title="Wilmington, Delaware">Wilmington, Delaware</a></td>
<td>2019-06-03</td>
<td>0001666700</td>
<td>2017 (1802)
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:EMN">EMN</a>
</td>
<td><a href="/wiki/Eastman_Chemical_Company" title="Eastman Chemical Company">Eastman Chemical Company</a></td>
<td>Materials</td>
<td>Specialty Chemicals</td>
<td><a href="/wiki/Kingsport,_Tennessee" title="Kingsport, Tennessee">Kingsport, Tennessee</a></td>
<td>1994-01-01</td>
<td>0000915389</td>
<td>1920
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:ETN">ETN</a>
</td>
<td><a href="/wiki/Eaton_Corporation" title="Eaton Corporation">Eaton Corporation</a></td>
<td>Industrials</td>
<td>Electrical Components &amp; Equipment</td>
<td><a href="/wiki/Dublin" title="Dublin">Dublin</a>, Ireland</td>
<td>1957-03-04</td>
<td>0001551182</td>
<td>1911
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/ebay">EBAY</a>
</td>
<td><a href="/wiki/EBay" title="EBay">eBay Inc.</a></td>
<td>Consumer Discretionary</td>
<td>Broadline Retail</td>
<td><a href="/wiki/San_Jose,_California" title="San Jose, California">San Jose, California</a></td>
<td>2002-07-22</td>
<td>0001065088</td>
<td>1995
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:ECL">ECL</a>
</td>
<td><a href="/wiki/Ecolab" title="Ecolab">Ecolab</a></td>
<td>Materials</td>
<td>Specialty Chemicals</td>
<td><a href="/wiki/Saint_Paul,_Minnesota" title="Saint Paul, Minnesota">Saint Paul, Minnesota</a></td>
<td>1989-01-31</td>
<td>0000031462</td>
<td>1923
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:EIX">EIX</a>
</td>
<td><a href="/wiki/Edison_International" title="Edison International">Edison International</a></td>
<td>Utilities</td>
<td>Electric Utilities</td>
<td><a href="/wiki/Rosemead,_California" title="Rosemead, California">Rosemead, California</a></td>
<td>1957-03-04</td>
<td>0000827052</td>
<td>1886
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:EW">EW</a>
</td>
<td><a href="/wiki/Edwards_Lifesciences" title="Edwards Lifesciences">Edwards Lifesciences</a></td>
<td>Health Care</td>
<td>Health Care Equipment</td>
<td><a href="/wiki/Irvine,_California" title="Irvine, California">Irvine, California</a></td>
<td>2011-04-01</td>
<td>0001099800</td>
<td>1958
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/ea">EA</a>
</td>
<td><a href="/wiki/Electronic_Arts" title="Electronic Arts">Electronic Arts</a></td>
<td>Communication Services</td>
<td>Interactive Home Entertainment</td>
<td><a href="/wiki/Redwood_City,_California" title="Redwood City, California">Redwood City, California</a></td>
<td>2002-07-22</td>
<td>0000712515</td>
<td>1982
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:ELV">ELV</a>
</td>
<td><a href="/wiki/Elevance_Health" title="Elevance Health">Elevance Health</a></td>
<td>Health Care</td>
<td>Managed Health Care</td>
<td><a href="/wiki/Indianapolis" title="Indianapolis">Indianapolis</a>, Indiana</td>
<td>2002-07-25</td>
<td>0001156039
</td>
<td>2014 (1946)
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:EMR">EMR</a>
</td>
<td><a href="/wiki/Emerson_Electric" title="Emerson Electric">Emerson Electric</a></td>
<td>Industrials</td>
<td>Electrical Components &amp; Equipment</td>
<td><a href="/wiki/Ferguson,_Missouri" title="Ferguson, Missouri">Ferguson, Missouri</a></td>
<td>1965-03-31</td>
<td>0000032604</td>
<td>1890
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/enph">ENPH</a>
</td>
<td><a href="/wiki/Enphase_Energy" title="Enphase Energy">Enphase Energy</a></td>
<td>Information Technology</td>
<td>Semiconductor Materials &amp; Equipment</td>
<td><a href="/wiki/Fremont,_California" title="Fremont, California">Fremont, California</a></td>
<td>2021-01-07</td>
<td>0001463101</td>
<td>2006
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:ETR">ETR</a>
</td>
<td><a href="/wiki/Entergy" title="Entergy">Entergy</a></td>
<td>Utilities</td>
<td>Electric Utilities</td>
<td><a href="/wiki/New_Orleans" title="New Orleans">New Orleans</a>, Louisiana</td>
<td>1957-03-04</td>
<td>0000065984</td>
<td>1913
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:EOG">EOG</a>
</td>
<td><a href="/wiki/EOG_Resources" title="EOG Resources">EOG Resources</a></td>
<td>Energy</td>
<td>Oil &amp; Gas Exploration &amp; Production</td>
<td><a href="/wiki/Houston" title="Houston">Houston</a>, Texas</td>
<td>2000-11-02</td>
<td>0000821189</td>
<td>1999
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:EPAM">EPAM</a>
</td>
<td><a href="/wiki/EPAM_Systems" title="EPAM Systems">EPAM Systems</a></td>
<td>Information Technology</td>
<td>IT Consulting &amp; Other Services</td>
<td><a href="/wiki/Newtown,_Bucks_County,_Pennsylvania" title="Newtown, Bucks County, Pennsylvania">Newtown, Pennsylvania</a></td>
<td>2021-12-14</td>
<td>0001352010</td>
<td>1993
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:EQT">EQT</a>
</td>
<td><a href="/wiki/EQT_Corporation" title="EQT Corporation">EQT Corporation</a></td>
<td>Energy</td>
<td>Oil &amp; Gas Exploration &amp; Production</td>
<td><a href="/wiki/Pittsburgh" title="Pittsburgh">Pittsburgh</a>, Pennsylvania</td>
<td>2022-10-03</td>
<td>0000033213</td>
<td>1888
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:EFX">EFX</a>
</td>
<td><a href="/wiki/Equifax" title="Equifax">Equifax</a></td>
<td>Industrials</td>
<td>Research &amp; Consulting Services</td>
<td><a href="/wiki/Atlanta" title="Atlanta">Atlanta</a>, Georgia</td>
<td>1997-06-19</td>
<td>0000033185</td>
<td>1899
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/eqix">EQIX</a>
</td>
<td><a href="/wiki/Equinix" title="Equinix">Equinix</a></td>
<td>Real Estate</td>
<td>Data Center REITs</td>
<td><a href="/wiki/Redwood_City,_California" title="Redwood City, California">Redwood City, California</a></td>
<td>2015-03-20</td>
<td>0001101239</td>
<td>1998
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:EQR">EQR</a>
</td>
<td><a href="/wiki/Equity_Residential" title="Equity Residential">Equity Residential</a></td>
<td>Real Estate</td>
<td>Multi-Family Residential REITs</td>
<td><a href="/wiki/Chicago" title="Chicago">Chicago</a>, Illinois</td>
<td>2001-12-03</td>
<td>0000906107</td>
<td>1969
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/erie">ERIE</a>
</td>
<td><a href="/wiki/Erie_Insurance_Group" title="Erie Insurance Group">Erie Indemnity</a></td>
<td>Financials</td>
<td>Insurance Brokers</td>
<td><a href="/wiki/Erie,_Pennsylvania" title="Erie, Pennsylvania">Erie, Pennsylvania</a></td>
<td>2024-09-23</td>
<td>0000922621</td>
<td>1925
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:ESS">ESS</a>
</td>
<td><a href="/wiki/Essex_Property_Trust" title="Essex Property Trust">Essex Property Trust</a></td>
<td>Real Estate</td>
<td>Multi-Family Residential REITs</td>
<td><a href="/wiki/San_Mateo,_California" title="San Mateo, California">San Mateo, California</a></td>
<td>2014-04-02</td>
<td>0000920522</td>
<td>1971
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:EL">EL</a>
</td>
<td><a href="/wiki/The_Est%C3%A9e_Lauder_Companies" title="The Estée Lauder Companies">Estée Lauder Companies (The)</a></td>
<td>Consumer Staples</td>
<td>Personal Care Products</td>
<td><a href="/wiki/New_York_City" title="New York City">New York City</a>, New York</td>
<td>2006-01-05</td>
<td>0001001250</td>
<td>1946
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:EG">EG</a>
</td>
<td><a href="/wiki/Everest_Group" title="Everest Group">Everest Group</a></td>
<td>Financials</td>
<td>Reinsurance</td>
<td><a href="/wiki/Hamilton,_Bermuda" title="Hamilton, Bermuda">Hamilton, Bermuda</a></td>
<td>2017-06-19</td>
<td>0001095073</td>
<td>1973
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:EVRG">EVRG</a>
</td>
<td><a href="/wiki/Evergy" title="Evergy">Evergy</a></td>
<td>Utilities</td>
<td>Electric Utilities</td>
<td><a href="/wiki/Kansas_City,_Missouri" title="Kansas City, Missouri">Kansas City, Missouri</a></td>
<td>2018-06-05</td>
<td>0001711269</td>
<td>1909
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:ES">ES</a>
</td>
<td><a href="/wiki/Eversource_Energy" title="Eversource Energy">Eversource Energy</a></td>
<td>Utilities</td>
<td>Electric Utilities</td>
<td><a href="/wiki/Hartford,_Connecticut" title="Hartford, Connecticut">Hartford, Connecticut</a></td>
<td>2009-07-24</td>
<td>0000072741</td>
<td>1966
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/exc">EXC</a>
</td>
<td><a href="/wiki/Exelon" title="Exelon">Exelon</a></td>
<td>Utilities</td>
<td>Electric Utilities</td>
<td><a href="/wiki/Chicago" title="Chicago">Chicago</a>, Illinois</td>
<td>1957-03-04</td>
<td>0001109357</td>
<td>2000
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/exe">EXE</a>
</td>
<td><a href="/wiki/Expand_Energy" title="Expand Energy">Expand Energy</a></td>
<td>Energy</td>
<td>Oil &amp; Gas Exploration &amp; Production</td>
<td><a href="/wiki/Oklahoma_City" title="Oklahoma City">Oklahoma City</a>, Oklahoma</td>
<td>2025-03-24</td>
<td>0000895126</td>
<td>1989
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/expe">EXPE</a>
</td>
<td><a href="/wiki/Expedia_Group" title="Expedia Group">Expedia Group</a></td>
<td>Consumer Discretionary</td>
<td>Hotels, Resorts &amp; Cruise Lines</td>
<td><a href="/wiki/Seattle" title="Seattle">Seattle</a>, Washington</td>
<td>2007-10-02</td>
<td>0001324424</td>
<td>1996
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/expd">EXPD</a>
</td>
<td><a href="/wiki/Expeditors_International" title="Expeditors International">Expeditors International</a></td>
<td>Industrials</td>
<td>Air Freight &amp; Logistics</td>
<td><a href="/wiki/Seattle" title="Seattle">Seattle</a>, Washington</td>
<td>2007-10-10</td>
<td>0000746515</td>
<td>1979
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:EXR">EXR</a>
</td>
<td><a href="/wiki/Extra_Space_Storage" title="Extra Space Storage">Extra Space Storage</a></td>
<td>Real Estate</td>
<td>Self-Storage REITs</td>
<td><a href="/wiki/Salt_Lake_City" title="Salt Lake City">Salt Lake City</a>, Utah</td>
<td>2016-01-19</td>
<td>0001289490</td>
<td>1977
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:XOM">XOM</a>
</td>
<td><a href="/wiki/ExxonMobil" title="ExxonMobil">ExxonMobil</a></td>
<td>Energy</td>
<td>Integrated Oil &amp; Gas</td>
<td><a href="/wiki/Irving,_Texas" title="Irving, Texas">Irving, Texas</a></td>
<td>1957-03-04</td>
<td>0000034088</td>
<td>1999
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/ffiv">FFIV</a>
</td>
<td><a href="/wiki/F5,_Inc." title="F5, Inc.">F5, Inc.</a></td>
<td>Information Technology</td>
<td>Communications Equipment</td>
<td><a href="/wiki/Seattle" title="Seattle">Seattle</a>, Washington</td>
<td>2010-12-20</td>
<td>0001048695</td>
<td>1996
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:FDS">FDS</a>
</td>
<td><a href="/wiki/FactSet" title="FactSet">FactSet</a></td>
<td>Financials</td>
<td>Financial Exchanges &amp; Data</td>
<td><a href="/wiki/Norwalk,_Connecticut" title="Norwalk, Connecticut">Norwalk, Connecticut</a></td>
<td>2021-12-20</td>
<td>0001013237</td>
<td>1978
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:FICO">FICO</a>
</td>
<td><a href="/wiki/FICO" title="FICO">Fair Isaac</a></td>
<td>Information Technology</td>
<td>Application Software</td>
<td><a href="/wiki/Bozeman,_Montana" title="Bozeman, Montana">Bozeman, Montana</a></td>
<td>2023-03-20</td>
<td>0000814547</td>
<td>1956
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/fast">FAST</a>
</td>
<td><a href="/wiki/Fastenal" title="Fastenal">Fastenal</a></td>
<td>Industrials</td>
<td>Trading Companies &amp; Distributors</td>
<td><a href="/wiki/Winona,_Minnesota" title="Winona, Minnesota">Winona, Minnesota</a></td>
<td>2008-09-15</td>
<td>0000815556</td>
<td>1967
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:FRT">FRT</a>
</td>
<td><a href="/wiki/Federal_Realty_Investment_Trust" title="Federal Realty Investment Trust">Federal Realty Investment Trust</a></td>
<td>Real Estate</td>
<td>Retail REITs</td>
<td><a href="/wiki/Rockville,_Maryland" title="Rockville, Maryland">Rockville, Maryland</a></td>
<td>2016-02-01</td>
<td>0000034903</td>
<td>1962
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:FDX">FDX</a>
</td>
<td><a href="/wiki/FedEx" title="FedEx">FedEx</a></td>
<td>Industrials</td>
<td>Air Freight &amp; Logistics</td>
<td><a href="/wiki/Memphis,_Tennessee" title="Memphis, Tennessee">Memphis, Tennessee</a></td>
<td>1980-12-31</td>
<td>0001048911
</td>
<td>1971
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:FIS">FIS</a>
</td>
<td><a href="/wiki/FIS_(company)" title="FIS (company)">Fidelity National Information Services</a></td>
<td>Financials</td>
<td>Transaction &amp; Payment Processing Services</td>
<td><a href="/wiki/Jacksonville,_Florida" title="Jacksonville, Florida">Jacksonville, Florida</a></td>
<td>2006-11-10</td>
<td>0001136893</td>
<td>1968
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/fitb">FITB</a>
</td>
<td><a href="/wiki/Fifth_Third_Bancorp" class="mw-redirect" title="Fifth Third Bancorp">Fifth Third Bancorp</a></td>
<td>Financials</td>
<td>Regional Banks</td>
<td><a href="/wiki/Cincinnati" title="Cincinnati">Cincinnati</a>, Ohio</td>
<td>1996-03-29</td>
<td>0000035527</td>
<td>1858
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/fslr">FSLR</a>
</td>
<td><a href="/wiki/First_Solar" title="First Solar">First Solar</a></td>
<td>Information Technology</td>
<td>Semiconductors</td>
<td><a href="/wiki/Tempe,_Arizona" title="Tempe, Arizona">Tempe, Arizona</a></td>
<td>2022-12-19</td>
<td>0001274494</td>
<td>1999
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:FE">FE</a>
</td>
<td><a href="/wiki/FirstEnergy" title="FirstEnergy">FirstEnergy</a></td>
<td>Utilities</td>
<td>Electric Utilities</td>
<td><a href="/wiki/Akron,_Ohio" title="Akron, Ohio">Akron, Ohio</a></td>
<td>1997-11-28</td>
<td>0001031296</td>
<td>1997
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:FI">FI</a>
</td>
<td><a href="/wiki/Fiserv" title="Fiserv">Fiserv</a></td>
<td>Financials</td>
<td>Transaction &amp; Payment Processing Services</td>
<td><a href="/wiki/Brookfield,_Wisconsin" title="Brookfield, Wisconsin">Brookfield, Wisconsin</a></td>
<td>2001-04-02</td>
<td>0000798354</td>
<td>1984
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:F">F</a>
</td>
<td><a href="/wiki/Ford_Motor_Company" title="Ford Motor Company">Ford Motor Company</a></td>
<td>Consumer Discretionary</td>
<td>Automobile Manufacturers</td>
<td><a href="/wiki/Dearborn,_Michigan" title="Dearborn, Michigan">Dearborn, Michigan</a></td>
<td>1957-03-04</td>
<td>0000037996</td>
<td>1903
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/ftnt">FTNT</a>
</td>
<td><a href="/wiki/Fortinet" title="Fortinet">Fortinet</a></td>
<td>Information Technology</td>
<td>Systems Software</td>
<td><a href="/wiki/Sunnyvale,_California" title="Sunnyvale, California">Sunnyvale, California</a></td>
<td>2018-10-11</td>
<td>0001262039</td>
<td>2000
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:FTV">FTV</a>
</td>
<td><a href="/wiki/Fortive" title="Fortive">Fortive</a></td>
<td>Industrials</td>
<td>Industrial Machinery &amp; Supplies &amp; Components</td>
<td><a href="/wiki/Everett,_Washington" title="Everett, Washington">Everett, Washington</a></td>
<td>2016-07-01</td>
<td>0001659166</td>
<td>2016
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/foxa">FOXA</a>
</td>
<td><a href="/wiki/Fox_Corporation" title="Fox Corporation">Fox Corporation</a> (Class A)</td>
<td>Communication Services</td>
<td>Broadcasting</td>
<td><a href="/wiki/New_York_City" title="New York City">New York City</a>, New York</td>
<td>2019-03-19</td>
<td>0001754301
</td>
<td>2019
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/fox">FOX</a>
</td>
<td><a href="/wiki/Fox_Corporation" title="Fox Corporation">Fox Corporation</a> (Class B)</td>
<td>Communication Services</td>
<td>Broadcasting</td>
<td><a href="/wiki/New_York_City" title="New York City">New York City</a>, New York</td>
<td>2019-03-19</td>
<td>0001754301
</td>
<td>2019
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:BEN">BEN</a>
</td>
<td><a href="/wiki/Franklin_Templeton_Investments" title="Franklin Templeton Investments">Franklin Resources</a></td>
<td>Financials</td>
<td>Asset Management &amp; Custody Banks</td>
<td><a href="/wiki/San_Mateo,_California" title="San Mateo, California">San Mateo, California</a></td>
<td>1998-04-30</td>
<td>0000038777</td>
<td>1947
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:FCX">FCX</a>
</td>
<td><a href="/wiki/Freeport-McMoRan" title="Freeport-McMoRan">Freeport-McMoRan</a></td>
<td>Materials</td>
<td>Copper</td>
<td><a href="/wiki/Phoenix,_Arizona" title="Phoenix, Arizona">Phoenix, Arizona</a></td>
<td>2011-07-01</td>
<td>0000831259</td>
<td>1912
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:GRMN">GRMN</a>
</td>
<td><a href="/wiki/Garmin" title="Garmin">Garmin</a></td>
<td>Consumer Discretionary</td>
<td>Consumer Electronics</td>
<td><a href="/wiki/Schaffhausen,_Switzerland" class="mw-redirect" title="Schaffhausen, Switzerland">Schaffhausen, Switzerland</a></td>
<td>2012-12-12</td>
<td>0001121788</td>
<td>1989
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:IT">IT</a>
</td>
<td><a href="/wiki/Gartner" title="Gartner">Gartner</a></td>
<td>Information Technology</td>
<td>IT Consulting &amp; Other Services</td>
<td><a href="/wiki/Stamford,_Connecticut" title="Stamford, Connecticut">Stamford, Connecticut</a></td>
<td>2017-04-05</td>
<td>0000749251</td>
<td>1979
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:GE">GE</a>
</td>
<td><a href="/wiki/GE_Aerospace" title="GE Aerospace">GE Aerospace</a></td>
<td>Industrials</td>
<td>Aerospace &amp; Defense</td>
<td><a href="/wiki/Evendale,_Ohio" title="Evendale, Ohio">Evendale, Ohio</a></td>
<td>1957-03-04</td>
<td>0000040545</td>
<td>1892
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/gehc">GEHC</a>
</td>
<td><a href="/wiki/GE_HealthCare" title="GE HealthCare">GE HealthCare</a></td>
<td>Health Care</td>
<td>Health Care Equipment</td>
<td><a href="/wiki/Chicago" title="Chicago">Chicago</a>, Illinois</td>
<td>2023-01-04</td>
<td>0001932393</td>
<td>1994
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:GEV">GEV</a>
</td>
<td><a href="/wiki/GE_Vernova" title="GE Vernova">GE Vernova</a></td>
<td>Industrials</td>
<td>Heavy Electrical Equipment</td>
<td><a href="/wiki/Cambridge,_Massachusetts" title="Cambridge, Massachusetts">Cambridge, Massachusetts</a></td>
<td>2024-04-02</td>
<td>0001996810</td>
<td>2024
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/gen">GEN</a>
</td>
<td><a href="/wiki/Gen_Digital" title="Gen Digital">Gen Digital</a></td>
<td>Information Technology</td>
<td>Systems Software</td>
<td><a href="/wiki/Tempe,_Arizona" title="Tempe, Arizona">Tempe, Arizona</a></td>
<td>2003-03-25</td>
<td>0000849399</td>
<td>1982
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:GNRC">GNRC</a>
</td>
<td><a href="/wiki/Generac" title="Generac">Generac</a></td>
<td>Industrials</td>
<td>Electrical Components &amp; Equipment</td>
<td><a href="/wiki/Waukesha,_Wisconsin" title="Waukesha, Wisconsin">Waukesha, Wisconsin</a></td>
<td>2021-03-22</td>
<td>0001474735</td>
<td>1959
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:GD">GD</a>
</td>
<td><a href="/wiki/General_Dynamics" title="General Dynamics">General Dynamics</a></td>
<td>Industrials</td>
<td>Aerospace &amp; Defense</td>
<td><a href="/wiki/Falls_Church,_Virginia" title="Falls Church, Virginia">Falls Church, Virginia</a></td>
<td>1957-03-04</td>
<td>0000040533</td>
<td>1899
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:GIS">GIS</a>
</td>
<td><a href="/wiki/General_Mills" title="General Mills">General Mills</a></td>
<td>Consumer Staples</td>
<td>Packaged Foods &amp; Meats</td>
<td><a href="/wiki/Golden_Valley,_Minnesota" title="Golden Valley, Minnesota">Golden Valley, Minnesota</a></td>
<td>1957-03-04</td>
<td>0000040704</td>
<td>1856
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:GM">GM</a>
</td>
<td><a href="/wiki/General_Motors" title="General Motors">General Motors</a></td>
<td>Consumer Discretionary</td>
<td>Automobile Manufacturers</td>
<td><a href="/wiki/Detroit" title="Detroit">Detroit</a>, Michigan</td>
<td>2013-06-06</td>
<td>0001467858
</td>
<td>1908
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:GPC">GPC</a>
</td>
<td><a href="/wiki/Genuine_Parts_Company" title="Genuine Parts Company">Genuine Parts Company</a></td>
<td>Consumer Discretionary</td>
<td>Distributors</td>
<td><a href="/wiki/Atlanta" title="Atlanta">Atlanta</a>, Georgia</td>
<td>1973-12-31</td>
<td>0000040987</td>
<td>1925
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/gild">GILD</a>
</td>
<td><a href="/wiki/Gilead_Sciences" title="Gilead Sciences">Gilead Sciences</a></td>
<td>Health Care</td>
<td>Biotechnology</td>
<td><a href="/wiki/Foster_City,_California" title="Foster City, California">Foster City, California</a></td>
<td>2004-07-01</td>
<td>0000882095</td>
<td>1987
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:GPN">GPN</a>
</td>
<td><a href="/wiki/Global_Payments" title="Global Payments">Global Payments</a></td>
<td>Financials</td>
<td>Transaction &amp; Payment Processing Services</td>
<td><a href="/wiki/Atlanta" title="Atlanta">Atlanta</a>, Georgia</td>
<td>2016-04-25</td>
<td>0001123360</td>
<td>2000
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:GL">GL</a>
</td>
<td><a href="/wiki/Globe_Life" title="Globe Life">Globe Life</a></td>
<td>Financials</td>
<td>Life &amp; Health Insurance</td>
<td><a href="/wiki/McKinney,_Texas" title="McKinney, Texas">McKinney, Texas</a></td>
<td>1989-04-30</td>
<td>0000320335</td>
<td>1900
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:GDDY">GDDY</a>
</td>
<td><a href="/wiki/GoDaddy" title="GoDaddy">GoDaddy</a></td>
<td>Information Technology</td>
<td>Internet Services &amp; Infrastructure</td>
<td><a href="/wiki/Tempe,_Arizona" title="Tempe, Arizona">Tempe, Arizona</a></td>
<td>2024-06-24</td>
<td>0001609711</td>
<td>1997
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:GS">GS</a>
</td>
<td><a href="/wiki/Goldman_Sachs" title="Goldman Sachs">Goldman Sachs</a></td>
<td>Financials</td>
<td>Investment Banking &amp; Brokerage</td>
<td><a href="/wiki/New_York_City" title="New York City">New York City</a>, New York</td>
<td>2002-07-22</td>
<td>0000886982</td>
<td>1869
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:HAL">HAL</a>
</td>
<td><a href="/wiki/Halliburton" title="Halliburton">Halliburton</a></td>
<td>Energy</td>
<td>Oil &amp; Gas Equipment &amp; Services</td>
<td><a href="/wiki/Houston" title="Houston">Houston</a>, Texas</td>
<td>1957-03-04</td>
<td>0000045012</td>
<td>1919
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:HIG">HIG</a>
</td>
<td><a href="/wiki/The_Hartford" title="The Hartford">Hartford (The)</a></td>
<td>Financials</td>
<td>Property &amp; Casualty Insurance</td>
<td><a href="/wiki/Hartford,_Connecticut" title="Hartford, Connecticut">Hartford, Connecticut</a></td>
<td>1957-03-04</td>
<td>0000874766</td>
<td>1810
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/has">HAS</a>
</td>
<td><a href="/wiki/Hasbro" title="Hasbro">Hasbro</a></td>
<td>Consumer Discretionary</td>
<td>Leisure Products</td>
<td><a href="/wiki/Pawtucket,_Rhode_Island" title="Pawtucket, Rhode Island">Pawtucket, Rhode Island</a></td>
<td>1984-09-30</td>
<td>0000046080</td>
<td>1923
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:HCA">HCA</a>
</td>
<td><a href="/wiki/HCA_Healthcare" title="HCA Healthcare">HCA Healthcare</a></td>
<td>Health Care</td>
<td>Health Care Facilities</td>
<td><a href="/wiki/Nashville,_Tennessee" title="Nashville, Tennessee">Nashville, Tennessee</a></td>
<td>2015-01-27</td>
<td>0000860730</td>
<td>1968
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:DOC">DOC</a>
</td>
<td><a href="/wiki/Healthpeak_Properties" title="Healthpeak Properties">Healthpeak Properties</a></td>
<td>Real Estate</td>
<td>Health Care REITs</td>
<td><a href="/wiki/Denver" title="Denver">Denver</a>, Colorado</td>
<td>2008-03-31</td>
<td>0000765880</td>
<td>1985
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/hsic">HSIC</a>
</td>
<td><a href="/wiki/Henry_Schein" title="Henry Schein">Henry Schein</a></td>
<td>Health Care</td>
<td>Health Care Distributors</td>
<td><a href="/wiki/Melville,_New_York" title="Melville, New York">Melville, New York</a></td>
<td>2015-03-17</td>
<td>0001000228</td>
<td>1932
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:HSY">HSY</a>
</td>
<td><a href="/wiki/The_Hershey_Company" title="The Hershey Company">Hershey Company (The)</a></td>
<td>Consumer Staples</td>
<td>Packaged Foods &amp; Meats</td>
<td><a href="/wiki/Hershey,_Pennsylvania" title="Hershey, Pennsylvania">Hershey, Pennsylvania</a></td>
<td>1957-03-04</td>
<td>0000047111</td>
<td>1894
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:HPE">HPE</a>
</td>
<td><a href="/wiki/Hewlett_Packard_Enterprise" title="Hewlett Packard Enterprise">Hewlett Packard Enterprise</a></td>
<td>Information Technology</td>
<td>Technology Hardware, Storage &amp; Peripherals</td>
<td><a href="/wiki/Houston" title="Houston">Houston</a>, Texas</td>
<td>2015-11-02</td>
<td>0001645590</td>
<td>2015
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:HLT">HLT</a>
</td>
<td><a href="/wiki/Hilton_Worldwide" title="Hilton Worldwide">Hilton Worldwide</a></td>
<td>Consumer Discretionary</td>
<td>Hotels, Resorts &amp; Cruise Lines</td>
<td><a href="/wiki/Tysons_Corner,_Virginia" class="mw-redirect" title="Tysons Corner, Virginia">Tysons Corner, Virginia</a></td>
<td>2017-06-19</td>
<td>0001585689</td>
<td>1919
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/holx">HOLX</a>
</td>
<td><a href="/wiki/Hologic" title="Hologic">Hologic</a></td>
<td>Health Care</td>
<td>Health Care Equipment</td>
<td><a href="/wiki/Marlborough,_Massachusetts" title="Marlborough, Massachusetts">Marlborough, Massachusetts</a></td>
<td>2016-03-30</td>
<td>0000859737</td>
<td>1985
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:HD">HD</a>
</td>
<td><a href="/wiki/Home_Depot" title="Home Depot">Home Depot (The)</a></td>
<td>Consumer Discretionary</td>
<td>Home Improvement Retail</td>
<td><a href="/wiki/Atlanta" title="Atlanta">Atlanta</a>, Georgia</td>
<td>1988-03-31</td>
<td>0000354950</td>
<td>1978
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/hon">HON</a>
</td>
<td><a href="/wiki/Honeywell" title="Honeywell">Honeywell</a></td>
<td>Industrials</td>
<td>Industrial Conglomerates</td>
<td><a href="/wiki/Charlotte,_North_Carolina" title="Charlotte, North Carolina">Charlotte, North Carolina</a></td>
<td>1957-03-04</td>
<td>0000773840</td>
<td>1906
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:HRL">HRL</a>
</td>
<td><a href="/wiki/Hormel_Foods" title="Hormel Foods">Hormel Foods</a></td>
<td>Consumer Staples</td>
<td>Packaged Foods &amp; Meats</td>
<td><a href="/wiki/Austin,_Minnesota" title="Austin, Minnesota">Austin, Minnesota</a></td>
<td>2009-03-04</td>
<td>0000048465</td>
<td>1891
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/hst">HST</a>
</td>
<td><a href="/wiki/Host_Hotels_%26_Resorts" title="Host Hotels &amp; Resorts">Host Hotels &amp; Resorts</a></td>
<td>Real Estate</td>
<td>Hotel &amp; Resort REITs</td>
<td><a href="/wiki/Bethesda,_Maryland" title="Bethesda, Maryland">Bethesda, Maryland</a></td>
<td>2007-03-20</td>
<td>0001070750</td>
<td>1993
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:HWM">HWM</a>
</td>
<td><a href="/wiki/Howmet_Aerospace" title="Howmet Aerospace">Howmet Aerospace</a></td>
<td>Industrials</td>
<td>Aerospace &amp; Defense</td>
<td><a href="/wiki/Pittsburgh" title="Pittsburgh">Pittsburgh</a>, Pennsylvania</td>
<td>2016-10-21</td>
<td>0000004281</td>
<td>1888
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:HPQ">HPQ</a>
</td>
<td><a href="/wiki/HP_Inc." title="HP Inc.">HP Inc.</a></td>
<td>Information Technology</td>
<td>Technology Hardware, Storage &amp; Peripherals</td>
<td><a href="/wiki/Palo_Alto,_California" title="Palo Alto, California">Palo Alto, California</a></td>
<td>1974-12-31</td>
<td>0000047217</td>
<td>1939 (2015)
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:HUBB">HUBB</a>
</td>
<td><a href="/wiki/Hubbell_Incorporated" title="Hubbell Incorporated">Hubbell Incorporated</a></td>
<td>Industrials</td>
<td>Industrial Machinery &amp; Supplies &amp; Components</td>
<td><a href="/wiki/Shelton,_Connecticut" title="Shelton, Connecticut">Shelton, Connecticut</a></td>
<td>2023-10-18</td>
<td>0000048898</td>
<td>1888
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:HUM">HUM</a>
</td>
<td><a href="/wiki/Humana" title="Humana">Humana</a></td>
<td>Health Care</td>
<td>Managed Health Care</td>
<td><a href="/wiki/Louisville,_Kentucky" title="Louisville, Kentucky">Louisville, Kentucky</a></td>
<td>2012-12-10</td>
<td>0000049071</td>
<td>1961
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/hban">HBAN</a>
</td>
<td><a href="/wiki/Huntington_Bancshares" title="Huntington Bancshares">Huntington Bancshares</a></td>
<td>Financials</td>
<td>Regional Banks</td>
<td><a href="/wiki/Columbus,_Ohio" title="Columbus, Ohio">Columbus, Ohio</a>; <a href="/wiki/Detroit" title="Detroit">Detroit</a>, Michigan</td>
<td>1997-08-28</td>
<td>0000049196</td>
<td>1866
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:HII">HII</a>
</td>
<td><a href="/wiki/Huntington_Ingalls_Industries" title="Huntington Ingalls Industries">Huntington Ingalls Industries</a></td>
<td>Industrials</td>
<td>Aerospace &amp; Defense</td>
<td><a href="/wiki/Newport_News,_Virginia" title="Newport News, Virginia">Newport News, Virginia</a></td>
<td>2018-01-03</td>
<td>0001501585</td>
<td>2011
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:IBM">IBM</a>
</td>
<td><a href="/wiki/IBM" title="IBM">IBM</a></td>
<td>Information Technology</td>
<td>IT Consulting &amp; Other Services</td>
<td><a href="/wiki/Armonk,_New_York" title="Armonk, New York">Armonk, New York</a></td>
<td>1957-03-04</td>
<td>0000051143</td>
<td>1911
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:IEX">IEX</a>
</td>
<td><a href="/wiki/IDEX_Corporation" title="IDEX Corporation">IDEX Corporation</a></td>
<td>Industrials</td>
<td>Industrial Machinery &amp; Supplies &amp; Components</td>
<td><a href="/wiki/Lake_Forest,_Illinois" title="Lake Forest, Illinois">Lake Forest, Illinois</a></td>
<td>2019-08-09</td>
<td>0000832101</td>
<td>1988
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/idxx">IDXX</a>
</td>
<td><a href="/wiki/Idexx_Laboratories" title="Idexx Laboratories">Idexx Laboratories</a></td>
<td>Health Care</td>
<td>Health Care Equipment</td>
<td><a href="/wiki/Westbrook,_Maine" title="Westbrook, Maine">Westbrook, Maine</a></td>
<td>2017-01-05</td>
<td>0000874716</td>
<td>1983
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:ITW">ITW</a>
</td>
<td><a href="/wiki/Illinois_Tool_Works" title="Illinois Tool Works">Illinois Tool Works</a></td>
<td>Industrials</td>
<td>Industrial Machinery &amp; Supplies &amp; Components</td>
<td><a href="/wiki/Glenview,_Cook_County,_Illinois" class="mw-redirect" title="Glenview, Cook County, Illinois">Glenview, Illinois</a></td>
<td>1986-02-28</td>
<td>0000049826</td>
<td>1912
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/incy">INCY</a>
</td>
<td><a href="/wiki/Incyte" title="Incyte">Incyte</a></td>
<td>Health Care</td>
<td>Biotechnology</td>
<td><a href="/wiki/Wilmington,_Delaware" title="Wilmington, Delaware">Wilmington, Delaware</a></td>
<td>2017-02-28</td>
<td>0000879169</td>
<td>1991
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:IR">IR</a>
</td>
<td><a href="/wiki/Ingersoll_Rand" title="Ingersoll Rand">Ingersoll Rand</a></td>
<td>Industrials</td>
<td>Industrial Machinery &amp; Supplies &amp; Components</td>
<td><a href="/wiki/Davidson,_North_Carolina" title="Davidson, North Carolina">Davidson, North Carolina</a></td>
<td>2020-03-03</td>
<td>0001699150</td>
<td>1859
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/podd">PODD</a>
</td>
<td><a href="/w/index.php?title=Insulet_Corporation&amp;action=edit&amp;redlink=1" class="new" title="Insulet Corporation (page does not exist)">Insulet Corporation</a></td>
<td>Health Care</td>
<td>Health Care Equipment</td>
<td><a href="/wiki/Acton,_Massachusetts" title="Acton, Massachusetts">Acton, Massachusetts</a></td>
<td>2023-03-15</td>
<td>0001145197</td>
<td>2000
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/intc">INTC</a>
</td>
<td><a href="/wiki/Intel" title="Intel">Intel</a></td>
<td>Information Technology</td>
<td>Semiconductors</td>
<td><a href="/wiki/Santa_Clara,_California" title="Santa Clara, California">Santa Clara, California</a></td>
<td>1976-12-31</td>
<td>0000050863
</td>
<td>1968
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/ibkr">IBKR</a>
</td>
<td><a href="/wiki/Interactive_Brokers" title="Interactive Brokers">Interactive Brokers</a></td>
<td>Financials</td>
<td>Investment Banking &amp; Brokerage</td>
<td><a href="/wiki/Greenwich,_Connecticut" title="Greenwich, Connecticut">Greenwich, Connecticut</a></td>
<td>2025-08-28</td>
<td>0001381197
</td>
<td>1977
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:ICE">ICE</a>
</td>
<td><a href="/wiki/Intercontinental_Exchange" title="Intercontinental Exchange">Intercontinental Exchange</a></td>
<td>Financials</td>
<td>Financial Exchanges &amp; Data</td>
<td><a href="/wiki/Atlanta" title="Atlanta">Atlanta</a>, Georgia</td>
<td>2007-09-26</td>
<td>0001571949</td>
<td>2000
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:IFF">IFF</a>
</td>
<td><a href="/wiki/International_Flavors_%26_Fragrances" title="International Flavors &amp; Fragrances">International Flavors &amp; Fragrances</a></td>
<td>Materials</td>
<td>Specialty Chemicals</td>
<td><a href="/wiki/New_York_City" title="New York City">New York City</a>, New York</td>
<td>1976-03-31</td>
<td>0000051253</td>
<td>1958 (1889)
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:IP">IP</a>
</td>
<td><a href="/wiki/International_Paper" title="International Paper">International Paper</a></td>
<td>Materials</td>
<td>Paper &amp; Plastic Packaging Products &amp; Materials</td>
<td><a href="/wiki/Memphis,_Tennessee" title="Memphis, Tennessee">Memphis, Tennessee</a></td>
<td>1957-03-04</td>
<td>0000051434</td>
<td>1898
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:IPG">IPG</a>
</td>
<td><a href="/wiki/The_Interpublic_Group_of_Companies" title="The Interpublic Group of Companies">Interpublic Group of Companies (The)</a></td>
<td>Communication Services</td>
<td>Advertising</td>
<td><a href="/wiki/New_York_City" title="New York City">New York City</a>, New York</td>
<td>1992-10-01</td>
<td>0000051644</td>
<td>1961 (1930)
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/intu">INTU</a>
</td>
<td><a href="/wiki/Intuit" title="Intuit">Intuit</a></td>
<td>Information Technology</td>
<td>Application Software</td>
<td><a href="/wiki/Mountain_View,_California" title="Mountain View, California">Mountain View, California</a></td>
<td>2000-12-05</td>
<td>0000896878</td>
<td>1983
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/isrg">ISRG</a>
</td>
<td><a href="/wiki/Intuitive_Surgical" title="Intuitive Surgical">Intuitive Surgical</a></td>
<td>Health Care</td>
<td>Health Care Equipment</td>
<td><a href="/wiki/Sunnyvale,_California" title="Sunnyvale, California">Sunnyvale, California</a></td>
<td>2008-06-02</td>
<td>0001035267</td>
<td>1995
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:IVZ">IVZ</a>
</td>
<td><a href="/wiki/Invesco" title="Invesco">Invesco</a></td>
<td>Financials</td>
<td>Asset Management &amp; Custody Banks</td>
<td><a href="/wiki/Atlanta" title="Atlanta">Atlanta</a>, Georgia</td>
<td>2008-08-21</td>
<td>0000914208</td>
<td>1935
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:INVH">INVH</a>
</td>
<td><a href="/wiki/Invitation_Homes" title="Invitation Homes">Invitation Homes</a></td>
<td>Real Estate</td>
<td>Single-Family Residential REITs</td>
<td><a href="/wiki/Dallas" title="Dallas">Dallas</a>, Texas</td>
<td>2022-09-19</td>
<td>0001687229</td>
<td>2012
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:IQV">IQV</a>
</td>
<td><a href="/wiki/IQVIA" title="IQVIA">IQVIA</a></td>
<td>Health Care</td>
<td>Life Sciences Tools &amp; Services</td>
<td><a href="/wiki/Durham,_North_Carolina" title="Durham, North Carolina">Durham, North Carolina</a></td>
<td>2017-08-29</td>
<td>0001478242
</td>
<td>1982
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:IRM">IRM</a>
</td>
<td><a href="/wiki/Iron_Mountain_(company)" title="Iron Mountain (company)">Iron Mountain</a></td>
<td>Real Estate</td>
<td>Other Specialized REITs</td>
<td><a href="/wiki/Boston" title="Boston">Boston</a>, Massachusetts</td>
<td>2009-01-06</td>
<td>0001020569</td>
<td>1951
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/jbht">JBHT</a>
</td>
<td><a href="/wiki/J.B._Hunt" class="mw-redirect" title="J.B. Hunt">J.B. Hunt</a></td>
<td>Industrials</td>
<td>Cargo Ground Transportation</td>
<td><a href="/wiki/Lowell,_Arkansas" title="Lowell, Arkansas">Lowell, Arkansas</a></td>
<td>2015-07-01</td>
<td>0000728535</td>
<td>1961
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:JBL">JBL</a>
</td>
<td><a href="/wiki/Jabil" title="Jabil">Jabil</a></td>
<td>Information Technology</td>
<td>Electronic Manufacturing Services</td>
<td><a href="/wiki/St._Petersburg,_Florida" title="St. Petersburg, Florida">St. Petersburg, Florida</a></td>
<td>2023-12-18</td>
<td>0000898293</td>
<td>1966
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/jkhy">JKHY</a>
</td>
<td><a href="/wiki/Jack_Henry_%26_Associates" title="Jack Henry &amp; Associates">Jack Henry &amp; Associates</a></td>
<td>Financials</td>
<td>Transaction &amp; Payment Processing Services</td>
<td><a href="/wiki/Monett,_Missouri" title="Monett, Missouri">Monett, Missouri</a></td>
<td>2018-11-13</td>
<td>0000779152</td>
<td>1976
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:J">J</a>
</td>
<td><a href="/wiki/Jacobs_Solutions" title="Jacobs Solutions">Jacobs Solutions</a></td>
<td>Industrials</td>
<td>Construction &amp; Engineering</td>
<td><a href="/wiki/Dallas" title="Dallas">Dallas</a>, Texas</td>
<td>2007-10-26</td>
<td>0000052988</td>
<td>1947
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:JNJ">JNJ</a>
</td>
<td><a href="/wiki/Johnson_%26_Johnson" title="Johnson &amp; Johnson">Johnson &amp; Johnson</a></td>
<td>Health Care</td>
<td>Pharmaceuticals</td>
<td><a href="/wiki/New_Brunswick,_New_Jersey" title="New Brunswick, New Jersey">New Brunswick, New Jersey</a></td>
<td>1973-06-30</td>
<td>0000200406</td>
<td>1886
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:JCI">JCI</a>
</td>
<td><a href="/wiki/Johnson_Controls" title="Johnson Controls">Johnson Controls</a></td>
<td>Industrials</td>
<td>Building Products</td>
<td><a href="/wiki/Cork_(city)" title="Cork (city)">Cork, Ireland</a></td>
<td>2010-08-27</td>
<td>0000833444</td>
<td>1885
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:JPM">JPM</a>
</td>
<td><a href="/wiki/JPMorgan_Chase" title="JPMorgan Chase">JPMorgan Chase</a></td>
<td>Financials</td>
<td>Diversified Banks</td>
<td><a href="/wiki/New_York_City" title="New York City">New York City</a>, New York</td>
<td>1975-06-30</td>
<td>0000019617
</td>
<td>2000 (1799 / 1871)
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:K">K</a>
</td>
<td><a href="/wiki/Kellanova" title="Kellanova">Kellanova</a></td>
<td>Consumer Staples</td>
<td>Packaged Foods &amp; Meats</td>
<td><a href="/wiki/Chicago" title="Chicago">Chicago</a>, Illinois</td>
<td>1989-09-11</td>
<td>0000055067</td>
<td>1906
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:KVUE">KVUE</a>
</td>
<td><a href="/wiki/Kenvue" title="Kenvue">Kenvue</a></td>
<td>Consumer Staples</td>
<td>Personal Care Products</td>
<td><a href="/wiki/Skillman,_New_Jersey" title="Skillman, New Jersey">Skillman, New Jersey</a></td>
<td>2023-08-25</td>
<td>0001944048</td>
<td>2022 (<a href="/wiki/Johnson_%26_Johnson" title="Johnson &amp; Johnson">Johnson &amp; Johnson</a> spinoff)
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/kdp">KDP</a>
</td>
<td><a href="/wiki/Keurig_Dr_Pepper" title="Keurig Dr Pepper">Keurig Dr Pepper</a></td>
<td>Consumer Staples</td>
<td>Soft Drinks &amp; Non-alcoholic Beverages</td>
<td><a href="/wiki/Burlington,_Massachusetts" title="Burlington, Massachusetts">Burlington, Massachusetts</a></td>
<td>2022-06-21</td>
<td>0001418135</td>
<td>1981
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:KEY">KEY</a>
</td>
<td><a href="/wiki/KeyCorp" class="mw-redirect" title="KeyCorp">KeyCorp</a></td>
<td>Financials</td>
<td>Regional Banks</td>
<td><a href="/wiki/Cleveland" title="Cleveland">Cleveland</a>, Ohio</td>
<td>1994-03-01</td>
<td>0000091576</td>
<td>1825
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:KEYS">KEYS</a>
</td>
<td><a href="/wiki/Keysight_Technologies" class="mw-redirect" title="Keysight Technologies">Keysight Technologies</a></td>
<td>Information Technology</td>
<td>Electronic Equipment &amp; Instruments</td>
<td><a href="/wiki/Santa_Rosa,_California" title="Santa Rosa, California">Santa Rosa, California</a></td>
<td>2018-11-06</td>
<td>0001601046</td>
<td>2014 (1939)
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/kmb">KMB</a>
</td>
<td><a href="/wiki/Kimberly-Clark" title="Kimberly-Clark">Kimberly-Clark</a></td>
<td>Consumer Staples</td>
<td>Household Products</td>
<td><a href="/wiki/Irving,_Texas" title="Irving, Texas">Irving, Texas</a></td>
<td>1957-03-04</td>
<td>0000055785</td>
<td>1872
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:KIM">KIM</a>
</td>
<td><a href="/wiki/Kimco_Realty" title="Kimco Realty">Kimco Realty</a></td>
<td>Real Estate</td>
<td>Retail REITs</td>
<td><a href="/wiki/Jericho,_New_York" title="Jericho, New York">Jericho, New York</a></td>
<td>2006-04-04</td>
<td>0000879101</td>
<td>1958
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:KMI">KMI</a>
</td>
<td><a href="/wiki/Kinder_Morgan" title="Kinder Morgan">Kinder Morgan</a></td>
<td>Energy</td>
<td>Oil &amp; Gas Storage &amp; Transportation</td>
<td><a href="/wiki/Houston" title="Houston">Houston</a>, Texas</td>
<td>2012-05-25</td>
<td>0001506307</td>
<td>1997
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:KKR">KKR</a>
</td>
<td><a href="/wiki/Kohlberg_Kravis_Roberts" class="mw-redirect" title="Kohlberg Kravis Roberts">KKR &amp; Co.</a></td>
<td>Financials</td>
<td>Asset Management &amp; Custody Banks</td>
<td><a href="/wiki/New_York_City" title="New York City">New York City</a>, New York</td>
<td>2024-06-24</td>
<td>0001404912</td>
<td>1976
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/klac">KLAC</a>
</td>
<td><a href="/wiki/KLA_Corporation" title="KLA Corporation">KLA Corporation</a></td>
<td>Information Technology</td>
<td>Semiconductor Materials &amp; Equipment</td>
<td><a href="/wiki/Milpitas,_California" title="Milpitas, California">Milpitas, California</a></td>
<td>1997-09-30</td>
<td>0000319201</td>
<td>1975/1977 (1997)
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/khc">KHC</a>
</td>
<td><a href="/wiki/Kraft_Heinz" title="Kraft Heinz">Kraft Heinz</a></td>
<td>Consumer Staples</td>
<td>Packaged Foods &amp; Meats</td>
<td><a href="/wiki/Chicago" title="Chicago">Chicago</a>, Illinois; <a href="/wiki/Pittsburgh" title="Pittsburgh">Pittsburgh</a>, Pennsylvania</td>
<td>2015-07-06</td>
<td>0001637459</td>
<td>2015 (1869)
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:KR">KR</a>
</td>
<td><a href="/wiki/Kroger" title="Kroger">Kroger</a></td>
<td>Consumer Staples</td>
<td>Food Retail</td>
<td><a href="/wiki/Cincinnati" title="Cincinnati">Cincinnati</a>, Ohio</td>
<td>1957-03-04</td>
<td>0000056873</td>
<td>1883
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:LHX">LHX</a>
</td>
<td><a href="/wiki/L3Harris" title="L3Harris">L3Harris</a></td>
<td>Industrials</td>
<td>Aerospace &amp; Defense</td>
<td><a href="/wiki/Melbourne,_Florida" title="Melbourne, Florida">Melbourne, Florida</a></td>
<td>2008-09-22</td>
<td>0000202058
</td>
<td>2019 (<a href="/wiki/L3_Technologies" title="L3 Technologies">L3</a> 1997, <a href="/wiki/Harris_Corporation" title="Harris Corporation">Harris</a> 1895)
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:LH">LH</a>
</td>
<td><a href="/wiki/Labcorp" title="Labcorp">Labcorp</a></td>
<td>Health Care</td>
<td>Health Care Services</td>
<td><a href="/wiki/Burlington,_North_Carolina" title="Burlington, North Carolina">Burlington, North Carolina</a></td>
<td>2004-11-01</td>
<td>0000920148</td>
<td>1978
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/lrcx">LRCX</a>
</td>
<td><a href="/wiki/Lam_Research" title="Lam Research">Lam Research</a></td>
<td>Information Technology</td>
<td>Semiconductor Materials &amp; Equipment</td>
<td><a href="/wiki/Fremont,_California" title="Fremont, California">Fremont, California</a></td>
<td>2012-06-29</td>
<td>0000707549</td>
<td>1980
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:LW">LW</a>
</td>
<td><a href="/wiki/Lamb_Weston" title="Lamb Weston">Lamb Weston</a></td>
<td>Consumer Staples</td>
<td>Packaged Foods &amp; Meats</td>
<td><a href="/wiki/Eagle,_Idaho" title="Eagle, Idaho">Eagle, Idaho</a></td>
<td>2018-12-03</td>
<td>0001679273</td>
<td>2016 (1950)
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:LVS">LVS</a>
</td>
<td><a href="/wiki/Las_Vegas_Sands" title="Las Vegas Sands">Las Vegas Sands</a></td>
<td>Consumer Discretionary</td>
<td>Casinos &amp; Gaming</td>
<td><a href="/wiki/Las_Vegas" title="Las Vegas">Las Vegas</a>, Nevada</td>
<td>2019-10-03</td>
<td>0001300514</td>
<td>1988
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:LDOS">LDOS</a>
</td>
<td><a href="/wiki/Leidos" title="Leidos">Leidos</a></td>
<td>Industrials</td>
<td>Diversified Support Services</td>
<td><a href="/wiki/Reston,_Virginia" title="Reston, Virginia">Reston, Virginia</a></td>
<td>2019-08-09</td>
<td>0001336920</td>
<td>1969
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:LEN">LEN</a>
</td>
<td><a href="/wiki/Lennar" title="Lennar">Lennar</a></td>
<td>Consumer Discretionary</td>
<td>Homebuilding</td>
<td><a href="/wiki/Miami" title="Miami">Miami</a>, Florida</td>
<td>2005-10-04</td>
<td>0000920760</td>
<td>1954
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:LII">LII</a>
</td>
<td><a href="/wiki/Lennox_International" title="Lennox International">Lennox International</a></td>
<td>Industrials</td>
<td>Building Products</td>
<td><a href="/wiki/Richardson,_Texas" title="Richardson, Texas">Richardson, Texas</a></td>
<td>2024-12-23</td>
<td>0001069202</td>
<td>1895
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:LLY">LLY</a>
</td>
<td><a href="/wiki/Eli_Lilly_and_Company" title="Eli Lilly and Company">Lilly (Eli)</a></td>
<td>Health Care</td>
<td>Pharmaceuticals</td>
<td><a href="/wiki/Indianapolis" title="Indianapolis">Indianapolis</a>, Indiana</td>
<td>1970-12-31</td>
<td>0000059478</td>
<td>1876
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/lin">LIN</a>
</td>
<td><a href="/wiki/Linde_plc" title="Linde plc">Linde plc</a></td>
<td>Materials</td>
<td>Industrial Gases</td>
<td><a href="/wiki/Guildford" title="Guildford">Guildford, United Kingdom</a></td>
<td>1992-07-01</td>
<td>0001707925</td>
<td>1879
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:LYV">LYV</a>
</td>
<td><a href="/wiki/Live_Nation_Entertainment" title="Live Nation Entertainment">Live Nation Entertainment</a></td>
<td>Communication Services</td>
<td>Movies &amp; Entertainment</td>
<td><a href="/wiki/Beverly_Hills,_California" title="Beverly Hills, California">Beverly Hills, California</a></td>
<td>2019-12-23</td>
<td>0001335258</td>
<td>2010
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/lkq">LKQ</a>
</td>
<td><a href="/wiki/LKQ_Corporation" title="LKQ Corporation">LKQ Corporation</a></td>
<td>Consumer Discretionary</td>
<td>Distributors</td>
<td><a href="/wiki/Chicago" title="Chicago">Chicago</a>, Illinois</td>
<td>2016-05-23</td>
<td>0001065696</td>
<td>1998
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:LMT">LMT</a>
</td>
<td><a href="/wiki/Lockheed_Martin" title="Lockheed Martin">Lockheed Martin</a></td>
<td>Industrials</td>
<td>Aerospace &amp; Defense</td>
<td><a href="/wiki/Bethesda,_Maryland" title="Bethesda, Maryland">Bethesda, Maryland</a></td>
<td>1957-03-04</td>
<td>0000936468</td>
<td>1995
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:L">L</a>
</td>
<td><a href="/wiki/Loews_Corporation" title="Loews Corporation">Loews Corporation</a></td>
<td>Financials</td>
<td>Multi-line Insurance</td>
<td><a href="/wiki/New_York_City" title="New York City">New York City</a>, New York</td>
<td>1995-05-31</td>
<td>0000060086
</td>
<td>1959
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:LOW">LOW</a>
</td>
<td><a href="/wiki/Lowe%27s" title="Lowe's">Lowe's</a></td>
<td>Consumer Discretionary</td>
<td>Home Improvement Retail</td>
<td><a href="/wiki/Mooresville,_North_Carolina" title="Mooresville, North Carolina">Mooresville, North Carolina</a></td>
<td>1984-02-29</td>
<td>0000060667</td>
<td>1904/1946/1959
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/lulu">LULU</a>
</td>
<td><a href="/wiki/Lululemon" title="Lululemon">Lululemon Athletica</a></td>
<td>Consumer Discretionary</td>
<td>Apparel, Accessories &amp; Luxury Goods</td>
<td><a href="/wiki/Vancouver,_Canada" class="mw-redirect" title="Vancouver, Canada">Vancouver, Canada</a></td>
<td>2023-10-18</td>
<td>0001397187</td>
<td>1998
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:LYB">LYB</a>
</td>
<td><a href="/wiki/LyondellBasell" title="LyondellBasell">LyondellBasell</a></td>
<td>Materials</td>
<td>Specialty Chemicals</td>
<td><a href="/wiki/Rotterdam,_Netherlands" class="mw-redirect" title="Rotterdam, Netherlands">Rotterdam, Netherlands</a></td>
<td>2012-09-05</td>
<td>0001489393
</td>
<td>2007
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:MTB">MTB</a>
</td>
<td><a href="/wiki/M%26T_Bank" title="M&amp;T Bank">M&amp;T Bank</a></td>
<td>Financials</td>
<td>Regional Banks</td>
<td><a href="/wiki/Buffalo,_New_York" title="Buffalo, New York">Buffalo, New York</a></td>
<td>2004-02-23</td>
<td>0000036270</td>
<td>1856
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:MPC">MPC</a>
</td>
<td><a href="/wiki/Marathon_Petroleum" title="Marathon Petroleum">Marathon Petroleum</a></td>
<td>Energy</td>
<td>Oil &amp; Gas Refining &amp; Marketing</td>
<td><a href="/wiki/Findlay,_Ohio" title="Findlay, Ohio">Findlay, Ohio</a></td>
<td>2011-07-01</td>
<td>0001510295
</td>
<td>2009 (1887)
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/mktx">MKTX</a>
</td>
<td><a href="/wiki/MarketAxess" title="MarketAxess">MarketAxess</a></td>
<td>Financials</td>
<td>Financial Exchanges &amp; Data</td>
<td><a href="/wiki/New_York_City" title="New York City">New York City</a>, New York</td>
<td>2019-07-01</td>
<td>0001278021
</td>
<td>2000
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/mar">MAR</a>
</td>
<td><a href="/wiki/Marriott_International" title="Marriott International">Marriott International</a></td>
<td>Consumer Discretionary</td>
<td>Hotels, Resorts &amp; Cruise Lines</td>
<td><a href="/wiki/Bethesda,_Maryland" title="Bethesda, Maryland">Bethesda, Maryland</a></td>
<td>1998-05-29</td>
<td>0001048286</td>
<td>1927
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:MMC">MMC</a>
</td>
<td><a href="/wiki/Marsh_McLennan" title="Marsh McLennan">Marsh McLennan</a></td>
<td>Financials</td>
<td>Insurance Brokers</td>
<td><a href="/wiki/New_York_City" title="New York City">New York City</a>, New York</td>
<td>1987-08-31</td>
<td>0000062709</td>
<td>1905
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:MLM">MLM</a>
</td>
<td><a href="/wiki/Martin_Marietta_Materials" title="Martin Marietta Materials">Martin Marietta Materials</a></td>
<td>Materials</td>
<td>Construction Materials</td>
<td><a href="/wiki/Raleigh,_North_Carolina" title="Raleigh, North Carolina">Raleigh, North Carolina</a></td>
<td>2014-07-02</td>
<td>0000916076</td>
<td>1993
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:MAS">MAS</a>
</td>
<td><a href="/wiki/Masco" title="Masco">Masco</a></td>
<td>Industrials</td>
<td>Building Products</td>
<td><a href="/wiki/Livonia,_Michigan" title="Livonia, Michigan">Livonia, Michigan</a></td>
<td>1981-06-30</td>
<td>0000062996</td>
<td>1929
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:MA">MA</a>
</td>
<td><a href="/wiki/Mastercard" title="Mastercard">Mastercard</a></td>
<td>Financials</td>
<td>Transaction &amp; Payment Processing Services</td>
<td><a href="/wiki/Harrison,_New_York" title="Harrison, New York">Harrison, New York</a></td>
<td>2008-07-18</td>
<td>0001141391</td>
<td>1966
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/mtch">MTCH</a>
</td>
<td><a href="/wiki/Match_Group" title="Match Group">Match Group</a></td>
<td>Communication Services</td>
<td>Interactive Media &amp; Services</td>
<td><a href="/wiki/Dallas" title="Dallas">Dallas</a>, Texas</td>
<td>2021-09-20</td>
<td>0000891103</td>
<td>1986
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:MKC">MKC</a>
</td>
<td><a href="/wiki/McCormick_%26_Company" title="McCormick &amp; Company">McCormick &amp; Company</a></td>
<td>Consumer Staples</td>
<td>Packaged Foods &amp; Meats</td>
<td><a href="/wiki/Hunt_Valley,_Maryland" title="Hunt Valley, Maryland">Hunt Valley, Maryland</a></td>
<td>2003-03-20</td>
<td>0000063754</td>
<td>1889
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:MCD">MCD</a>
</td>
<td><a href="/wiki/McDonald%27s" title="McDonald's">McDonald's</a></td>
<td>Consumer Discretionary</td>
<td>Restaurants</td>
<td><a href="/wiki/Chicago" title="Chicago">Chicago</a>, Illinois</td>
<td>1970-06-30</td>
<td>0000063908</td>
<td>1940
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:MCK">MCK</a>
</td>
<td><a href="/wiki/McKesson_Corporation" title="McKesson Corporation">McKesson Corporation</a></td>
<td>Health Care</td>
<td>Health Care Distributors</td>
<td><a href="/wiki/Irving,_Texas" title="Irving, Texas">Irving, Texas</a></td>
<td>1999-01-13</td>
<td>0000927653</td>
<td>1833
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:MDT">MDT</a>
</td>
<td><a href="/wiki/Medtronic" title="Medtronic">Medtronic</a></td>
<td>Health Care</td>
<td>Health Care Equipment</td>
<td><a href="/wiki/Dublin" title="Dublin">Dublin</a>, Ireland</td>
<td>1986-10-31</td>
<td>0001613103</td>
<td>1949
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:MRK">MRK</a>
</td>
<td><a href="/wiki/Merck_%26_Co." title="Merck &amp; Co.">Merck &amp; Co.</a></td>
<td>Health Care</td>
<td>Pharmaceuticals</td>
<td><a href="/wiki/Kenilworth,_New_Jersey" title="Kenilworth, New Jersey">Kenilworth, New Jersey</a></td>
<td>1957-03-04</td>
<td>0000310158</td>
<td>1891
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/meta">META</a>
</td>
<td><a href="/wiki/Meta_Platforms" title="Meta Platforms">Meta Platforms</a></td>
<td>Communication Services</td>
<td>Interactive Media &amp; Services</td>
<td><a href="/wiki/Menlo_Park,_California" title="Menlo Park, California">Menlo Park, California</a></td>
<td>2013-12-23</td>
<td>0001326801</td>
<td>2004
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:MET">MET</a>
</td>
<td><a href="/wiki/MetLife" title="MetLife">MetLife</a></td>
<td>Financials</td>
<td>Life &amp; Health Insurance</td>
<td><a href="/wiki/New_York_City" title="New York City">New York City</a>, New York</td>
<td>2000-12-11</td>
<td>0001099219</td>
<td>1868
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:MTD">MTD</a>
</td>
<td><a href="/wiki/Mettler_Toledo" title="Mettler Toledo">Mettler Toledo</a></td>
<td>Health Care</td>
<td>Life Sciences Tools &amp; Services</td>
<td><a href="/wiki/Columbus,_Ohio" title="Columbus, Ohio">Columbus, Ohio</a></td>
<td>2016-09-06</td>
<td>0001037646</td>
<td>1945
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:MGM">MGM</a>
</td>
<td><a href="/wiki/MGM_Resorts" class="mw-redirect" title="MGM Resorts">MGM Resorts</a></td>
<td>Consumer Discretionary</td>
<td>Casinos &amp; Gaming</td>
<td><a href="/wiki/Paradise,_Nevada" title="Paradise, Nevada">Paradise, Nevada</a></td>
<td>2017-07-26</td>
<td>0000789570</td>
<td>1986
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/mchp">MCHP</a>
</td>
<td><a href="/wiki/Microchip_Technology" title="Microchip Technology">Microchip Technology</a></td>
<td>Information Technology</td>
<td>Semiconductors</td>
<td><a href="/wiki/Chandler,_Arizona" title="Chandler, Arizona">Chandler, Arizona</a></td>
<td>2007-09-07</td>
<td>0000827054</td>
<td>1989
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/mu">MU</a>
</td>
<td><a href="/wiki/Micron_Technology" title="Micron Technology">Micron Technology</a></td>
<td>Information Technology</td>
<td>Semiconductors</td>
<td><a href="/wiki/Boise,_Idaho" title="Boise, Idaho">Boise, Idaho</a></td>
<td>1994-09-27</td>
<td>0000723125</td>
<td>1978
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/msft">MSFT</a>
</td>
<td><a href="/wiki/Microsoft" title="Microsoft">Microsoft</a></td>
<td>Information Technology</td>
<td>Systems Software</td>
<td><a href="/wiki/Redmond,_Washington" title="Redmond, Washington">Redmond, Washington</a></td>
<td>1994-06-01</td>
<td>0000789019</td>
<td>1975
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:MAA">MAA</a>
</td>
<td><a href="/wiki/Mid-America_Apartment_Communities" title="Mid-America Apartment Communities">Mid-America Apartment Communities</a></td>
<td>Real Estate</td>
<td>Multi-Family Residential REITs</td>
<td><a href="/wiki/Memphis,_Tennessee" title="Memphis, Tennessee">Memphis, Tennessee</a></td>
<td>2016-12-02</td>
<td>0000912595</td>
<td>1977
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/mrna">MRNA</a>
</td>
<td><a href="/wiki/Moderna" title="Moderna">Moderna</a></td>
<td>Health Care</td>
<td>Biotechnology</td>
<td><a href="/wiki/Cambridge,_Massachusetts" title="Cambridge, Massachusetts">Cambridge, Massachusetts</a></td>
<td>2021-07-21</td>
<td>0001682852</td>
<td>2010
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:MHK">MHK</a>
</td>
<td><a href="/wiki/Mohawk_Industries" title="Mohawk Industries">Mohawk Industries</a></td>
<td>Consumer Discretionary</td>
<td>Home Furnishings</td>
<td><a href="/wiki/Calhoun,_Georgia" title="Calhoun, Georgia">Calhoun, Georgia</a></td>
<td>2013-12-23</td>
<td>0000851968</td>
<td>1878
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:MOH">MOH</a>
</td>
<td><a href="/wiki/Molina_Healthcare" title="Molina Healthcare">Molina Healthcare</a></td>
<td>Health Care</td>
<td>Managed Health Care</td>
<td><a href="/wiki/Long_Beach,_California" title="Long Beach, California">Long Beach, California</a></td>
<td>2022-03-02</td>
<td>0001179929</td>
<td>1980
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:TAP">TAP</a>
</td>
<td><a href="/wiki/Molson_Coors" title="Molson Coors">Molson Coors Beverage Company</a></td>
<td>Consumer Staples</td>
<td>Brewers</td>
<td><a href="/wiki/Chicago" title="Chicago">Chicago</a>, Illinois</td>
<td>1976-06-30</td>
<td>0000024545</td>
<td>2005 (Molson 1786, Coors 1873)
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/mdlz">MDLZ</a>
</td>
<td><a href="/wiki/Mondelez_International" title="Mondelez International">Mondelez International</a></td>
<td>Consumer Staples</td>
<td>Packaged Foods &amp; Meats</td>
<td><a href="/wiki/Chicago" title="Chicago">Chicago</a>, Illinois</td>
<td>2012-10-02</td>
<td>0001103982</td>
<td>2012
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/mpwr">MPWR</a>
</td>
<td><a href="/wiki/Monolithic_Power_Systems" title="Monolithic Power Systems">Monolithic Power Systems</a></td>
<td>Information Technology</td>
<td>Semiconductors</td>
<td><a href="/wiki/Kirkland,_Washington" title="Kirkland, Washington">Kirkland, Washington</a></td>
<td>2021-02-12</td>
<td>0001280452</td>
<td>1997
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/mnst">MNST</a>
</td>
<td><a href="/wiki/Monster_Beverage" title="Monster Beverage">Monster Beverage</a></td>
<td>Consumer Staples</td>
<td>Soft Drinks &amp; Non-alcoholic Beverages</td>
<td><a href="/wiki/Corona,_California" title="Corona, California">Corona, California</a></td>
<td>2012-06-28</td>
<td>0000865752</td>
<td>2012 (1935)
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:MCO">MCO</a>
</td>
<td><a href="/wiki/Moody%27s_Corporation" title="Moody's Corporation">Moody's Corporation</a></td>
<td>Financials</td>
<td>Financial Exchanges &amp; Data</td>
<td><a href="/wiki/New_York_City" title="New York City">New York City</a>, New York</td>
<td>1998-07-01</td>
<td>0001059556</td>
<td>1909
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:MS">MS</a>
</td>
<td><a href="/wiki/Morgan_Stanley" title="Morgan Stanley">Morgan Stanley</a></td>
<td>Financials</td>
<td>Investment Banking &amp; Brokerage</td>
<td><a href="/wiki/New_York_City" title="New York City">New York City</a>, New York</td>
<td>1993-07-29</td>
<td>0000895421</td>
<td>1935
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:MOS">MOS</a>
</td>
<td><a href="/wiki/The_Mosaic_Company" title="The Mosaic Company">Mosaic Company (The)</a></td>
<td>Materials</td>
<td>Fertilizers &amp; Agricultural Chemicals</td>
<td><a href="/wiki/Tampa,_Florida" title="Tampa, Florida">Tampa, Florida</a></td>
<td>2011-09-26</td>
<td>0001285785
</td>
<td>2004 (1865 / 1909)
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:MSI">MSI</a>
</td>
<td><a href="/wiki/Motorola_Solutions" title="Motorola Solutions">Motorola Solutions</a></td>
<td>Information Technology</td>
<td>Communications Equipment</td>
<td><a href="/wiki/Chicago" title="Chicago">Chicago</a>, Illinois</td>
<td>1957-03-04</td>
<td>0000068505</td>
<td>1928 (2011)
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:MSCI">MSCI</a>
</td>
<td><a href="/wiki/MSCI" title="MSCI">MSCI Inc.</a></td>
<td>Financials</td>
<td>Financial Exchanges &amp; Data</td>
<td><a href="/wiki/New_York_City" title="New York City">New York City</a>, New York</td>
<td>2018-04-04</td>
<td>0001408198</td>
<td>1969
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/ndaq">NDAQ</a>
</td>
<td><a href="/wiki/Nasdaq,_Inc." title="Nasdaq, Inc.">Nasdaq, Inc.</a></td>
<td>Financials</td>
<td>Financial Exchanges &amp; Data</td>
<td><a href="/wiki/New_York_City" title="New York City">New York City</a>, New York</td>
<td>2008-10-22</td>
<td>0001120193</td>
<td>1971
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/ntap">NTAP</a>
</td>
<td><a href="/wiki/NetApp" title="NetApp">NetApp</a></td>
<td>Information Technology</td>
<td>Technology Hardware, Storage &amp; Peripherals</td>
<td><a href="/wiki/San_Jose,_California" title="San Jose, California">San Jose, California</a></td>
<td>1999-06-25</td>
<td>0001002047</td>
<td>1992
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/nflx">NFLX</a>
</td>
<td><a href="/wiki/Netflix,_Inc." title="Netflix, Inc.">Netflix</a></td>
<td>Communication Services</td>
<td>Movies &amp; Entertainment</td>
<td><a href="/wiki/Los_Gatos,_California" title="Los Gatos, California">Los Gatos, California</a></td>
<td>2010-12-20</td>
<td>0001065280</td>
<td>1997
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:NEM">NEM</a>
</td>
<td><a href="/wiki/Newmont" title="Newmont">Newmont</a></td>
<td>Materials</td>
<td>Gold</td>
<td><a href="/wiki/Denver" title="Denver">Denver</a>, Colorado</td>
<td>1969-06-30</td>
<td>0001164727</td>
<td>1921
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/nwsa">NWSA</a>
</td>
<td><a href="/wiki/News_Corp" title="News Corp">News Corp</a> (Class A)</td>
<td>Communication Services</td>
<td>Publishing</td>
<td><a href="/wiki/New_York_City" title="New York City">New York City</a>, New York</td>
<td>2013-08-01</td>
<td>0001564708</td>
<td>2013 (<a href="/wiki/News_Corporation" title="News Corporation">News Corporation</a> 1980)
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/nws">NWS</a>
</td>
<td><a href="/wiki/News_Corp" title="News Corp">News Corp</a> (Class B)</td>
<td>Communication Services</td>
<td>Publishing</td>
<td><a href="/wiki/New_York_City" title="New York City">New York City</a>, New York</td>
<td>2015-09-18</td>
<td>0001564708</td>
<td>2013 (<a href="/wiki/News_Corporation" title="News Corporation">News Corporation</a> 1980)
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:NEE">NEE</a>
</td>
<td><a href="/wiki/NextEra_Energy" title="NextEra Energy">NextEra Energy</a></td>
<td>Utilities</td>
<td>Multi-Utilities</td>
<td><a href="/wiki/Juno_Beach,_Florida" title="Juno Beach, Florida">Juno Beach, Florida</a></td>
<td>1976-06-30</td>
<td>0000753308
</td>
<td>1984 (1925)
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:NKE">NKE</a>
</td>
<td><a href="/wiki/Nike,_Inc." title="Nike, Inc.">Nike, Inc.</a></td>
<td>Consumer Discretionary</td>
<td>Apparel, Accessories &amp; Luxury Goods</td>
<td><a href="/wiki/Washington_County,_Oregon" title="Washington County, Oregon">Washington County, Oregon</a></td>
<td>1988-11-30</td>
<td>0000320187</td>
<td>1964
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:NI">NI</a>
</td>
<td><a href="/wiki/NiSource" title="NiSource">NiSource</a></td>
<td>Utilities</td>
<td>Multi-Utilities</td>
<td><a href="/wiki/Merrillville,_Indiana" title="Merrillville, Indiana">Merrillville, Indiana</a></td>
<td>2000-11-02</td>
<td>0001111711</td>
<td>1912
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/ndsn">NDSN</a>
</td>
<td><a href="/wiki/Nordson_Corporation" title="Nordson Corporation">Nordson Corporation</a></td>
<td>Industrials</td>
<td>Industrial Machinery &amp; Supplies &amp; Components</td>
<td><a href="/wiki/Westlake,_Ohio" title="Westlake, Ohio">Westlake, Ohio</a></td>
<td>2022-02-15</td>
<td>0000072331</td>
<td>1935
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:NSC">NSC</a>
</td>
<td><a href="/wiki/Norfolk_Southern_Railway" title="Norfolk Southern Railway">Norfolk Southern</a></td>
<td>Industrials</td>
<td>Rail Transportation</td>
<td><a href="/wiki/Atlanta" title="Atlanta">Atlanta</a>, Georgia</td>
<td>1957-03-04</td>
<td>0000702165</td>
<td>1881/1894 (1980)
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/ntrs">NTRS</a>
</td>
<td><a href="/wiki/Northern_Trust" title="Northern Trust">Northern Trust</a></td>
<td>Financials</td>
<td>Asset Management &amp; Custody Banks</td>
<td><a href="/wiki/Chicago" title="Chicago">Chicago</a>, Illinois</td>
<td>1998-01-30</td>
<td>0000073124</td>
<td>1889
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:NOC">NOC</a>
</td>
<td><a href="/wiki/Northrop_Grumman" title="Northrop Grumman">Northrop Grumman</a></td>
<td>Industrials</td>
<td>Aerospace &amp; Defense</td>
<td><a href="/wiki/West_Falls_Church,_Virginia" title="West Falls Church, Virginia">West Falls Church, Virginia</a></td>
<td>1957-03-04</td>
<td>0001133421</td>
<td>1994 (Northrop 1939, Grumman 1930)
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:NCLH">NCLH</a>
</td>
<td><a href="/wiki/Norwegian_Cruise_Line_Holdings" title="Norwegian Cruise Line Holdings">Norwegian Cruise Line Holdings</a></td>
<td>Consumer Discretionary</td>
<td>Hotels, Resorts &amp; Cruise Lines</td>
<td><a href="/wiki/Miami" title="Miami">Miami</a>, Florida</td>
<td>2017-10-13</td>
<td>0001513761</td>
<td>2011 (1966)
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:NRG">NRG</a>
</td>
<td><a href="/wiki/NRG_Energy" title="NRG Energy">NRG Energy</a></td>
<td>Utilities</td>
<td>Independent Power Producers &amp; Energy Traders</td>
<td><a href="/wiki/Houston" title="Houston">Houston</a>, Texas</td>
<td>2010-01-29</td>
<td>0001013871</td>
<td>1992
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:NUE">NUE</a>
</td>
<td><a href="/wiki/Nucor" title="Nucor">Nucor</a></td>
<td>Materials</td>
<td>Steel</td>
<td><a href="/wiki/Charlotte,_North_Carolina" title="Charlotte, North Carolina">Charlotte, North Carolina</a></td>
<td>1985-04-30</td>
<td>0000073309</td>
<td>1940
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/nvda">NVDA</a>
</td>
<td><a href="/wiki/Nvidia" title="Nvidia">Nvidia</a></td>
<td>Information Technology</td>
<td>Semiconductors</td>
<td><a href="/wiki/Santa_Clara,_California" title="Santa Clara, California">Santa Clara, California</a></td>
<td>2001-11-30</td>
<td>0001045810</td>
<td>1993
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:NVR">NVR</a>
</td>
<td><a href="/wiki/NVR,_Inc." title="NVR, Inc.">NVR, Inc.</a></td>
<td>Consumer Discretionary</td>
<td>Homebuilding</td>
<td><a href="/wiki/Reston,_Virginia" title="Reston, Virginia">Reston, Virginia</a></td>
<td>2019-09-26</td>
<td>0000906163</td>
<td>1980
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/nxpi">NXPI</a>
</td>
<td><a href="/wiki/NXP_Semiconductors" title="NXP Semiconductors">NXP Semiconductors</a></td>
<td>Information Technology</td>
<td>Semiconductors</td>
<td><a href="/wiki/Eindhoven,_Netherlands" class="mw-redirect" title="Eindhoven, Netherlands">Eindhoven, Netherlands</a></td>
<td>2021-03-22</td>
<td>0001413447</td>
<td>1953
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/orly">ORLY</a>
</td>
<td><a href="/wiki/O%27Reilly_Auto_Parts" title="O'Reilly Auto Parts">O’Reilly Automotive</a></td>
<td>Consumer Discretionary</td>
<td>Automotive Retail</td>
<td><a href="/wiki/Springfield,_Missouri" title="Springfield, Missouri">Springfield, Missouri</a></td>
<td>2009-03-27</td>
<td>0000898173</td>
<td>1957
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:OXY">OXY</a>
</td>
<td><a href="/wiki/Occidental_Petroleum" title="Occidental Petroleum">Occidental Petroleum</a></td>
<td>Energy</td>
<td>Oil &amp; Gas Exploration &amp; Production</td>
<td><a href="/wiki/Houston" title="Houston">Houston</a>, Texas</td>
<td>1957-03-04</td>
<td>0000797468</td>
<td>1920
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/odfl">ODFL</a>
</td>
<td><a href="/wiki/Old_Dominion_Freight_Line" title="Old Dominion Freight Line">Old Dominion</a></td>
<td>Industrials</td>
<td>Cargo Ground Transportation</td>
<td><a href="/wiki/Thomasville,_North_Carolina" title="Thomasville, North Carolina">Thomasville, North Carolina</a></td>
<td>2019-12-09</td>
<td>0000878927</td>
<td>1934
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:OMC">OMC</a>
</td>
<td><a href="/wiki/Omnicom_Group" title="Omnicom Group">Omnicom Group</a></td>
<td>Communication Services</td>
<td>Advertising</td>
<td><a href="/wiki/New_York_City" title="New York City">New York City</a>, New York</td>
<td>1997-12-31</td>
<td>0000029989</td>
<td>1986
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/on">ON</a>
</td>
<td><a href="/wiki/Onsemi" title="Onsemi">ON Semiconductor</a></td>
<td>Information Technology</td>
<td>Semiconductors</td>
<td><a href="/wiki/Phoenix,_Arizona" title="Phoenix, Arizona">Phoenix, Arizona</a></td>
<td>2022-06-21</td>
<td>0001097864</td>
<td>1999
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:OKE">OKE</a>
</td>
<td><a href="/wiki/Oneok" title="Oneok">Oneok</a></td>
<td>Energy</td>
<td>Oil &amp; Gas Storage &amp; Transportation</td>
<td><a href="/wiki/Tulsa,_Oklahoma" title="Tulsa, Oklahoma">Tulsa, Oklahoma</a></td>
<td>2010-03-15</td>
<td>0001039684</td>
<td>1906
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:ORCL">ORCL</a>
</td>
<td><a href="/wiki/Oracle_Corporation" title="Oracle Corporation">Oracle Corporation</a></td>
<td>Information Technology</td>
<td>Application Software</td>
<td><a href="/wiki/Austin,_Texas" title="Austin, Texas">Austin, Texas</a></td>
<td>1989-08-31</td>
<td>0001341439</td>
<td>1977
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:OTIS">OTIS</a>
</td>
<td><a href="/wiki/Otis_Worldwide" title="Otis Worldwide">Otis Worldwide</a></td>
<td>Industrials</td>
<td>Industrial Machinery &amp; Supplies &amp; Components</td>
<td><a href="/wiki/Farmington,_Connecticut" title="Farmington, Connecticut">Farmington, Connecticut</a></td>
<td>2020-04-03</td>
<td>0001781335
</td>
<td>2020 (1853, <a href="/wiki/United_Technologies" title="United Technologies">United Technologies</a> spinoff)
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/pcar">PCAR</a>
</td>
<td><a href="/wiki/Paccar" title="Paccar">Paccar</a></td>
<td>Industrials</td>
<td>Construction Machinery &amp; Heavy Transportation Equipment</td>
<td><a href="/wiki/Bellevue,_Washington" title="Bellevue, Washington">Bellevue, Washington</a></td>
<td>1980-12-31</td>
<td>0000075362</td>
<td>1905
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:PKG">PKG</a>
</td>
<td><a href="/wiki/Packaging_Corporation_of_America" title="Packaging Corporation of America">Packaging Corporation of America</a></td>
<td>Materials</td>
<td>Paper &amp; Plastic Packaging Products &amp; Materials</td>
<td><a href="/wiki/Lake_Forest,_Illinois" title="Lake Forest, Illinois">Lake Forest, Illinois</a></td>
<td>2017-07-26</td>
<td>0000075677</td>
<td>1959
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/pltr">PLTR</a>
</td>
<td><a href="/wiki/Palantir_Technologies" title="Palantir Technologies">Palantir Technologies</a></td>
<td>Information Technology</td>
<td>Application Software</td>
<td><a href="/wiki/Denver" title="Denver">Denver</a>, Colorado</td>
<td>2024-09-23</td>
<td>0001321655</td>
<td>2003
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/panw">PANW</a>
</td>
<td><a href="/wiki/Palo_Alto_Networks" title="Palo Alto Networks">Palo Alto Networks</a></td>
<td>Information Technology</td>
<td>Systems Software</td>
<td><a href="/wiki/Santa_Clara,_California" title="Santa Clara, California">Santa Clara, California</a></td>
<td>2023-06-20</td>
<td>0001327567</td>
<td>2005
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/psky">PSKY</a>
</td>
<td><a href="/wiki/Paramount_Skydance" title="Paramount Skydance">Paramount Skydance Corporation</a></td>
<td>Communication Services</td>
<td>Movies &amp; Entertainment</td>
<td><a href="/wiki/Los_Angeles" title="Los Angeles">Los Angeles</a>, California</td>
<td>1994-09-30</td>
<td>0002041610</td>
<td>2025 (<a href="/wiki/Paramount_Pictures" title="Paramount Pictures">Paramount Pictures</a> 1912)
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:PH">PH</a>
</td>
<td><a href="/wiki/Parker_Hannifin" title="Parker Hannifin">Parker Hannifin</a></td>
<td>Industrials</td>
<td>Industrial Machinery &amp; Supplies &amp; Components</td>
<td><a href="/wiki/Cleveland" title="Cleveland">Cleveland</a>, Ohio</td>
<td>1985-11-30</td>
<td>0000076334</td>
<td>1917
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/payx">PAYX</a>
</td>
<td><a href="/wiki/Paychex" title="Paychex">Paychex</a></td>
<td>Industrials</td>
<td>Human Resource &amp; Employment Services</td>
<td><a href="/wiki/Penfield,_New_York" title="Penfield, New York">Penfield, New York</a></td>
<td>1998-10-01</td>
<td>0000723531</td>
<td>1971
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:PAYC">PAYC</a>
</td>
<td><a href="/wiki/Paycom" title="Paycom">Paycom</a></td>
<td>Industrials</td>
<td>Human Resource &amp; Employment Services</td>
<td><a href="/wiki/Oklahoma_City" title="Oklahoma City">Oklahoma City</a>, Oklahoma</td>
<td>2020-01-28</td>
<td>0001590955</td>
<td>1998
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/pypl">PYPL</a>
</td>
<td><a href="/wiki/PayPal" title="PayPal">PayPal</a></td>
<td>Financials</td>
<td>Transaction &amp; Payment Processing Services</td>
<td><a href="/wiki/San_Jose,_California" title="San Jose, California">San Jose, California</a></td>
<td>2015-07-20</td>
<td>0001633917</td>
<td>1998
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:PNR">PNR</a>
</td>
<td><a href="/wiki/Pentair" title="Pentair">Pentair</a></td>
<td>Industrials</td>
<td>Industrial Machinery &amp; Supplies &amp; Components</td>
<td><a href="/wiki/Worsley" title="Worsley">Worsley, United Kingdom</a></td>
<td>2012-10-01</td>
<td>0000077360</td>
<td>1966
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/pep">PEP</a>
</td>
<td><a href="/wiki/PepsiCo" title="PepsiCo">PepsiCo</a></td>
<td>Consumer Staples</td>
<td>Soft Drinks &amp; Non-alcoholic Beverages</td>
<td><a href="/wiki/Purchase,_New_York" title="Purchase, New York">Purchase, New York</a></td>
<td>1957-03-04</td>
<td>0000077476</td>
<td>1898
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:PFE">PFE</a>
</td>
<td><a href="/wiki/Pfizer" title="Pfizer">Pfizer</a></td>
<td>Health Care</td>
<td>Pharmaceuticals</td>
<td><a href="/wiki/New_York_City" title="New York City">New York City</a>, New York</td>
<td>1957-03-04</td>
<td>0000078003</td>
<td>1849
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:PCG">PCG</a>
</td>
<td><a href="/wiki/PG%26E" class="mw-redirect" title="PG&amp;E">PG&amp;E Corporation</a></td>
<td>Utilities</td>
<td>Multi-Utilities</td>
<td><a href="/wiki/Oakland,_California" title="Oakland, California">Oakland, California</a></td>
<td>2022-10-03</td>
<td>0001004980</td>
<td>1905
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:PM">PM</a>
</td>
<td><a href="/wiki/Philip_Morris_International" title="Philip Morris International">Philip Morris International</a></td>
<td>Consumer Staples</td>
<td>Tobacco</td>
<td><a href="/wiki/New_York_City" title="New York City">New York City</a>, New York</td>
<td>2008-03-31</td>
<td>0001413329</td>
<td>2008 (1847)
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:PSX">PSX</a>
</td>
<td><a href="/wiki/Phillips_66" title="Phillips 66">Phillips 66</a></td>
<td>Energy</td>
<td>Oil &amp; Gas Refining &amp; Marketing</td>
<td><a href="/wiki/Houston" title="Houston">Houston</a>, Texas</td>
<td>2012-05-01</td>
<td>0001534701</td>
<td>2012 (1917)
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:PNW">PNW</a>
</td>
<td><a href="/wiki/Pinnacle_West_Capital" title="Pinnacle West Capital">Pinnacle West Capital</a></td>
<td>Utilities</td>
<td>Multi-Utilities</td>
<td><a href="/wiki/Phoenix,_Arizona" title="Phoenix, Arizona">Phoenix, Arizona</a></td>
<td>1999-10-04</td>
<td>0000764622</td>
<td>1985
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:PNC">PNC</a>
</td>
<td><a href="/wiki/PNC_Financial_Services" title="PNC Financial Services">PNC Financial Services</a></td>
<td>Financials</td>
<td>Diversified Banks</td>
<td><a href="/wiki/Pittsburgh" title="Pittsburgh">Pittsburgh</a>, Pennsylvania</td>
<td>1988-04-30</td>
<td>0000713676</td>
<td>1845
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/pool">POOL</a>
</td>
<td><a href="/wiki/Pool_Corporation" title="Pool Corporation">Pool Corporation</a></td>
<td>Consumer Discretionary</td>
<td>Distributors</td>
<td><a href="/wiki/Covington,_Louisiana" title="Covington, Louisiana">Covington, Louisiana</a></td>
<td>2020-10-07</td>
<td>0000945841</td>
<td>1993
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:PPG">PPG</a>
</td>
<td><a href="/wiki/PPG_Industries" title="PPG Industries">PPG Industries</a></td>
<td>Materials</td>
<td>Specialty Chemicals</td>
<td><a href="/wiki/Pittsburgh" title="Pittsburgh">Pittsburgh</a>, Pennsylvania</td>
<td>1957-03-04</td>
<td>0000079879</td>
<td>1883
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:PPL">PPL</a>
</td>
<td><a href="/wiki/PPL_Corporation" title="PPL Corporation">PPL Corporation</a></td>
<td>Utilities</td>
<td>Electric Utilities</td>
<td><a href="/wiki/Allentown,_Pennsylvania" title="Allentown, Pennsylvania">Allentown, Pennsylvania</a></td>
<td>2001-10-01</td>
<td>0000922224</td>
<td>1920
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/pfg">PFG</a>
</td>
<td><a href="/wiki/Principal_Financial_Group" title="Principal Financial Group">Principal Financial Group</a></td>
<td>Financials</td>
<td>Life &amp; Health Insurance</td>
<td><a href="/wiki/Des_Moines,_Iowa" title="Des Moines, Iowa">Des Moines, Iowa</a></td>
<td>2002-07-22</td>
<td>0001126328</td>
<td>1879
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:PG">PG</a>
</td>
<td><a href="/wiki/Procter_%26_Gamble" title="Procter &amp; Gamble">Procter &amp; Gamble</a></td>
<td>Consumer Staples</td>
<td>Personal Care Products</td>
<td><a href="/wiki/Cincinnati" title="Cincinnati">Cincinnati</a>, Ohio</td>
<td>1957-03-04</td>
<td>0000080424</td>
<td>1837
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:PGR">PGR</a>
</td>
<td><a href="/wiki/Progressive_Corporation" title="Progressive Corporation">Progressive Corporation</a></td>
<td>Financials</td>
<td>Property &amp; Casualty Insurance</td>
<td><a href="/wiki/Mayfield_Village,_Ohio" class="mw-redirect" title="Mayfield Village, Ohio">Mayfield Village, Ohio</a></td>
<td>1997-08-04</td>
<td>0000080661</td>
<td>1937
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:PLD">PLD</a>
</td>
<td><a href="/wiki/Prologis" title="Prologis">Prologis</a></td>
<td>Real Estate</td>
<td>Industrial REITs</td>
<td><a href="/wiki/San_Francisco" title="San Francisco">San Francisco</a>, California</td>
<td>2003-07-17</td>
<td>0001045609</td>
<td>1983
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:PRU">PRU</a>
</td>
<td><a href="/wiki/Prudential_Financial" title="Prudential Financial">Prudential Financial</a></td>
<td>Financials</td>
<td>Life &amp; Health Insurance</td>
<td><a href="/wiki/Newark,_New_Jersey" title="Newark, New Jersey">Newark, New Jersey</a></td>
<td>2002-07-22</td>
<td>0001137774</td>
<td>1875
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:PEG">PEG</a>
</td>
<td><a href="/wiki/Public_Service_Enterprise_Group" title="Public Service Enterprise Group">Public Service Enterprise Group</a></td>
<td>Utilities</td>
<td>Electric Utilities</td>
<td><a href="/wiki/Newark,_New_Jersey" title="Newark, New Jersey">Newark, New Jersey</a></td>
<td>1957-03-04</td>
<td>0000788784</td>
<td>1903
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/ptc">PTC</a>
</td>
<td><a href="/wiki/PTC_(software_company)" class="mw-redirect" title="PTC (software company)">PTC Inc.</a></td>
<td>Information Technology</td>
<td>Application Software</td>
<td><a href="/wiki/Boston" title="Boston">Boston</a>, Massachusetts</td>
<td>2021-04-20</td>
<td>0000857005</td>
<td>1985
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:PSA">PSA</a>
</td>
<td><a href="/wiki/Public_Storage" title="Public Storage">Public Storage</a></td>
<td>Real Estate</td>
<td>Self-Storage REITs</td>
<td><a href="/wiki/Glendale,_California" title="Glendale, California">Glendale, California</a></td>
<td>2005-08-19</td>
<td>0001393311</td>
<td>1972
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:PHM">PHM</a>
</td>
<td><a href="/wiki/PulteGroup" title="PulteGroup">PulteGroup</a></td>
<td>Consumer Discretionary</td>
<td>Homebuilding</td>
<td><a href="/wiki/Atlanta" title="Atlanta">Atlanta</a>, Georgia</td>
<td>1984-04-30</td>
<td>0000822416</td>
<td>1956
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:PWR">PWR</a>
</td>
<td><a href="/wiki/Quanta_Services" title="Quanta Services">Quanta Services</a></td>
<td>Industrials</td>
<td>Construction &amp; Engineering</td>
<td><a href="/wiki/Houston" title="Houston">Houston</a>, Texas</td>
<td>2009-07-01</td>
<td>0001050915</td>
<td>1997
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/qcom">QCOM</a>
</td>
<td><a href="/wiki/Qualcomm" title="Qualcomm">Qualcomm</a></td>
<td>Information Technology</td>
<td>Semiconductors</td>
<td><a href="/wiki/San_Diego" title="San Diego">San Diego</a>, California</td>
<td>1999-07-22</td>
<td>0000804328</td>
<td>1985
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:DGX">DGX</a>
</td>
<td><a href="/wiki/Quest_Diagnostics" title="Quest Diagnostics">Quest Diagnostics</a></td>
<td>Health Care</td>
<td>Health Care Services</td>
<td><a href="/wiki/Secaucus,_New_Jersey" title="Secaucus, New Jersey">Secaucus, New Jersey</a></td>
<td>2002-12-12</td>
<td>0001022079</td>
<td>1967
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:RL">RL</a>
</td>
<td><a href="/wiki/Ralph_Lauren_Corporation" title="Ralph Lauren Corporation">Ralph Lauren Corporation</a></td>
<td>Consumer Discretionary</td>
<td>Apparel, Accessories &amp; Luxury Goods</td>
<td><a href="/wiki/New_York_City" title="New York City">New York City</a>, New York</td>
<td>2007-02-02</td>
<td>0001037038</td>
<td>1967
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:RJF">RJF</a>
</td>
<td><a href="/wiki/Raymond_James_Financial" title="Raymond James Financial">Raymond James Financial</a></td>
<td>Financials</td>
<td>Investment Banking &amp; Brokerage</td>
<td><a href="/wiki/St._Petersburg,_Florida" title="St. Petersburg, Florida">St. Petersburg, Florida</a></td>
<td>2017-03-20</td>
<td>0000720005</td>
<td>1962
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:RTX">RTX</a>
</td>
<td><a href="/wiki/RTX_Corporation" title="RTX Corporation">RTX Corporation</a></td>
<td>Industrials</td>
<td>Aerospace &amp; Defense</td>
<td><a href="/wiki/Waltham,_Massachusetts" title="Waltham, Massachusetts">Waltham, Massachusetts</a></td>
<td>1957-03-04</td>
<td>0000101829</td>
<td>1922
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:O">O</a>
</td>
<td><a href="/wiki/Realty_Income" title="Realty Income">Realty Income</a></td>
<td>Real Estate</td>
<td>Retail REITs</td>
<td><a href="/wiki/San_Diego" title="San Diego">San Diego</a>, California</td>
<td>2015-04-07</td>
<td>0000726728</td>
<td>1969
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/reg">REG</a>
</td>
<td><a href="/wiki/Regency_Centers" title="Regency Centers">Regency Centers</a></td>
<td>Real Estate</td>
<td>Retail REITs</td>
<td><a href="/wiki/Jacksonville,_Florida" title="Jacksonville, Florida">Jacksonville, Florida</a></td>
<td>2017-03-02</td>
<td>0000910606</td>
<td>1963
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/regn">REGN</a>
</td>
<td><a href="/wiki/Regeneron_Pharmaceuticals" title="Regeneron Pharmaceuticals">Regeneron Pharmaceuticals</a></td>
<td>Health Care</td>
<td>Biotechnology</td>
<td><a href="/wiki/Tarrytown,_New_York" title="Tarrytown, New York">Tarrytown, New York</a></td>
<td>2013-05-01</td>
<td>0000872589</td>
<td>1988
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:RF">RF</a>
</td>
<td><a href="/wiki/Regions_Financial_Corporation" title="Regions Financial Corporation">Regions Financial Corporation</a></td>
<td>Financials</td>
<td>Regional Banks</td>
<td><a href="/wiki/Birmingham,_Alabama" title="Birmingham, Alabama">Birmingham, Alabama</a></td>
<td>1998-08-28</td>
<td>0001281761</td>
<td>1971
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:RSG">RSG</a>
</td>
<td><a href="/wiki/Republic_Services" title="Republic Services">Republic Services</a></td>
<td>Industrials</td>
<td>Environmental &amp; Facilities Services</td>
<td><a href="/wiki/Phoenix,_Arizona" title="Phoenix, Arizona">Phoenix, Arizona</a></td>
<td>2008-12-05</td>
<td>0001060391</td>
<td>1998 (1981)
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:RMD">RMD</a>
</td>
<td><a href="/wiki/ResMed" title="ResMed">ResMed</a></td>
<td>Health Care</td>
<td>Health Care Equipment</td>
<td><a href="/wiki/San_Diego" title="San Diego">San Diego</a>, California</td>
<td>2017-07-26</td>
<td>0000943819</td>
<td>1989
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:RVTY">RVTY</a>
</td>
<td><a href="/wiki/Revvity" title="Revvity">Revvity</a></td>
<td>Health Care</td>
<td>Health Care Equipment</td>
<td><a href="/wiki/Waltham,_Massachusetts" title="Waltham, Massachusetts">Waltham, Massachusetts</a></td>
<td>1985-05-31</td>
<td>0000031791</td>
<td>1937
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:ROK">ROK</a>
</td>
<td><a href="/wiki/Rockwell_Automation" title="Rockwell Automation">Rockwell Automation</a></td>
<td>Industrials</td>
<td>Electrical Components &amp; Equipment</td>
<td><a href="/wiki/Milwaukee" title="Milwaukee">Milwaukee</a>, Wisconsin</td>
<td>2000-03-12</td>
<td>0001024478
</td>
<td>1903
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:ROL">ROL</a>
</td>
<td><a href="/wiki/Rollins,_Inc." title="Rollins, Inc.">Rollins, Inc.</a></td>
<td>Industrials</td>
<td>Environmental &amp; Facilities Services</td>
<td><a href="/wiki/Atlanta" title="Atlanta">Atlanta</a>, Georgia</td>
<td>2018-10-01</td>
<td>0000084839</td>
<td>1948
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/rop">ROP</a>
</td>
<td><a href="/wiki/Roper_Technologies" title="Roper Technologies">Roper Technologies</a></td>
<td>Information Technology</td>
<td>Electronic Equipment &amp; Instruments</td>
<td><a href="/wiki/Sarasota,_Florida" title="Sarasota, Florida">Sarasota, Florida</a></td>
<td>2009-12-23</td>
<td>0000882835</td>
<td>1981
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/rost">ROST</a>
</td>
<td><a href="/wiki/Ross_Stores" title="Ross Stores">Ross Stores</a></td>
<td>Consumer Discretionary</td>
<td>Apparel Retail</td>
<td><a href="/wiki/Dublin,_California" title="Dublin, California">Dublin, California</a></td>
<td>2009-12-21</td>
<td>0000745732</td>
<td>1982
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:RCL">RCL</a>
</td>
<td><a href="/wiki/Royal_Caribbean_Group" title="Royal Caribbean Group">Royal Caribbean Group</a></td>
<td>Consumer Discretionary</td>
<td>Hotels, Resorts &amp; Cruise Lines</td>
<td><a href="/wiki/Miami" title="Miami">Miami</a>, Florida</td>
<td>2014-12-05</td>
<td>0000884887</td>
<td>1997
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:SPGI">SPGI</a>
</td>
<td><a href="/wiki/S%26P_Global" title="S&amp;P Global">S&amp;P Global</a></td>
<td>Financials</td>
<td>Financial Exchanges &amp; Data</td>
<td><a href="/wiki/New_York_City" title="New York City">New York City</a>, New York</td>
<td>1957-03-04</td>
<td>0000064040
</td>
<td>1917
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:CRM">CRM</a>
</td>
<td><a href="/wiki/Salesforce" title="Salesforce">Salesforce</a></td>
<td>Information Technology</td>
<td>Application Software</td>
<td><a href="/wiki/San_Francisco" title="San Francisco">San Francisco</a>, California</td>
<td>2008-09-15</td>
<td>0001108524</td>
<td>1999
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/sbac">SBAC</a>
</td>
<td><a href="/wiki/SBA_Communications" title="SBA Communications">SBA Communications</a></td>
<td>Real Estate</td>
<td>Telecom Tower REITs</td>
<td><a href="/wiki/Boca_Raton,_Florida" title="Boca Raton, Florida">Boca Raton, Florida</a></td>
<td>2017-09-01</td>
<td>0001034054</td>
<td>1989
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:SLB">SLB</a>
</td>
<td><a href="/wiki/Schlumberger" title="Schlumberger">Schlumberger</a></td>
<td>Energy</td>
<td>Oil &amp; Gas Equipment &amp; Services</td>
<td><a href="/wiki/Houston" title="Houston">Houston</a>, Texas</td>
<td>1957-03-04</td>
<td>0000087347</td>
<td>1926
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/stx">STX</a>
</td>
<td><a href="/wiki/Seagate_Technology" title="Seagate Technology">Seagate Technology</a></td>
<td>Information Technology</td>
<td>Technology Hardware, Storage &amp; Peripherals</td>
<td><a href="/wiki/Dublin" title="Dublin">Dublin</a>, Ireland</td>
<td>2012-07-02</td>
<td>0001137789</td>
<td>1979
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:SRE">SRE</a>
</td>
<td><a href="/wiki/Sempra" title="Sempra">Sempra</a></td>
<td>Utilities</td>
<td>Multi-Utilities</td>
<td><a href="/wiki/San_Diego" title="San Diego">San Diego</a>, California</td>
<td>2017-03-17</td>
<td>0001032208</td>
<td>1998
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:NOW">NOW</a>
</td>
<td><a href="/wiki/ServiceNow" title="ServiceNow">ServiceNow</a></td>
<td>Information Technology</td>
<td>Systems Software</td>
<td><a href="/wiki/Santa_Clara,_California" title="Santa Clara, California">Santa Clara, California</a></td>
<td>2019-11-21</td>
<td>0001373715</td>
<td>2003
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:SHW">SHW</a>
</td>
<td><a href="/wiki/Sherwin-Williams" title="Sherwin-Williams">Sherwin-Williams</a></td>
<td>Materials</td>
<td>Specialty Chemicals</td>
<td><a href="/wiki/Cleveland" title="Cleveland">Cleveland</a>, Ohio</td>
<td>1964-06-30</td>
<td>0000089800</td>
<td>1866
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:SPG">SPG</a>
</td>
<td><a href="/wiki/Simon_Property_Group" title="Simon Property Group">Simon Property Group</a></td>
<td>Real Estate</td>
<td>Retail REITs</td>
<td><a href="/wiki/Indianapolis" title="Indianapolis">Indianapolis</a>, Indiana</td>
<td>2002-06-26</td>
<td>0001063761
</td>
<td>2003
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/swks">SWKS</a>
</td>
<td><a href="/wiki/Skyworks_Solutions" title="Skyworks Solutions">Skyworks Solutions</a></td>
<td>Information Technology</td>
<td>Semiconductors</td>
<td><a href="/wiki/Irvine,_California" title="Irvine, California">Irvine, California</a></td>
<td>2015-03-12</td>
<td>0000004127</td>
<td>2002
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:SJM">SJM</a>
</td>
<td><a href="/wiki/The_J.M._Smucker_Company" title="The J.M. Smucker Company">J.M. Smucker Company (The)</a></td>
<td>Consumer Staples</td>
<td>Packaged Foods &amp; Meats</td>
<td><a href="/wiki/Orrville,_Ohio" title="Orrville, Ohio">Orrville, Ohio</a></td>
<td>2008-11-06</td>
<td>0000091419</td>
<td>1897
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:SW">SW</a>
</td>
<td><a href="/wiki/Smurfit_Westrock" title="Smurfit Westrock">Smurfit Westrock</a></td>
<td>Materials</td>
<td>Paper &amp; Plastic Packaging Products &amp; Materials</td>
<td><a href="/wiki/Dublin" title="Dublin">Dublin</a>, Ireland</td>
<td>2024-07-08</td>
<td>0002005951</td>
<td>1934
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:SNA">SNA</a>
</td>
<td><a href="/wiki/Snap-on" title="Snap-on">Snap-on</a></td>
<td>Industrials</td>
<td>Industrial Machinery &amp; Supplies &amp; Components</td>
<td><a href="/wiki/Kenosha,_Wisconsin" title="Kenosha, Wisconsin">Kenosha, Wisconsin</a></td>
<td>1982-09-30</td>
<td>0000091440</td>
<td>1920
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:SOLV">SOLV</a>
</td>
<td><a href="/wiki/Solventum" title="Solventum">Solventum</a></td>
<td>Health Care</td>
<td>Health Care Technology</td>
<td><a href="/wiki/Saint_Paul,_Minnesota" title="Saint Paul, Minnesota">Saint Paul, Minnesota</a></td>
<td>2024-04-01</td>
<td>0001964738</td>
<td>2023
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:SO">SO</a>
</td>
<td><a href="/wiki/Southern_Company" title="Southern Company">Southern Company</a></td>
<td>Utilities</td>
<td>Electric Utilities</td>
<td><a href="/wiki/Atlanta" title="Atlanta">Atlanta</a>, Georgia</td>
<td>1957-03-04</td>
<td>0000092122</td>
<td>1945
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:LUV">LUV</a>
</td>
<td><a href="/wiki/Southwest_Airlines" title="Southwest Airlines">Southwest Airlines</a></td>
<td>Industrials</td>
<td>Passenger Airlines</td>
<td><a href="/wiki/Dallas" title="Dallas">Dallas</a>, Texas</td>
<td>1994-07-01</td>
<td>0000092380</td>
<td>1967
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:SWK">SWK</a>
</td>
<td><a href="/wiki/Stanley_Black_%26_Decker" title="Stanley Black &amp; Decker">Stanley Black &amp; Decker</a></td>
<td>Industrials</td>
<td>Industrial Machinery &amp; Supplies &amp; Components</td>
<td><a href="/wiki/New_Britain,_Connecticut" title="New Britain, Connecticut">New Britain, Connecticut</a></td>
<td>1982-09-30</td>
<td>0000093556</td>
<td>1843
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/sbux">SBUX</a>
</td>
<td><a href="/wiki/Starbucks" title="Starbucks">Starbucks</a></td>
<td>Consumer Discretionary</td>
<td>Restaurants</td>
<td><a href="/wiki/Seattle" title="Seattle">Seattle</a>, Washington</td>
<td>2000-06-07</td>
<td>0000829224</td>
<td>1971
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:STT">STT</a>
</td>
<td><a href="/wiki/State_Street_Corporation" title="State Street Corporation">State Street Corporation</a></td>
<td>Financials</td>
<td>Asset Management &amp; Custody Banks</td>
<td><a href="/wiki/Boston" title="Boston">Boston</a>, Massachusetts</td>
<td>2003-03-14</td>
<td>0000093751</td>
<td>1792
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/stld">STLD</a>
</td>
<td><a href="/wiki/Steel_Dynamics" title="Steel Dynamics">Steel Dynamics</a></td>
<td>Materials</td>
<td>Steel</td>
<td><a href="/wiki/Fort_Wayne,_Indiana" title="Fort Wayne, Indiana">Fort Wayne, Indiana</a></td>
<td>2022-12-22</td>
<td>0001022671</td>
<td>1993
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:STE">STE</a>
</td>
<td><a href="/wiki/Steris" title="Steris">Steris</a></td>
<td>Health Care</td>
<td>Health Care Equipment</td>
<td><a href="/wiki/Dublin" title="Dublin">Dublin</a>, Ireland</td>
<td>2019-12-23</td>
<td>0001757898</td>
<td>1985
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:SYK">SYK</a>
</td>
<td><a href="/wiki/Stryker_Corporation" title="Stryker Corporation">Stryker Corporation</a></td>
<td>Health Care</td>
<td>Health Care Equipment</td>
<td><a href="/wiki/Kalamazoo,_Michigan" title="Kalamazoo, Michigan">Kalamazoo, Michigan</a></td>
<td>2000-12-12</td>
<td>0000310764</td>
<td>1941
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/smci">SMCI</a>
</td>
<td><a href="/wiki/Supermicro" title="Supermicro">Supermicro</a></td>
<td>Information Technology</td>
<td>Technology Hardware, Storage &amp; Peripherals</td>
<td><a href="/wiki/San_Jose,_California" title="San Jose, California">San Jose, California</a></td>
<td>2024-03-18</td>
<td>0001375365</td>
<td>1993
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:SYF">SYF</a>
</td>
<td><a href="/wiki/Synchrony_Financial" title="Synchrony Financial">Synchrony Financial</a></td>
<td>Financials</td>
<td>Consumer Finance</td>
<td><a href="/wiki/Stamford,_Connecticut" title="Stamford, Connecticut">Stamford, Connecticut</a></td>
<td>2015-11-18</td>
<td>0001601712</td>
<td>2003
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/snps">SNPS</a>
</td>
<td><a href="/wiki/Synopsys" title="Synopsys">Synopsys</a></td>
<td>Information Technology</td>
<td>Application Software</td>
<td><a href="/wiki/Sunnyvale,_California" title="Sunnyvale, California">Sunnyvale, California</a></td>
<td>2017-03-16</td>
<td>0000883241</td>
<td>1986
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:SYY">SYY</a>
</td>
<td><a href="/wiki/Sysco" title="Sysco">Sysco</a></td>
<td>Consumer Staples</td>
<td>Food Distributors</td>
<td><a href="/wiki/Houston" title="Houston">Houston</a>, Texas</td>
<td>1986-12-31</td>
<td>0000096021</td>
<td>1969
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/tmus">TMUS</a>
</td>
<td><a href="/wiki/T-Mobile_US" title="T-Mobile US">T-Mobile US</a></td>
<td>Communication Services</td>
<td>Wireless Telecommunication Services</td>
<td><a href="/wiki/Bellevue,_Washington" title="Bellevue, Washington">Bellevue, Washington</a></td>
<td>2019-07-15</td>
<td>0001283699</td>
<td>1994
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/trow">TROW</a>
</td>
<td><a href="/wiki/T._Rowe_Price" title="T. Rowe Price">T. Rowe Price</a></td>
<td>Financials</td>
<td>Asset Management &amp; Custody Banks</td>
<td><a href="/wiki/Baltimore" title="Baltimore">Baltimore</a>, Maryland</td>
<td>2019-07-29</td>
<td>0001113169</td>
<td>1937
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/ttwo">TTWO</a>
</td>
<td><a href="/wiki/Take-Two_Interactive" title="Take-Two Interactive">Take-Two Interactive</a></td>
<td>Communication Services</td>
<td>Interactive Home Entertainment</td>
<td><a href="/wiki/New_York_City" title="New York City">New York City</a>, New York</td>
<td>2018-03-19</td>
<td>0000946581</td>
<td>1993
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:TPR">TPR</a>
</td>
<td><a href="/wiki/Tapestry,_Inc." title="Tapestry, Inc.">Tapestry, Inc.</a></td>
<td>Consumer Discretionary</td>
<td>Apparel, Accessories &amp; Luxury Goods</td>
<td><a href="/wiki/New_York_City" title="New York City">New York City</a>, New York</td>
<td>2004-09-01</td>
<td>0001116132</td>
<td>2017
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:TRGP">TRGP</a>
</td>
<td><a href="/wiki/Targa_Resources" title="Targa Resources">Targa Resources</a></td>
<td>Energy</td>
<td>Oil &amp; Gas Storage &amp; Transportation</td>
<td><a href="/wiki/Houston" title="Houston">Houston</a>, Texas</td>
<td>2022-10-12</td>
<td>0001389170</td>
<td>2005
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:TGT">TGT</a>
</td>
<td><a href="/wiki/Target_Corporation" title="Target Corporation">Target Corporation</a></td>
<td>Consumer Staples</td>
<td>Consumer Staples Merchandise Retail</td>
<td><a href="/wiki/Minneapolis" title="Minneapolis">Minneapolis</a>, Minnesota</td>
<td>1976-12-31</td>
<td>0000027419
</td>
<td>1902
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:TEL">TEL</a>
</td>
<td><a href="/wiki/TE_Connectivity" title="TE Connectivity">TE Connectivity</a></td>
<td>Information Technology</td>
<td>Electronic Manufacturing Services</td>
<td><a href="/wiki/Galway,_Ireland" class="mw-redirect" title="Galway, Ireland">Galway, Ireland</a></td>
<td>2011-10-17</td>
<td>0001385157
</td>
<td>2007
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:TDY">TDY</a>
</td>
<td><a href="/wiki/Teledyne_Technologies" title="Teledyne Technologies">Teledyne Technologies</a></td>
<td>Information Technology</td>
<td>Electronic Equipment &amp; Instruments</td>
<td><a href="/wiki/Thousand_Oaks,_California" title="Thousand Oaks, California">Thousand Oaks, California</a></td>
<td>2020-06-22</td>
<td>0001094285
</td>
<td>1960
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/ter">TER</a>
</td>
<td><a href="/wiki/Teradyne" title="Teradyne">Teradyne</a></td>
<td>Information Technology</td>
<td>Semiconductor Materials &amp; Equipment</td>
<td><a href="/wiki/North_Reading,_Massachusetts" title="North Reading, Massachusetts">North Reading, Massachusetts</a></td>
<td>2020-09-21</td>
<td>0000097210</td>
<td>1960
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/tsla">TSLA</a>
</td>
<td><a href="/wiki/Tesla,_Inc." title="Tesla, Inc.">Tesla, Inc.</a></td>
<td>Consumer Discretionary</td>
<td>Automobile Manufacturers</td>
<td><a href="/wiki/Austin,_Texas" title="Austin, Texas">Austin, Texas</a></td>
<td>2020-12-21</td>
<td>0001318605</td>
<td>2003
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/txn">TXN</a>
</td>
<td><a href="/wiki/Texas_Instruments" title="Texas Instruments">Texas Instruments</a></td>
<td>Information Technology</td>
<td>Semiconductors</td>
<td><a href="/wiki/Dallas" title="Dallas">Dallas</a>, Texas</td>
<td>2001-03-12</td>
<td>0000097476</td>
<td>1930
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:TPL">TPL</a>
</td>
<td><a href="/wiki/Texas_Pacific_Land_Corporation" title="Texas Pacific Land Corporation">Texas Pacific Land Corporation</a></td>
<td>Energy</td>
<td>Oil &amp; Gas Exploration &amp; Production</td>
<td><a href="/wiki/Dallas" title="Dallas">Dallas</a>, Texas</td>
<td>2024-11-26</td>
<td>0001811074</td>
<td>1888
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:TXT">TXT</a>
</td>
<td><a href="/wiki/Textron" title="Textron">Textron</a></td>
<td>Industrials</td>
<td>Aerospace &amp; Defense</td>
<td><a href="/wiki/Providence,_Rhode_Island" title="Providence, Rhode Island">Providence, Rhode Island</a></td>
<td>1978-12-31</td>
<td>0000217346
</td>
<td>1923
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:TMO">TMO</a>
</td>
<td><a href="/wiki/Thermo_Fisher_Scientific" title="Thermo Fisher Scientific">Thermo Fisher Scientific</a></td>
<td>Health Care</td>
<td>Life Sciences Tools &amp; Services</td>
<td><a href="/wiki/Waltham,_Massachusetts" title="Waltham, Massachusetts">Waltham, Massachusetts</a></td>
<td>2004-08-03</td>
<td>0000097745</td>
<td>2006 (1902)
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:TJX">TJX</a>
</td>
<td><a href="/wiki/TJX_Companies" class="mw-redirect" title="TJX Companies">TJX Companies</a></td>
<td>Consumer Discretionary</td>
<td>Apparel Retail</td>
<td><a href="/wiki/Framingham,_Massachusetts" title="Framingham, Massachusetts">Framingham, Massachusetts</a></td>
<td>1985-09-30</td>
<td>0000109198</td>
<td>1987
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:TKO">TKO</a>
</td>
<td><a href="/wiki/TKO_Group_Holdings" title="TKO Group Holdings">TKO Group Holdings</a></td>
<td>Communication Services</td>
<td>Movies &amp; Entertainment</td>
<td><a href="/wiki/New_York_City" title="New York City">New York City</a>, New York</td>
<td>2025-03-24</td>
<td>0001973266</td>
<td>2023
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/ttd">TTD</a>
</td>
<td><a href="/wiki/The_Trade_Desk" title="The Trade Desk">Trade Desk (The)</a></td>
<td>Communication Services</td>
<td>Advertising</td>
<td><a href="/wiki/Ventura,_California" title="Ventura, California">Ventura, California</a></td>
<td>2025-07-18</td>
<td>0001671933</td>
<td>2009
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/tsco">TSCO</a>
</td>
<td><a href="/wiki/Tractor_Supply" class="mw-redirect" title="Tractor Supply">Tractor Supply</a></td>
<td>Consumer Discretionary</td>
<td>Other Specialty Retail</td>
<td><a href="/wiki/Brentwood,_Tennessee" title="Brentwood, Tennessee">Brentwood, Tennessee</a></td>
<td>2014-01-24</td>
<td>0000916365</td>
<td>1938
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:TT">TT</a>
</td>
<td><a href="/wiki/Trane_Technologies" title="Trane Technologies">Trane Technologies</a></td>
<td>Industrials</td>
<td>Building Products</td>
<td><a href="/wiki/Dublin" title="Dublin">Dublin</a>, Ireland</td>
<td>2010-11-17</td>
<td>0001466258
</td>
<td>1871
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:TDG">TDG</a>
</td>
<td><a href="/wiki/TransDigm_Group" title="TransDigm Group">TransDigm Group</a></td>
<td>Industrials</td>
<td>Aerospace &amp; Defense</td>
<td><a href="/wiki/Cleveland" title="Cleveland">Cleveland</a>, Ohio</td>
<td>2016-06-03</td>
<td>0001260221
</td>
<td>1993
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:TRV">TRV</a>
</td>
<td><a href="/wiki/The_Travelers_Companies" title="The Travelers Companies">Travelers Companies (The)</a></td>
<td>Financials</td>
<td>Property &amp; Casualty Insurance</td>
<td><a href="/wiki/New_York_City" title="New York City">New York City</a>, New York</td>
<td>2002-08-21</td>
<td>0000086312</td>
<td>1853
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/trmb">TRMB</a>
</td>
<td><a href="/wiki/Trimble_Inc." title="Trimble Inc.">Trimble Inc.</a></td>
<td>Information Technology</td>
<td>Electronic Equipment &amp; Instruments</td>
<td><a href="/wiki/Westminster,_Colorado" title="Westminster, Colorado">Westminster, Colorado</a></td>
<td>2021-01-21</td>
<td>0000864749</td>
<td>1978
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:TFC">TFC</a>
</td>
<td><a href="/wiki/Truist_Financial" title="Truist Financial">Truist Financial</a></td>
<td>Financials</td>
<td>Diversified Banks</td>
<td><a href="/wiki/Charlotte,_North_Carolina" title="Charlotte, North Carolina">Charlotte, North Carolina</a></td>
<td>1997-12-04</td>
<td>0000092230</td>
<td>1872
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:TYL">TYL</a>
</td>
<td><a href="/wiki/Tyler_Technologies" title="Tyler Technologies">Tyler Technologies</a></td>
<td>Information Technology</td>
<td>Application Software</td>
<td><a href="/wiki/Plano,_Texas" title="Plano, Texas">Plano, Texas</a></td>
<td>2020-06-22</td>
<td>0000860731</td>
<td>1966
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:TSN">TSN</a>
</td>
<td><a href="/wiki/Tyson_Foods" title="Tyson Foods">Tyson Foods</a></td>
<td>Consumer Staples</td>
<td>Packaged Foods &amp; Meats</td>
<td><a href="/wiki/Springdale,_Arkansas" title="Springdale, Arkansas">Springdale, Arkansas</a></td>
<td>2005-08-10</td>
<td>0000100493</td>
<td>1935
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:USB">USB</a>
</td>
<td><a href="/wiki/U.S._Bancorp" title="U.S. Bancorp">U.S. Bancorp</a></td>
<td>Financials</td>
<td>Diversified Banks</td>
<td><a href="/wiki/Minneapolis" title="Minneapolis">Minneapolis</a>, Minnesota</td>
<td>1999-11-01</td>
<td>0000036104</td>
<td>1968
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:UBER">UBER</a>
</td>
<td><a href="/wiki/Uber" title="Uber">Uber</a></td>
<td>Industrials</td>
<td>Passenger Ground Transportation</td>
<td><a href="/wiki/San_Francisco" title="San Francisco">San Francisco</a>, California</td>
<td>2023-12-18</td>
<td>0001543151</td>
<td>2009
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:UDR">UDR</a>
</td>
<td><a href="/wiki/UDR,_Inc." title="UDR, Inc.">UDR, Inc.</a></td>
<td>Real Estate</td>
<td>Multi-Family Residential REITs</td>
<td><a href="/wiki/Highlands_Ranch,_Colorado" title="Highlands Ranch, Colorado">Highlands Ranch, Colorado</a></td>
<td>2016-03-07</td>
<td>0000074208</td>
<td>1972
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/ulta">ULTA</a>
</td>
<td><a href="/wiki/Ulta_Beauty" title="Ulta Beauty">Ulta Beauty</a></td>
<td>Consumer Discretionary</td>
<td>Other Specialty Retail</td>
<td><a href="/wiki/Bolingbrook,_Illinois" title="Bolingbrook, Illinois">Bolingbrook, Illinois</a></td>
<td>2016-04-18</td>
<td>0001403568</td>
<td>1990
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:UNP">UNP</a>
</td>
<td><a href="/wiki/Union_Pacific_Corporation" title="Union Pacific Corporation">Union Pacific Corporation</a></td>
<td>Industrials</td>
<td>Rail Transportation</td>
<td><a href="/wiki/Omaha,_Nebraska" title="Omaha, Nebraska">Omaha, Nebraska</a></td>
<td>1957-03-04</td>
<td>0000100885</td>
<td>1862
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/ual">UAL</a>
</td>
<td><a href="/wiki/United_Airlines_Holdings" class="mw-redirect" title="United Airlines Holdings">United Airlines Holdings</a></td>
<td>Industrials</td>
<td>Passenger Airlines</td>
<td><a href="/wiki/Chicago" title="Chicago">Chicago</a>, Illinois</td>
<td>2015-09-03</td>
<td>0000100517</td>
<td>1967
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:UPS">UPS</a>
</td>
<td><a href="/wiki/United_Parcel_Service" title="United Parcel Service">United Parcel Service</a></td>
<td>Industrials</td>
<td>Air Freight &amp; Logistics</td>
<td><a href="/wiki/Sandy_Springs,_Georgia" title="Sandy Springs, Georgia">Sandy Springs, Georgia</a></td>
<td>2002-07-22</td>
<td>0001090727</td>
<td>1907
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:URI">URI</a>
</td>
<td><a href="/wiki/United_Rentals" title="United Rentals">United Rentals</a></td>
<td>Industrials</td>
<td>Trading Companies &amp; Distributors</td>
<td><a href="/wiki/Stamford,_Connecticut" title="Stamford, Connecticut">Stamford, Connecticut</a></td>
<td>2014-09-20</td>
<td>0001067701</td>
<td>1997
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:UNH">UNH</a>
</td>
<td><a href="/wiki/UnitedHealth_Group" title="UnitedHealth Group">UnitedHealth Group</a></td>
<td>Health Care</td>
<td>Managed Health Care</td>
<td><a href="/wiki/Minnetonka,_Minnesota" title="Minnetonka, Minnesota">Minnetonka, Minnesota</a></td>
<td>1994-07-01</td>
<td>0000731766</td>
<td>1977
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:UHS">UHS</a>
</td>
<td><a href="/wiki/Universal_Health_Services" title="Universal Health Services">Universal Health Services</a></td>
<td>Health Care</td>
<td>Health Care Facilities</td>
<td><a href="/wiki/King_of_Prussia,_Pennsylvania" title="King of Prussia, Pennsylvania">King of Prussia, Pennsylvania</a></td>
<td>2014-09-20</td>
<td>0000352915</td>
<td>1979
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:VLO">VLO</a>
</td>
<td><a href="/wiki/Valero_Energy" title="Valero Energy">Valero Energy</a></td>
<td>Energy</td>
<td>Oil &amp; Gas Refining &amp; Marketing</td>
<td><a href="/wiki/San_Antonio" title="San Antonio">San Antonio</a>, Texas</td>
<td>2002-12-20</td>
<td>0001035002</td>
<td>1980
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:VTR">VTR</a>
</td>
<td><a href="/wiki/Ventas_(company)" title="Ventas (company)">Ventas</a></td>
<td>Real Estate</td>
<td>Health Care REITs</td>
<td><a href="/wiki/Chicago" title="Chicago">Chicago</a>, Illinois</td>
<td>2009-03-04</td>
<td>0000740260</td>
<td>1998
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:VLTO">VLTO</a>
</td>
<td><a href="/wiki/Veralto" title="Veralto">Veralto</a></td>
<td>Industrials</td>
<td>Environmental &amp; Facilities Services</td>
<td><a href="/wiki/Waltham,_Massachusetts" title="Waltham, Massachusetts">Waltham, Massachusetts</a></td>
<td>2023-10-02</td>
<td>0001967680</td>
<td>2023
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/vrsn">VRSN</a>
</td>
<td><a href="/wiki/Verisign" title="Verisign">Verisign</a></td>
<td>Information Technology</td>
<td>Internet Services &amp; Infrastructure</td>
<td><a href="/wiki/Dulles,_Virginia" title="Dulles, Virginia">Dulles, Virginia</a></td>
<td>2006-02-01</td>
<td>0001014473</td>
<td>1995
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/vrsk">VRSK</a>
</td>
<td><a href="/wiki/Verisk_Analytics" title="Verisk Analytics">Verisk Analytics</a></td>
<td>Industrials</td>
<td>Research &amp; Consulting Services</td>
<td><a href="/wiki/Jersey_City,_New_Jersey" title="Jersey City, New Jersey">Jersey City, New Jersey</a></td>
<td>2015-10-08</td>
<td>0001442145</td>
<td>1971
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:VZ">VZ</a>
</td>
<td><a href="/wiki/Verizon" title="Verizon">Verizon</a></td>
<td>Communication Services</td>
<td>Integrated Telecommunication Services</td>
<td><a href="/wiki/New_York_City" title="New York City">New York City</a>, New York</td>
<td>1983-11-30</td>
<td>0000732712
</td>
<td>1983 (1877)
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/vrtx">VRTX</a>
</td>
<td><a href="/wiki/Vertex_Pharmaceuticals" title="Vertex Pharmaceuticals">Vertex Pharmaceuticals</a></td>
<td>Health Care</td>
<td>Biotechnology</td>
<td><a href="/wiki/Boston" title="Boston">Boston</a>, Massachusetts</td>
<td>2013-09-23</td>
<td>0000875320</td>
<td>1989
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/vtrs">VTRS</a>
</td>
<td><a href="/wiki/Viatris" title="Viatris">Viatris</a></td>
<td>Health Care</td>
<td>Pharmaceuticals</td>
<td><a href="/wiki/Pittsburgh" title="Pittsburgh">Pittsburgh</a>, Pennsylvania</td>
<td>2004-04-23</td>
<td>0001792044</td>
<td>1961
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:VICI">VICI</a>
</td>
<td><a href="/wiki/Vici_Properties" title="Vici Properties">Vici Properties</a></td>
<td>Real Estate</td>
<td>Hotel &amp; Resort REITs</td>
<td><a href="/wiki/New_York_City" title="New York City">New York City</a>, New York</td>
<td>2022-06-08</td>
<td>0001705696</td>
<td>2017
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:V">V</a>
</td>
<td><a href="/wiki/Visa_Inc." title="Visa Inc.">Visa Inc.</a></td>
<td>Financials</td>
<td>Transaction &amp; Payment Processing Services</td>
<td><a href="/wiki/San_Francisco" title="San Francisco">San Francisco</a>, California</td>
<td>2009-12-21</td>
<td>0001403161</td>
<td>1958
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:VST">VST</a>
</td>
<td><a href="/wiki/Vistra_Corp" class="mw-redirect" title="Vistra Corp">Vistra Corp</a>.</td>
<td>Utilities</td>
<td>Electric Utilities</td>
<td><a href="/wiki/Irving,_Texas" title="Irving, Texas">Irving, Texas</a></td>
<td>2024-05-08</td>
<td>0001692819</td>
<td>2016
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:VMC">VMC</a>
</td>
<td><a href="/wiki/Vulcan_Materials_Company" title="Vulcan Materials Company">Vulcan Materials Company</a></td>
<td>Materials</td>
<td>Construction Materials</td>
<td><a href="/wiki/Birmingham,_Alabama" title="Birmingham, Alabama">Birmingham, Alabama</a></td>
<td>1999-06-30</td>
<td>0001396009</td>
<td>1909
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:WRB">WRB</a>
</td>
<td><a href="/wiki/W._R._Berkley_Corporation" title="W. R. Berkley Corporation">W. R. Berkley Corporation</a></td>
<td>Financials</td>
<td>Property &amp; Casualty Insurance</td>
<td><a href="/wiki/Greenwich,_Connecticut" title="Greenwich, Connecticut">Greenwich, Connecticut</a></td>
<td>2019-12-05</td>
<td>0000011544</td>
<td>1967
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:GWW">GWW</a>
</td>
<td><a href="/wiki/W._W._Grainger" title="W. W. Grainger">W. W. Grainger</a></td>
<td>Industrials</td>
<td>Industrial Machinery &amp; Supplies &amp; Components</td>
<td><a href="/wiki/Lake_Forest,_Illinois" title="Lake Forest, Illinois">Lake Forest, Illinois</a></td>
<td>1981-06-30</td>
<td>0000277135</td>
<td>1927
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:WAB">WAB</a>
</td>
<td><a href="/wiki/Wabtec" title="Wabtec">Wabtec</a></td>
<td>Industrials</td>
<td>Construction Machinery &amp; Heavy Transportation Equipment</td>
<td><a href="/wiki/Pittsburgh" title="Pittsburgh">Pittsburgh</a>, Pennsylvania</td>
<td>2019-02-27</td>
<td>0000943452</td>
<td>1999 (1869)
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:WMT">WMT</a>
</td>
<td><a href="/wiki/Walmart" title="Walmart">Walmart</a></td>
<td>Consumer Staples</td>
<td>Consumer Staples Merchandise Retail</td>
<td><a href="/wiki/Bentonville,_Arkansas" title="Bentonville, Arkansas">Bentonville, Arkansas</a></td>
<td>1982-08-31</td>
<td>0000104169</td>
<td>1962
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:DIS">DIS</a>
</td>
<td><a href="/wiki/The_Walt_Disney_Company" title="The Walt Disney Company">Walt Disney Company (The)</a></td>
<td>Communication Services</td>
<td>Movies &amp; Entertainment</td>
<td><a href="/wiki/Burbank,_California" title="Burbank, California">Burbank, California</a></td>
<td>1976-06-30</td>
<td>0001744489</td>
<td>1923
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/wbd">WBD</a>
</td>
<td><a href="/wiki/Warner_Bros._Discovery" title="Warner Bros. Discovery">Warner Bros. Discovery</a></td>
<td>Communication Services</td>
<td>Broadcasting</td>
<td><a href="/wiki/New_York_City" title="New York City">New York City</a>, New York</td>
<td>2022-04-11</td>
<td>0001437107</td>
<td>2022 (<a href="/wiki/Warner_Bros." title="Warner Bros.">Warner Bros.</a> 1923)
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:WM">WM</a>
</td>
<td><a href="/wiki/Waste_Management,_Inc." title="Waste Management, Inc.">Waste Management</a></td>
<td>Industrials</td>
<td>Environmental &amp; Facilities Services</td>
<td><a href="/wiki/Houston" title="Houston">Houston</a>, Texas</td>
<td>1998-08-31</td>
<td>0000823768</td>
<td>1968
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:WAT">WAT</a>
</td>
<td><a href="/wiki/Waters_Corporation" title="Waters Corporation">Waters Corporation</a></td>
<td>Health Care</td>
<td>Life Sciences Tools &amp; Services</td>
<td><a href="/wiki/Milford,_Massachusetts" title="Milford, Massachusetts">Milford, Massachusetts</a></td>
<td>2002-01-02</td>
<td>0001000697</td>
<td>1958
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:WEC">WEC</a>
</td>
<td><a href="/wiki/WEC_Energy_Group" title="WEC Energy Group">WEC Energy Group</a></td>
<td>Utilities</td>
<td>Electric Utilities</td>
<td><a href="/wiki/Milwaukee" title="Milwaukee">Milwaukee</a>, Wisconsin</td>
<td>2008-10-31</td>
<td>0000783325
</td>
<td>1896
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:WFC">WFC</a>
</td>
<td><a href="/wiki/Wells_Fargo" title="Wells Fargo">Wells Fargo</a></td>
<td>Financials</td>
<td>Diversified Banks</td>
<td><a href="/wiki/San_Francisco" title="San Francisco">San Francisco</a>, California</td>
<td>1976-06-30</td>
<td>0000072971
</td>
<td>1852
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:WELL">WELL</a>
</td>
<td><a href="/wiki/Welltower" title="Welltower">Welltower</a></td>
<td>Real Estate</td>
<td>Health Care REITs</td>
<td><a href="/wiki/Toledo,_Ohio" title="Toledo, Ohio">Toledo, Ohio</a></td>
<td>2009-01-30</td>
<td>0000766704
</td>
<td>1970
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:WST">WST</a>
</td>
<td><a href="/wiki/West_Pharmaceutical_Services" title="West Pharmaceutical Services">West Pharmaceutical Services</a></td>
<td>Health Care</td>
<td>Health Care Supplies</td>
<td><a href="/wiki/Exton,_Pennsylvania" title="Exton, Pennsylvania">Exton, Pennsylvania</a></td>
<td>2020-05-22</td>
<td>0000105770
</td>
<td>1923
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/wdc">WDC</a>
</td>
<td><a href="/wiki/Western_Digital" title="Western Digital">Western Digital</a></td>
<td>Information Technology</td>
<td>Technology Hardware, Storage &amp; Peripherals</td>
<td><a href="/wiki/San_Jose,_California" title="San Jose, California">San Jose, California</a></td>
<td>2009-07-01</td>
<td>0000106040
</td>
<td>1970
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:WY">WY</a>
</td>
<td><a href="/wiki/Weyerhaeuser" title="Weyerhaeuser">Weyerhaeuser</a></td>
<td>Real Estate</td>
<td>Timber REITs</td>
<td><a href="/wiki/Seattle" title="Seattle">Seattle</a>, Washington</td>
<td>1979-10-01</td>
<td>0000106535</td>
<td>1900
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:WSM">WSM</a>
</td>
<td><a href="/wiki/Williams-Sonoma,_Inc." title="Williams-Sonoma, Inc.">Williams-Sonoma, Inc.</a></td>
<td>Consumer Discretionary</td>
<td>Homefurnishing Retail</td>
<td><a href="/wiki/San_Francisco" title="San Francisco">San Francisco</a>, California</td>
<td>2025-03-24</td>
<td>0000719955</td>
<td>1956
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:WMB">WMB</a>
</td>
<td><a href="/wiki/Williams_Companies" title="Williams Companies">Williams Companies</a></td>
<td>Energy</td>
<td>Oil &amp; Gas Storage &amp; Transportation</td>
<td><a href="/wiki/Tulsa,_Oklahoma" title="Tulsa, Oklahoma">Tulsa, Oklahoma</a></td>
<td>1975-03-31</td>
<td>0000107263
</td>
<td>1908
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/wtw">WTW</a>
</td>
<td><a href="/wiki/Willis_Towers_Watson" title="Willis Towers Watson">Willis Towers Watson</a></td>
<td>Financials</td>
<td>Insurance Brokers</td>
<td><a href="/wiki/London" title="London">London</a>, United Kingdom</td>
<td>2016-01-05</td>
<td>0001140536
</td>
<td>2016
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/wday">WDAY</a>
</td>
<td><a href="/wiki/Workday,_Inc." title="Workday, Inc.">Workday, Inc.</a></td>
<td>Information Technology</td>
<td>Application Software</td>
<td><a href="/wiki/Pleasanton,_California" title="Pleasanton, California">Pleasanton, California</a></td>
<td>2024-12-23</td>
<td>0001327811</td>
<td>2005
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/wynn">WYNN</a>
</td>
<td><a href="/wiki/Wynn_Resorts" title="Wynn Resorts">Wynn Resorts</a></td>
<td>Consumer Discretionary</td>
<td>Casinos &amp; Gaming</td>
<td><a href="/wiki/Paradise,_Nevada" title="Paradise, Nevada">Paradise, Nevada</a></td>
<td>2008-11-14</td>
<td>0001174922
</td>
<td>2002
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/xel">XEL</a>
</td>
<td><a href="/wiki/Xcel_Energy" title="Xcel Energy">Xcel Energy</a></td>
<td>Utilities</td>
<td>Multi-Utilities</td>
<td><a href="/wiki/Minneapolis" title="Minneapolis">Minneapolis</a>, Minnesota</td>
<td>1957-03-04</td>
<td>0000072903</td>
<td>1909
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:XYL">XYL</a>
</td>
<td><a href="/wiki/Xylem_Inc." title="Xylem Inc.">Xylem Inc.</a></td>
<td>Industrials</td>
<td>Industrial Machinery &amp; Supplies &amp; Components</td>
<td><a href="/wiki/White_Plains,_New_York" title="White Plains, New York">White Plains, New York</a></td>
<td>2011-11-01</td>
<td>0001524472</td>
<td>2011
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:YUM">YUM</a>
</td>
<td><a href="/wiki/Yum!_Brands" title="Yum! Brands">Yum! Brands</a></td>
<td>Consumer Discretionary</td>
<td>Restaurants</td>
<td><a href="/wiki/Louisville,_Kentucky" title="Louisville, Kentucky">Louisville, Kentucky</a></td>
<td>1997-10-06</td>
<td>0001041061
</td>
<td>1997
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nasdaq.com/market-activity/stocks/zbra">ZBRA</a>
</td>
<td><a href="/wiki/Zebra_Technologies" title="Zebra Technologies">Zebra Technologies</a></td>
<td>Information Technology</td>
<td>Electronic Equipment &amp; Instruments</td>
<td><a href="/wiki/Lincolnshire,_Illinois" title="Lincolnshire, Illinois">Lincolnshire, Illinois</a></td>
<td>2019-12-23</td>
<td>0000877212
</td>
<td>1969
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:ZBH">ZBH</a>
</td>
<td><a href="/wiki/Zimmer_Biomet" title="Zimmer Biomet">Zimmer Biomet</a></td>
<td>Health Care</td>
<td>Health Care Equipment</td>
<td><a href="/wiki/Warsaw,_Indiana" title="Warsaw, Indiana">Warsaw, Indiana</a></td>
<td>2001-08-07</td>
<td>0001136869
</td>
<td>1927
</td></tr>
<tr>
<td><a rel="nofollow" class="external text" href="https://www.nyse.com/quote/XNYS:ZTS">ZTS</a>
</td>
<td><a href="/wiki/Zoetis" title="Zoetis">Zoetis</a></td>
<td>Health Care</td>
<td>Pharmaceuticals</td>
<td><a href="/wiki/Parsippany,_New_Jersey" class="mw-redirect" title="Parsippany, New Jersey">Parsippany, New Jersey</a></td>
<td>2013-06-21</td>
<td>0001555280</td>
<td>1952
</td></tr></tbody><tfoot></tfoot></table>
"""
# Wrap the snippet in a minimal table to help parsing, since it looks like a fragment
wrapped_html = f"<table><tbody>{html_content}</tbody></table>"
soup = BeautifulSoup(wrapped_html, "html.parser")

rows = []
for tr in soup.find_all("tr"):
    # Extract text from each <td>, stripping whitespace; BeautifulSoup removes the <a> tags but retains their text
    cells = [td.get_text(strip=True).replace("\xa0", " ") for td in tr.find_all("td")]
    # Keep only rows with the expected number of columns (8)
    if len(cells) == 8:
        rows.append(cells)

# Define the expected column names
columns = ["Ticker", "Security", "Sector", "GICS Sub-Industry", "Headquarters Location", "Date added", "CIK", "Founded"]

df_start = pd.DataFrame(rows, columns=columns)
df_start


Ticker             Security                  Sector  \
0      MMM                   3M             Industrials   
1      AOS          A. O. Smith             Industrials   
2      ABT  Abbott Laboratories             Health Care   
3     ABBV               AbbVie             Health Care   
4      ACN            Accenture  Information Technology   
..     ...                  ...                     ...   
498    XYL           Xylem Inc.             Industrials   
499    YUM          Yum! Brands  Consumer Discretionary   
500   ZBRA   Zebra Technologies  Information Technology   
501    ZBH        Zimmer Biomet             Health Care   
502    ZTS               Zoetis             Health Care   

                                GICS Sub-Industry    Headquarters Location  \
0                        Industrial Conglomerates    Saint Paul, Minnesota   
1                               Building Products     Milwaukee, Wisconsin   
2                           Health Care Equipment  North Chicago, Illinois   
3                                   Biotechnology  North Chicago, Illinois   
4                  IT Consulting & Other Services          Dublin, Ireland   
..                                            ...                      ...   
498  Industrial Machinery & Supplies & Components   White Plains, New York   
499                                   Restaurants     Louisville, Kentucky   
500            Electronic Equipment & Instruments   Lincolnshire, Illinois   
501                         Health Care Equipment          Warsaw, Indiana   
502                               Pharmaceuticals   Parsippany, New Jersey   

     Date added         CIK      Founded  
0    1957-03-04  0000066740         1902  
1    2017-07-26  0000091142         1916  
2    1957-03-04  0000001800         1888  
3    2012-12-31  0001551152  2013 (1888)  
4    2011-07-06  0001467373         1989  
..          ...         ...          ...  
498  2011-11-01  0001524472         2011  
499  1997-10-06  0001041061         1997  
500  2019-12-23  0000877212         1969  
501  2001-08-07  0001136869         1927  
502  2013-06-21  0001555280         1952  

[503 rows x 8 columns]

In [32]:
import pandas as pd
from bs4 import BeautifulSoup
import re

# HTML table data (the provided HTML content)
html_content = """<table class="wikitable sortable jquery-tablesorter" id="changes">

<thead><tr>
<th data-sort-type="date" rowspan="2" class="headerSort" tabindex="0" role="columnheader button" title="Sort ascending">Effective Date
</th>
<th colspan="2">Added
</th>
<th colspan="2">Removed
</th>
<th rowspan="2" class="headerSort" tabindex="0" role="columnheader button" title="Sort ascending">Reason
</th></tr><tr>
<th class="headerSort" tabindex="0" role="columnheader button" title="Sort ascending">Ticker</th>
<th class="headerSort" tabindex="0" role="columnheader button" title="Sort ascending">Security</th>
<th class="headerSort" tabindex="0" role="columnheader button" title="Sort ascending">Ticker</th>
<th class="headerSort" tabindex="0" role="columnheader button" title="Sort ascending">Security
</th></tr></thead><tbody>

<tr>
<td>September 22, 2025
</td>
<td>EME
</td>
<td><a href="/wiki/Emcor" title="Emcor">Emcor</a>
</td>
<td>ENPH
</td>
<td><a href="/wiki/Enphase_Energy" title="Enphase Energy">Enphase Energy</a>
</td>
<td>Market capitalization change.<sup id="cite_ref-sp20250905_4-0" class="reference"><a href="#cite_note-sp20250905-4"><span class="cite-bracket">[</span>4<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>September 22, 2025
</td>
<td>HOOD
</td>
<td><a href="/wiki/Robinhood_Markets" title="Robinhood Markets">Robinhood Markets</a>
</td>
<td>CZR
</td>
<td><a href="/wiki/Caesars_Entertainment" title="Caesars Entertainment">Caesars Entertainment</a>
</td>
<td>Market capitalization change.<sup id="cite_ref-sp20250905_4-1" class="reference"><a href="#cite_note-sp20250905-4"><span class="cite-bracket">[</span>4<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>September 22, 2025
</td>
<td>APP
</td>
<td><a href="/wiki/AppLovin" title="AppLovin">AppLovin</a>
</td>
<td>MKTX
</td>
<td><a href="/wiki/MarketAxess" title="MarketAxess">MarketAxess</a>
</td>
<td>Market capitalization change.<sup id="cite_ref-sp20250905_4-2" class="reference"><a href="#cite_note-sp20250905-4"><span class="cite-bracket">[</span>4<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>August 28, 2025</td>
<td>IBKR</td>
<td><a href="/wiki/Interactive_Brokers" title="Interactive Brokers">Interactive Brokers</a></td>
<td>WBA</td>
<td><a href="/wiki/Walgreens_Boots_Alliance" title="Walgreens Boots Alliance">Walgreens Boots Alliance</a></td>
<td><a href="/wiki/Sycamore_Partners" title="Sycamore Partners">Sycamore Partners</a> acquired Walgreen Boots Alliance.<sup id="cite_ref-5" class="reference"><a href="#cite_note-5"><span class="cite-bracket">[</span>5<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>July 23, 2025</td>
<td>XYZ</td>
<td><a href="/wiki/Block,_Inc." title="Block, Inc.">Block, Inc.</a></td>
<td>HES</td>
<td><a href="/wiki/Hess_Corporation" title="Hess Corporation">Hess Corporation</a></td>
<td>S&amp;P 500 and S&amp;P 100 constituent Chevron Corp. acquired <a href="/wiki/Hess_Corporation" title="Hess Corporation">Hess Corporation</a><sup id="cite_ref-6" class="reference"><a href="#cite_note-6"><span class="cite-bracket">[</span>6<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>July 18, 2025</td>
<td>TTD</td>
<td><a href="/wiki/The_Trade_Desk" title="The Trade Desk">Trade Desk (The)</a></td>
<td>ANSS</td>
<td><a href="/wiki/Ansys" title="Ansys">Ansys</a></td>
<td>S&amp;P 500 constituent Synopsys Inc. acquired Ansys.<sup id="cite_ref-7" class="reference"><a href="#cite_note-7"><span class="cite-bracket">[</span>7<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>July 9, 2025</td>
<td>DDOG</td>
<td><a href="/wiki/Datadog" title="Datadog">Datadog</a></td>
<td>JNPR</td>
<td><a href="/wiki/Juniper_Networks" title="Juniper Networks">Juniper Networks</a></td>
<td>S&amp;P 500 constituent Hewlett Packard Enterprise Co. acquired Juniper Networks.<sup id="cite_ref-8" class="reference"><a href="#cite_note-8"><span class="cite-bracket">[</span>8<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>May 19, 2025</td>
<td>COIN</td>
<td><a href="/wiki/Coinbase" title="Coinbase">Coinbase</a></td>
<td>DFS</td>
<td><a href="/wiki/Discover_Financial" title="Discover Financial">Discover Financial</a></td>
<td>S&amp;P 500 constituent Capital One Financial Corp. acquired Discover Financial Services.<sup id="cite_ref-9" class="reference"><a href="#cite_note-9"><span class="cite-bracket">[</span>9<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>March 24, 2025</td>
<td>DASH</td>
<td><a href="/wiki/DoorDash" title="DoorDash">DoorDash</a></td>
<td>BWA</td>
<td><a href="/wiki/BorgWarner" title="BorgWarner">BorgWarner</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20250307_10-0" class="reference"><a href="#cite_note-sp20250307-10"><span class="cite-bracket">[</span>10<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>March 24, 2025</td>
<td>TKO</td>
<td><a href="/wiki/TKO_Group_Holdings" title="TKO Group Holdings">TKO Group Holdings</a></td>
<td>TFX</td>
<td><a href="/wiki/Teleflex" title="Teleflex">Teleflex</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20250307_10-1" class="reference"><a href="#cite_note-sp20250307-10"><span class="cite-bracket">[</span>10<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>March 24, 2025</td>
<td>WSM</td>
<td><a href="/wiki/Williams-Sonoma,_Inc." title="Williams-Sonoma, Inc.">Williams-Sonoma, Inc.</a></td>
<td>CE</td>
<td><a href="/wiki/Celanese" title="Celanese">Celanese</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20250307_10-2" class="reference"><a href="#cite_note-sp20250307-10"><span class="cite-bracket">[</span>10<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>March 24, 2025</td>
<td>EXE</td>
<td><a href="/wiki/Expand_Energy" title="Expand Energy">Expand Energy</a></td>
<td>FMC</td>
<td><a href="/wiki/FMC_Corporation" title="FMC Corporation">FMC Corporation</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20250307_10-3" class="reference"><a href="#cite_note-sp20250307-10"><span class="cite-bracket">[</span>10<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>December 23, 2024</td>
<td>APO</td>
<td><a href="/wiki/Apollo_Global_Management" title="Apollo Global Management">Apollo Global Management</a></td>
<td>QRVO</td>
<td><a href="/wiki/Qorvo" title="Qorvo">Qorvo</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20241206_11-0" class="reference"><a href="#cite_note-sp20241206-11"><span class="cite-bracket">[</span>11<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>December 23, 2024</td>
<td>WDAY</td>
<td><a href="/wiki/Workday,_Inc." title="Workday, Inc.">Workday, Inc.</a></td>
<td>AMTM</td>
<td><a href="/wiki/Amentum_(company)" title="Amentum (company)">Amentum</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20241206_11-1" class="reference"><a href="#cite_note-sp20241206-11"><span class="cite-bracket">[</span>11<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>December 23, 2024</td>
<td>LII</td>
<td><a href="/wiki/Lennox_International" title="Lennox International">Lennox International</a></td>
<td>CTLT</td>
<td><a href="/wiki/Catalent" title="Catalent">Catalent</a></td>
<td><a href="/wiki/Novo_Holdings_A/S" title="Novo Holdings A/S">Novo Holdings A/S</a> acquired Catalent.<sup id="cite_ref-12" class="reference"><a href="#cite_note-12"><span class="cite-bracket">[</span>12<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>November 26, 2024</td>
<td>TPL</td>
<td><a href="/wiki/Texas_Pacific_Land_Corporation" title="Texas Pacific Land Corporation">Texas Pacific Land Corporation</a></td>
<td>MRO</td>
<td><a href="/wiki/Marathon_Oil" title="Marathon Oil">Marathon Oil</a></td>
<td>S&amp;P 500 &amp; 100 constituent ConocoPhillips acquired Marathon Oil.<sup id="cite_ref-13" class="reference"><a href="#cite_note-13"><span class="cite-bracket">[</span>13<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>October 1, 2024</td>
<td></td>
<td></td>
<td>BBWI</td>
<td><a href="/wiki/Bath_%26_Body_Works,_Inc." title="Bath &amp; Body Works, Inc.">Bath &amp; Body Works, Inc.</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20240924_14-0" class="reference"><a href="#cite_note-sp20240924-14"><span class="cite-bracket">[</span>14<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>September 30, 2024</td>
<td>AMTM</td>
<td><a href="/wiki/Amentum_(company)" title="Amentum (company)">Amentum</a></td>
<td></td>
<td></td>
<td>S&amp;P 500 constituent <a href="/wiki/Jacobs_Solutions" title="Jacobs Solutions">Jacobs Solutions</a> spun off its Critical Mission Solutions and Cyber Intelligence business, which merged with private Amentum to create newly publicly traded Amentum Holdings.<sup id="cite_ref-sp20240924_14-1" class="reference"><a href="#cite_note-sp20240924-14"><span class="cite-bracket">[</span>14<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>September 23, 2024</td>
<td>PLTR</td>
<td><a href="/wiki/Palantir_Technologies" title="Palantir Technologies">Palantir Technologies</a></td>
<td>AAL</td>
<td><a href="/wiki/American_Airlines_Group" title="American Airlines Group">American Airlines Group</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20240906_15-0" class="reference"><a href="#cite_note-sp20240906-15"><span class="cite-bracket">[</span>15<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>September 23, 2024</td>
<td>DELL</td>
<td><a href="/wiki/Dell_Technologies" title="Dell Technologies">Dell Technologies</a></td>
<td>ETSY</td>
<td><a href="/wiki/Etsy" title="Etsy">Etsy</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20240906_15-1" class="reference"><a href="#cite_note-sp20240906-15"><span class="cite-bracket">[</span>15<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>September 23, 2024</td>
<td>ERIE</td>
<td><a href="/wiki/Erie_Insurance_Group" title="Erie Insurance Group">Erie Indemnity</a></td>
<td>BIO</td>
<td><a href="/wiki/Bio-Rad_Laboratories" title="Bio-Rad Laboratories">Bio-Rad Laboratories</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20240906_15-2" class="reference"><a href="#cite_note-sp20240906-15"><span class="cite-bracket">[</span>15<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>June 24, 2024</td>
<td>KKR</td>
<td><a href="/wiki/KKR_(company)" class="mw-redirect" title="KKR (company)">KKR</a></td>
<td>RHI</td>
<td><a href="/wiki/Robert_Half" title="Robert Half">Robert Half</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20240607_16-0" class="reference"><a href="#cite_note-sp20240607-16"><span class="cite-bracket">[</span>16<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>June 24, 2024</td>
<td>CRWD</td>
<td><a href="/wiki/CrowdStrike" title="CrowdStrike">CrowdStrike</a></td>
<td>CMA</td>
<td><a href="/wiki/Comerica" title="Comerica">Comerica</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20240607_16-1" class="reference"><a href="#cite_note-sp20240607-16"><span class="cite-bracket">[</span>16<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>June 24, 2024</td>
<td>GDDY</td>
<td><a href="/wiki/GoDaddy" title="GoDaddy">GoDaddy</a></td>
<td>ILMN</td>
<td><a href="/wiki/Illumina,_Inc." title="Illumina, Inc.">Illumina, Inc.</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20240607_16-2" class="reference"><a href="#cite_note-sp20240607-16"><span class="cite-bracket">[</span>16<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>May 8, 2024</td>
<td>VST</td>
<td><a href="/wiki/Vistra_Corp" class="mw-redirect" title="Vistra Corp">Vistra</a></td>
<td>PXD</td>
<td><a href="/wiki/Pioneer_Natural_Resources" title="Pioneer Natural Resources">Pioneer Natural Resources</a></td>
<td>S&amp;P 500 and S&amp;P 100 constituent <a href="/wiki/ExxonMobil" title="ExxonMobil">ExxonMobil</a> acquired Pioneer Natural Resources.<sup id="cite_ref-17" class="reference"><a href="#cite_note-17"><span class="cite-bracket">[</span>17<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>April 3, 2024</td>
<td></td>
<td></td>
<td>XRAY</td>
<td><a href="/wiki/Dentsply_Sirona" title="Dentsply Sirona">Dentsply Sirona</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20240327_18-0" class="reference"><a href="#cite_note-sp20240327-18"><span class="cite-bracket">[</span>18<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>April 3, 2024</td>
<td></td>
<td></td>
<td>VFC</td>
<td><a href="/wiki/VF_Corporation" title="VF Corporation">VF Corporation</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20240327_18-1" class="reference"><a href="#cite_note-sp20240327-18"><span class="cite-bracket">[</span>18<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>April 2, 2024
</td>
<td>GEV
</td>
<td><a href="/wiki/GE_Vernova" title="GE Vernova">GE Vernova</a>
</td>
<td>
</td>
<td>
</td>
<td>S&amp;P 500 and 100 constituent General Electric Corp. spun off GE Vernova.<sup id="cite_ref-sp20240327_18-2" class="reference"><a href="#cite_note-sp20240327-18"><span class="cite-bracket">[</span>18<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>April 1, 2024
</td>
<td>SOLV
</td>
<td><a href="/wiki/Solventum" title="Solventum">Solventum</a>
</td>
<td>
</td>
<td>
</td>
<td>S&amp;P 500 and 100 constituent 3M Co. spun off Solventum.<sup id="cite_ref-sp20240327_18-3" class="reference"><a href="#cite_note-sp20240327-18"><span class="cite-bracket">[</span>18<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>March 18, 2024</td>
<td>SMCI</td>
<td><a href="/wiki/Supermicro" title="Supermicro">Supermicro</a></td>
<td>WHR</td>
<td><a href="/wiki/Whirlpool_Corporation" title="Whirlpool Corporation">Whirlpool Corporation</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20240301_19-0" class="reference"><a href="#cite_note-sp20240301-19"><span class="cite-bracket">[</span>19<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>March 18, 2024</td>
<td>DECK</td>
<td><a href="/wiki/Deckers_Brands" title="Deckers Brands">Deckers Brands</a></td>
<td>ZION</td>
<td><a href="/wiki/Zions_Bancorporation" title="Zions Bancorporation">Zions Bancorporation</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20240301_19-1" class="reference"><a href="#cite_note-sp20240301-19"><span class="cite-bracket">[</span>19<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>December 18, 2023</td>
<td>UBER</td>
<td><a href="/wiki/Uber" title="Uber">Uber</a></td>
<td>SEE</td>
<td><a href="/wiki/Sealed_Air" title="Sealed Air">Sealed Air</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20231201_20-0" class="reference"><a href="#cite_note-sp20231201-20"><span class="cite-bracket">[</span>20<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>December 18, 2023</td>
<td>JBL</td>
<td><a href="/wiki/Jabil" title="Jabil">Jabil</a></td>
<td>ALK</td>
<td><a href="/wiki/Alaska_Air_Group" title="Alaska Air Group">Alaska Air Group</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20231201_20-1" class="reference"><a href="#cite_note-sp20231201-20"><span class="cite-bracket">[</span>20<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>December 18, 2023</td>
<td>BLDR</td>
<td><a href="/wiki/Builders_FirstSource" title="Builders FirstSource">Builders FirstSource</a></td>
<td>SEDG</td>
<td><a href="/wiki/SolarEdge" title="SolarEdge">SolarEdge</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20231201_20-2" class="reference"><a href="#cite_note-sp20231201-20"><span class="cite-bracket">[</span>20<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>October 18, 2023</td>
<td>HUBB</td>
<td><a href="/wiki/Hubbell_Incorporated" title="Hubbell Incorporated">Hubbell</a></td>
<td>OGN</td>
<td><a href="/wiki/Organon_%26_Co." title="Organon &amp; Co.">Organon &amp; Co.</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20231013_21-0" class="reference"><a href="#cite_note-sp20231013-21"><span class="cite-bracket">[</span>21<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>October 18, 2023</td>
<td>LULU</td>
<td><a href="/wiki/Lululemon" title="Lululemon">Lululemon Athletica</a></td>
<td>ATVI</td>
<td><a href="/wiki/Activision_Blizzard" title="Activision Blizzard">Activision Blizzard</a></td>
<td>S&amp;P 500 and S&amp;P 100 constituent <a href="/wiki/Acquisition_of_Activision_Blizzard_by_Microsoft" title="Acquisition of Activision Blizzard by Microsoft">Microsoft acquired Activision Blizzard</a>.<sup id="cite_ref-sp20231013_21-1" class="reference"><a href="#cite_note-sp20231013-21"><span class="cite-bracket">[</span>21<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>October 3, 2023</td>
<td></td>
<td></td>
<td>DXC</td>
<td><a href="/wiki/DXC_Technology" title="DXC Technology">DXC Technology</a></td>
<td>Market capitalization change.<sup id="cite_ref-Sept28_22-0" class="reference"><a href="#cite_note-Sept28-22"><span class="cite-bracket">[</span>22<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>October 2, 2023</td>
<td>VLTO</td>
<td><a href="/wiki/Danaher_Corporation" title="Danaher Corporation">Veralto</a></td>
<td></td>
<td></td>
<td>S&amp;P 500 and S&amp;P 100 constituent Danaher Corporation spun off Veralto.<sup id="cite_ref-Sept28_22-1" class="reference"><a href="#cite_note-Sept28-22"><span class="cite-bracket">[</span>22<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>September 18, 2023
</td>
<td>BX
</td>
<td><a href="/wiki/Blackstone_Inc" class="mw-redirect" title="Blackstone Inc">Blackstone</a>
</td>
<td>LNC
</td>
<td><a href="/wiki/Lincoln_National_Corporation" title="Lincoln National Corporation">Lincoln National Corporation</a>
</td>
<td>Market capitalization change.<sup id="cite_ref-:1_23-0" class="reference"><a href="#cite_note-:1-23"><span class="cite-bracket">[</span>23<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>September 18, 2023
</td>
<td>ABNB
</td>
<td><a href="/wiki/Airbnb" title="Airbnb">Airbnb</a>
</td>
<td>NWL
</td>
<td><a href="/wiki/Newell_Brands" title="Newell Brands">Newell Brands</a>
</td>
<td>Market capitalization change.<sup id="cite_ref-:1_23-1" class="reference"><a href="#cite_note-:1-23"><span class="cite-bracket">[</span>23<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>August 25, 2023</td>
<td>KVUE</td>
<td><a href="/wiki/Kenvue" title="Kenvue">Kenvue</a></td>
<td>AAP</td>
<td><a href="/wiki/Advance_Auto_Parts" title="Advance Auto Parts">Advance Auto Parts</a></td>
<td>S&amp;P 500 and S&amp;P 100 constituent Johnson &amp; Johnson offered to exchange the shares of Kenvue held for shares of Johnson &amp; Johnson in a split-off exchange offer.<sup id="cite_ref-24" class="reference"><a href="#cite_note-24"><span class="cite-bracket">[</span>24<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>June 20, 2023</td>
<td>PANW</td>
<td><a href="/wiki/Palo_Alto_Networks" title="Palo Alto Networks">Palo Alto Networks</a></td>
<td>DISH</td>
<td><a href="/wiki/Dish_Network" title="Dish Network">Dish Network</a></td>
<td>Market capitalization change.<sup id="cite_ref-25" class="reference"><a href="#cite_note-25"><span class="cite-bracket">[</span>25<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>May 4, 2023</td>
<td>AXON</td>
<td><a href="/wiki/Axon_Enterprise" title="Axon Enterprise">Axon Enterprise</a></td>
<td>FRC</td>
<td><a href="/wiki/First_Republic_Bank" title="First Republic Bank">First Republic Bank</a></td>
<td>The <a href="/wiki/Federal_Deposit_Insurance_Corporation" title="Federal Deposit Insurance Corporation">Federal Deposit Insurance Corporation</a> (FDIC) placed First Republic Bank into FDIC Receivership.<sup id="cite_ref-26" class="reference"><a href="#cite_note-26"><span class="cite-bracket">[</span>26<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>March 20, 2023</td>
<td>FICO</td>
<td><a href="/wiki/FICO" title="FICO">Fair Isaac</a></td>
<td>LUMN</td>
<td><a href="/wiki/Lumen_Technologies" title="Lumen Technologies">Lumen Technologies</a></td>
<td>Market capitalization change.<sup id="cite_ref-27" class="reference"><a href="#cite_note-27"><span class="cite-bracket">[</span>27<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>March 15, 2023</td>
<td>BG</td>
<td><a href="/wiki/Bunge_Global" title="Bunge Global">Bunge Global</a></td>
<td>SBNY</td>
<td><a href="/wiki/Signature_Bank" title="Signature Bank">Signature Bank</a></td>
<td>The FDIC placed Signature Bank into FDIC Receivership.<sup id="cite_ref-28" class="reference"><a href="#cite_note-28"><span class="cite-bracket">[</span>28<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>March 15, 2023</td>
<td>PODD</td>
<td><a href="/wiki/Insulet" class="mw-redirect" title="Insulet">Insulet</a></td>
<td>SIVB</td>
<td><a href="/wiki/SVB_Financial_Group" title="SVB Financial Group">SVB Financial Group</a></td>
<td>The FDIC placed SVB's main subsidiary, <a href="/wiki/Silicon_Valley_Bank" title="Silicon Valley Bank">Silicon Valley Bank</a>, into receivership.<sup id="cite_ref-29" class="reference"><a href="#cite_note-29"><span class="cite-bracket">[</span>29<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>January 5, 2023</td>
<td></td>
<td></td>
<td>VNO</td>
<td><a href="/wiki/Vornado_Realty_Trust" title="Vornado Realty Trust">Vornado Realty Trust</a></td>
<td>Market capitalization change.<sup id="cite_ref-30" class="reference"><a href="#cite_note-30"><span class="cite-bracket">[</span>30<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>January 4, 2023</td>
<td>GEHC</td>
<td><a href="/wiki/GE_HealthCare" title="GE HealthCare">GE HealthCare</a></td>
<td></td>
<td></td>
<td>S&amp;P 500 constituent General Electric spun off GE HealthCare.<sup id="cite_ref-31" class="reference"><a href="#cite_note-31"><span class="cite-bracket">[</span>31<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>December 22, 2022</td>
<td>STLD</td>
<td><a href="/wiki/Steel_Dynamics" title="Steel Dynamics">Steel Dynamics</a></td>
<td>ABMD</td>
<td><a href="/wiki/Abiomed" title="Abiomed">Abiomed</a></td>
<td>S&amp;P 500 constituent Johnson &amp; Johnson acquired Abiomed.<sup id="cite_ref-32" class="reference"><a href="#cite_note-32"><span class="cite-bracket">[</span>32<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>December 19, 2022</td>
<td>FSLR</td>
<td><a href="/wiki/First_Solar" title="First Solar">First Solar</a></td>
<td>FBHS</td>
<td><a href="/wiki/Fortune_Brands_Home_%26_Security" class="mw-redirect" title="Fortune Brands Home &amp; Security">Fortune Brands Home &amp; Security</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20221212_33-0" class="reference"><a href="#cite_note-sp20221212-33"><span class="cite-bracket">[</span>33<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>December 19, 2022</td>
<td></td>
<td></td>
<td>MBC</td>
<td><a href="/wiki/Fortune_Brands_Home_%26_Security" class="mw-redirect" title="Fortune Brands Home &amp; Security">MasterBrand</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20221212_33-1" class="reference"><a href="#cite_note-sp20221212-33"><span class="cite-bracket">[</span>33<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>December 15, 2022</td>
<td>MBC</td>
<td><a href="/wiki/Fortune_Brands_Home_%26_Security" class="mw-redirect" title="Fortune Brands Home &amp; Security">MasterBrand</a></td>
<td></td>
<td></td>
<td>S&amp;P 500 constituent Fortune Brands Home &amp; Security spun off MasterBrand.<sup id="cite_ref-sp20221212_33-2" class="reference"><a href="#cite_note-sp20221212-33"><span class="cite-bracket">[</span>33<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>November 1, 2022</td>
<td>ACGL</td>
<td><a href="/wiki/Arch_Capital_Group" title="Arch Capital Group">Arch Capital Group</a></td>
<td>TWTR</td>
<td><a href="/wiki/Twitter,_Inc." title="Twitter, Inc.">Twitter</a></td>
<td><a href="/wiki/Elon_Musk" title="Elon Musk">Elon Musk</a> acquired Twitter.<sup id="cite_ref-34" class="reference"><a href="#cite_note-34"><span class="cite-bracket">[</span>34<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>October 12, 2022</td>
<td>TRGP</td>
<td><a href="/wiki/Targa_Resources" title="Targa Resources">Targa Resources</a></td>
<td>NLSN</td>
<td><a href="/wiki/Nielsen_Holdings" title="Nielsen Holdings">Nielsen Holdings</a></td>
<td><a href="/wiki/Elliott_Investment_Management" title="Elliott Investment Management">Elliot Management Corp</a> acquired Nielsen Holdings.<sup id="cite_ref-35" class="reference"><a href="#cite_note-35"><span class="cite-bracket">[</span>35<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>October 3, 2022</td>
<td>PCG</td>
<td><a href="/wiki/PG%26E" class="mw-redirect" title="PG&amp;E">PG&amp;E</a></td>
<td>CTXS</td>
<td><a href="/wiki/Citrix_Systems" title="Citrix Systems">Citrix Systems</a></td>
<td><a href="/wiki/Vista_Equity_Partners" title="Vista Equity Partners">Vista Equity Partners</a> acquired Citrix Systems.<sup id="cite_ref-sp20220923_36-0" class="reference"><a href="#cite_note-sp20220923-36"><span class="cite-bracket">[</span>36<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>October 3, 2022</td>
<td>EQT</td>
<td><a href="/wiki/EQT_Corporation" title="EQT Corporation">EQT Corporation</a></td>
<td>DRE</td>
<td><a href="/wiki/Duke_Realty" title="Duke Realty">Duke Realty</a></td>
<td>S&amp;P 500 constituent Prologis Inc. acquired Duke Realty.<sup id="cite_ref-sp20220923_36-1" class="reference"><a href="#cite_note-sp20220923-36"><span class="cite-bracket">[</span>36<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>September 19, 2022</td>
<td>CSGP</td>
<td><a href="/wiki/CoStar_Group" title="CoStar Group">CoStar Group</a></td>
<td>PVH</td>
<td><a href="/wiki/PVH_(company)" class="mw-redirect" title="PVH (company)">PVH</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20220902_37-0" class="reference"><a href="#cite_note-sp20220902-37"><span class="cite-bracket">[</span>37<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>September 19, 2022</td>
<td>INVH</td>
<td><a href="/wiki/Invitation_Homes" title="Invitation Homes">Invitation Homes</a></td>
<td>PENN</td>
<td><a href="/wiki/Penn_Entertainment" title="Penn Entertainment">Penn Entertainment</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20220902_37-1" class="reference"><a href="#cite_note-sp20220902-37"><span class="cite-bracket">[</span>37<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>June 21, 2022</td>
<td></td>
<td></td>
<td>UA</td>
<td><a href="/wiki/Under_Armour" title="Under Armour">Under Armour</a> (Class C)</td>
<td>Market capitalization change.<sup id="cite_ref-sp20220603_38-0" class="reference"><a href="#cite_note-sp20220603-38"><span class="cite-bracket">[</span>38<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>June 21, 2022</td>
<td>KDP</td>
<td><a href="/wiki/Keurig_Dr_Pepper" title="Keurig Dr Pepper">Keurig Dr Pepper</a></td>
<td>UAA</td>
<td><a href="/wiki/Under_Armour" title="Under Armour">Under Armour</a> (Class A)</td>
<td>Market capitalization change.<sup id="cite_ref-sp20220603_38-1" class="reference"><a href="#cite_note-sp20220603-38"><span class="cite-bracket">[</span>38<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>June 21, 2022</td>
<td>ON</td>
<td><a href="/wiki/ON_Semiconductor" class="mw-redirect" title="ON Semiconductor">ON Semiconductor</a></td>
<td>IPGP</td>
<td><a href="/wiki/IPG_Photonics" title="IPG Photonics">IPG Photonics</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20220603_38-2" class="reference"><a href="#cite_note-sp20220603-38"><span class="cite-bracket">[</span>38<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>June 8, 2022</td>
<td>VICI</td>
<td><a href="/wiki/Vici_Properties" title="Vici Properties">Vici Properties</a></td>
<td>CERN</td>
<td><a href="/wiki/Cerner" class="mw-redirect" title="Cerner">Cerner</a></td>
<td>S&amp;P 500 constituent Oracle Corp. acquired Cerner.<sup id="cite_ref-sp20220603_38-3" class="reference"><a href="#cite_note-sp20220603-38"><span class="cite-bracket">[</span>38<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>April 11, 2022</td>
<td>WBD</td>
<td><a href="/wiki/Warner_Bros._Discovery" title="Warner Bros. Discovery">Warner Bros. Discovery</a></td>
<td>DISCA</td>
<td><a href="/wiki/Discovery,_Inc." title="Discovery, Inc.">Discovery, Inc.</a></td>
<td>WarnerMedia and Discovery merge to create <a href="/wiki/Warner_Bros._Discovery" title="Warner Bros. Discovery">Warner Bros. Discovery</a>.<sup id="cite_ref-sp20220411_39-0" class="reference"><a href="#cite_note-sp20220411-39"><span class="cite-bracket">[</span>39<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>April 11, 2022</td>
<td></td>
<td></td>
<td>DISCK</td>
<td><a href="/wiki/Discovery,_Inc." title="Discovery, Inc.">Discovery, Inc.</a></td>
<td>WarnerMedia and Discovery merge to create <a href="/wiki/Warner_Bros._Discovery" title="Warner Bros. Discovery">Warner Bros. Discovery</a>.<sup id="cite_ref-sp20220411_39-1" class="reference"><a href="#cite_note-sp20220411-39"><span class="cite-bracket">[</span>39<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>April 4, 2022</td>
<td>CPT</td>
<td><a href="/wiki/Camden_Property_Trust" title="Camden Property Trust">Camden Property Trust</a></td>
<td>PBCT</td>
<td><a href="/wiki/People%27s_United_Financial" title="People's United Financial">People's United Financial</a></td>
<td>S&amp;P 500 constituent M&amp;T Bank Corp. acquired People's United Financial.<sup id="cite_ref-40" class="reference"><a href="#cite_note-40"><span class="cite-bracket">[</span>40<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>March 2, 2022</td>
<td>MOH</td>
<td><a href="/wiki/Molina_Healthcare" title="Molina Healthcare">Molina Healthcare</a></td>
<td>INFO</td>
<td><a href="/wiki/IHS_Markit" class="mw-redirect" title="IHS Markit">IHS Markit</a></td>
<td>S&amp;P 500 constituent S&amp;P Global Inc. acquired IHS Markit.<sup id="cite_ref-41" class="reference"><a href="#cite_note-41"><span class="cite-bracket">[</span>41<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>February 15, 2022</td>
<td>NDSN</td>
<td><a href="/wiki/Nordson_Corporation" title="Nordson Corporation">Nordson Corporation</a></td>
<td>XLNX</td>
<td><a href="/wiki/Xilinx" title="Xilinx">Xilinx</a></td>
<td>S&amp;P 500 constituent Advanced Micro Devices acquired Xilinx.<sup id="cite_ref-42" class="reference"><a href="#cite_note-42"><span class="cite-bracket">[</span>42<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>February 3, 2022</td>
<td></td>
<td></td>
<td>GPS</td>
<td><a href="/wiki/Gap_Inc" class="mw-redirect" title="Gap Inc">Gap</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20220126_43-0" class="reference"><a href="#cite_note-sp20220126-43"><span class="cite-bracket">[</span>43<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>February 2, 2022</td>
<td>CEG</td>
<td><a href="/wiki/Constellation_Energy" title="Constellation Energy">Constellation Energy</a></td>
<td></td>
<td></td>
<td>S&amp;P 500 and 100 constituent Exelon Corp. spun off Constellation Energy.<sup id="cite_ref-sp20220126_43-1" class="reference"><a href="#cite_note-sp20220126-43"><span class="cite-bracket">[</span>43<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>December 20, 2021</td>
<td>SBNY</td>
<td><a href="/wiki/Signature_Bank" title="Signature Bank">Signature Bank</a></td>
<td>LEG</td>
<td><a href="/wiki/Leggett_%26_Platt" title="Leggett &amp; Platt">Leggett &amp; Platt</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20211203_44-0" class="reference"><a href="#cite_note-sp20211203-44"><span class="cite-bracket">[</span>44<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>December 20, 2021</td>
<td>SEDG</td>
<td><a href="/wiki/SolarEdge" title="SolarEdge">SolarEdge</a></td>
<td>HBI</td>
<td><a href="/wiki/Hanesbrands" title="Hanesbrands">Hanesbrands</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20211203_44-1" class="reference"><a href="#cite_note-sp20211203-44"><span class="cite-bracket">[</span>44<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>December 20, 2021</td>
<td>FDS</td>
<td><a href="/wiki/FactSet" title="FactSet">FactSet</a></td>
<td>WU</td>
<td><a href="/wiki/Western_Union" title="Western Union">Western Union</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20211203_44-2" class="reference"><a href="#cite_note-sp20211203-44"><span class="cite-bracket">[</span>44<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>December 14, 2021</td>
<td>EPAM</td>
<td><a href="/wiki/EPAM_Systems" title="EPAM Systems">EPAM Systems</a></td>
<td>KSU</td>
<td><a href="/wiki/Kansas_City_Southern_(company)" title="Kansas City Southern (company)">Kansas City Southern</a></td>
<td><a href="/wiki/Canadian_Pacific" class="mw-redirect" title="Canadian Pacific">Canadian Pacific</a> acquired Kansas City Southern.<sup id="cite_ref-45" class="reference"><a href="#cite_note-45"><span class="cite-bracket">[</span>45<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>September 20, 2021</td>
<td>MTCH</td>
<td><a href="/wiki/Match_Group" title="Match Group">Match Group</a></td>
<td>PRGO</td>
<td><a href="/wiki/Perrigo" title="Perrigo">Perrigo</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20210903_46-0" class="reference"><a href="#cite_note-sp20210903-46"><span class="cite-bracket">[</span>46<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>September 20, 2021</td>
<td>CDAY</td>
<td><a href="/wiki/Ceridian" class="mw-redirect" title="Ceridian">Ceridian</a></td>
<td>UNM</td>
<td><a href="/wiki/Unum" title="Unum">Unum</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20210903_46-1" class="reference"><a href="#cite_note-sp20210903-46"><span class="cite-bracket">[</span>46<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>September 20, 2021</td>
<td>BRO</td>
<td><a href="/wiki/Brown_%26_Brown" title="Brown &amp; Brown">Brown &amp; Brown</a></td>
<td>NOV</td>
<td><a href="/wiki/NOV_Inc." title="NOV Inc.">Nov</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20210903_46-2" class="reference"><a href="#cite_note-sp20210903-46"><span class="cite-bracket">[</span>46<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>August 30, 2021</td>
<td>TECH</td>
<td><a href="/wiki/Bio-Techne" title="Bio-Techne">Bio-Techne</a></td>
<td>MXIM</td>
<td><a href="/wiki/Maxim_Integrated" title="Maxim Integrated">Maxim Integrated</a></td>
<td>S&amp;P 500 constituent Analog Devices acquired Maxim Integrated Products.<sup id="cite_ref-47" class="reference"><a href="#cite_note-47"><span class="cite-bracket">[</span>47<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>July 21, 2021</td>
<td>MRNA</td>
<td><a href="/wiki/Moderna" title="Moderna">Moderna</a></td>
<td>ALXN</td>
<td><a href="/wiki/Alexion_Pharmaceuticals" title="Alexion Pharmaceuticals">Alexion Pharmaceuticals</a></td>
<td><a href="/wiki/AstraZeneca" title="AstraZeneca">AstraZeneca</a> acquired Alexion Pharmaceuticals.<sup id="cite_ref-48" class="reference"><a href="#cite_note-48"><span class="cite-bracket">[</span>48<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>June 4, 2021</td>
<td></td>
<td></td>
<td>HFC</td>
<td><a href="/wiki/HollyFrontier" class="mw-redirect" title="HollyFrontier">HollyFrontier</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20210527_49-0" class="reference"><a href="#cite_note-sp20210527-49"><span class="cite-bracket">[</span>49<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>June 3, 2021</td>
<td>OGN</td>
<td><a href="/wiki/Organon_%26_Co." title="Organon &amp; Co.">Organon &amp; Co.</a></td>
<td></td>
<td></td>
<td>S&amp;P 500/100 constituent Merck &amp; Co. spun off Organon.<sup id="cite_ref-sp20210527_49-1" class="reference"><a href="#cite_note-sp20210527-49"><span class="cite-bracket">[</span>49<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>May 14, 2021</td>
<td>CRL</td>
<td><a href="/wiki/Charles_River_Laboratories" title="Charles River Laboratories">Charles River Laboratories</a></td>
<td>FLIR</td>
<td><a href="/wiki/FLIR_Systems" class="mw-redirect" title="FLIR Systems">FLIR Systems</a></td>
<td>S&amp;P 500 constituent <a href="/wiki/Teledyne_Technologies" title="Teledyne Technologies">Teledyne Technologies</a> acquired FLIR Systems.<sup id="cite_ref-50" class="reference"><a href="#cite_note-50"><span class="cite-bracket">[</span>50<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>April 20, 2021</td>
<td>PTC</td>
<td><a href="/wiki/PTC_(software_company)" class="mw-redirect" title="PTC (software company)">PTC</a></td>
<td>VAR</td>
<td><a href="/wiki/Varian_Medical_Systems" title="Varian Medical Systems">Varian Medical Systems</a></td>
<td><a href="/wiki/Siemens_Healthineers" title="Siemens Healthineers">Siemens Healthineers</a> acquired Varian Medical Systems.<sup id="cite_ref-51" class="reference"><a href="#cite_note-51"><span class="cite-bracket">[</span>51<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>March 22, 2021</td>
<td>NXPI</td>
<td><a href="/wiki/NXP" class="mw-redirect" title="NXP">NXP</a></td>
<td>FLS</td>
<td><a href="/wiki/Flowserve" title="Flowserve">Flowserve</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20210312_52-0" class="reference"><a href="#cite_note-sp20210312-52"><span class="cite-bracket">[</span>52<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>March 22, 2021</td>
<td>PENN</td>
<td><a href="/wiki/Penn_National_Gaming" class="mw-redirect" title="Penn National Gaming">Penn National Gaming</a></td>
<td>SLG</td>
<td><a href="/wiki/SL_Green_Realty" title="SL Green Realty">SL Green Realty</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20210312_52-1" class="reference"><a href="#cite_note-sp20210312-52"><span class="cite-bracket">[</span>52<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>March 22, 2021</td>
<td>GNRC</td>
<td><a href="/wiki/Generac_Holdings" class="mw-redirect" title="Generac Holdings">Generac Holdings</a></td>
<td>XRX</td>
<td><a href="/wiki/Xerox" title="Xerox">Xerox</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20210312_52-2" class="reference"><a href="#cite_note-sp20210312-52"><span class="cite-bracket">[</span>52<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>March 22, 2021</td>
<td>CZR</td>
<td><a href="/wiki/Caesars_Entertainment_(2020)" class="mw-redirect" title="Caesars Entertainment (2020)">Caesars Entertainment</a></td>
<td>VNT</td>
<td><a href="/wiki/Vontier" title="Vontier">Vontier</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20210312_52-3" class="reference"><a href="#cite_note-sp20210312-52"><span class="cite-bracket">[</span>52<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>February 12, 2021</td>
<td>MPWR</td>
<td><a href="/wiki/Monolithic_Power_Systems" title="Monolithic Power Systems">Monolithic Power Systems</a></td>
<td>FTI</td>
<td><a href="/wiki/TechnipFMC" title="TechnipFMC">TechnipFMC</a></td>
<td>TechnipFMC was removed from the S&amp;P 500 in anticipation of its announced spin-off of Technip Energies.<sup id="cite_ref-53" class="reference"><a href="#cite_note-53"><span class="cite-bracket">[</span>53<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>January 21, 2021</td>
<td>TRMB</td>
<td><a href="/wiki/Trimble_Inc" class="mw-redirect" title="Trimble Inc">Trimble</a></td>
<td>CXO</td>
<td><a href="/wiki/Concho_Resources" title="Concho Resources">Concho Resources</a></td>
<td>S&amp;P 500/100 constituent <a href="/wiki/ConocoPhillips" title="ConocoPhillips">ConocoPhillips</a> acquired Concho Resources.<sup id="cite_ref-54" class="reference"><a href="#cite_note-54"><span class="cite-bracket">[</span>54<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>January 7, 2021</td>
<td>ENPH</td>
<td><a href="/wiki/Enphase_Energy" title="Enphase Energy">Enphase Energy</a></td>
<td>TIF</td>
<td><a href="/wiki/Tiffany_%26_Co" class="mw-redirect" title="Tiffany &amp; Co">Tiffany &amp; Co</a></td>
<td><a href="/wiki/LVMH" title="LVMH">LVMH</a> Moet Hennessy-Louis Vuitton SE acquired Tiffany &amp; Co.<sup id="cite_ref-55" class="reference"><a href="#cite_note-55"><span class="cite-bracket">[</span>55<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>December 21, 2020</td>
<td>TSLA</td>
<td><a href="/wiki/Tesla_Inc" class="mw-redirect" title="Tesla Inc">Tesla</a></td>
<td>AIV</td>
<td><a href="/wiki/Aimco" title="Aimco">Apartment Investment &amp; Management</a></td>
<td>Apartment Investment and Management (Aimco) spun off Apartment Income REIT.<sup id="cite_ref-56" class="reference"><a href="#cite_note-56"><span class="cite-bracket">[</span>56<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>October 12, 2020</td>
<td></td>
<td></td>
<td>NBL</td>
<td><a href="/wiki/Noble_Energy" title="Noble Energy">Noble Energy</a></td>
<td>Chevron acquired Noble Energy.<sup id="cite_ref-sp20201005_57-0" class="reference"><a href="#cite_note-sp20201005-57"><span class="cite-bracket">[</span>57<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>October 9, 2020</td>
<td>VNT</td>
<td><a href="/wiki/Vontier" title="Vontier">Vontier</a></td>
<td></td>
<td></td>
<td>S&amp;P 500 constituent <a href="/wiki/Fortive" title="Fortive">Fortive</a> spun off Vontier.<sup id="cite_ref-sp20201005_57-1" class="reference"><a href="#cite_note-sp20201005-57"><span class="cite-bracket">[</span>57<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>October 7, 2020</td>
<td>POOL</td>
<td><a href="/wiki/Pool_Corporation" title="Pool Corporation">Pool Corporation</a></td>
<td>ETFC</td>
<td><a href="/wiki/E-Trade" title="E-Trade">E-Trade</a></td>
<td>Morgan Stanley acquired E*Trade.<sup id="cite_ref-58" class="reference"><a href="#cite_note-58"><span class="cite-bracket">[</span>58<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>September 21, 2020</td>
<td>ETSY</td>
<td><a href="/wiki/Etsy" title="Etsy">Etsy</a></td>
<td>HRB</td>
<td><a href="/wiki/H%26R_Block" title="H&amp;R Block">H&amp;R Block</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20200904_59-0" class="reference"><a href="#cite_note-sp20200904-59"><span class="cite-bracket">[</span>59<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>September 21, 2020</td>
<td>TER</td>
<td><a href="/wiki/Teradyne" title="Teradyne">Teradyne</a></td>
<td>COTY</td>
<td><a href="/wiki/Coty" title="Coty">Coty</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20200904_59-1" class="reference"><a href="#cite_note-sp20200904-59"><span class="cite-bracket">[</span>59<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>September 21, 2020</td>
<td>CTLT</td>
<td><a href="/wiki/Catalent" title="Catalent">Catalent</a></td>
<td>KSS</td>
<td><a href="/wiki/Kohl%27s" title="Kohl's">Kohl's</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20200904_59-2" class="reference"><a href="#cite_note-sp20200904-59"><span class="cite-bracket">[</span>59<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>June 22, 2020</td>
<td>BIO</td>
<td><a href="/wiki/Bio-Rad_Laboratories" title="Bio-Rad Laboratories">Bio-Rad Laboratories</a></td>
<td>ADS</td>
<td><a href="/wiki/Alliance_Data_Systems" class="mw-redirect" title="Alliance Data Systems">Alliance Data Systems</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20200612_60-0" class="reference"><a href="#cite_note-sp20200612-60"><span class="cite-bracket">[</span>60<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>June 22, 2020</td>
<td>TDY</td>
<td><a href="/wiki/Teledyne" class="mw-redirect" title="Teledyne">Teledyne</a></td>
<td>HOG</td>
<td><a href="/wiki/Harley-Davidson" title="Harley-Davidson">Harley-Davidson</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20200612_60-1" class="reference"><a href="#cite_note-sp20200612-60"><span class="cite-bracket">[</span>60<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>June 22, 2020</td>
<td>TYL</td>
<td><a href="/wiki/Tyler_Technologies" title="Tyler Technologies">Tyler Technologies</a></td>
<td>JWN</td>
<td><a href="/wiki/Nordstrom" title="Nordstrom">Nordstrom</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20200612_60-2" class="reference"><a href="#cite_note-sp20200612-60"><span class="cite-bracket">[</span>60<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>May 22, 2020</td>
<td>WST</td>
<td><a href="/wiki/West_Pharmaceutical_Services" title="West Pharmaceutical Services">West Pharmaceutical Services</a></td>
<td>HP</td>
<td><a href="/wiki/Helmerich_%26_Payne" title="Helmerich &amp; Payne">Helmerich &amp; Payne</a></td>
<td>Market capitalization change.<sup id="cite_ref-61" class="reference"><a href="#cite_note-61"><span class="cite-bracket">[</span>61<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>May 12, 2020</td>
<td>DPZ</td>
<td><a href="/wiki/Domino%27s_Pizza" class="mw-redirect" title="Domino's Pizza">Domino's Pizza</a></td>
<td>CPRI</td>
<td><a href="/wiki/Capri_Holdings" title="Capri Holdings">Capri Holdings</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20200506_62-0" class="reference"><a href="#cite_note-sp20200506-62"><span class="cite-bracket">[</span>62<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>May 12, 2020</td>
<td>DXCM</td>
<td><a href="/wiki/Dexcom" title="Dexcom">Dexcom</a></td>
<td>AGN</td>
<td><a href="/wiki/Allergan" title="Allergan">Allergan</a></td>
<td>Allergan acquired by <a href="/wiki/AbbVie" title="AbbVie">AbbVie</a>.<sup id="cite_ref-sp20200506_62-1" class="reference"><a href="#cite_note-sp20200506-62"><span class="cite-bracket">[</span>62<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>April 6, 2020</td>
<td></td>
<td></td>
<td>M</td>
<td><a href="/wiki/Macy%27s" title="Macy's">Macy's</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20200331_63-0" class="reference"><a href="#cite_note-sp20200331-63"><span class="cite-bracket">[</span>63<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>April 6, 2020</td>
<td></td>
<td></td>
<td>RTN</td>
<td><a href="/wiki/Raytheon_Company" class="mw-redirect" title="Raytheon Company">Raytheon Company</a></td>
<td>United Technologies spun off Otis and Carrier and acquired Raytheon Company.<sup id="cite_ref-sp20200331_63-1" class="reference"><a href="#cite_note-sp20200331-63"><span class="cite-bracket">[</span>63<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>April 3, 2020</td>
<td>OTIS</td>
<td><a href="/wiki/Otis_Worldwide" title="Otis Worldwide">Otis Worldwide</a></td>
<td></td>
<td></td>
<td>United Technologies spun off Otis and Carrier and acquired Raytheon Company.<sup id="cite_ref-sp20200331_63-2" class="reference"><a href="#cite_note-sp20200331-63"><span class="cite-bracket">[</span>63<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>April 3, 2020</td>
<td>CARR</td>
<td><a href="/wiki/Carrier_Global" title="Carrier Global">Carrier</a></td>
<td></td>
<td></td>
<td>United Technologies spun off Otis and Carrier and acquired Raytheon Company.<sup id="cite_ref-sp20200331_63-3" class="reference"><a href="#cite_note-sp20200331-63"><span class="cite-bracket">[</span>63<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>April 1, 2020</td>
<td>HWM</td>
<td><a href="/wiki/Howmet_Aerospace" title="Howmet Aerospace">Howmet Aerospace</a></td>
<td>ARNC</td>
<td><a href="/wiki/Arconic" title="Arconic">Arconic</a></td>
<td>Arconic separated into 2 companies - Howmet remained on the index.<sup id="cite_ref-64" class="reference"><a href="#cite_note-64"><span class="cite-bracket">[</span>64<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>March 2, 2020</td>
<td>IR</td>
<td><a href="/wiki/Ingersoll_Rand" title="Ingersoll Rand">Ingersoll Rand</a></td>
<td>XEC</td>
<td><a href="/wiki/Cimarex_Energy" title="Cimarex Energy">Cimarex Energy</a></td>
<td>Gardner Denver acquired <a href="/wiki/Ingersoll_Rand" title="Ingersoll Rand">Ingersoll Rand</a>'s industrial businesses then changed its name to the "new" Ingersoll Rand Inc.<sup id="cite_ref-65" class="reference"><a href="#cite_note-65"><span class="cite-bracket">[</span>65<span class="cite-bracket">]</span></a></sup><sup id="cite_ref-66" class="reference"><a href="#cite_note-66"><span class="cite-bracket">[</span>66<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>January 28, 2020</td>
<td>PAYC</td>
<td><a href="/wiki/Paycom" title="Paycom">Paycom</a></td>
<td>WCG</td>
<td><a href="/wiki/WellCare" title="WellCare">WellCare</a></td>
<td>S&amp;P 500 constituent Centene Corp. (NYSE: CNC) acquired Wellcare Health Plans.<sup id="cite_ref-67" class="reference"><a href="#cite_note-67"><span class="cite-bracket">[</span>67<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>December 23, 2019</td>
<td>LYV</td>
<td><a href="/wiki/Live_Nation_Entertainment" title="Live Nation Entertainment">Live Nation Entertainment</a></td>
<td>AMG</td>
<td><a href="/wiki/Affiliated_Managers_Group" title="Affiliated Managers Group">Affiliated Managers Group</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20191213_68-0" class="reference"><a href="#cite_note-sp20191213-68"><span class="cite-bracket">[</span>68<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>December 23, 2019</td>
<td>ZBRA</td>
<td><a href="/wiki/Zebra_Technologies" title="Zebra Technologies">Zebra Technologies</a></td>
<td>TRIP</td>
<td><a href="/wiki/TripAdvisor" class="mw-redirect" title="TripAdvisor">TripAdvisor</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20191213_68-1" class="reference"><a href="#cite_note-sp20191213-68"><span class="cite-bracket">[</span>68<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>December 23, 2019</td>
<td>STE</td>
<td><a href="/wiki/Steris" title="Steris">Steris</a></td>
<td>MAC</td>
<td><a href="/wiki/Macerich" title="Macerich">Macerich</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20191213_68-2" class="reference"><a href="#cite_note-sp20191213-68"><span class="cite-bracket">[</span>68<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>December 9, 2019</td>
<td>ODFL</td>
<td><a href="/wiki/Old_Dominion_Freight_Line" title="Old Dominion Freight Line">Old Dominion Freight Line</a></td>
<td>STI</td>
<td><a href="/wiki/SunTrust_Banks" title="SunTrust Banks">SunTrust Banks</a></td>
<td>BB&amp;T acquired SunTrust to form <a href="/wiki/Truist_Financial" title="Truist Financial">Truist Financial</a>.<sup id="cite_ref-69" class="reference"><a href="#cite_note-69"><span class="cite-bracket">[</span>69<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>December 5, 2019</td>
<td>WRB</td>
<td><a href="/wiki/W._R._Berkley_Corporation" title="W. R. Berkley Corporation">W. R. Berkley Corporation</a></td>
<td>VIAB</td>
<td><a href="/wiki/Viacom_(2005-2019)" class="mw-redirect" title="Viacom (2005-2019)">Viacom</a></td>
<td>CBS acquired Viacom to form <a href="/wiki/ViacomCBS" class="mw-redirect" title="ViacomCBS">ViacomCBS</a>.<sup id="cite_ref-70" class="reference"><a href="#cite_note-70"><span class="cite-bracket">[</span>70<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>November 21, 2019</td>
<td>NOW</td>
<td><a href="/wiki/ServiceNow" title="ServiceNow">ServiceNow</a></td>
<td>CELG</td>
<td><a href="/wiki/Celgene" title="Celgene">Celgene</a></td>
<td><a href="/wiki/Bristol-Myers_Squibb" class="mw-redirect" title="Bristol-Myers Squibb">Bristol-Myers Squibb</a> (NYSE:BMY) acquired Celgene.<sup id="cite_ref-71" class="reference"><a href="#cite_note-71"><span class="cite-bracket">[</span>71<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>October 3, 2019</td>
<td>LVS</td>
<td><a href="/wiki/Las_Vegas_Sands" title="Las Vegas Sands">Las Vegas Sands</a></td>
<td>NKTR</td>
<td><a href="/wiki/Nektar_Therapeutics" title="Nektar Therapeutics">Nektar Therapeutics</a></td>
<td>Market capitalization change.<sup id="cite_ref-72" class="reference"><a href="#cite_note-72"><span class="cite-bracket">[</span>72<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>September 26, 2019</td>
<td>NVR</td>
<td><a href="/wiki/NVR_Inc" class="mw-redirect" title="NVR Inc">NVR</a></td>
<td>JEF</td>
<td><a href="/wiki/Jefferies_Financial_Group" title="Jefferies Financial Group">Jefferies Financial Group</a></td>
<td>JEF spun off SPB.<sup id="cite_ref-73" class="reference"><a href="#cite_note-73"><span class="cite-bracket">[</span>73<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>September 23, 2019</td>
<td>CDW</td>
<td><a href="/wiki/CDW" title="CDW">CDW Corporation</a></td>
<td>TSS</td>
<td><a href="/wiki/TSYS" title="TSYS">TSYS</a></td>
<td>S&amp;P 500 constituent <a href="/wiki/Global_Payments" title="Global Payments">Global Payments</a> (NYSE: GPN) acquired TSS.<sup id="cite_ref-74" class="reference"><a href="#cite_note-74"><span class="cite-bracket">[</span>74<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>August 9, 2019</td>
<td>LDOS</td>
<td><a href="/wiki/Leidos" title="Leidos">Leidos</a></td>
<td>APC</td>
<td><a href="/wiki/Anadarko_Petroleum" title="Anadarko Petroleum">Anadarko Petroleum</a></td>
<td>S&amp;P 500 &amp; 100 constituent Occidental Petroleum Corp. (NYSE:OXY) acquired Anadarko Petroleum.<sup id="cite_ref-sp20190801_75-0" class="reference"><a href="#cite_note-sp20190801-75"><span class="cite-bracket">[</span>75<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>August 9, 2019</td>
<td>IEX</td>
<td><a href="/wiki/IDEX_Corporation" title="IDEX Corporation">IDEX Corporation</a></td>
<td>FL</td>
<td><a href="/wiki/Foot_Locker" title="Foot Locker">Foot Locker</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20190801_75-1" class="reference"><a href="#cite_note-sp20190801-75"><span class="cite-bracket">[</span>75<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>July 15, 2019</td>
<td>TMUS</td>
<td><a href="/wiki/T-Mobile_US" title="T-Mobile US">T-Mobile US</a></td>
<td>RHT</td>
<td><a href="/wiki/Red_Hat" title="Red Hat">Red Hat</a></td>
<td>S&amp;P 500 &amp; 100 constituent <a href="/wiki/IBM" title="IBM">IBM</a> acquired Red Hat.<sup id="cite_ref-76" class="reference"><a href="#cite_note-76"><span class="cite-bracket">[</span>76<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>July 1, 2019</td>
<td>MKTX</td>
<td><a href="/wiki/MarketAxess" title="MarketAxess">MarketAxess</a></td>
<td>LLL</td>
<td><a href="/wiki/L3_Technologies" title="L3 Technologies">L3 Technologies</a></td>
<td>L3 purchased by Harris Corporation<sup id="cite_ref-77" class="reference"><a href="#cite_note-77"><span class="cite-bracket">[</span>77<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>June 11, 2019</td>
<td>AMCR</td>
<td><a href="/wiki/Amcor" title="Amcor">Amcor</a></td>
<td>BMS</td>
<td><a href="/wiki/Bemis_Company" title="Bemis Company">Bemis</a></td>
<td>BMS changed to AMCR post merger with Amcor;<sup id="cite_ref-78" class="reference"><a href="#cite_note-78"><span class="cite-bracket">[</span>78<span class="cite-bracket">]</span></a></sup> subsequently renamed to <a href="/wiki/Amcor" title="Amcor">Amcor</a><sup id="cite_ref-79" class="reference"><a href="#cite_note-79"><span class="cite-bracket">[</span>79<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>June 7, 2019</td>
<td>BMS</td>
<td><a href="/wiki/Bemis_Company" title="Bemis Company">Bemis</a></td>
<td>MAT</td>
<td><a href="/wiki/Mattel" title="Mattel">Mattel</a></td>
<td>Pending merger of Bemis and Amcor; Bemis treated as the surviving entity.<sup id="cite_ref-80" class="reference"><a href="#cite_note-80"><span class="cite-bracket">[</span>80<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>June 3, 2019
</td>
<td>DD
</td>
<td><a href="/wiki/DuPont" title="DuPont">DuPont</a>
</td>
<td>DWDP
</td>
<td><a href="/wiki/DuPont" title="DuPont">DuPont</a>
</td>
<td>DWDP changed to DD after spinning off Corteva.<sup id="cite_ref-:0_81-0" class="reference"><a href="#cite_note-:0-81"><span class="cite-bracket">[</span>81<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>June 3, 2019</td>
<td>CTVA</td>
<td><a href="/wiki/Corteva" title="Corteva">Corteva</a></td>
<td>FLR</td>
<td><a href="/wiki/Fluor_Corporation" title="Fluor Corporation">Fluor Corporation</a></td>
<td>CTVA spun off from DWDP (which then changed symbol to DD)<sup id="cite_ref-:0_81-1" class="reference"><a href="#cite_note-:0-81"><span class="cite-bracket">[</span>81<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>April 2, 2019</td>
<td>DOW</td>
<td><a href="/wiki/Dow_Inc" class="mw-redirect" title="Dow Inc">Dow</a></td>
<td>BHF</td>
<td><a href="/wiki/Brighthouse_Financial" title="Brighthouse Financial">Brighthouse Financial</a></td>
<td>DOW spun off from DWDP<sup id="cite_ref-82" class="reference"><a href="#cite_note-82"><span class="cite-bracket">[</span>82<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>March 19, 2019</td>
<td>FOXA</td>
<td><a href="/wiki/Fox_Corporation" title="Fox Corporation">Fox Corporation</a></td>
<td>FOXA</td>
<td><a href="/wiki/21st_Century_Fox" title="21st Century Fox">21st Century Fox</a></td>
<td>21st Century Fox merged with Disney and some parts spun off as Fox Corporation.<sup id="cite_ref-sp20190314_83-0" class="reference"><a href="#cite_note-sp20190314-83"><span class="cite-bracket">[</span>83<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>March 19, 2019</td>
<td>FOX</td>
<td><a href="/wiki/Fox_Corporation" title="Fox Corporation">Fox Corporation</a></td>
<td>FOX</td>
<td><a href="/wiki/21st_Century_Fox" title="21st Century Fox">21st Century Fox</a></td>
<td>21st Century Fox merged with Disney and some parts spun off as Fox Corporation.<sup id="cite_ref-sp20190314_83-1" class="reference"><a href="#cite_note-sp20190314-83"><span class="cite-bracket">[</span>83<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>February 27, 2019</td>
<td>WAB</td>
<td><a href="/wiki/Wabtec" title="Wabtec">Wabtec</a></td>
<td>GT</td>
<td><a href="/wiki/The_Goodyear_Tire_%26_Rubber_Company" class="mw-redirect" title="The Goodyear Tire &amp; Rubber Company">The Goodyear Tire &amp; Rubber Company</a></td>
<td>WAB acquired GE transportation business<sup id="cite_ref-84" class="reference"><a href="#cite_note-84"><span class="cite-bracket">[</span>84<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>February 15, 2019</td>
<td>ATO</td>
<td><a href="/wiki/Atmos_Energy" title="Atmos Energy">Atmos Energy</a></td>
<td>NFX</td>
<td><a href="/wiki/Newfield_Exploration" title="Newfield Exploration">Newfield Exploration</a></td>
<td>ECA acquired NFX<sup id="cite_ref-85" class="reference"><a href="#cite_note-85"><span class="cite-bracket">[</span>85<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>January 18, 2019</td>
<td>TFX</td>
<td><a href="/wiki/Teleflex" title="Teleflex">Teleflex</a></td>
<td>PCG</td>
<td><a href="/wiki/Pacific_Gas_%26_Electric_Company" class="mw-redirect" title="Pacific Gas &amp; Electric Company">Pacific Gas &amp; Electric Company</a></td>
<td>PCG filed for bankruptcy<sup id="cite_ref-86" class="reference"><a href="#cite_note-86"><span class="cite-bracket">[</span>86<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>January 2, 2019</td>
<td>FRC</td>
<td><a href="/wiki/First_Republic_Bank" title="First Republic Bank">First Republic Bank</a></td>
<td>SCG</td>
<td><a href="/wiki/SCANA" title="SCANA">SCANA</a></td>
<td>Dominion Energy acquired SCANA Corporation<sup id="cite_ref-87" class="reference"><a href="#cite_note-87"><span class="cite-bracket">[</span>87<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>December 24, 2018</td>
<td>CE</td>
<td><a href="/wiki/Celanese" title="Celanese">Celanese</a></td>
<td>ESRX</td>
<td><a href="/wiki/Express_Scripts" title="Express Scripts">Express Scripts</a></td>
<td>S&amp;P 500 constituent Cigna (NYSE: CI) acquired ESRX<sup id="cite_ref-88" class="reference"><a href="#cite_note-88"><span class="cite-bracket">[</span>88<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>December 3, 2018</td>
<td>LW</td>
<td><a href="/wiki/Lamb_Weston" title="Lamb Weston">Lamb Weston</a></td>
<td>COL</td>
<td><a href="/wiki/Rockwell_Collins" title="Rockwell Collins">Rockwell Collins</a></td>
<td>UTX acquired COL<sup id="cite_ref-sp20181126_89-0" class="reference"><a href="#cite_note-sp20181126-89"><span class="cite-bracket">[</span>89<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>December 3, 2018</td>
<td>MXIM</td>
<td><a href="/wiki/Maxim_Integrated" title="Maxim Integrated">Maxim Integrated</a></td>
<td>AET</td>
<td><a href="/wiki/Aetna" title="Aetna">Aetna</a></td>
<td>CVS acquired Aetna<sup id="cite_ref-sp20181126_89-1" class="reference"><a href="#cite_note-sp20181126-89"><span class="cite-bracket">[</span>89<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>December 3, 2018</td>
<td>FANG</td>
<td><a href="/wiki/Diamondback_Energy" title="Diamondback Energy">Diamondback Energy</a></td>
<td>SRCL</td>
<td><a href="/wiki/Stericycle" title="Stericycle">Stericycle</a></td>
<td>Market Capitalization change<sup id="cite_ref-sp20181126_89-2" class="reference"><a href="#cite_note-sp20181126-89"><span class="cite-bracket">[</span>89<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>November 13, 2018</td>
<td>JKHY</td>
<td><a href="/wiki/Jack_Henry_%26_Associates" title="Jack Henry &amp; Associates">Jack Henry &amp; Associates</a></td>
<td>EQT</td>
<td><a href="/wiki/EQT_Corporation" title="EQT Corporation">EQT Corporation</a></td>
<td>EQT spun off ETRN<sup id="cite_ref-90" class="reference"><a href="#cite_note-90"><span class="cite-bracket">[</span>90<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>November 6, 2018</td>
<td>KEYS</td>
<td><a href="/wiki/Keysight" title="Keysight">Keysight</a></td>
<td>CA</td>
<td><a href="/wiki/CA_Technologies" title="CA Technologies">CA Technologies</a></td>
<td>CA acquired by <a href="/wiki/Broadcom" title="Broadcom">Broadcom</a>.<sup id="cite_ref-91" class="reference"><a href="#cite_note-91"><span class="cite-bracket">[</span>91<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>October 11, 2018</td>
<td>FTNT</td>
<td><a href="/wiki/Fortinet" title="Fortinet">Fortinet</a></td>
<td>EVHC</td>
<td><a href="/wiki/Envision_Healthcare" title="Envision Healthcare">Envision Healthcare</a></td>
<td>EVHC acquired by <a href="/wiki/KKR_(company)" class="mw-redirect" title="KKR (company)">KKR</a>.<sup id="cite_ref-92" class="reference"><a href="#cite_note-92"><span class="cite-bracket">[</span>92<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>October 1, 2018</td>
<td>ROL</td>
<td><a href="/wiki/Rollins_Inc" class="mw-redirect" title="Rollins Inc">Rollins</a></td>
<td>ANDV</td>
<td><a href="/wiki/Andeavor" class="mw-redirect" title="Andeavor">Andeavor</a></td>
<td>ANDV acquired by <a href="/wiki/Marathon_Petroleum" title="Marathon Petroleum">Marathon Petroleum</a>.<sup id="cite_ref-93" class="reference"><a href="#cite_note-93"><span class="cite-bracket">[</span>93<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>September 14, 2018</td>
<td>WCG</td>
<td><a href="/wiki/WellCare" title="WellCare">WellCare</a></td>
<td>XL</td>
<td><a href="/wiki/XL_Group" class="mw-redirect" title="XL Group">XL Group</a></td>
<td>XL acquired by <a href="/wiki/Axa" title="Axa">Axa</a>.<sup id="cite_ref-94" class="reference"><a href="#cite_note-94"><span class="cite-bracket">[</span>94<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>August 28, 2018</td>
<td>ANET</td>
<td><a href="/wiki/Arista_Networks" title="Arista Networks">Arista Networks</a></td>
<td>GGP</td>
<td><a href="/wiki/GGP_Inc." title="GGP Inc.">GGP</a></td>
<td>GGP acquired by <a href="/wiki/Brookfield_Property_Partners" title="Brookfield Property Partners">Brookfield Property Partners</a>.<sup id="cite_ref-95" class="reference"><a href="#cite_note-95"><span class="cite-bracket">[</span>95<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>July 2, 2018</td>
<td>CPRT</td>
<td><a href="/wiki/Copart" title="Copart">Copart</a></td>
<td>DPS</td>
<td><a href="/wiki/Dr_Pepper_Snapple_Group" title="Dr Pepper Snapple Group">Dr Pepper Snapple Group</a></td>
<td>DPS acquired by <a href="/wiki/Keurig_Green_Mountain" class="mw-redirect" title="Keurig Green Mountain">Keurig Green Mountain</a>.<sup id="cite_ref-96" class="reference"><a href="#cite_note-96"><span class="cite-bracket">[</span>96<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>June 20, 2018</td>
<td>FLT</td>
<td><a href="/wiki/FleetCor_Technologies" class="mw-redirect" title="FleetCor Technologies">FleetCor Technologies</a></td>
<td>TWX</td>
<td><a href="/wiki/Time_Warner" class="mw-redirect" title="Time Warner">Time Warner</a></td>
<td>AT&amp;T acquired Time Warner.<sup id="cite_ref-97" class="reference"><a href="#cite_note-97"><span class="cite-bracket">[</span>97<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>June 18, 2018</td>
<td>BR</td>
<td><a href="/wiki/Broadridge_Financial_Solutions" title="Broadridge Financial Solutions">Broadridge Financial Solutions</a></td>
<td>RRC</td>
<td><a href="/wiki/Range_Resources" title="Range Resources">Range Resources</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20180608_98-0" class="reference"><a href="#cite_note-sp20180608-98"><span class="cite-bracket">[</span>98<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>June 18, 2018</td>
<td>HFC</td>
<td><a href="/wiki/HollyFrontier" class="mw-redirect" title="HollyFrontier">HollyFrontier</a></td>
<td>AYI</td>
<td><a href="/wiki/Acuity_Brands" title="Acuity Brands">Acuity Brands</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20180608_98-1" class="reference"><a href="#cite_note-sp20180608-98"><span class="cite-bracket">[</span>98<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>June 7, 2018</td>
<td>TWTR</td>
<td><a href="/wiki/Twitter" title="Twitter">Twitter</a></td>
<td>MON</td>
<td><a href="/wiki/Monsanto" title="Monsanto">Monsanto</a></td>
<td><a href="/wiki/Bayer" title="Bayer">Bayer</a> acquired Monsanto.<sup id="cite_ref-99" class="reference"><a href="#cite_note-99"><span class="cite-bracket">[</span>99<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>June 5, 2018</td>
<td>EVRG</td>
<td><a href="/wiki/Evergy" title="Evergy">Evergy</a></td>
<td>NAVI</td>
<td><a href="/wiki/Navient" title="Navient">Navient</a></td>
<td>Westar Energy (NYSE: WR) acquired Great Plains Energy (NYSE: GXP) and changed name to Evergy.<sup id="cite_ref-100" class="reference"><a href="#cite_note-100"><span class="cite-bracket">[</span>100<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>May 31, 2018</td>
<td>ABMD</td>
<td><a href="/wiki/Abiomed" title="Abiomed">Abiomed</a></td>
<td>WYN</td>
<td><a href="/wiki/Wyndham_Worldwide" class="mw-redirect" title="Wyndham Worldwide">Wyndham Worldwide</a></td>
<td>Wyndham Worldwide spun off <a href="/wiki/Wyndham_Hotels_%26_Resorts" title="Wyndham Hotels &amp; Resorts">Wyndham Hotels &amp; Resorts</a> (NYSE:WH).<sup id="cite_ref-101" class="reference"><a href="#cite_note-101"><span class="cite-bracket">[</span>101<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>April 4, 2018</td>
<td>MSCI</td>
<td><a href="/wiki/MSCI" title="MSCI">MSCI</a></td>
<td>CSRA</td>
<td><a href="/wiki/CSRA_Inc" class="mw-redirect" title="CSRA Inc">CSRA</a></td>
<td>S&amp;P 500 constituent <a href="/wiki/General_Dynamics" title="General Dynamics">General Dynamics</a> (NYSE: GD) acquired CSRA.<sup id="cite_ref-102" class="reference"><a href="#cite_note-102"><span class="cite-bracket">[</span>102<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>March 19, 2018</td>
<td>TTWO</td>
<td><a href="/wiki/Take-Two_Interactive" title="Take-Two Interactive">Take-Two Interactive</a></td>
<td>SIG</td>
<td><a href="/wiki/Signet_Jewelers" title="Signet Jewelers">Signet Jewelers</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20180309_103-0" class="reference"><a href="#cite_note-sp20180309-103"><span class="cite-bracket">[</span>103<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>March 19, 2018</td>
<td>SIVB</td>
<td><a href="/wiki/SVB_Financial_Group" title="SVB Financial Group">SVB Financial Group</a></td>
<td>PDCO</td>
<td><a href="/wiki/Patterson_Companies" title="Patterson Companies">Patterson Companies</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20180309_103-1" class="reference"><a href="#cite_note-sp20180309-103"><span class="cite-bracket">[</span>103<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>March 19, 2018</td>
<td>NKTR</td>
<td><a href="/wiki/Nektar_Therapeutics" title="Nektar Therapeutics">Nektar Therapeutics</a></td>
<td>CHK</td>
<td><a href="/wiki/Chesapeake_Energy" class="mw-redirect" title="Chesapeake Energy">Chesapeake Energy</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20180309_103-2" class="reference"><a href="#cite_note-sp20180309-103"><span class="cite-bracket">[</span>103<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>March 7, 2018</td>
<td>IPGP</td>
<td><a href="/wiki/IPG_Photonics" title="IPG Photonics">IPG Photonics</a></td>
<td>SNI</td>
<td><a href="/wiki/Scripps_Networks_Interactive" title="Scripps Networks Interactive">Scripps Networks Interactive</a></td>
<td><a href="/wiki/Discovery_Communications" class="mw-redirect" title="Discovery Communications">Discovery Communications</a> acquired SNI.<sup id="cite_ref-104" class="reference"><a href="#cite_note-104"><span class="cite-bracket">[</span>104<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>January 3, 2018</td>
<td>HII</td>
<td><a href="/wiki/Huntington_Ingalls_Industries" title="Huntington Ingalls Industries">Huntington Ingalls Industries</a></td>
<td>BCR</td>
<td><a href="/wiki/CR_Bard" class="mw-redirect" title="CR Bard">CR Bard</a></td>
<td><a href="/wiki/Becton_Dickinson" class="mw-redirect" title="Becton Dickinson">Becton Dickinson</a> acquired BCR.<sup id="cite_ref-105" class="reference"><a href="#cite_note-105"><span class="cite-bracket">[</span>105<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>October 13, 2017</td>
<td>NCLH</td>
<td><a href="/wiki/Norwegian_Cruise_Line_Holdings" title="Norwegian Cruise Line Holdings">Norwegian Cruise Line Holdings</a></td>
<td>LVLT</td>
<td><a href="/wiki/Level_3_Communications" title="Level 3 Communications">Level 3 Communications</a></td>
<td><a href="/wiki/Lumen_Technologies" title="Lumen Technologies">CenturyLink</a> acquired LVLT.<sup id="cite_ref-106" class="reference"><a href="#cite_note-106"><span class="cite-bracket">[</span>106<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>September 18, 2017</td>
<td>CDNS</td>
<td><a href="/wiki/Cadence_Design_Systems" title="Cadence Design Systems">Cadence Design Systems</a></td>
<td>SPLS</td>
<td><a href="/wiki/Staples_Inc" class="mw-redirect" title="Staples Inc">Staples</a></td>
<td><a href="/wiki/Sycamore_Partners" title="Sycamore Partners">Sycamore Partners</a> acquired Staples.<sup id="cite_ref-107" class="reference"><a href="#cite_note-107"><span class="cite-bracket">[</span>107<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>September 1, 2017
</td>
<td>DWDP
</td>
<td><a href="/wiki/DuPont" title="DuPont">DuPont</a>
</td>
<td>DOW
</td>
<td><a href="/wiki/Dow_Chemical_Company" title="Dow Chemical Company">Dow Chemical Company</a>
</td>
<td>The Dow Chemical Company renamed to DowDuPont Inc. and ticker changed from DOW to DWDP after acquiring DuPont.<sup id="cite_ref-sp170824_108-0" class="reference"><a href="#cite_note-sp170824-108"><span class="cite-bracket">[</span>108<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>September 1, 2017</td>
<td>SBAC</td>
<td><a href="/wiki/SBA_Communications" title="SBA Communications">SBA Communications</a></td>
<td>DD</td>
<td><a href="/wiki/DuPont" title="DuPont">DuPont</a></td>
<td>The Dow Chemical Company acquired DuPont.<sup id="cite_ref-sp170824_108-1" class="reference"><a href="#cite_note-sp170824-108"><span class="cite-bracket">[</span>108<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>August 29, 2017</td>
<td>Q</td>
<td><a href="/wiki/QuintilesIMS" class="mw-redirect" title="QuintilesIMS">QuintilesIMS</a></td>
<td>WFM</td>
<td><a href="/wiki/Whole_Foods_Market" title="Whole Foods Market">Whole Foods Market</a></td>
<td><a href="/wiki/Amazon_(company)" title="Amazon (company)">Amazon</a> acquired Whole Foods Market.<sup id="cite_ref-sp170824_108-2" class="reference"><a href="#cite_note-sp170824-108"><span class="cite-bracket">[</span>108<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>August 8, 2017</td>
<td>BHF</td>
<td><a href="/wiki/Brighthouse_Financial" title="Brighthouse Financial">Brighthouse Financial</a></td>
<td>AN</td>
<td><a href="/wiki/AutoNation" title="AutoNation">AutoNation</a></td>
<td>BHF replaced AN,<sup id="cite_ref-sp170731_109-0" class="reference"><a href="#cite_note-sp170731-109"><span class="cite-bracket">[</span>109<span class="cite-bracket">]</span></a></sup> MET spun off BHF<sup id="cite_ref-sp170731_109-1" class="reference"><a href="#cite_note-sp170731-109"><span class="cite-bracket">[</span>109<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>July 26, 2017</td>
<td>DRE</td>
<td><a href="/wiki/Duke_Realty" title="Duke Realty">Duke Realty</a> Corp</td>
<td>RIG</td>
<td><a href="/wiki/Transocean" title="Transocean">Transocean</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20170719_110-0" class="reference"><a href="#cite_note-sp20170719-110"><span class="cite-bracket">[</span>110<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>July 26, 2017</td>
<td>AOS</td>
<td><a href="/wiki/A._O._Smith" title="A. O. Smith">A. O. Smith</a></td>
<td>BBBY</td>
<td><a href="/wiki/Bed_Bath_%26_Beyond_Inc." class="mw-redirect" title="Bed Bath &amp; Beyond Inc.">Bed Bath &amp; Beyond</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20170719_110-1" class="reference"><a href="#cite_note-sp20170719-110"><span class="cite-bracket">[</span>110<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>July 26, 2017</td>
<td>PKG</td>
<td><a href="/wiki/Packaging_Corporation_of_America" title="Packaging Corporation of America">Packaging Corporation of America</a></td>
<td>MUR</td>
<td><a href="/wiki/Murphy_Oil" title="Murphy Oil">Murphy Oil</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20170719_110-2" class="reference"><a href="#cite_note-sp20170719-110"><span class="cite-bracket">[</span>110<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>July 26, 2017</td>
<td>RMD</td>
<td><a href="/wiki/ResMed" title="ResMed">ResMed</a></td>
<td>MNK</td>
<td><a href="/wiki/Mallinckrodt" title="Mallinckrodt">Mallinckrodt</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20170719_110-3" class="reference"><a href="#cite_note-sp20170719-110"><span class="cite-bracket">[</span>110<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>July 26, 2017</td>
<td>MGM</td>
<td><a href="/wiki/MGM_Resorts_International" title="MGM Resorts International">MGM Resorts International</a></td>
<td>RAI</td>
<td><a href="/wiki/Reynolds_American" title="Reynolds American">Reynolds American</a></td>
<td><a href="/wiki/British_American_Tobacco" title="British American Tobacco">British American Tobacco</a> (NYSE MKT:BTI) acquired Reynolds American.<sup id="cite_ref-sp20170719_110-4" class="reference"><a href="#cite_note-sp20170719-110"><span class="cite-bracket">[</span>110<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>July 7, 2017</td>
<td>BKR</td>
<td><a href="/wiki/Baker_Hughes" title="Baker Hughes">Baker Hughes</a></td>
<td>BHI</td>
<td><a href="/wiki/Baker_Hughes" title="Baker Hughes">Baker Hughes</a></td>
<td>Baker Hughes merged with GE Oil &amp; Gas to form new company.<sup id="cite_ref-bkrpress_111-0" class="reference"><a href="#cite_note-bkrpress-111"><span class="cite-bracket">[</span>111<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>June 19, 2017</td>
<td>HLT</td>
<td><a href="/wiki/Hilton_Worldwide" title="Hilton Worldwide">Hilton</a></td>
<td>YHOO</td>
<td><a href="/wiki/Yahoo!_Inc._(1995%E2%80%932017)" title="Yahoo! Inc. (1995–2017)">Yahoo!</a></td>
<td>VZ acquired YHOO operations; remainder of YHOO converted to closed-end company known as <a href="/wiki/Altaba" title="Altaba">Altaba</a>.<sup id="cite_ref-sp170609_112-0" class="reference"><a href="#cite_note-sp170609-112"><span class="cite-bracket">[</span>112<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>June 19, 2017</td>
<td>ALGN</td>
<td><a href="/wiki/Align_Technology" title="Align Technology">Align Technology</a></td>
<td>TDC</td>
<td><a href="/wiki/Teradata" title="Teradata">Teradata</a></td>
<td>Market capitalization changes.<sup id="cite_ref-sp170609_112-1" class="reference"><a href="#cite_note-sp170609-112"><span class="cite-bracket">[</span>112<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>June 19, 2017</td>
<td>ANSS</td>
<td><a href="/wiki/Ansys" title="Ansys">Ansys</a></td>
<td>R</td>
<td><a href="/wiki/Ryder_System" class="mw-redirect" title="Ryder System">Ryder System</a></td>
<td>Market capitalization changes.<sup id="cite_ref-sp170609_112-2" class="reference"><a href="#cite_note-sp170609-112"><span class="cite-bracket">[</span>112<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>June 19, 2017</td>
<td>RE</td>
<td><a href="/wiki/Everest_Re" class="mw-redirect" title="Everest Re">Everest Re</a></td>
<td>MJN</td>
<td><a href="/wiki/Mead_Johnson" title="Mead Johnson">Mead Johnson</a></td>
<td><a href="/wiki/Reckitt_Benckiser" class="mw-redirect" title="Reckitt Benckiser">Reckitt Benckiser</a> acquired Mead Johnson Nutrition.<sup id="cite_ref-113" class="reference"><a href="#cite_note-113"><span class="cite-bracket">[</span>113<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>June 2, 2017</td>
<td>INFO</td>
<td><a href="/wiki/IHS_Markit" class="mw-redirect" title="IHS Markit">IHS Markit</a></td>
<td>TGNA</td>
<td><a href="/wiki/Tegna_Inc" class="mw-redirect" title="Tegna Inc">Tegna</a></td>
<td>TGNA spins off <a href="/wiki/Cars.com" title="Cars.com">Cars.com</a><sup id="cite_ref-114" class="reference"><a href="#cite_note-114"><span class="cite-bracket">[</span>114<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>April 5, 2017</td>
<td>IT</td>
<td><a href="/wiki/Gartner" title="Gartner">Gartner</a></td>
<td>DNB</td>
<td><a href="/wiki/Dun_%26_Bradstreet" title="Dun &amp; Bradstreet">Dun &amp; Bradstreet</a></td>
<td>IT acquiring CEB<sup id="cite_ref-115" class="reference"><a href="#cite_note-115"><span class="cite-bracket">[</span>115<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>April 4, 2017</td>
<td>DXC</td>
<td><a href="/wiki/DXC_Technology" title="DXC Technology">DXC Technology</a></td>
<td>SWN</td>
<td><a href="/wiki/Southwestern_Energy" title="Southwestern Energy">Southwestern Energy</a></td>
<td>HPE spins off Everett, merged with CSC to form DXC<sup id="cite_ref-116" class="reference"><a href="#cite_note-116"><span class="cite-bracket">[</span>116<span class="cite-bracket">]</span></a></sup><sup id="cite_ref-117" class="reference"><a href="#cite_note-117"><span class="cite-bracket">[</span>117<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>March 20, 2017</td>
<td>AMD</td>
<td><a href="/wiki/Advanced_Micro_Devices" class="mw-redirect" title="Advanced Micro Devices">Advanced Micro Devices</a></td>
<td>URBN</td>
<td><a href="/wiki/Urban_Outfitters" title="Urban Outfitters">Urban Outfitters</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20170310_118-0" class="reference"><a href="#cite_note-sp20170310-118"><span class="cite-bracket">[</span>118<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>March 20, 2017</td>
<td>RJF</td>
<td><a href="/wiki/Raymond_James_Financial" title="Raymond James Financial">Raymond James Financial</a></td>
<td>FTR</td>
<td><a href="/wiki/Frontier_Communications" title="Frontier Communications">Frontier Communications</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20170310_118-1" class="reference"><a href="#cite_note-sp20170310-118"><span class="cite-bracket">[</span>118<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>March 20, 2017</td>
<td>ARE</td>
<td><a href="/wiki/Alexandria_Real_Estate_Equities" title="Alexandria Real Estate Equities">Alexandria Real Estate Equities</a></td>
<td>FSLR</td>
<td><a href="/wiki/First_Solar" title="First Solar">First Solar</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20170310_118-2" class="reference"><a href="#cite_note-sp20170310-118"><span class="cite-bracket">[</span>118<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>March 16, 2017</td>
<td>SNPS</td>
<td><a href="/wiki/Synopsys" title="Synopsys">Synopsys</a></td>
<td>HAR</td>
<td><a href="/wiki/Harman_International" title="Harman International">Harman International</a></td>
<td><a href="/wiki/Samsung_Electronics" title="Samsung Electronics">Samsung Electronics</a> acquired Harman International Industries.<sup id="cite_ref-119" class="reference"><a href="#cite_note-119"><span class="cite-bracket">[</span>119<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>March 13, 2017</td>
<td>DISH</td>
<td><a href="/wiki/Dish_Network" title="Dish Network">Dish Network</a></td>
<td>LLTC</td>
<td><a href="/wiki/Linear_Technology" title="Linear Technology">Linear Technology</a></td>
<td>S&amp;P 500 constituent <a href="/wiki/Analog_Devices" title="Analog Devices">Analog Devices</a> (NASD:ADI) acquired Linear Technology.<sup id="cite_ref-120" class="reference"><a href="#cite_note-120"><span class="cite-bracket">[</span>120<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>March 2, 2017</td>
<td>REG</td>
<td><a href="/wiki/Regency_Centers" title="Regency Centers">Regency Centers</a></td>
<td>ENDP</td>
<td><a href="/wiki/Endo_International" title="Endo International">Endo International</a></td>
<td>REG acquires EQY<sup id="cite_ref-sp170223_121-0" class="reference"><a href="#cite_note-sp170223-121"><span class="cite-bracket">[</span>121<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>March 1, 2017</td>
<td>CBOE</td>
<td><a href="/wiki/Cboe_Holdings" class="mw-redirect" title="Cboe Holdings">Cboe Holdings</a></td>
<td>PBI</td>
<td><a href="/wiki/Pitney_Bowes" title="Pitney Bowes">Pitney Bowes</a></td>
<td>CBOE acquires BATS<sup id="cite_ref-sp170223_121-1" class="reference"><a href="#cite_note-sp170223-121"><span class="cite-bracket">[</span>121<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>February 28, 2017</td>
<td>INCY</td>
<td><a href="/wiki/Incyte" title="Incyte">Incyte</a></td>
<td>SE</td>
<td><a href="/wiki/Spectra_Energy" title="Spectra Energy">Spectra Energy</a></td>
<td>SE acquired by ENB<sup id="cite_ref-sp170223_121-2" class="reference"><a href="#cite_note-sp170223-121"><span class="cite-bracket">[</span>121<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>January 5, 2017</td>
<td>IDXX</td>
<td><a href="/wiki/Idexx_Laboratories" title="Idexx Laboratories">Idexx Laboratories</a></td>
<td>STJ</td>
<td><a href="/wiki/St_Jude_Medical" class="mw-redirect" title="St Jude Medical">St Jude Medical</a></td>
<td>S&amp;P 100 &amp; 500 constituent Abbott Laboratories (NYSE:ABT) acquired St. Jude Medical.<sup id="cite_ref-122" class="reference"><a href="#cite_note-122"><span class="cite-bracket">[</span>122<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>December 2, 2016</td>
<td>MAA</td>
<td><a href="/wiki/Mid-America_Apartments" class="mw-redirect" title="Mid-America Apartments">Mid-America Apartments</a></td>
<td>OI</td>
<td><a href="/wiki/Owens-Illinois" class="mw-redirect" title="Owens-Illinois">Owens-Illinois</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20161201_123-0" class="reference"><a href="#cite_note-sp20161201-123"><span class="cite-bracket">[</span>123<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>December 2, 2016</td>
<td>EVHC</td>
<td><a href="/wiki/Envision_Healthcare" title="Envision Healthcare">Envision Healthcare</a></td>
<td>LM</td>
<td><a href="/wiki/Legg_Mason" title="Legg Mason">Legg Mason</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20161201_123-1" class="reference"><a href="#cite_note-sp20161201-123"><span class="cite-bracket">[</span>123<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>November 1, 2016
</td>
<td>ARNC
</td>
<td><a href="/wiki/Arconic" title="Arconic">Arconic</a>
</td>
<td>AA
</td>
<td><a href="/wiki/Alcoa" title="Alcoa">Alcoa</a>
</td>
<td>AA spins off ARNC
</td></tr>
<tr>
<td>September 30, 2016</td>
<td>COTY</td>
<td><a href="/wiki/Coty" title="Coty">Coty</a></td>
<td>DO</td>
<td><a href="/wiki/Diamond_Offshore_Drilling" title="Diamond Offshore Drilling">Diamond Offshore Drilling</a></td>
<td>COTY replaces DO<sup id="cite_ref-124" class="reference"><a href="#cite_note-124"><span class="cite-bracket">[</span>124<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>September 22, 2016</td>
<td>COO</td>
<td><a href="/wiki/The_Cooper_Companies" title="The Cooper Companies">The Cooper Companies</a></td>
<td>HOT</td>
<td><a href="/wiki/Starwood_Hotels_and_Resorts" title="Starwood Hotels and Resorts">Starwood</a></td>
<td>MAR acquires HOT<sup id="cite_ref-125" class="reference"><a href="#cite_note-125"><span class="cite-bracket">[</span>125<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>September 8, 2016</td>
<td>CHTR</td>
<td><a href="/wiki/Charter_Communications" title="Charter Communications">Charter Communications</a></td>
<td>EMC</td>
<td><a href="/wiki/EMC_Corporation" title="EMC Corporation">EMC Corporation</a></td>
<td>Dell acquires EMC<sup id="cite_ref-126" class="reference"><a href="#cite_note-126"><span class="cite-bracket">[</span>126<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>September 6, 2016</td>
<td>MTD</td>
<td><a href="/wiki/Mettler_Toledo" title="Mettler Toledo">Mettler Toledo</a></td>
<td>TYC</td>
<td><a href="/wiki/Tyco_International" title="Tyco International">Tyco International</a></td>
<td>TYC acquires JCI (and retains JCI ticker).<sup id="cite_ref-sp160825_127-0" class="reference"><a href="#cite_note-sp160825-127"><span class="cite-bracket">[</span>127<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>July 5, 2016</td>
<td>FTV</td>
<td><a href="/wiki/Fortive_Corp" class="mw-redirect" title="Fortive Corp">Fortive Corp</a></td>
<td>CPGX</td>
<td><a href="/wiki/TC_Energy#History" title="TC Energy">Columbia Pipeline Group</a></td>
<td>CPGX acquired by TRP<sup id="cite_ref-https_128-0" class="reference"><a href="#cite_note-https-128"><span class="cite-bracket">[</span>128<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>July 1, 2016</td>
<td>LNT</td>
<td><a href="/wiki/Alliant_Energy_Corp" class="mw-redirect" title="Alliant Energy Corp">Alliant Energy Corp</a></td>
<td>GAS</td>
<td><a href="/wiki/AGL_Resources" class="mw-redirect" title="AGL Resources">AGL Resources</a></td>
<td>GAS acquired by SO<sup id="cite_ref-129" class="reference"><a href="#cite_note-129"><span class="cite-bracket">[</span>129<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>July 1, 2016</td>
<td>ALB</td>
<td><a href="/wiki/Albemarle_Corporation" title="Albemarle Corporation">Albemarle Corporation</a></td>
<td>TE</td>
<td><a href="/wiki/TECO_Energy" title="TECO Energy">TECO Energy</a></td>
<td>TE acquired by EMA<sup id="cite_ref-https_128-1" class="reference"><a href="#cite_note-https-128"><span class="cite-bracket">[</span>128<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>June 22, 2016</td>
<td>FBHS</td>
<td><a href="/wiki/Fortune_Brands_Home_%26_Security" class="mw-redirect" title="Fortune Brands Home &amp; Security">Fortune Brands Home &amp; Security</a></td>
<td>CVC</td>
<td><a href="/wiki/Cablevision_Systems" class="mw-redirect" title="Cablevision Systems">Cablevision Systems</a></td>
<td>CVC acquired by Altice NV<sup id="cite_ref-130" class="reference"><a href="#cite_note-130"><span class="cite-bracket">[</span>130<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>June 3, 2016</td>
<td>TDG</td>
<td><a href="/wiki/TransDigm_Group" title="TransDigm Group">TransDigm Group</a></td>
<td>BXLT</td>
<td><a href="/wiki/Baxalta" title="Baxalta">Baxalta</a></td>
<td>SHPG acquiring BXLT<sup id="cite_ref-131" class="reference"><a href="#cite_note-131"><span class="cite-bracket">[</span>131<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>May 31, 2016</td>
<td>AJG</td>
<td><a href="/wiki/Arthur_J._Gallagher_%26_Co." title="Arthur J. Gallagher &amp; Co.">Arthur J. Gallagher &amp; Co.</a></td>
<td>CCE</td>
<td><a href="/wiki/Coca-Cola_Enterprises" title="Coca-Cola Enterprises">Coca-Cola Enterprises</a></td>
<td>CCE merging with European bottlers<sup id="cite_ref-132" class="reference"><a href="#cite_note-132"><span class="cite-bracket">[</span>132<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>May 23, 2016</td>
<td>LKQ</td>
<td><a href="/wiki/LKQ_Corporation" title="LKQ Corporation">LKQ Corporation</a></td>
<td>ARG</td>
<td><a href="/wiki/Airgas" title="Airgas">Airgas</a></td>
<td>ARG acquired by Air Liquide<sup id="cite_ref-133" class="reference"><a href="#cite_note-133"><span class="cite-bracket">[</span>133<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>May 18, 2016</td>
<td>DLR</td>
<td><a href="/wiki/Digital_Realty" title="Digital Realty">Digital Realty</a></td>
<td>TWC</td>
<td><a href="/wiki/Time_Warner_Cable" title="Time Warner Cable">Time Warner Cable</a></td>
<td>TWC acquired by CHTR<sup id="cite_ref-134" class="reference"><a href="#cite_note-134"><span class="cite-bracket">[</span>134<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>May 13, 2016</td>
<td>ALK</td>
<td><a href="/wiki/Alaska_Air_Group" title="Alaska Air Group">Alaska Air Group</a></td>
<td>SNDK</td>
<td><a href="/wiki/SanDisk" class="mw-redirect" title="SanDisk">SanDisk</a></td>
<td>SNDK acquired by WDC<sup id="cite_ref-135" class="reference"><a href="#cite_note-135"><span class="cite-bracket">[</span>135<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>May 3, 2016</td>
<td>AYI</td>
<td><a href="/wiki/Acuity_Brands" title="Acuity Brands">Acuity Brands</a></td>
<td>ADT</td>
<td><a href="/wiki/ADT_Inc." title="ADT Inc.">ADT</a></td>
<td>ADT acquired by APO<sup id="cite_ref-136" class="reference"><a href="#cite_note-136"><span class="cite-bracket">[</span>136<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>April 25, 2016</td>
<td>GPN</td>
<td><a href="/wiki/Global_Payments" title="Global Payments">Global Payments</a></td>
<td>GME</td>
<td><a href="/wiki/GameStop" title="GameStop">GameStop</a></td>
<td>Global Payments is acquiring Heartland Payment Systems<sup id="cite_ref-137" class="reference"><a href="#cite_note-137"><span class="cite-bracket">[</span>137<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>April 18, 2016</td>
<td>ULTA</td>
<td><a href="/wiki/Ulta_Beauty" title="Ulta Beauty">Ulta Beauty</a></td>
<td>THC</td>
<td><a href="/wiki/Tenet_Healthcare" title="Tenet Healthcare">Tenet Healthcare</a></td>
<td>Ulta replaces Tenet<sup id="cite_ref-138" class="reference"><a href="#cite_note-138"><span class="cite-bracket">[</span>138<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>April 8, 2016</td>
<td>UA</td>
<td><a href="/wiki/Under_Armour" title="Under Armour">Under Armour</a> (Class C)</td>
<td></td>
<td></td>
<td>Under Armour distribution of second class of stock
</td></tr>
<tr>
<td>April 4, 2016</td>
<td>FL</td>
<td><a href="/wiki/Foot_Locker" title="Foot Locker">Foot Locker</a></td>
<td>CAM</td>
<td><a href="/wiki/Cameron_International" title="Cameron International">Cameron International</a></td>
<td>Schlumberger acquired Cameron<sup id="cite_ref-139" class="reference"><a href="#cite_note-139"><span class="cite-bracket">[</span>139<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>March 30, 2016</td>
<td>HOLX</td>
<td><a href="/wiki/Hologic" title="Hologic">Hologic</a></td>
<td>POM</td>
<td><a href="/wiki/Pepco_Holdings" title="Pepco Holdings">Pepco Holdings</a></td>
<td><a href="/wiki/Exelon" title="Exelon">Exelon</a> acquired Pepco.<sup id="cite_ref-spice-indices.com_140-0" class="reference"><a href="#cite_note-spice-indices.com-140"><span class="cite-bracket">[</span>140<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>March 30, 2016</td>
<td>CNC</td>
<td><a href="/wiki/Centene_Corporation" title="Centene Corporation">Centene Corporation</a></td>
<td>ESV</td>
<td><a href="/wiki/Valaris_plc" class="mw-redirect" title="Valaris plc">Ensco</a></td>
<td>Centene acquired <a href="/wiki/Health_Net" title="Health Net">Health Net</a>.<sup id="cite_ref-spice-indices.com_140-1" class="reference"><a href="#cite_note-spice-indices.com-140"><span class="cite-bracket">[</span>140<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>March 7, 2016</td>
<td>UDR</td>
<td><a href="/wiki/UDR_Inc" class="mw-redirect" title="UDR Inc">UDR</a></td>
<td>GMCR</td>
<td><a href="/wiki/Keurig_Green_Mountain" class="mw-redirect" title="Keurig Green Mountain">Keurig Green Mountain</a></td>
<td>JAB Holding Company acquired Keurig Green Mountain<sup id="cite_ref-141" class="reference"><a href="#cite_note-141"><span class="cite-bracket">[</span>141<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>March 4, 2016</td>
<td>AWK</td>
<td><a href="/wiki/American_Water_Works" title="American Water Works">American Water Works</a></td>
<td>CNX</td>
<td><a href="/wiki/Consol_Energy" title="Consol Energy">Consol Energy</a></td>
<td>AWK replaces CNX<sup id="cite_ref-142" class="reference"><a href="#cite_note-142"><span class="cite-bracket">[</span>142<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>February 22, 2016</td>
<td>CXO</td>
<td><a href="/wiki/Concho_Resources" title="Concho Resources">Concho Resources</a></td>
<td>PCL</td>
<td><a href="/wiki/Plum_Creek_Timber" title="Plum Creek Timber">Plum Creek Timber</a></td>
<td>PCL taken over by WY<sup id="cite_ref-143" class="reference"><a href="#cite_note-143"><span class="cite-bracket">[</span>143<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>February 1, 2016</td>
<td>CFG</td>
<td><a href="/wiki/Citizens_Financial_Group" title="Citizens Financial Group">Citizens</a></td>
<td>PCP</td>
<td><a href="/wiki/Precision_Castparts_Corporation" class="mw-redirect" title="Precision Castparts Corporation">Precision Castparts Corporation</a></td>
<td>CFG replaces PCP<sup id="cite_ref-144" class="reference"><a href="#cite_note-144"><span class="cite-bracket">[</span>144<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>February 1, 2016</td>
<td>FRT</td>
<td><a href="/wiki/Federal_Realty_Investment_Trust" title="Federal Realty Investment Trust">Federal Realty Investment Trust</a></td>
<td>BRCM</td>
<td><a href="/wiki/Broadcom_Corporation" title="Broadcom Corporation">Broadcom Corporation</a></td>
<td>FRT replaces BRCM<sup id="cite_ref-145" class="reference"><a href="#cite_note-145"><span class="cite-bracket">[</span>145<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>January 19, 2016</td>
<td>EXR</td>
<td><a href="/wiki/Extra_Space_Storage" title="Extra Space Storage">Extra Space Storage</a></td>
<td>ACE</td>
<td><a href="/wiki/Chubb_Limited" title="Chubb Limited">Chubb</a></td>
<td>EXR replaces ACE as ACE Ltd acquires Chubb and retains the CB ticker, giving up ACE<sup id="cite_ref-146" class="reference"><a href="#cite_note-146"><span class="cite-bracket">[</span>146<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>January 5, 2016</td>
<td>WLTW</td>
<td><a href="/wiki/Willis_Towers_Watson" title="Willis Towers Watson">Willis Towers Watson</a></td>
<td>FOSL</td>
<td><a href="/wiki/Fossil_Group" title="Fossil Group">Fossil Group</a></td>
<td>WSH merges with TW (and renames to WLTW)<sup id="cite_ref-147" class="reference"><a href="#cite_note-147"><span class="cite-bracket">[</span>147<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>December 29, 2015</td>
<td>CHD</td>
<td><a href="/wiki/Church_%26_Dwight" title="Church &amp; Dwight">Church &amp; Dwight</a></td>
<td>ALTR</td>
<td><a href="/wiki/Altera" title="Altera">Altera</a></td>
<td>ALTR taken over by INTC<sup id="cite_ref-148" class="reference"><a href="#cite_note-148"><span class="cite-bracket">[</span>148<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>December 15, 2015</td>
<td></td>
<td></td>
<td>CMCSK</td>
<td><a href="/wiki/Comcast" title="Comcast">Comcast K Corp</a></td>
<td>CMCSK shares no longer listed<sup id="cite_ref-149" class="reference"><a href="#cite_note-149"><span class="cite-bracket">[</span>149<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>December 1, 2015</td>
<td>CSRA</td>
<td><a href="/wiki/CSRA_Inc" class="mw-redirect" title="CSRA Inc">CSRA</a></td>
<td>CSC</td>
<td><a href="/wiki/Computer_Sciences_Corporation" title="Computer Sciences Corporation">Computer Sciences Corporation</a></td>
<td>CSC spins off CSRA<sup id="cite_ref-150" class="reference"><a href="#cite_note-150"><span class="cite-bracket">[</span>150<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>November 19, 2015</td>
<td>ILMN</td>
<td><a href="/wiki/Illumina_(company)" class="mw-redirect" title="Illumina (company)">Illumina</a></td>
<td>SIAL</td>
<td><a href="/wiki/Sigma-Aldrich" title="Sigma-Aldrich">Sigma-Aldrich</a></td>
<td>Sigma-Aldrich acquired by Merck KGaA (MKGAY)<sup id="cite_ref-151" class="reference"><a href="#cite_note-151"><span class="cite-bracket">[</span>151<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>November 18, 2015</td>
<td>SYF</td>
<td><a href="/wiki/Synchrony_Financial" title="Synchrony Financial">Synchrony Financial</a></td>
<td>GNW</td>
<td><a href="/wiki/Genworth_Financial" title="Genworth Financial">Genworth Financial</a></td>
<td>GE spinning off Synchrony Financial<sup id="cite_ref-152" class="reference"><a href="#cite_note-152"><span class="cite-bracket">[</span>152<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>November 2, 2015</td>
<td>HPE</td>
<td><a href="/wiki/Hewlett_Packard_Enterprise" title="Hewlett Packard Enterprise">Hewlett Packard Enterprise</a></td>
<td>HCBK</td>
<td><a href="/wiki/Hudson_City_Bancorp" title="Hudson City Bancorp">Hudson City Bancorp</a></td>
<td>HPQ spins off HPE<sup id="cite_ref-153" class="reference"><a href="#cite_note-153"><span class="cite-bracket">[</span>153<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>October 7, 2015</td>
<td>VRSK</td>
<td><a href="/wiki/Verisk_Analytics" title="Verisk Analytics">Verisk Analytics</a></td>
<td>JOY</td>
<td><a href="/wiki/Joy_Global" title="Joy Global">Joy Global</a></td>
<td>Market capitalization change.<sup id="cite_ref-154" class="reference"><a href="#cite_note-154"><span class="cite-bracket">[</span>154<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>September 18, 2015</td>
<td>CMCSK</td>
<td><a href="/wiki/Comcast" title="Comcast">Comcast</a> Class K Special</td>
<td></td>
<td></td>
<td>Share class methodology change<sup id="cite_ref-155" class="reference"><a href="#cite_note-155"><span class="cite-bracket">[</span>155<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>September 18, 2015</td>
<td>FOX</td>
<td><a href="/wiki/Twenty-First_Century_Fox" class="mw-redirect" title="Twenty-First Century Fox">Twenty-First Century Fox</a> Class B</td>
<td></td>
<td></td>
<td>Share class methodology change
</td></tr>
<tr>
<td>September 18, 2015</td>
<td>NWS</td>
<td><a href="/wiki/News_Corporation" title="News Corporation">News Corporation</a> Class B</td>
<td></td>
<td></td>
<td>Share class methodology change
</td></tr>
<tr>
<td>September 2, 2015</td>
<td>UAL</td>
<td><a href="/wiki/United_Continental_Holdings" class="mw-redirect" title="United Continental Holdings">United Continental Holdings</a></td>
<td>HSP</td>
<td><a href="/wiki/Hospira" title="Hospira">Hospira</a></td>
<td>Hospira taken over<sup id="cite_ref-auto_156-0" class="reference"><a href="#cite_note-auto-156"><span class="cite-bracket">[</span>156<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>August 28, 2015</td>
<td>ATVI</td>
<td><a href="/wiki/Activision_Blizzard" title="Activision Blizzard">Activision Blizzard</a></td>
<td>PLL</td>
<td><a href="/wiki/Pall_Corporation" title="Pall Corporation">Pall Corporation</a></td>
<td>Pall taken over<sup id="cite_ref-auto_156-1" class="reference"><a href="#cite_note-auto-156"><span class="cite-bracket">[</span>156<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>July 29, 2015</td>
<td>SIG</td>
<td><a href="/wiki/Signet_Jewelers" title="Signet Jewelers">Signet Jewelers</a></td>
<td>DTV</td>
<td><a href="/wiki/DirecTV" title="DirecTV">DirecTV</a></td>
<td>DirecTV acquired by AT&amp;T.<sup id="cite_ref-157" class="reference"><a href="#cite_note-157"><span class="cite-bracket">[</span>157<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>July 20, 2015</td>
<td>PYPL</td>
<td><a href="/wiki/PayPal" title="PayPal">PayPal</a></td>
<td>NE</td>
<td><a href="/wiki/Noble_Corporation" title="Noble Corporation">Noble Corporation</a></td>
<td>PayPal Spun off by eBay<sup id="cite_ref-158" class="reference"><a href="#cite_note-158"><span class="cite-bracket">[</span>158<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>July 8, 2015</td>
<td>AAP</td>
<td><a href="/wiki/Advance_Auto_Parts" title="Advance Auto Parts">Advance Auto Parts</a></td>
<td>FDO</td>
<td><a href="/wiki/Family_Dollar" title="Family Dollar">Family Dollar</a></td>
<td>Family Dollar acquired.<sup id="cite_ref-159" class="reference"><a href="#cite_note-159"><span class="cite-bracket">[</span>159<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>July 6, 2015</td>
<td>KHC</td>
<td><a href="/wiki/Kraft_Heinz" title="Kraft Heinz">Kraft Heinz</a></td>
<td>KRFT</td>
<td><a href="/wiki/Kraft_Foods" title="Kraft Foods">Kraft Foods</a></td>
<td>Kraft merger with Heinz.<sup id="cite_ref-160" class="reference"><a href="#cite_note-160"><span class="cite-bracket">[</span>160<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>July 2, 2015</td>
<td>CPGX</td>
<td><a href="/wiki/TC_Energy#History" title="TC Energy">Columbia Pipeline Group</a></td>
<td>ATI</td>
<td><a href="/wiki/Allegheny_Technologies" title="Allegheny Technologies">Allegheny Technologies</a></td>
<td>Spin off of Columbia Pipeline.<sup id="cite_ref-161" class="reference"><a href="#cite_note-161"><span class="cite-bracket">[</span>161<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>July 1, 2015</td>
<td>JBHT</td>
<td><a href="/wiki/J.B._Hunt" class="mw-redirect" title="J.B. Hunt">J.B. Hunt</a></td>
<td>TEG</td>
<td><a href="/wiki/Integrys_Energy_Group" title="Integrys Energy Group">Integrys Energy Group</a></td>
<td>Integrys taken over.<sup id="cite_ref-162" class="reference"><a href="#cite_note-162"><span class="cite-bracket">[</span>162<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>July 1, 2015</td>
<td>BXLT</td>
<td><a href="/wiki/Baxalta" title="Baxalta">Baxalta</a></td>
<td>QEP</td>
<td><a href="/wiki/QEP_Resources" class="mw-redirect" title="QEP Resources">QEP Resources</a></td>
<td>Baxalta spun off by Baxter.<sup id="cite_ref-163" class="reference"><a href="#cite_note-163"><span class="cite-bracket">[</span>163<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>June 11, 2015</td>
<td>QRVO</td>
<td><a href="/wiki/Qorvo" title="Qorvo">Qorvo</a></td>
<td>LO</td>
<td><a href="/wiki/Lorillard_Tobacco_Company" title="Lorillard Tobacco Company">Lorillard Tobacco Company</a></td>
<td>Lorillard gets acquired.<sup id="cite_ref-164" class="reference"><a href="#cite_note-164"><span class="cite-bracket">[</span>164<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>April 7, 2015</td>
<td>O</td>
<td><a href="/wiki/Realty_Income_Corporation" class="mw-redirect" title="Realty Income Corporation">Realty Income Corporation</a></td>
<td>WIN</td>
<td><a href="/wiki/Windstream_Communications" class="mw-redirect" title="Windstream Communications">Windstream Communications</a></td>
<td>Market capitalization change.<sup id="cite_ref-165" class="reference"><a href="#cite_note-165"><span class="cite-bracket">[</span>165<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>March 23, 2015</td>
<td>AAL</td>
<td><a href="/wiki/American_Airlines_Group" title="American Airlines Group">American Airlines Group</a></td>
<td>AGN</td>
<td><a href="/wiki/Allergan_Inc" class="mw-redirect" title="Allergan Inc">Allergan</a></td>
<td>Allergan acquired by Actavis (and changed name to <a href="/wiki/Allergan" title="Allergan">Allergan</a>).<sup id="cite_ref-166" class="reference"><a href="#cite_note-166"><span class="cite-bracket">[</span>166<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>March 23, 2015</td>
<td>EQIX</td>
<td><a href="/wiki/Equinix" title="Equinix">Equinix</a></td>
<td>DNR</td>
<td><a href="/wiki/Denbury_Resources" title="Denbury Resources">Denbury Resources</a></td>
<td>Market Capitalization Changes.<sup id="cite_ref-167" class="reference"><a href="#cite_note-167"><span class="cite-bracket">[</span>167<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>March 23, 2015</td>
<td>SLG</td>
<td><a href="/wiki/SL_Green_Realty" title="SL Green Realty">SL Green Realty</a></td>
<td>NBR</td>
<td><a href="/wiki/Nabors_Industries" title="Nabors Industries">Nabors Industries</a></td>
<td>Market Capitalization Changes.
</td></tr>
<tr>
<td>March 23, 2015</td>
<td>HBI</td>
<td><a href="/wiki/Hanesbrands" title="Hanesbrands">Hanesbrands</a></td>
<td>AVP</td>
<td><a href="/wiki/Avon_Products" title="Avon Products">Avon Products</a></td>
<td>Market Capitalization Changes.
</td></tr>
<tr>
<td>March 18, 2015</td>
<td>HSIC</td>
<td><a href="/wiki/Henry_Schein" title="Henry Schein">Henry Schein</a></td>
<td>CFN</td>
<td><a href="/wiki/Carefusion" class="mw-redirect" title="Carefusion">Carefusion</a></td>
<td>Carefusion acquired by Becton Dickinson<sup id="cite_ref-168" class="reference"><a href="#cite_note-168"><span class="cite-bracket">[</span>168<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>March 12, 2015</td>
<td>SWKS</td>
<td><a href="/wiki/Skyworks_Solutions" title="Skyworks Solutions">Skyworks</a></td>
<td>PETM</td>
<td><a href="/wiki/PetSmart" title="PetSmart">PetSmart</a></td>
<td>PetSmart acquired by private equity consortium<sup id="cite_ref-169" class="reference"><a href="#cite_note-169"><span class="cite-bracket">[</span>169<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>January 27, 2015</td>
<td>HCA</td>
<td><a href="/wiki/HCA_Holdings" class="mw-redirect" title="HCA Holdings">HCA Holdings</a></td>
<td>SWY</td>
<td><a href="/wiki/Safeway_Inc" class="mw-redirect" title="Safeway Inc">Safeway</a></td>
<td>Safeway acquired by private equity consortium<sup id="cite_ref-170" class="reference"><a href="#cite_note-170"><span class="cite-bracket">[</span>170<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>January 27, 2015</td>
<td>ENDP</td>
<td><a href="/wiki/Endo_International" title="Endo International">Endo International</a></td>
<td>COV</td>
<td><a href="/wiki/Covidien" title="Covidien">Covidien</a></td>
<td>Covidien acquired by Medtronic<sup id="cite_ref-171" class="reference"><a href="#cite_note-171"><span class="cite-bracket">[</span>171<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>December 5, 2014</td>
<td>RCL</td>
<td><a href="/wiki/Royal_Caribbean_Group" title="Royal Caribbean Group">Royal Caribbean Cruises</a></td>
<td>BMS</td>
<td><a href="/wiki/Bemis_Company" title="Bemis Company">Bemis Company</a></td>
<td>Market cap changes<sup id="cite_ref-172" class="reference"><a href="#cite_note-172"><span class="cite-bracket">[</span>172<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>November 5, 2014</td>
<td>LVLT</td>
<td><a href="/wiki/Level_3_Communications" title="Level 3 Communications">Level 3 Communications</a></td>
<td>JBL</td>
<td><a href="/wiki/Jabil_Circuit" class="mw-redirect" title="Jabil Circuit">Jabil Circuit</a></td>
<td>Market cap changes<sup id="cite_ref-173" class="reference"><a href="#cite_note-173"><span class="cite-bracket">[</span>173<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>September 20, 2014</td>
<td>URI</td>
<td><a href="/wiki/United_Rentals" title="United Rentals">United Rentals</a></td>
<td>BTU</td>
<td><a href="/wiki/Peabody_Energy" title="Peabody Energy">Peabody Energy</a></td>
<td>Market cap changes<sup id="cite_ref-174" class="reference"><a href="#cite_note-174"><span class="cite-bracket">[</span>174<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>September 20, 2014</td>
<td>UHS</td>
<td><a href="/wiki/Universal_Health_Services" title="Universal Health Services">Universal Health Services</a></td>
<td>GHC</td>
<td><a href="/wiki/Graham_Holdings" title="Graham Holdings">Graham Holdings</a></td>
<td>Market cap changes
</td></tr>
<tr>
<td>August 18, 2014</td>
<td>MNK</td>
<td><a href="/wiki/Mallinckrodt" title="Mallinckrodt">Mallinckrodt</a></td>
<td>RDC</td>
<td><a href="/wiki/Valaris_plc" class="mw-redirect" title="Valaris plc">Rowan Companies</a></td>
<td>Market cap changes<sup id="cite_ref-175" class="reference"><a href="#cite_note-175"><span class="cite-bracket">[</span>175<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>August 6, 2014</td>
<td>DISCK</td>
<td><a href="/wiki/Discovery_Communications" class="mw-redirect" title="Discovery Communications">Discovery Communications</a></td>
<td></td>
<td></td>
<td>Class C share distribution<sup id="cite_ref-176" class="reference"><a href="#cite_note-176"><span class="cite-bracket">[</span>176<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>July 2, 2014</td>
<td>MLM</td>
<td><a href="/wiki/Martin_Marietta_Inc." class="mw-redirect" title="Martin Marietta Inc.">Martin Marietta</a></td>
<td>X</td>
<td><a href="/wiki/United_States_Steel" class="mw-redirect" title="United States Steel">United States Steel</a></td>
<td>Market capitalization changes<sup id="cite_ref-177" class="reference"><a href="#cite_note-177"><span class="cite-bracket">[</span>177<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>July 1, 2014</td>
<td>AMG</td>
<td><a href="/wiki/Affiliated_Managers_Group" title="Affiliated Managers Group">Affiliated Managers Group</a></td>
<td>FRX</td>
<td><a href="/wiki/Forest_Laboratories" title="Forest Laboratories">Forest Laboratories</a></td>
<td>Actavis acquires Forest Laboratories<sup id="cite_ref-178" class="reference"><a href="#cite_note-178"><span class="cite-bracket">[</span>178<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>June 20, 2014</td>
<td>XEC</td>
<td><a href="/wiki/Cimarex_Energy" title="Cimarex Energy">Cimarex Energy</a></td>
<td>IGT</td>
<td><a href="/wiki/International_Game_Technology_(1975-2015)" class="mw-redirect" title="International Game Technology (1975-2015)">International Game Technology</a></td>
<td>Market capitalization changes<sup id="cite_ref-179" class="reference"><a href="#cite_note-179"><span class="cite-bracket">[</span>179<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>May 8, 2014</td>
<td>AVGO</td>
<td><a href="/wiki/Avago_Technologies" class="mw-redirect" title="Avago Technologies">Avago Technologies</a></td>
<td>LSI</td>
<td><a href="/wiki/LSI_Corporation" class="mw-redirect" title="LSI Corporation">LSI Corporation</a></td>
<td>Avago acquires LSI<sup id="cite_ref-180" class="reference"><a href="#cite_note-180"><span class="cite-bracket">[</span>180<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>May 1, 2014</td>
<td>UA</td>
<td><a href="/wiki/Under_Armour" title="Under Armour">Under Armour</a></td>
<td>BEAM</td>
<td><a href="/wiki/Suntory_Global_Spirits" title="Suntory Global Spirits">Suntory Global Spirits</a></td>
<td>Beam acquired by Suntory<sup id="cite_ref-www.spice-indices.com_181-0" class="reference"><a href="#cite_note-www.spice-indices.com-181"><span class="cite-bracket">[</span>181<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>May 1, 2014</td>
<td>NAVI</td>
<td><a href="/wiki/Navient" title="Navient">Navient</a></td>
<td>SLM</td>
<td><a href="/wiki/SLM_Corporation" class="mw-redirect" title="SLM Corporation">SLM Corporation</a></td>
<td>Navient Spun off from SLM<sup id="cite_ref-www.spice-indices.com_181-1" class="reference"><a href="#cite_note-www.spice-indices.com-181"><span class="cite-bracket">[</span>181<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>April 3, 2014</td>
<td>GOOGL</td>
<td><a href="/wiki/Google" title="Google">Google</a></td>
<td></td>
<td></td>
<td>Google Class C share distribution<sup id="cite_ref-182" class="reference"><a href="#cite_note-182"><span class="cite-bracket">[</span>182<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>April 2, 2014</td>
<td>ESS</td>
<td><a href="/wiki/Essex_Property_Trust" title="Essex Property Trust">Essex Property Trust</a></td>
<td>CLF</td>
<td><a href="/wiki/Cliffs_Natural_Resources" class="mw-redirect" title="Cliffs Natural Resources">Cliffs Natural Resources</a></td>
<td>Market capitalization changes<sup id="cite_ref-183" class="reference"><a href="#cite_note-183"><span class="cite-bracket">[</span>183<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>March 21, 2014</td>
<td>GMCR</td>
<td><a href="/wiki/Keurig_Green_Mountain" class="mw-redirect" title="Keurig Green Mountain">Keurig Green Mountain</a></td>
<td>WPX</td>
<td><a href="/wiki/WPX_Energy" title="WPX Energy">WPX Energy</a></td>
<td>Market capitalization changes<sup id="cite_ref-184" class="reference"><a href="#cite_note-184"><span class="cite-bracket">[</span>184<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>January 24, 2014</td>
<td>TSCO</td>
<td><a href="/wiki/Tractor_Supply" class="mw-redirect" title="Tractor Supply">Tractor Supply</a></td>
<td>LIFE</td>
<td><a href="/wiki/Life_Technologies_(Thermo_Fisher_Scientific)" class="mw-redirect" title="Life Technologies (Thermo Fisher Scientific)">Life Technologies</a></td>
<td>Life Technologies acquired by Thermo Fisher Scientific Inc<sup id="cite_ref-185" class="reference"><a href="#cite_note-185"><span class="cite-bracket">[</span>185<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>December 23, 2013</td>
<td>ADS</td>
<td><a href="/wiki/Alliance_Data_Systems" class="mw-redirect" title="Alliance Data Systems">Alliance Data Systems</a></td>
<td>ANF</td>
<td><a href="/wiki/Abercrombie_%26_Fitch" title="Abercrombie &amp; Fitch">Abercrombie &amp; Fitch</a></td>
<td>Market capitalization changes.<sup id="cite_ref-sp20131211_186-0" class="reference"><a href="#cite_note-sp20131211-186"><span class="cite-bracket">[</span>186<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>December 23, 2013</td>
<td>MHK</td>
<td><a href="/wiki/Mohawk_Industries" title="Mohawk Industries">Mohawk Industries</a></td>
<td>JDSU</td>
<td><a href="/wiki/JDS_Uniphase" class="mw-redirect" title="JDS Uniphase">JDS Uniphase</a></td>
<td>Market capitalization changes.<sup id="cite_ref-sp20131211_186-1" class="reference"><a href="#cite_note-sp20131211-186"><span class="cite-bracket">[</span>186<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>December 23, 2013</td>
<td>FB</td>
<td><a href="/wiki/Meta_Platforms" title="Meta Platforms">Facebook</a></td>
<td>TER</td>
<td><a href="/wiki/Teradyne" title="Teradyne">Teradyne</a></td>
<td>Market capitalization changes.<sup id="cite_ref-sp20131211_186-2" class="reference"><a href="#cite_note-sp20131211-186"><span class="cite-bracket">[</span>186<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>December 10, 2013</td>
<td>GGP</td>
<td><a href="/wiki/General_Growth_Properties" class="mw-redirect" title="General Growth Properties">General Growth Properties</a></td>
<td>MOLX</td>
<td><a href="/wiki/Molex" title="Molex">Molex</a></td>
<td>MOLX acquired by <a href="/wiki/Koch_Industries" class="mw-redirect" title="Koch Industries">Koch Industries</a>.<sup id="cite_ref-187" class="reference"><a href="#cite_note-187"><span class="cite-bracket">[</span>187<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>December 2, 2013</td>
<td>ALLE</td>
<td><a href="/wiki/Allegion" title="Allegion">Allegion</a></td>
<td>JCP</td>
<td><a href="/wiki/JCPenney" title="JCPenney">JCPenney</a></td>
<td>Allegion spun off by Ingersoll Rand.<sup id="cite_ref-188" class="reference"><a href="#cite_note-188"><span class="cite-bracket">[</span>188<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>November 13, 2013</td>
<td>KORS</td>
<td><a href="/wiki/Capri_Holdings" title="Capri Holdings">Michael Kors</a></td>
<td>NYX</td>
<td><a href="/wiki/NYSE_Euronext" title="NYSE Euronext">NYSE Euronext</a></td>
<td>ICE Exchange acquired NYSE Euronext.<sup id="cite_ref-189" class="reference"><a href="#cite_note-189"><span class="cite-bracket">[</span>189<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>October 29, 2013</td>
<td>RIG</td>
<td><a href="/wiki/Transocean" title="Transocean">Transocean</a></td>
<td>DELL</td>
<td><a href="/wiki/Dell" title="Dell">Dell</a></td>
<td>Founder Michael Dell and Silver Lake Partners acquired Dell.<sup id="cite_ref-190" class="reference"><a href="#cite_note-190"><span class="cite-bracket">[</span>190<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>September 20, 2013</td>
<td>VRTX</td>
<td><a href="/wiki/Vertex_Pharmaceuticals" title="Vertex Pharmaceuticals">Vertex Pharmaceuticals</a></td>
<td>AMD</td>
<td><a href="/wiki/Advanced_Micro_Devices" class="mw-redirect" title="Advanced Micro Devices">Advanced Micro Devices</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20130911_191-0" class="reference"><a href="#cite_note-sp20130911-191"><span class="cite-bracket">[</span>191<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>September 20, 2013</td>
<td>AME</td>
<td><a href="/wiki/Ametek" title="Ametek">Ametek</a></td>
<td>SAI</td>
<td><a href="/wiki/Science_Applications_International_Corporation" title="Science Applications International Corporation">SAIC</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20130911_191-1" class="reference"><a href="#cite_note-sp20130911-191"><span class="cite-bracket">[</span>191<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>September 10, 2013</td>
<td>DAL</td>
<td><a href="/wiki/Delta_Air_Lines" title="Delta Air Lines">Delta Air Lines</a></td>
<td>BMC</td>
<td><a href="/wiki/BMC_Software" title="BMC Software">BMC Software</a></td>
<td>BMC taken private by consortium<sup id="cite_ref-192" class="reference"><a href="#cite_note-192"><span class="cite-bracket">[</span>192<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>July 8, 2013</td>
<td>NLSN</td>
<td><a href="/wiki/Nielsen_Holdings" title="Nielsen Holdings">Nielsen Holdings</a></td>
<td>S</td>
<td><a href="/wiki/Sprint_Corporation" title="Sprint Corporation">Sprint Nextel</a></td>
<td>Softbank consortium purchase results in public float below 50%<sup id="cite_ref-193" class="reference"><a href="#cite_note-193"><span class="cite-bracket">[</span>193<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>July 1, 2013</td>
<td>NWSA</td>
<td><a href="/wiki/21st_Century_Fox" title="21st Century Fox">21st Century Fox</a></td>
<td>APOL</td>
<td><a href="/wiki/Apollo_Education_Group" title="Apollo Education Group">Apollo Education Group</a></td>
<td>Apollo Group's market cap more representative of a mid-cap<sup id="cite_ref-194" class="reference"><a href="#cite_note-194"><span class="cite-bracket">[</span>194<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>June 21, 2013</td>
<td>ZTS</td>
<td><a href="/wiki/Zoetis" title="Zoetis">Zoetis</a></td>
<td>FHN</td>
<td><a href="/wiki/First_Horizon" class="mw-redirect" title="First Horizon">First Horizon</a></td>
<td>Zoetis spun off by Pfizer<sup id="cite_ref-195" class="reference"><a href="#cite_note-195"><span class="cite-bracket">[</span>195<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>June 6, 2013</td>
<td>GM</td>
<td><a href="/wiki/General_Motors" title="General Motors">General Motors</a></td>
<td>HNZ</td>
<td><a href="/wiki/Heinz" title="Heinz">Heinz</a></td>
<td>HNZ acquired by consortium<sup id="cite_ref-196" class="reference"><a href="#cite_note-196"><span class="cite-bracket">[</span>196<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>May 23, 2013</td>
<td>KSU</td>
<td><a href="/wiki/Kansas_City_Southern_(company)" title="Kansas City Southern (company)">Kansas City Southern</a></td>
<td>DF</td>
<td><a href="/wiki/Dean_Foods" title="Dean Foods">Dean Foods</a></td>
<td>DF too small after spinoff of White Wave Foods<sup id="cite_ref-197" class="reference"><a href="#cite_note-197"><span class="cite-bracket">[</span>197<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>May 8, 2013</td>
<td>MAC</td>
<td><a href="/wiki/Macerich" title="Macerich">Macerich</a></td>
<td>CVH</td>
<td><a href="/wiki/Coventry_Health_Care" title="Coventry Health Care">Coventry Health Care</a></td>
<td>Acquired by Aetna (AET)<sup id="cite_ref-198" class="reference"><a href="#cite_note-198"><span class="cite-bracket">[</span>198<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>April 30, 2013</td>
<td>REGN</td>
<td><a href="/wiki/Regeneron_Pharmaceuticals" title="Regeneron Pharmaceuticals">Regeneron Pharmaceuticals</a></td>
<td>PCS</td>
<td><a href="/wiki/Metro_by_T-Mobile" title="Metro by T-Mobile">MetroPCS</a></td>
<td>A majority of MetroPCS was acquired by T-Mobile<sup id="cite_ref-199" class="reference"><a href="#cite_note-199"><span class="cite-bracket">[</span>199<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>February 15, 2013</td>
<td>PVH</td>
<td><a href="/wiki/PVH_(company)" class="mw-redirect" title="PVH (company)">PVH</a></td>
<td>BIG</td>
<td><a href="/wiki/Big_Lots" title="Big Lots">Big Lots</a></td>
<td>Market capitalization changes<sup id="cite_ref-200" class="reference"><a href="#cite_note-200"><span class="cite-bracket">[</span>200<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>January 2, 2013</td>
<td>ABBV</td>
<td><a href="/wiki/AbbVie" title="AbbVie">AbbVie</a></td>
<td>FII</td>
<td><a href="/wiki/Federated_Investors" class="mw-redirect" title="Federated Investors">Federated Investors</a></td>
<td>ABBV spun off from Abbott Labs (ABT)<sup id="cite_ref-201" class="reference"><a href="#cite_note-201"><span class="cite-bracket">[</span>201<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>December 21, 2012</td>
<td>DLPH</td>
<td><a href="/wiki/Aptiv" title="Aptiv">Delphi Automotive</a></td>
<td>TIE</td>
<td><a href="/wiki/Titanium_Metals" class="mw-redirect" title="Titanium Metals">Titanium Metals</a></td>
<td>TIE acquired by Precision Cast Parts (PCP)<sup id="cite_ref-202" class="reference"><a href="#cite_note-202"><span class="cite-bracket">[</span>202<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>December 11, 2012</td>
<td>GRMN</td>
<td><a href="/wiki/Garmin" title="Garmin">Garmin</a></td>
<td>RRD</td>
<td><a href="/wiki/RR_Donnelley" title="RR Donnelley">RR Donnelley</a></td>
<td>Market capitalization changes<sup id="cite_ref-203" class="reference"><a href="#cite_note-203"><span class="cite-bracket">[</span>203<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>December 3, 2012</td>
<td>DG</td>
<td><a href="/wiki/Dollar_General" title="Dollar General">Dollar General</a></td>
<td>CBE</td>
<td><a href="/wiki/Cooper_Industries" title="Cooper Industries">Cooper Industries</a></td>
<td>Acquired by Eaton Corp. (ETN)<sup id="cite_ref-204" class="reference"><a href="#cite_note-204"><span class="cite-bracket">[</span>204<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>October 10, 2012</td>
<td>PETM</td>
<td><a href="/wiki/PetSmart" title="PetSmart">PetSmart</a></td>
<td>SUN</td>
<td><a href="/wiki/Sunoco" title="Sunoco">Sunoco</a></td>
<td>Acquired by Energy Transfer Partners (ETP)<sup id="cite_ref-205" class="reference"><a href="#cite_note-205"><span class="cite-bracket">[</span>205<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>October 2, 2012</td>
<td>KRFT</td>
<td><a href="/wiki/Kraft_Foods" title="Kraft Foods">Kraft Foods</a></td>
<td>ANR</td>
<td><a href="/wiki/Alpha_Natural_Resources" title="Alpha Natural Resources">Alpha Natural Resources</a></td>
<td>Kraft split into two companies<sup id="cite_ref-206" class="reference"><a href="#cite_note-206"><span class="cite-bracket">[</span>206<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>October 2, 2012</td>
<td>MDLZ</td>
<td><a href="/wiki/Mondelez" class="mw-redirect" title="Mondelez">Mondelez</a></td>
<td>KFT</td>
<td><a href="/wiki/Kraft_Foods" title="Kraft Foods">Kraft Foods</a></td>
<td>Old Kraft Foods renamed Mondelez<sup id="cite_ref-207" class="reference"><a href="#cite_note-207"><span class="cite-bracket">[</span>207<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>October 1, 2012</td>
<td>ADT</td>
<td><a href="/wiki/ADT_Inc." title="ADT Inc.">ADT</a></td>
<td>LXK</td>
<td><a href="/wiki/Lexmark" title="Lexmark">Lexmark</a></td>
<td>Tyco spun off ADT
</td></tr>
<tr>
<td>October 1, 2012</td>
<td>PNR</td>
<td><a href="/wiki/Pentair" title="Pentair">Pentair</a></td>
<td>DV</td>
<td><a href="/wiki/Adtalem_Global_Education" title="Adtalem Global Education">DeVry</a></td>
<td>Tyco spin-off merged w/Pentair
</td></tr>
<tr>
<td>September 5, 2012</td>
<td>LYB</td>
<td><a href="/wiki/LyondellBasell" title="LyondellBasell">LyondellBasell</a></td>
<td>SHLD</td>
<td><a href="/wiki/Sears_Holdings" title="Sears Holdings">Sears Holdings</a></td>
<td>SHLD below public float threshold
</td></tr>
<tr>
<td>July 31, 2012</td>
<td>ESV</td>
<td><a href="/wiki/Valaris_plc" class="mw-redirect" title="Valaris plc">Ensco</a></td>
<td>GR</td>
<td><a href="/wiki/Goodrich_Corporation" title="Goodrich Corporation">Goodrich Corporation</a></td>
<td>Goodrich acquired by United Technologies (UTX).<sup id="cite_ref-208" class="reference"><a href="#cite_note-208"><span class="cite-bracket">[</span>208<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>July 2, 2012</td>
<td>STX</td>
<td><a href="/wiki/Seagate_Technology" title="Seagate Technology">Seagate Technology</a></td>
<td>PGN</td>
<td><a href="/wiki/Progress_Energy_Inc" title="Progress Energy Inc">Progress Energy</a></td>
<td>Acquired by Duke Energy (DUK)<sup id="cite_ref-209" class="reference"><a href="#cite_note-209"><span class="cite-bracket">[</span>209<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>June 29, 2012</td>
<td>MNST</td>
<td><a href="/wiki/Monster_Beverage" title="Monster Beverage">Monster Beverage</a></td>
<td>SLE</td>
<td><a href="/wiki/Sara_Lee_Corporation" title="Sara Lee Corporation">Sara Lee Corporation</a></td>
<td>Split up of Sara Lee<sup id="cite_ref-210" class="reference"><a href="#cite_note-210"><span class="cite-bracket">[</span>210<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>June 5, 2012</td>
<td>LRCX</td>
<td><a href="/wiki/Lam_Research" title="Lam Research">Lam Research</a></td>
<td>NVLS</td>
<td><a href="/wiki/Novellus_Systems" title="Novellus Systems">Novellus Systems</a></td>
<td>Acquired by Lam Research (LRCX)<sup id="cite_ref-211" class="reference"><a href="#cite_note-211"><span class="cite-bracket">[</span>211<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>May 21, 2012</td>
<td>ALXN</td>
<td><a href="/wiki/Alexion_Pharmaceuticals" title="Alexion Pharmaceuticals">Alexion Pharmaceuticals</a></td>
<td>MMI</td>
<td><a href="/wiki/Motorola_Mobility" title="Motorola Mobility">Motorola Mobility</a></td>
<td>Acquired by Google (GOOG)<sup id="cite_ref-212" class="reference"><a href="#cite_note-212"><span class="cite-bracket">[</span>212<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>May 17, 2012</td>
<td>KMI</td>
<td><a href="/wiki/Kinder_Morgan" title="Kinder Morgan">Kinder Morgan</a></td>
<td>EP</td>
<td><a href="/wiki/El_Paso_Corporation" class="mw-redirect" title="El Paso Corporation">El Paso Corporation</a></td>
<td>Acquired by Kinder Morgan (KMI)<sup id="cite_ref-213" class="reference"><a href="#cite_note-213"><span class="cite-bracket">[</span>213<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>April 23, 2012</td>
<td>PSX</td>
<td><a href="/wiki/Phillips_66" title="Phillips 66">Phillips 66</a></td>
<td>SVU</td>
<td><a href="/wiki/SuperValu_(United_States)" title="SuperValu (United States)">Supervalu</a></td>
<td>ConocoPhillips spun off Phillips 66<sup id="cite_ref-214" class="reference"><a href="#cite_note-214"><span class="cite-bracket">[</span>214<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>April 3, 2012</td>
<td>FOSL</td>
<td><a href="/wiki/Fossil_Group" title="Fossil Group">Fossil</a></td>
<td>MHS</td>
<td><a href="/wiki/Medco_Health_Solutions" title="Medco Health Solutions">Medco Health Solutions</a></td>
<td>Acquired by Express Scripts (ESRX)<sup id="cite_ref-215" class="reference"><a href="#cite_note-215"><span class="cite-bracket">[</span>215<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>March 13, 2012</td>
<td>CCI</td>
<td><a href="/wiki/Crown_Castle" title="Crown Castle">Crown Castle</a></td>
<td>CEG</td>
<td><a href="/wiki/Constellation_(energy_company)" class="mw-redirect" title="Constellation (energy company)">Constellation Energy Group</a></td>
<td>Acquired by Exelon Corp. (EXC)<sup id="cite_ref-216" class="reference"><a href="#cite_note-216"><span class="cite-bracket">[</span>216<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>December 31, 2011</td>
<td>WPX</td>
<td><a href="/wiki/WPX_Energy" title="WPX Energy">WPX Energy</a></td>
<td>CPWR</td>
<td><a href="/wiki/Compuware" title="Compuware">Compuware</a></td>
<td>Market capitalization changes<sup id="cite_ref-217" class="reference"><a href="#cite_note-217"><span class="cite-bracket">[</span>217<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>December 20, 2011</td>
<td>TRIP</td>
<td><a href="/wiki/TripAdvisor" class="mw-redirect" title="TripAdvisor">TripAdvisor</a></td>
<td>TLAB</td>
<td><a href="/wiki/Tellabs" title="Tellabs">Tellabs</a></td>
<td><a href="/wiki/Expedia_Group" title="Expedia Group">Expedia</a> spun off TripAdvisor.<sup id="cite_ref-218" class="reference"><a href="#cite_note-218"><span class="cite-bracket">[</span>218<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>December 16, 2011</td>
<td>BWA</td>
<td><a href="/wiki/BorgWarner" title="BorgWarner">BorgWarner</a></td>
<td>AKS</td>
<td><a href="/wiki/AK_Steel" title="AK Steel">AK Steel</a></td>
<td>Market capitalization changes<sup id="cite_ref-219" class="reference"><a href="#cite_note-219"><span class="cite-bracket">[</span>219<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>December 16, 2011</td>
<td>PRGO</td>
<td><a href="/wiki/Perrigo" title="Perrigo">Perrigo</a></td>
<td>MWW</td>
<td><a href="/wiki/Monster_Worldwide" title="Monster Worldwide">Monster Worldwide</a></td>
<td>Market capitalization changes
</td></tr>
<tr>
<td>December 16, 2011</td>
<td>DLTR</td>
<td><a href="/wiki/Dollar_Tree" title="Dollar Tree">Dollar Tree</a></td>
<td>WFR</td>
<td><a href="/wiki/SunEdison" title="SunEdison">MEMC Electronic Materials</a></td>
<td>Market capitalization changes
</td></tr>
<tr>
<td>December 12, 2011</td>
<td>GAS</td>
<td><a href="/wiki/Southern_Company_Gas" title="Southern Company Gas">AGL Resources.</a></td>
<td>GAS</td>
<td><a href="/wiki/Nicor_Gas" title="Nicor Gas">Nicor Gas</a></td>
<td>Nicor acquired by AGL, which retained the GAS ticker.<sup id="cite_ref-220" class="reference"><a href="#cite_note-220"><span class="cite-bracket">[</span>220<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>November 18, 2011</td>
<td>CBE</td>
<td><a href="/wiki/Cooper_Industries" title="Cooper Industries">Cooper Industries</a></td>
<td>JNS</td>
<td><a href="/wiki/Janus_Capital_Group" title="Janus Capital Group">Janus Capital Group</a></td>
<td>Janus Capital Group's market capitalization is less than $1.2 billion<br> and is no longer representative of the large cap market space.<sup id="cite_ref-221" class="reference"><a href="#cite_note-221"><span class="cite-bracket">[</span>221<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>October 31, 2011</td>
<td>XYL</td>
<td><a href="/wiki/Xylem_Inc" class="mw-redirect" title="Xylem Inc">Xylem</a></td>
<td>ITT</td>
<td><a href="/wiki/ITT_Inc" class="mw-redirect" title="ITT Inc">ITT</a></td>
<td>Spun off from ITT Corp.<sup id="cite_ref-222" class="reference"><a href="#cite_note-222"><span class="cite-bracket">[</span>222<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>October 14, 2011</td>
<td>TEL</td>
<td><a href="/wiki/TE_Connectivity" title="TE Connectivity">TE Connectivity</a></td>
<td>CEPH</td>
<td><a href="/wiki/Cephalon" title="Cephalon">Cephalon</a></td>
<td>Acquired by <a href="/wiki/Teva_Pharmaceutical_Industries" class="mw-redirect" title="Teva Pharmaceutical Industries">Teva Pharmaceutical Industries</a> (TEVA).<sup id="cite_ref-223" class="reference"><a href="#cite_note-223"><span class="cite-bracket">[</span>223<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>September 23, 2011</td>
<td>MOS</td>
<td><a href="/wiki/The_Mosaic_Company" title="The Mosaic Company">The Mosaic Company</a></td>
<td>NSM</td>
<td><a href="/wiki/National_Semiconductor" title="National Semiconductor">National Semiconductor</a></td>
<td>Acquired by <a href="/wiki/Texas_Instruments" title="Texas Instruments">Texas Instruments</a> (TXN).<sup id="cite_ref-224" class="reference"><a href="#cite_note-224"><span class="cite-bracket">[</span>224<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>July 5, 2011</td>
<td>ACN</td>
<td><a href="/wiki/Accenture" title="Accenture">Accenture</a></td>
<td>MI</td>
<td><a href="/wiki/Marshall_%26_Ilsley" title="Marshall &amp; Ilsley">Marshall &amp; Ilsley</a></td>
<td>Marshall &amp; Iisley is being bought by Bank of Montreal<sup id="cite_ref-225" class="reference"><a href="#cite_note-225"><span class="cite-bracket">[</span>225<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>June 30, 2011</td>
<td>MPC</td>
<td><a href="/wiki/Marathon_Oil" title="Marathon Oil">Marathon Oil</a></td>
<td>RSH</td>
<td><a href="/wiki/RadioShack" title="RadioShack">RadioShack</a></td>
<td>Market capitalization adjustments.<sup id="cite_ref-226" class="reference"><a href="#cite_note-226"><span class="cite-bracket">[</span>226<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>June 1, 2011</td>
<td>ANR</td>
<td><a href="/wiki/Alpha_Natural_Resources" title="Alpha Natural Resources">Alpha Natural Resources</a></td>
<td>MEE</td>
<td><a href="/wiki/Massey_Energy" title="Massey Energy">Massey Energy</a></td>
<td>Alpha Natural Resources acquired Massey Energy.<sup id="cite_ref-227" class="reference"><a href="#cite_note-227"><span class="cite-bracket">[</span>227<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>April 27, 2011</td>
<td>CMG</td>
<td><a href="/wiki/Chipotle_Mexican_Grill" title="Chipotle Mexican Grill">Chipotle Mexican Grill</a></td>
<td>NOVL</td>
<td><a href="/wiki/Novell" title="Novell">Novell</a></td>
<td>Acquired by private equity firms.<sup id="cite_ref-228" class="reference"><a href="#cite_note-228"><span class="cite-bracket">[</span>228<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>April 1, 2011</td>
<td>BLK</td>
<td><a href="/wiki/BlackRock" title="BlackRock">BlackRock</a></td>
<td>GENZ</td>
<td><a href="/wiki/Genzyme" title="Genzyme">Genzyme</a></td>
<td>Acquired by <a href="/wiki/Sanofi" title="Sanofi">Sanofi</a> Aventis (SNY)<sup id="cite_ref-229" class="reference"><a href="#cite_note-229"><span class="cite-bracket">[</span>229<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>March 31, 2011</td>
<td>EW</td>
<td><a href="/wiki/Edwards_Lifesciences" title="Edwards Lifesciences">Edwards Lifesciences</a></td>
<td>Q</td>
<td><a href="/wiki/Qwest_Communications" class="mw-redirect" title="Qwest Communications">Qwest Communications</a></td>
<td>Acquired by CenturyLink<sup id="cite_ref-230" class="reference"><a href="#cite_note-230"><span class="cite-bracket">[</span>230<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>February 28, 2011</td>
<td>COV</td>
<td><a href="/wiki/Covidien" title="Covidien">Covidien</a></td>
<td>MFE</td>
<td><a href="/wiki/McAfee" title="McAfee">McAfee</a></td>
<td>Acquired by <a href="/wiki/Intel" title="Intel">Intel</a><sup id="cite_ref-231" class="reference"><a href="#cite_note-231"><span class="cite-bracket">[</span>231<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>February 25, 2011</td>
<td>JOYG</td>
<td><a href="/wiki/Joy_Global" title="Joy Global">Joy Global</a></td>
<td>AYE</td>
<td><a href="/wiki/Allegheny_Energy" title="Allegheny Energy">Allegheny Energy</a></td>
<td>Acquired by First Energy (FE).<sup id="cite_ref-232" class="reference"><a href="#cite_note-232"><span class="cite-bracket">[</span>232<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>January 3, 2011</td>
<td>MMI</td>
<td><a href="/wiki/Motorola_Mobility" title="Motorola Mobility">Motorola Mobility</a></td>
<td>MDP</td>
<td><a href="/wiki/Meredith_Corp" class="mw-redirect" title="Meredith Corp">Meredith Corp</a></td>
<td>S&amp;P constituent Motorola spun off Motorola Mobility.<sup id="cite_ref-233" class="reference"><a href="#cite_note-233"><span class="cite-bracket">[</span>233<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>December 17, 2010</td>
<td>CVC</td>
<td><a href="/wiki/Cablevision" title="Cablevision">Cablevision</a></td>
<td>KG</td>
<td><a href="/wiki/King_Pharmaceuticals" title="King Pharmaceuticals">King Pharmaceuticals</a></td>
<td>Acquired by <a href="/wiki/Pfizer" title="Pfizer">Pfizer</a>.<sup id="cite_ref-pr101209_234-0" class="reference"><a href="#cite_note-pr101209-234"><span class="cite-bracket">[</span>234<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>December 17, 2010</td>
<td>FFIV</td>
<td><a href="/wiki/F5_Networks" class="mw-redirect" title="F5 Networks">F5 Networks</a></td>
<td>EK</td>
<td><a href="/wiki/Kodak" title="Kodak">Eastman Kodak</a></td>
<td>Market Cap changes.<sup id="cite_ref-pr101209_234-1" class="reference"><a href="#cite_note-pr101209-234"><span class="cite-bracket">[</span>234<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>December 17, 2010</td>
<td>NFLX</td>
<td><a href="/wiki/Netflix,_Inc." title="Netflix, Inc.">Netflix</a></td>
<td>ODP</td>
<td><a href="/wiki/The_ODP_Corporation" class="mw-redirect" title="The ODP Corporation">Office Depot</a></td>
<td>Market Cap changes.
</td></tr>
<tr>
<td>December 17, 2010</td>
<td>NFX</td>
<td><a href="/wiki/Newfield_Exploration" title="Newfield Exploration">Newfield Exploration</a></td>
<td>NYT</td>
<td><a href="/wiki/The_New_York_Times_Company" title="The New York Times Company">The New York Times Company</a></td>
<td>Market Cap changes.
</td></tr>
<tr>
<td>November 17, 2010</td>
<td>IR</td>
<td><a href="/wiki/Trane_Technologies" title="Trane Technologies">Ingersoll-Rand</a></td>
<td>PTV</td>
<td><a href="/wiki/Pactiv" class="mw-redirect" title="Pactiv">Pactiv</a></td>
<td><a href="/wiki/Reynolds_Group_Holdings" title="Reynolds Group Holdings">Reynolds Group Holdings</a> acquired Pactiv.<sup id="cite_ref-235" class="reference"><a href="#cite_note-235"><span class="cite-bracket">[</span>235<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>August 26, 2010</td>
<td>TYC</td>
<td><a href="/wiki/Tyco_International" title="Tyco International">Tyco International</a></td>
<td>SII</td>
<td><a href="/wiki/Smith_International" title="Smith International">Smith International</a></td>
<td>Acquired by <a href="/wiki/Schlumberger" title="Schlumberger">Schlumberger</a> (SLB)<sup id="cite_ref-236" class="reference"><a href="#cite_note-236"><span class="cite-bracket">[</span>236<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>July 14, 2010</td>
<td>CB</td>
<td><a href="/wiki/Chubb_Limited" title="Chubb Limited">Chubb</a></td>
<td>MIL</td>
<td><a href="/wiki/Merck_Millipore" title="Merck Millipore">Millipore</a></td>
<td>Acquired by Merck KGaA (MKGAY)<sup id="cite_ref-237" class="reference"><a href="#cite_note-237"><span class="cite-bracket">[</span>237<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>June 30, 2010</td>
<td>QEP</td>
<td><a href="/wiki/QEP_Resources" class="mw-redirect" title="QEP Resources">QEP Resources</a></td>
<td>STR</td>
<td><a href="/wiki/Questar_Corporation_(gas_company)" title="Questar Corporation (gas company)">Questar</a></td>
<td>Company split. QEP retained, but ticker changed.<sup id="cite_ref-238" class="reference"><a href="#cite_note-238"><span class="cite-bracket">[</span>238<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>June 28, 2010</td>
<td>KMX</td>
<td><a href="/wiki/CarMax" title="CarMax">CarMax</a></td>
<td>XTO</td>
<td><a href="/wiki/XTO_Energy" title="XTO Energy">XTO Energy</a></td>
<td>Acquired by <a href="/wiki/ExxonMobil" title="ExxonMobil">ExxonMobil</a><sup id="cite_ref-239" class="reference"><a href="#cite_note-239"><span class="cite-bracket">[</span>239<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>April 29, 2010</td>
<td>CERN</td>
<td><a href="/wiki/Cerner" class="mw-redirect" title="Cerner">Cerner</a></td>
<td>BJS</td>
<td><a href="/wiki/BJ_Services" class="mw-redirect" title="BJ Services">BJ Services</a></td>
<td>Acquired by <a href="/wiki/Baker_Hughes" title="Baker Hughes">Baker Hughes</a><sup id="cite_ref-240" class="reference"><a href="#cite_note-240"><span class="cite-bracket">[</span>240<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>February 26, 2010</td>
<td>HP</td>
<td><a href="/wiki/Helmerich_%26_Payne" title="Helmerich &amp; Payne">Helmerich &amp; Payne</a></td>
<td>RX</td>
<td><a href="/wiki/IMS_Health" title="IMS Health">IMS Health</a></td>
<td>Taken private
</td></tr>
<tr>
<td>December 18, 2009</td>
<td>V</td>
<td><a href="/wiki/Visa_Inc" class="mw-redirect" title="Visa Inc">Visa</a></td>
<td>CIEN</td>
<td><a href="/wiki/Ciena" title="Ciena">Ciena</a></td>
<td>Market capitalization change.<sup class="noprint Inline-Template Template-Fact" style="white-space:nowrap;">[<i><a href="/wiki/Wikipedia:Citation_needed" title="Wikipedia:Citation needed"><span title="This claim needs references to reliable sources. (April 2025)">citation needed</span></a></i>]</sup>
</td></tr>
<tr>
<td>December 18, 2009</td>
<td>MJN</td>
<td><a href="/wiki/Mead_Johnson_Nutrition" class="mw-redirect" title="Mead Johnson Nutrition">Mead Johnson Nutrition</a></td>
<td>DYN</td>
<td><a href="/wiki/Dynegy" title="Dynegy">Dynegy</a></td>
<td>Market capitalization change.<sup class="noprint Inline-Template Template-Fact" style="white-space:nowrap;">[<i><a href="/wiki/Wikipedia:Citation_needed" title="Wikipedia:Citation needed"><span title="This claim needs references to reliable sources. (April 2025)">citation needed</span></a></i>]</sup>}
</td></tr>
<tr>
<td>December 18, 2009</td>
<td>CLF</td>
<td><a href="/wiki/Cliffs_Natural_Resources" class="mw-redirect" title="Cliffs Natural Resources">Cliffs Natural Resources</a></td>
<td>KBH</td>
<td><a href="/wiki/KB_Home" title="KB Home">KB Home</a></td>
<td>Market capitalization change.<sup class="noprint Inline-Template Template-Fact" style="white-space:nowrap;">[<i><a href="/wiki/Wikipedia:Citation_needed" title="Wikipedia:Citation needed"><span title="This claim needs references to reliable sources. (April 2025)">citation needed</span></a></i>]</sup>
</td></tr>
<tr>
<td>December 18, 2009</td>
<td>SAI</td>
<td><a href="/wiki/Science_Applications_International_Corporation" title="Science Applications International Corporation">SAIC</a></td>
<td>CVG</td>
<td><a href="/wiki/Convergys" title="Convergys">Convergys</a></td>
<td>Market capitalization change.<sup class="noprint Inline-Template Template-Fact" style="white-space:nowrap;">[<i><a href="/wiki/Wikipedia:Citation_needed" title="Wikipedia:Citation needed"><span title="This claim needs references to reliable sources. (April 2025)">citation needed</span></a></i>]</sup>
</td></tr>
<tr>
<td>December 18, 2009</td>
<td>ROST</td>
<td><a href="/wiki/Ross_Stores" title="Ross Stores">Ross Stores</a></td>
<td>MBI</td>
<td><a href="/wiki/MBIA" title="MBIA">MBIA</a></td>
<td>Market capitalization change.<sup class="noprint Inline-Template Template-Fact" style="white-space:nowrap;">[<i><a href="/wiki/Wikipedia:Citation_needed" title="Wikipedia:Citation needed"><span title="This claim needs references to reliable sources. (April 2025)">citation needed</span></a></i>]</sup>
</td></tr>
<tr>
<td>November 3, 2009</td>
<td>PCLN</td>
<td><a href="/wiki/Priceline.com" title="Priceline.com">Priceline.com</a></td>
<td>SGP</td>
<td><a href="/wiki/Schering-Plough" title="Schering-Plough">Schering-Plough</a></td>
<td>Acquired by Merck &amp; Co. (MRK)<sup id="cite_ref-241" class="reference"><a href="#cite_note-241"><span class="cite-bracket">[</span>241<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>September 28, 2009</td>
<td>ARG</td>
<td><a href="/wiki/Airgas" title="Airgas">Airgas</a></td>
<td>CBE</td>
<td><a href="/wiki/Cooper_Industries" title="Cooper Industries">Cooper Industries</a></td>
<td>Redomesticated to Ireland<sup id="cite_ref-242" class="reference"><a href="#cite_note-242"><span class="cite-bracket">[</span>242<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>August 19, 2009</td>
<td>FMC</td>
<td><a href="/wiki/FMC_Corporation" title="FMC Corporation">FMC Corporation</a></td>
<td>CTX</td>
<td><a href="/wiki/Centex_Corp." class="mw-redirect" title="Centex Corp.">Centex Corp.</a></td>
<td>Centex acquired by <a href="/wiki/Pulte_Homes" class="mw-redirect" title="Pulte Homes">Pulte Homes</a>.<sup id="cite_ref-243" class="reference"><a href="#cite_note-243"><span class="cite-bracket">[</span>243<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>June 29, 2009</td>
<td>PCS</td>
<td><a href="/wiki/Metro_by_T-Mobile" title="Metro by T-Mobile">MetroPCS</a></td>
<td></td>
<td></td>
<td>PCS replaced TEL.<sup id="cite_ref-June_22,_2009_244-0" class="reference"><a href="#cite_note-June_22,_2009-244"><span class="cite-bracket">[</span>244<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>June 25, 2009</td>
<td></td>
<td></td>
<td>TEL</td>
<td><a href="/wiki/TE_Connectivity" title="TE Connectivity">TE Connectivity</a></td>
<td>Tyco Electronics left the index because it was reincorporating in Switzerland, making it ineligible for inclusion.<sup id="cite_ref-June_22,_2009_244-1" class="reference"><a href="#cite_note-June_22,_2009-244"><span class="cite-bracket">[</span>244<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>June 5, 2009</td>
<td>FTI</td>
<td><a href="/wiki/FMC_Technologies" title="FMC Technologies">FMC Technologies</a></td>
<td>COV</td>
<td><a href="/wiki/Covidien" title="Covidien">Covidien</a></td>
<td>Covidien moved its place of incorporation to Ireland, making it ineligible for inclusion in the index.<sup id="cite_ref-245" class="reference"><a href="#cite_note-245"><span class="cite-bracket">[</span>245<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>March 3, 2009</td>
<td>HRL</td>
<td><a href="/wiki/Hormel_Foods" title="Hormel Foods">Hormel Foods</a></td>
<td>ACAS</td>
<td><a href="/wiki/American_Capital" title="American Capital">American Capital</a></td>
<td>Capitalization rebalance.<sup id="cite_ref-246" class="reference"><a href="#cite_note-246"><span class="cite-bracket">[</span>246<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>March 3, 2009</td>
<td>VTR</td>
<td><a href="/wiki/Ventas_(company)" title="Ventas (company)">Ventas</a></td>
<td>JNY</td>
<td><a href="/wiki/Nine_West_Holdings" title="Nine West Holdings">Jones Apparel Group</a></td>
<td>Capitalization rebalance.
</td></tr>
<tr>
<td>December 31, 2008</td>
<td>OI</td>
<td><a href="/wiki/Owens-Illinois" class="mw-redirect" title="Owens-Illinois">Owens-Illinois</a></td>
<td>WB</td>
<td><a href="/wiki/Wachovia_Bank" class="mw-redirect" title="Wachovia Bank">Wachovia Bank</a></td>
<td>Wachovia Bank acquired by <a href="/wiki/Wells_Fargo" title="Wells Fargo">Wells Fargo</a>.<sup id="cite_ref-247" class="reference"><a href="#cite_note-247"><span class="cite-bracket">[</span>247<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>September 16, 2008</td>
<td>HRS</td>
<td><a href="/wiki/Harris_Corporation" title="Harris Corporation">Harris Corporation</a></td>
<td>LEH</td>
<td><a href="/wiki/Lehman_Brothers" title="Lehman Brothers">Lehman Brothers</a></td>
<td>Lehman Brothers <a href="/wiki/Bankruptcy_of_Lehman_Brothers" title="Bankruptcy of Lehman Brothers">filed for bankruptcy</a>.<sup id="cite_ref-248" class="reference"><a href="#cite_note-248"><span class="cite-bracket">[</span>248<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>September 12, 2008</td>
<td>CRM</td>
<td><a href="/wiki/Salesforce" title="Salesforce">Salesforce</a></td>
<td>FRE</td>
<td><a href="/wiki/Freddie_Mac" title="Freddie Mac">Freddie Mac</a></td>
<td>Capitalization rebalance.<sup id="cite_ref-Eric_Savitz_249-0" class="reference"><a href="#cite_note-Eric_Savitz-249"><span class="cite-bracket">[</span>249<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>September 12, 2008</td>
<td>FAST</td>
<td><a href="/wiki/Fastenal" title="Fastenal">Fastenal</a></td>
<td>FNM</td>
<td><a href="/wiki/Fannie_Mae" title="Fannie Mae">Fannie Mae</a></td>
<td>Capitalization rebalance.<sup id="cite_ref-Eric_Savitz_249-1" class="reference"><a href="#cite_note-Eric_Savitz-249"><span class="cite-bracket">[</span>249<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>July 1, 2008</td>
<td>AKS</td>
<td><a href="/wiki/AK_Steel" title="AK Steel">AK Steel</a></td>
<td>CFC</td>
<td><a href="/wiki/Countrywide_Financial_Corp" class="mw-redirect" title="Countrywide Financial Corp">Countrywide Financial Corp</a></td>
<td>Ak Steel replaced Countrywide Financial.<sup id="cite_ref-250" class="reference"><a href="#cite_note-250"><span class="cite-bracket">[</span>250<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>June 23, 2008</td>
<td>COG</td>
<td><a href="/wiki/Cabot_Oil_%26_Gas" class="mw-redirect" title="Cabot Oil &amp; Gas">Cabot Oil &amp; Gas</a></td>
<td>BC</td>
<td><a href="/wiki/Brunswick_Corporation" title="Brunswick Corporation">Brunswick</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20080612_251-0" class="reference"><a href="#cite_note-sp20080612-251"><span class="cite-bracket">[</span>251<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>June 23, 2008</td>
<td>MEE</td>
<td><a href="/wiki/Massey_Energy" title="Massey Energy">Massey Energy</a></td>
<td>OMX</td>
<td><a href="/wiki/OfficeMax" title="OfficeMax">OfficeMax</a></td>
<td>Market capitalization change.<sup id="cite_ref-sp20080612_251-1" class="reference"><a href="#cite_note-sp20080612-251"><span class="cite-bracket">[</span>251<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>June 10, 2008</td>
<td>LO</td>
<td><a href="/wiki/Lorillard_Tobacco_Company" title="Lorillard Tobacco Company">Lorillard Tobacco Company</a></td>
<td>ABK</td>
<td><a href="/wiki/Ambac_Financial" class="mw-redirect" title="Ambac Financial">Ambac Financial</a></td>
<td>Market Value Decline<sup id="cite_ref-252" class="reference"><a href="#cite_note-252"><span class="cite-bracket">[</span>252<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>December 20, 2007</td>
<td>RRC</td>
<td><a href="/wiki/Range_Resources" title="Range Resources">Range Resources</a></td>
<td>TRB</td>
<td><a href="/wiki/Tribune_Media" title="Tribune Media">Tribune Media</a></td>
<td>Taken private<sup id="cite_ref-253" class="reference"><a href="#cite_note-253"><span class="cite-bracket">[</span>253<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>December 13, 2007</td>
<td>GME</td>
<td><a href="/wiki/GameStop" title="GameStop">GameStop</a></td>
<td>DJ</td>
<td><a href="/wiki/Dow_Jones_%26_Company" title="Dow Jones &amp; Company">Dow Jones</a></td>
<td>Acquired by <a href="/wiki/News_Corporation" title="News Corporation">News Corporation</a>
</td></tr>
<tr>
<td>October 26, 2007</td>
<td>JEC</td>
<td><a href="/wiki/Jacobs_Engineering_Group" class="mw-redirect" title="Jacobs Engineering Group">Jacobs Engineering Group</a></td>
<td>AV</td>
<td><a href="/wiki/Avaya" title="Avaya">Avaya</a></td>
<td>Taken private<sup id="cite_ref-254" class="reference"><a href="#cite_note-254"><span class="cite-bracket">[</span>254<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>October 2, 2007</td>
<td>EXPE</td>
<td><a href="/wiki/Expedia_Group" title="Expedia Group">Expedia</a></td>
<td>SLR</td>
<td><a href="/wiki/Solectron" title="Solectron">Solectron</a></td>
<td>Solectron acquired by <a href="/wiki/Flextronics" class="mw-redirect" title="Flextronics">Flextronics</a>.<sup id="cite_ref-sp20070927_255-0" class="reference"><a href="#cite_note-sp20070927-255"><span class="cite-bracket">[</span>255<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>October 1, 2007</td>
<td>TDC</td>
<td><a href="/wiki/Teradata" title="Teradata">Teradata</a></td>
<td>NCR</td>
<td><a href="/wiki/NCR_Corporation" class="mw-redirect" title="NCR Corporation">NCR Corporation</a></td>
<td>Teradata spun off by NCR Corporation.<sup id="cite_ref-sp20070927_255-1" class="reference"><a href="#cite_note-sp20070927-255"><span class="cite-bracket">[</span>255<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>September 27, 2007</td>
<td>TSO</td>
<td><a href="/wiki/Tesoro_Corporation" title="Tesoro Corporation">Tesoro Corporation</a></td>
<td>MXIM</td>
<td><a href="/wiki/Maxim_Integrated_Products" class="mw-redirect" title="Maxim Integrated Products">Maxim Integrated Products</a></td>
<td>MXIM delisted from NASDAQ exchange.<sup id="cite_ref-sp20070927_255-2" class="reference"><a href="#cite_note-sp20070927-255"><span class="cite-bracket">[</span>255<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>September 26, 2007</td>
<td>ICE</td>
<td><a href="/wiki/Intercontinental_Exchange" title="Intercontinental Exchange">Intercontinental Exchange</a></td>
<td>FDC</td>
<td><a href="/wiki/First_Data" title="First Data">First Data</a></td>
<td>FDC acquired by <a href="/wiki/KKR_(company)" class="mw-redirect" title="KKR (company)">KKR</a>.<sup id="cite_ref-sp20070927_255-3" class="reference"><a href="#cite_note-sp20070927-255"><span class="cite-bracket">[</span>255<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>August 24, 2007</td>
<td>LUK</td>
<td><a href="/wiki/Leucadia_National" class="mw-redirect" title="Leucadia National">Leucadia National</a></td>
<td>KSE</td>
<td><a href="/wiki/KeySpan" title="KeySpan">KeySpan</a></td>
<td>Acquired by <a href="/wiki/National_Grid_plc" title="National Grid plc">National Grid plc</a><sup id="cite_ref-256" class="reference"><a href="#cite_note-256"><span class="cite-bracket">[</span>256<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>July 2, 2007</td>
<td>DFS</td>
<td><a href="/wiki/Discover_Financial" title="Discover Financial">Discover Financial</a></td>
<td>ADCT</td>
<td><a href="/wiki/ADC_Telecommunications" title="ADC Telecommunications">ADC Telecommunications</a></td>
<td>Discover Financial Services debuts on New York Stock Exchange.<sup id="cite_ref-257" class="reference"><a href="#cite_note-257"><span class="cite-bracket">[</span>257<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>March 30, 2007</td>
<td>KFT</td>
<td><a href="/wiki/Kraft_Foods" title="Kraft Foods">Kraft Foods</a></td>
<td>TSG</td>
<td><a href="/wiki/Sabre_Corporation" title="Sabre Corporation">Sabre Corporation</a></td>
<td>Taken Private<sup id="cite_ref-258" class="reference"><a href="#cite_note-258"><span class="cite-bracket">[</span>258<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>January 10, 2007</td>
<td>AVB</td>
<td><a href="/wiki/AvalonBay_Communities" title="AvalonBay Communities">AvalonBay Communities</a></td>
<td>SBL</td>
<td><a href="/wiki/Symbol_Technologies" title="Symbol Technologies">Symbol Technologies</a></td>
<td>Acquired by Motorola<sup id="cite_ref-259" class="reference"><a href="#cite_note-259"><span class="cite-bracket">[</span>259<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>June 2, 2006</td>
<td>JNPR</td>
<td><a href="/wiki/Juniper_Networks" title="Juniper Networks">Juniper Networks</a></td>
<td>ABS</td>
<td><a href="/wiki/Albertsons" title="Albertsons">Albertsons</a></td>
<td>Albertsons acquired by SuperValu and CVS Corp.<sup id="cite_ref-260" class="reference"><a href="#cite_note-260"><span class="cite-bracket">[</span>260<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>November 18, 2005</td>
<td>AMZN</td>
<td><a href="/wiki/Amazon_(company)" title="Amazon (company)">Amazon</a></td>
<td>T</td>
<td><a href="/wiki/AT%26T_Corporation" title="AT&amp;T Corporation">AT&amp;T Corporation</a></td>
<td>AT&amp;T Corp. acquired by <a href="/wiki/AT%26T" title="AT&amp;T">SBC Communications</a><sup id="cite_ref-261" class="reference"><a href="#cite_note-261"><span class="cite-bracket">[</span>261<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>July 1, 2005</td>
<td>STZ</td>
<td><a href="/wiki/Constellation_Brands" title="Constellation Brands">Constellation Brands</a></td>
<td>GLK</td>
<td><a href="/wiki/Great_Lakes_Chemical" class="mw-redirect" title="Great Lakes Chemical">Great Lakes Chemical</a></td>
<td>Acquired by <a href="/wiki/Crompton_Corp." class="mw-redirect" title="Crompton Corp.">Crompton Corp.</a>
</td></tr>
<tr>
<td>September 25, 2003</td>
<td>ESRX</td>
<td><a href="/wiki/Express_Scripts" title="Express Scripts">Express Scripts</a></td>
<td>QTRN</td>
<td><a href="/wiki/Quintiles_Transnational" class="mw-redirect" title="Quintiles Transnational">Quintiles Transnational</a></td>
<td>Taken private
</td></tr>
<tr>
<td>December 5, 2000</td>
<td>INTU</td>
<td><a href="/wiki/Intuit" title="Intuit">Intuit</a></td>
<td>BS</td>
<td><a href="/wiki/Bethlehem_Steel" title="Bethlehem Steel">Bethlehem Steel</a></td>
<td>Market Cap changes.<sup id="cite_ref-262" class="reference"><a href="#cite_note-262"><span class="cite-bracket">[</span>262<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>December 5, 2000</td>
<td>SBL</td>
<td><a href="/wiki/Symbol_Technologies" title="Symbol Technologies">Symbol Technologies</a></td>
<td>OI</td>
<td><a href="/wiki/Owens-Illinois" class="mw-redirect" title="Owens-Illinois">Owens-Illinois</a></td>
<td>Market Cap changes.
</td></tr>
<tr>
<td>December 5, 2000</td>
<td>AYE</td>
<td><a href="/wiki/Allegheny_Energy" title="Allegheny Energy">Allegheny Energy</a></td>
<td>GRA</td>
<td><a href="/wiki/WR_Grace_and_Company" class="mw-redirect" title="WR Grace and Company">WR Grace</a></td>
<td>Market Cap changes.
</td></tr>
<tr>
<td>December 5, 2000</td>
<td>ABK</td>
<td><a href="/wiki/Ambac_Financial" class="mw-redirect" title="Ambac Financial">Ambac Financial</a></td>
<td>CCK</td>
<td><a href="/wiki/Crown_Holdings" title="Crown Holdings">Crown Holdings</a></td>
<td>Market Cap changes.
</td></tr>
<tr>
<td>July 27, 2000</td>
<td>JDSU</td>
<td><a href="/wiki/JDS_Uniphase" class="mw-redirect" title="JDS Uniphase">JDS Uniphase</a></td>
<td>RAD</td>
<td><a href="/wiki/Rite_Aid" title="Rite Aid">Rite Aid</a></td>
<td>Market Cap change.<sup id="cite_ref-263" class="reference"><a href="#cite_note-263"><span class="cite-bracket">[</span>263<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>June 12, 2000</td>
<td>CVG</td>
<td><a href="/wiki/Convergys" title="Convergys">Convergys</a></td>
<td>TMC</td>
<td><a href="/wiki/Times_Mirror" class="mw-redirect" title="Times Mirror">Times Mirror</a></td>
<td><a href="/wiki/Tribune_Co." class="mw-redirect" title="Tribune Co.">Tribune Co.</a> acquired Times Mirror.<sup id="cite_ref-sp20000605_264-0" class="reference"><a href="#cite_note-sp20000605-264"><span class="cite-bracket">[</span>264<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>June 7, 2000</td>
<td>SBUX</td>
<td><a href="/wiki/Starbucks" title="Starbucks">Starbucks</a></td>
<td>SMS</td>
<td><a href="/wiki/Shared_Medical_Systems" class="mw-redirect" title="Shared Medical Systems">Shared Medical Systems</a></td>
<td><a href="/wiki/Siemens_AG" class="mw-redirect" title="Siemens AG">Siemens AG</a> acquired Shared Medical Systems.<sup id="cite_ref-sp20000605_264-1" class="reference"><a href="#cite_note-sp20000605-264"><span class="cite-bracket">[</span>264<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>December 8, 1999</td>
<td>YHOO</td>
<td><a href="/wiki/Yahoo!_Inc._(1995%E2%80%932017)" title="Yahoo! Inc. (1995–2017)">Yahoo!</a></td>
<td>LDW</td>
<td><a href="/wiki/Laidlaw" title="Laidlaw">Laidlaw</a></td>
<td>Market capitalization change.<sup id="cite_ref-265" class="reference"><a href="#cite_note-265"><span class="cite-bracket">[</span>265<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>June 9, 1999</td>
<td>WLP</td>
<td><a href="/wiki/Wellpoint" class="mw-redirect" title="Wellpoint">Wellpoint</a></td>
<td>HPH</td>
<td><a href="/wiki/Harnischfeger_Industries" class="mw-redirect" title="Harnischfeger Industries">Harnischfeger Industries</a></td>
<td>Harnischfeger filed for bankruptcy.<sup id="cite_ref-266" class="reference"><a href="#cite_note-266"><span class="cite-bracket">[</span>266<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>April 12, 1999
</td>
<td>ACT
</td>
<td><a href="/wiki/Actavis" title="Actavis">Actavis</a>
</td>
<td>
</td>
<td>
</td>
<td>Actavis plc (NYSE:ACT) added to S&amp;P 500
</td></tr>
<tr>
<td>December 11, 1998</td>
<td>FSR</td>
<td><a href="/wiki/Firstar" class="mw-redirect" title="Firstar">Firstar</a></td>
<td>AN</td>
<td><a href="/wiki/Amoco" title="Amoco">Amoco</a></td>
<td><a href="/wiki/BP" title="BP">BP</a> purchased Amoco.<sup id="cite_ref-sp19981211_267-0" class="reference"><a href="#cite_note-sp19981211-267"><span class="cite-bracket">[</span>267<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>December 11, 1998</td>
<td>CCL</td>
<td><a href="/wiki/Carnival_Corp." class="mw-redirect" title="Carnival Corp.">Carnival Corp.</a></td>
<td>GRN</td>
<td><a href="/wiki/General_Re" class="mw-redirect" title="General Re">General Re</a></td>
<td><a href="/wiki/Berkshire_Hathaway" title="Berkshire Hathaway">Berkshire Hathaway</a> purchased General Re.<sup id="cite_ref-sp19981211_267-1" class="reference"><a href="#cite_note-sp19981211-267"><span class="cite-bracket">[</span>267<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>December 11, 1998</td>
<td>CPWR</td>
<td><a href="/wiki/Compuware" title="Compuware">Compuware</a></td>
<td>SUN</td>
<td><a href="/wiki/SunAmerica" class="mw-redirect" title="SunAmerica">SunAmerica</a></td>
<td><a href="/wiki/AIG" class="mw-redirect" title="AIG">AIG</a> purchased SunAmerica.<sup id="cite_ref-sp19981211_267-2" class="reference"><a href="#cite_note-sp19981211-267"><span class="cite-bracket">[</span>267<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>June 17, 1997</td>
<td>CCR</td>
<td><a href="/wiki/Countrywide_Credit_Industries" class="mw-redirect" title="Countrywide Credit Industries">Countrywide Credit Industries</a></td>
<td>USL</td>
<td><a href="/wiki/USLife" class="mw-redirect" title="USLife">USLife</a></td>
<td><a href="/wiki/AIG" class="mw-redirect" title="AIG">AIG</a> acquired USLife.<sup id="cite_ref-268" class="reference"><a href="#cite_note-268"><span class="cite-bracket">[</span>268<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>September 30, 1994</td>
<td>NCC</td>
<td><a href="/wiki/National_City_Corp." title="National City Corp.">National City</a></td>
<td>MCK</td>
<td><a href="/wiki/McKesson_Corporation" title="McKesson Corporation">McKesson</a></td>
<td>McKesson sold PCS Health Services to <a href="/wiki/Eli_Lilly" title="Eli Lilly">Eli Lilly</a>.<sup id="cite_ref-269" class="reference"><a href="#cite_note-269"><span class="cite-bracket">[</span>269<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>July 1, 1976
</td>
<td>BUD
</td>
<td><a href="/wiki/Anheuser_Busch" class="mw-redirect" title="Anheuser Busch">Anheuser Busch</a></td>
<td>HNG</td>
<td><a href="/wiki/Houston_Natural_Gas" title="Houston Natural Gas">Houston Natural Gas</a></td>
<td>Major restructuring of S&amp;P 500 to have fewer industrials and utilities, and more financial companies to add "new strength and breadth"<sup id="cite_ref-:2_270-0" class="reference"><a href="#cite_note-:2-270"><span class="cite-bracket">[</span>270<span class="cite-bracket">]</span></a></sup>
</td></tr>
<tr>
<td>July 1, 1976
</td>
<td>DIS
</td>
<td><a href="/wiki/The_Walt_Disney_Company" title="The Walt Disney Company">The Walt Disney Company</a></td>
<td>AYE</td>
<td><a href="/wiki/Allegheny_Energy" title="Allegheny Energy">Allegheny Energy</a></td>
<td>Major restructuring of S&amp;P 500 to have fewer industrials and utilities, and more financial companies to add "new strength and breadth"<sup id="cite_ref-:2_270-1" class="reference"><a href="#cite_note-:2-270"><span class="cite-bracket">[</span>270<span class="cite-bracket">]</span></a></sup>
</td></tr></tbody><tfoot></tfoot></table>
"""
soup = BeautifulSoup(html_content, "html.parser")

columns = ["Effective Date", "Added - Ticker", "Added - Security",
           "Removed - Ticker", "Removed - Security", "Reason"]

rows = []
for tr in soup.select("tbody tr"):
    tds = tr.find_all("td")
    cells = []
    for td in tds:
        # Remove superscripts (citations)
        for sup in td.find_all("sup"):
            sup.decompose()
        text = td.get_text(separator=" ", strip=True)
        # Remove citation brackets like [4], [263], etc.
        text = re.sub(r"\[\d+\]", "", text)
        text = re.sub(r"\s+", " ", text).strip()
        cells.append(text)
    # Expect exactly 6 columns; skip "..." or malformed rows
    if len(cells) == 6 and cells[0] != "...":
        rows.append(cells)

df_changes = pd.DataFrame(rows, columns=columns)
df_changes


Effective Date Added - Ticker               Added - Security  \
0    September 22, 2025            EME                          Emcor   
1    September 22, 2025           HOOD              Robinhood Markets   
2    September 22, 2025            APP                       AppLovin   
3       August 28, 2025           IBKR            Interactive Brokers   
4         July 23, 2025            XYZ                    Block, Inc.   
..                  ...            ...                            ...   
374   December 11, 1998           CPWR                      Compuware   
375       June 17, 1997            CCR  Countrywide Credit Industries   
376  September 30, 1994            NCC                  National City   
377        July 1, 1976            BUD                 Anheuser Busch   
378        July 1, 1976            DIS        The Walt Disney Company   

    Removed - Ticker        Removed - Security  \
0               ENPH            Enphase Energy   
1                CZR     Caesars Entertainment   
2               MKTX               MarketAxess   
3                WBA  Walgreens Boots Alliance   
4                HES          Hess Corporation   
..               ...                       ...   
374              SUN                SunAmerica   
375              USL                    USLife   
376              MCK                  McKesson   
377              HNG       Houston Natural Gas   
378              AYE          Allegheny Energy   

                                                Reason  
0                        Market capitalization change.  
1                        Market capitalization change.  
2                        Market capitalization change.  
3    Sycamore Partners acquired Walgreen Boots Alli...  
4    S&P 500 and S&P 100 constituent Chevron Corp. ...  
..                                                 ...  
374                          AIG purchased SunAmerica.  
375                               AIG acquired USLife.  
376   McKesson sold PCS Health Services to Eli Lilly .  
377  Major restructuring of S&P 500 to have fewer i...  
378  Major restructuring of S&P 500 to have fewer i...  

[379 rows x 6 columns]

# Prices & Volume

In [71]:
import yfinance as yf

def get_ohlcv(
        tickers,
        start,
        end
    ):
    ohlcv = yf.download(
        tickers=tickers,
        interval="1d",
        start=start,
        end=end,
        # group_by="ticker"
    )

    ohlcv.columns = ohlcv.columns.droplevel(1)
    ohlcv = ohlcv.reset_index()
    ohlcv=ohlcv[['Date', 'Close', 'High', 'Low', 'Open', 'Volume']]
    ohlcv.insert(0, "Ticker", tickers)
    return ohlcv


get_ohlcv(tickers="AAPL",
    start="2025-01-01",
    end="2025-09-01")

/var/folders/wk/hj0v_fks1xs_swqng8sw_6j40000gn/T/ipykernel_39492/585082695.py:8: FutureWarning: YF.download() has changed argument auto_adjust default to True
  ohlcv = yf.download(
[*********************100%***********************]  1 of 1 completed


Price Ticker       Date       Close        High         Low        Open  \
0       AAPL 2025-01-02  242.987427  248.218856  240.964609  248.049444   
1       AAPL 2025-01-03  242.499146  243.316237  241.034344  242.499146   
2       AAPL 2025-01-06  244.133347  246.455106  242.339711  243.445785   
3       AAPL 2025-01-07  241.353226  244.681407  240.496267  242.120491   
4       AAPL 2025-01-08  241.841476  242.847913  239.200857  241.064237   
..       ...        ...         ...         ...         ...         ...   
160     AAPL 2025-08-25  227.160004  229.300003  226.229996  226.479996   
161     AAPL 2025-08-26  229.309998  229.490005  224.690002  226.869995   
162     AAPL 2025-08-27  230.490005  230.899994  228.259995  228.610001   
163     AAPL 2025-08-28  232.559998  233.410004  229.339996  230.820007   
164     AAPL 2025-08-29  232.139999  233.380005  231.369995  232.509995   

Price    Volume  
0      55740700  
1      40244100  
2      45045600  
3      40856000  
4      37628900  
..          ...  
160    30983100  
161    54575100  
162    31259500  
163    38074700  
164    39418400  

[165 rows x 7 columns]

In [67]:
df_start

Ticker             Security                  Sector  \
0      MMM                   3M             Industrials   
1      AOS          A. O. Smith             Industrials   
2      ABT  Abbott Laboratories             Health Care   
3     ABBV               AbbVie             Health Care   
4      ACN            Accenture  Information Technology   
..     ...                  ...                     ...   
498    XYL           Xylem Inc.             Industrials   
499    YUM          Yum! Brands  Consumer Discretionary   
500   ZBRA   Zebra Technologies  Information Technology   
501    ZBH        Zimmer Biomet             Health Care   
502    ZTS               Zoetis             Health Care   

                                GICS Sub-Industry    Headquarters Location  \
0                        Industrial Conglomerates    Saint Paul, Minnesota   
1                               Building Products     Milwaukee, Wisconsin   
2                           Health Care Equipment  North Chicago, Illinois   
3                                   Biotechnology  North Chicago, Illinois   
4                  IT Consulting & Other Services          Dublin, Ireland   
..                                            ...                      ...   
498  Industrial Machinery & Supplies & Components   White Plains, New York   
499                                   Restaurants     Louisville, Kentucky   
500            Electronic Equipment & Instruments   Lincolnshire, Illinois   
501                         Health Care Equipment          Warsaw, Indiana   
502                               Pharmaceuticals   Parsippany, New Jersey   

     Date added         CIK      Founded  
0    1957-03-04  0000066740         1902  
1    2017-07-26  0000091142         1916  
2    1957-03-04  0000001800         1888  
3    2012-12-31  0001551152  2013 (1888)  
4    2011-07-06  0001467373         1989  
..          ...         ...          ...  
498  2011-11-01  0001524472         2011  
499  1997-10-06  0001041061         1997  
500  2019-12-23  0000877212         1969  
501  2001-08-07  0001136869         1927  
502  2013-06-21  0001555280         1952  

[503 rows x 8 columns]

In [ ]:

df_ohlcv_sp500=pd.DataFrame()

for idx, row in df_start.iterrows():
    ticker = row["Ticker"]
    date_added = row["Date added"]
    if date_added >= "2005-01-01":
        start_date=date_added
    else:
        start_date="2005-01-01"
    df = get_ohlcv(
        tickers=ticker,
        start=start_date,
        end="2025-06-30")
    df_ohlcv_sp500 = pd.concat([df_ohlcv_sp500,df], ignore_index=True)

df_ohlcv_sp500
        

/var/folders/wk/hj0v_fks1xs_swqng8sw_6j40000gn/T/ipykernel_39492/585082695.py:8: FutureWarning: YF.download() has changed argument auto_adjust default to True
  ohlcv = yf.download(
[*********************100%***********************]  1 of 1 completed
/var/folders/wk/hj0v_fks1xs_swqng8sw_6j40000gn/T/ipykernel_39492/585082695.py:8: FutureWarning: YF.download() has changed argument auto_adjust default to True
  ohlcv = yf.download(
[*********************100%***********************]  1 of 1 completed
/var/folders/wk/hj0v_fks1xs_swqng8sw_6j40000gn/T/ipykernel_39492/585082695.py:8: FutureWarning: YF.download() has changed argument auto_adjust default to True
  ohlcv = yf.download(
[*********************100%***********************]  1 of 1 completed
/var/folders/wk/hj0v_fks1xs_swqng8sw_6j40000gn/T/ipykernel_39492/585082695.py:8: FutureWarning: YF.download() has changed argument auto_adjust default to True
  ohlcv = yf.download(
[*********************100%***********************]  1 of 1 comple

Price   Ticker       Date       Close        High         Low        Open  \
0          MMM 2005-01-03   37.621830   38.078406   37.462025   37.516814   
1          MMM 2005-01-04   37.315933   37.904917   37.288537   37.621841   
2          MMM 2005-01-05   36.859356   37.416377   36.859356   37.302233   
3          MMM 2005-01-06   37.192665   37.621849   36.900456   36.927853   
4          MMM 2005-01-07   37.576183   37.804471   37.096781   37.210925   
...        ...        ...         ...         ...         ...         ...   
2048814    ZTS 2025-06-23  156.815628  157.931906  155.470136  156.247536   
2048815    ZTS 2025-06-24  157.244202  158.121259  153.745890  156.955160   
2048816    ZTS 2025-06-25  156.705994  158.171096  154.593064  156.357169   
2048817    ZTS 2025-06-26  155.270798  157.094701  154.742565  156.955168   
2048818    ZTS 2025-06-27  155.649536  156.805674  154.882098  155.809007   

Price       Volume  
0        3817632.0  
1        4358942.0  
2        3462779.0  
3        3605342.0  
4        3938428.0  
...            ...  
2048814  2392700.0  
2048815  4554500.0  
2048816  2974800.0  
2048817  3122700.0  
2048818  2987800.0  

[2048819 rows x 7 columns]

In [79]:
df_ohlcv_sp500_comp=df_ohlcv_sp500[["Ticker", "Date", "Close", "Volume"]]
df_ohlcv_sp500_comp

Price   Ticker       Date       Close     Volume
0          MMM 2005-01-03   37.621830  3817632.0
1          MMM 2005-01-04   37.315933  4358942.0
2          MMM 2005-01-05   36.859356  3462779.0
3          MMM 2005-01-06   37.192665  3605342.0
4          MMM 2005-01-07   37.576183  3938428.0
...        ...        ...         ...        ...
2048814    ZTS 2025-06-23  156.815628  2392700.0
2048815    ZTS 2025-06-24  157.244202  4554500.0
2048816    ZTS 2025-06-25  156.705994  2974800.0
2048817    ZTS 2025-06-26  155.270798  3122700.0
2048818    ZTS 2025-06-27  155.649536  2987800.0

[2048819 rows x 4 columns]

In [80]:
df_ohlcv_sp500_comp.to_csv("ohlcv_sp500.csv", index=False)

# Financial Statments

In [133]:
import json
from pathlib import Path
from typing import Dict, List, Optional
import pandas as pd

_TAG_CANDIDATES: Dict[str, List[str]] = {
    "capitalExpenditures": [
        "PaymentsToAcquirePropertyPlantAndEquipment",
        "CapitalExpenditures",
        "CapitalExpendituresIncurredButNotYetPaid",
    ],
    "totalAssets": [
        "Assets",
        "AssetsCurrent",
        "AssetsNoncurrent",
    ],
    "totalLiabilities": [
        "Liabilities",
        "LiabilitiesAndStockholdersEquity",
        "LiabilitiesCurrent",
        "LiabilitiesOtherThanLongtermDebtNoncurrent",
        "OtherAccruedLiabilitiesCurrent",
        "OtherAccruedLiabilitiesNoncurrent",
    ],
    "netIncome": [
        "NetIncomeLoss",
        "ProfitLoss",
        "NetIncomeLossAvailableToCommonStockholdersBasic",
        "NetIncomeLossAvailableToCommonStockholdersDiluted",
        "NetIncomeLossAttributableToParentDiluted",
    ],
    "commonStockSharesOutstanding": [
        # us-gaap concept first, then the DEI fallback commonly used in cover pages
        "CommonStockSharesOutstanding",           # us-gaap
        # The JSON groups by taxonomy, so we'll also check 'dei' for:
        "EntityCommonStockSharesOutstanding",     # dei
        "WeightedAverageNumberOfSharesOutstandingBasic",
    ],
}

def fetch_fs_basic(
        symbol: str = "ABT",
        cik: str = "0000001800",
        companyfacts_dir: str = "companyfacts") -> pd.DataFrame:
    """
    Load local companyfacts JSON (companyfacts/CIK000########.json) and return a DataFrame
    with columns: label, currency_unit, start, end, val, fy, fp, form, filed, frame,
    collecting all units for these metrics: capitalExpenditures, totalAssets, totalLiabilities,
    netIncome, commonStockSharesOutstanding.

    Parameters
    ----------
    cik : int
        Numeric CIK (e.g., 1800 for Abbott). The function will zero-pad to 10 digits and
        look for 'companyfacts/CIK000########.json'.
    companyfacts_dir : str
        Folder containing the companyfacts JSON files (relative to the notebook).

    Returns
    -------
    pandas.DataFrame
    """
    # padded = _pad_cik(cik)
    path = Path(companyfacts_dir) / f"CIK{cik}.json"
    if not path.exists():
        raise FileNotFoundError(f"Could not find file: {path}")

    with path.open("r", encoding="utf-8") as f:
        data = json.load(f)

    facts = data.get("facts", {})
    rows = []

    # We’ll check both 'us-gaap' and 'dei' (for shares outstanding fallback).
    # Some filers may include relevant facts in either taxonomy.
    TAXONOMIES_TO_CHECK = ["us-gaap", "dei"]

    for metric, candidates in _TAG_CANDIDATES.items():
        for tax in TAXONOMIES_TO_CHECK:
            taxonomy = facts.get(tax, {})
            # Try each candidate tag in priority order
            for tag in candidates:
                # Only match tags that actually live under this taxonomy
                if tag not in taxonomy:
                    continue

                concept_obj = taxonomy[tag]
                concept_label = concept_obj.get("label", tag)
                units = concept_obj.get("units", {})

                for unit_name, fact_list in units.items():
                    # unit_name is e.g. "USD", "USD/shares", "shares", etc.
                    for fact in fact_list:
                        # Pull out the standard fields; use None if missing.
                        rows.append({
                            "ticker": symbol,
                            "cik": cik,
                            "label": concept_label,                    # human-readable label from JSON
                            "currency_unit": unit_name,                # the unit key
                            "start": fact.get("start"),
                            "end": fact.get("end"),
                            "val": fact.get("val"),
                            "fy": fact.get("fy"),
                            "fp": fact.get("fp"),
                            "form": fact.get("form"),
                            "filed": fact.get("filed"),
                            "frame": fact.get("frame"),
                            # (Optional extras you might want later:)
                            # "metric": metric,
                            # "concept": f"{tax}:{tag}",
                            # "accn": fact.get("accn"),
                        })
                # Stop after the first tag hit for this metric to respect priority order.
                break

    df = pd.DataFrame(rows, columns=[
        "ticker", "cik", "label", "currency_unit", "start", "end", "val", "fy", "fp", "form", "filed", "frame"
    ])

    # Nice-to-have: sort by label, then (end date desc, filed desc)
    if not df.empty:
        # Coerce dates where possible for reliable sorting
        for col in ("start", "end", "filed"):
            df[col] = pd.to_datetime(df[col], errors="coerce")
        df = df.sort_values(by=["label", "end", "filed"], ascending=[True, False, False]).reset_index(drop=True)

    return df

# Example:
# df = fetch_fs_basic(cik=1800)
# df.head()

In [134]:
df = fetch_fs_basic(cik="0000001800")
df

ticker         cik                                              label  \
0      ABT  0000001800                                             Assets   
1      ABT  0000001800                                             Assets   
2      ABT  0000001800                                             Assets   
3      ABT  0000001800                                             Assets   
4      ABT  0000001800                                             Assets   
..     ...         ...                                                ...   
902    ABT  0000001800  Weighted Average Number of Shares Outstanding,...   
903    ABT  0000001800  Weighted Average Number of Shares Outstanding,...   
904    ABT  0000001800  Weighted Average Number of Shares Outstanding,...   
905    ABT  0000001800  Weighted Average Number of Shares Outstanding,...   
906    ABT  0000001800  Weighted Average Number of Shares Outstanding,...   

    currency_unit      start        end          val    fy  fp  form  \
0             USD        NaT 2025-06-30  83999000000  2025  Q2  10-Q   
1             USD        NaT 2025-03-31  81448000000  2025  Q1  10-Q   
2             USD        NaT 2024-12-31  81414000000  2025  Q2  10-Q   
3             USD        NaT 2024-12-31  81414000000  2025  Q1  10-Q   
4             USD        NaT 2024-12-31  81414000000  2024  FY  10-K   
..            ...        ...        ...          ...   ...  ..   ...   
902        shares 2008-01-01 2008-09-30   1543605000  2009  Q3  10-Q   
903        shares 2008-07-01 2008-09-30   1545639000  2009  Q3  10-Q   
904        shares 2008-01-01 2008-06-30   1541909000  2009  Q2  10-Q   
905        shares 2008-04-01 2008-06-30   1539786000  2009  Q2  10-Q   
906        shares 2007-01-01 2007-12-31   1543082000  2009  FY  10-K   

         filed      frame  
0   2025-07-30  CY2025Q2I  
1   2025-04-30  CY2025Q1I  
2   2025-07-30  CY2024Q4I  
3   2025-04-30       None  
4   2025-02-21       None  
..         ...        ...  
902 2009-11-06       None  
903 2009-11-06   CY2008Q3  
904 2009-08-07       None  
905 2009-08-07   CY2008Q2  
906 2010-02-19     CY2007  

[907 rows x 12 columns]

In [130]:
df["label"].unique()

array(['Assets', 'Entity Common Stock, Shares Outstanding',
       'Liabilities and Equity',
       'Net Income (Loss) Attributable to Parent',
       'Payments to Acquire Property, Plant, and Equipment',
       'Weighted Average Number of Shares Outstanding, Basic'],
      dtype=object)

In [151]:
df_fs_sp500 = pd.DataFrame()

for idx, row in df_start[["Ticker", "CIK", "Date added"]].iterrows():
    ticker=row["Ticker"]
    cik=row["CIK"]
    df_fs_row = fetch_fs_basic(
        symbol=ticker,
        cik=cik
        )
    df_fs_sp500 = pd.concat([df_fs_row, df_fs_sp500], ignore_index=True)

df_fs_sp500
    

ticker         cik                                              label  \
0         ZTS  0001555280                                             Assets   
1         ZTS  0001555280                                             Assets   
2         ZTS  0001555280                                             Assets   
3         ZTS  0001555280                                             Assets   
4         ZTS  0001555280                                             Assets   
...       ...         ...                                                ...   
368401    MMM  0000066740  Payments to Acquire Property, Plant, and Equip...   
368402    MMM  0000066740  Payments to Acquire Property, Plant, and Equip...   
368403    MMM  0000066740  Payments to Acquire Property, Plant, and Equip...   
368404    MMM  0000066740  Payments to Acquire Property, Plant, and Equip...   
368405    MMM  0000066740  Payments to Acquire Property, Plant, and Equip...   

       currency_unit      start        end           val      fy  fp  form  \
0                USD        NaT 2025-06-30  1.447900e+10  2025.0  Q2  10-Q   
1                USD        NaT 2025-03-31  1.409800e+10  2025.0  Q1  10-Q   
2                USD        NaT 2024-12-31  1.423700e+10  2025.0  Q2  10-Q   
3                USD        NaT 2024-12-31  1.423700e+10  2025.0  Q1  10-Q   
4                USD        NaT 2024-12-31  1.423700e+10  2024.0  FY  10-K   
...              ...        ...        ...           ...     ...  ..   ...   
368401           USD 2008-01-01 2008-12-31  1.471000e+09  2009.0  FY  10-K   
368402           USD 2008-01-01 2008-09-30  1.008000e+09  2009.0  Q3  10-Q   
368403           USD 2008-01-01 2008-06-30  6.320000e+08  2009.0  Q2  10-Q   
368404           USD 2007-01-01 2007-12-31  1.422000e+09  2009.0  FY   8-K   
368405           USD 2007-01-01 2007-12-31  1.422000e+09  2009.0  FY  10-K   

            filed      frame  
0      2025-08-05  CY2025Q2I  
1      2025-05-06  CY2025Q1I  
2      2025-08-05  CY2024Q4I  
3      2025-05-06       None  
4      2025-02-13       None  
...           ...        ...  
368401 2010-02-16       None  
368402 2009-10-30       None  
368403 2009-07-31       None  
368404 2010-05-17     CY2007  
368405 2010-02-16       None  

[368406 rows x 12 columns]

In [152]:
df_fs_sp500.to_csv("fs_sp500.csv", index=False)

In [ ]:
# --- EDGAR financials puller for S&P 500 ---
import time, json, math, re, io
import pandas as pd
import requests
from datetime import datetime

UA = "Your Name your.email@example.com"   # <-- REQUIRED per SEC guidance
SESS = requests.Session()
SESS.headers.update({
    "User-Agent": UA,
    "Accept-Encoding": "gzip, deflate",
    "Host": "data.sec.gov"
})

# 1) Get S&P 500 tickers from Wikipedia
sp500 = pd.read_html("https://en.wikipedia.org/wiki/List_of_S%26P_500_companies")[0]
sp500 = sp500.rename(columns={"Symbol":"ticker","Security":"company"})
sp500["ticker"] = sp500["ticker"].str.upper().str.strip()

# 2) Ticker→CIK map (official)
# The SEC serves a JSON: https://www.sec.gov/files/company_tickers.json  (or company_tickers_exchange.json)
# The /file/ page documents it and is kept current. We'll try both common paths.
def load_cik_map():
    urls = [
        "https://www.sec.gov/files/company_tickers.json",
        "https://www.sec.gov/files/company_tickers_exchange.json"
    ]
    for url in urls:
        r = SESS.get(url, timeout=30)
        if r.ok:
            try:
                data = r.json()
            except json.JSONDecodeError:
                continue
            # Normalize to {TICKER: CIK}
            if isinstance(data, dict) and "data" in data:  # exchange version
                # columns: 0:CIK, 1:Ticker, 2:Name, 3:Exchange
                df = pd.DataFrame(data["data"], columns=[x["name"] for x in data["fields"]])
                return {row["ticker"].upper(): int(row["cik"]) for _, row in df.iterrows()}
            elif isinstance(data, dict):
                # legacy keyed by index strings
                rows = []
                for _, v in data.items():
                    rows.append((v.get("ticker","").upper(), v.get("cik_str")))
                return {t:int(c) for t,c in rows if t and c}
    raise RuntimeError("Could not load SEC company tickers JSON")

ticker_to_cik = load_cik_map()

sp500["cik"] = sp500["ticker"].map(ticker_to_cik)
missing_cik = sp500[sp500["cik"].isna()]
if not missing_cik.empty:
    print("Tickers with missing CIK (might be dual-class, recent changes, or name mismatches):")
    print(missing_cik[["ticker","company"]].to_string(index=False))

# 3) Helper to fetch companyfacts and extract a value set
BASE = "https://data.sec.gov/api/xbrl/companyfacts/CIK{cik:010d}.json"

def get_companyfacts(cik):
    url = BASE.format(cik=int(cik))
    r = SESS.get(url, timeout=30)
    if r.status_code == 404:
        return None
    r.raise_for_status()
    return r.json()

# Pick the most recent annual 10-K value for a given US-GAAP concept
def latest_annual_value(facts_json, concept):
    try:
        fact = facts_json["facts"]["us-gaap"][concept]["units"]["USD"]
    except Exception:
        return None, None
    # prefer 10-K / annual
    # fields: fy, fp ("FY","Q1"...), form ("10-K","10-Q"...), end, val
    candidates = [x for x in fact if x.get("form") in ("10-K","20-F","40-F") and x.get("fy")]
    if not candidates:
        candidates = fact
    # sort by end date
    def _end(x):
        try: return datetime.fromisoformat(x["end"])
        except: return datetime.min
    candidates = sorted(candidates, key=_end, reverse=True)
    top = candidates[0] if candidates else None
    if not top: return None, None
    return top.get("val"), top.get("end")

# Common concepts (you can expand as needed)
CONCEPTS = {
    "Revenue": "Revenues",
    "NetIncome": "NetIncomeLoss",
    "EPSBasic": "EarningsPerShareBasic",
    "EPSDiluted": "EarningsPerShareDiluted",
    "Assets": "Assets",
    "Liabilities": "Liabilities",
    "Equity": "StockholdersEquityIncludingPortionAttributableToNoncontrollingInterest",
    "CashFromOps": "NetCashProvidedByUsedInOperatingActivities",
    "CapEx": "PaymentsToAcquirePropertyPlantAndEquipment",
    "FreeCashFlow": None,  # derive: CFO - CapEx
}

rows = []
for _, row in sp500.dropna(subset=["cik"]).iterrows():
    cik = int(row["cik"]); ticker = row["ticker"]; name = row["company"]
    try:
        facts = get_companyfacts(cik)
        if not facts:
            continue
        vals = {}
        for label, tag in CONCEPTS.items():
            if tag is None:
                continue
            v, asof = latest_annual_value(facts, tag)
            vals[label] = v
        # derive FCF if both present
        fcf = None
        if vals.get("CashFromOps") is not None and vals.get("CapEx") is not None:
            try:
                fcf = vals["CashFromOps"] - abs(vals["CapEx"])
            except Exception:
                pass
        out = {
            "ticker": ticker,
            "company": name,
            "cik": f"{cik:010d}",
            "asof": asof,
            **vals,
            "FreeCashFlow": fcf
        }
        rows.append(out)
        time.sleep(0.2)  # be polite to SEC
    except requests.HTTPError as e:
        print(f"[HTTP] {ticker}: {e}")
    except Exception as e:
        print(f"[ERR ] {ticker}: {e}")

fin = pd.DataFrame(rows)
fin.to_csv("sp500_financials_latest_annual.csv", index=False)
print(f"Saved sp500_financials_latest_annual.csv with {len(fin)} companies")

In [3]:
import time, json, math, re, io
import pandas as pd
import requests
from datetime import datetime

UA = "whw1213@gmail.com"   # <-- REQUIRED per SEC guidance
SESS = requests.Session()
SESS.headers.update({
    "User-Agent": UA,
    "Accept-Encoding": "gzip, deflate",
    "Host": "data.sec.gov"
})

SESS.headers

{'User-Agent': 'whw1213@gmail.com', 'Accept-Encoding': 'gzip, deflate', 'Accept': '*/*', 'Connection': 'keep-alive', 'Host': 'data.sec.gov'}

In [10]:
import requests

# Simple session for financial data APIs
session = requests.Session()
session.headers.update({
    'User-Agent': 'whw1213@gmail.com'  # Just an email is sufficient!
})

# Get Apple's financial data
response = session.get('https://data.sec.gov/api/xbrl/companyfacts/CIK0000320193.json')
financial_data = response.json()

In [14]:
financial_data

{'cik': 320193,
 'entityName': 'Apple Inc.',
 'facts': {'dei': {'EntityCommonStockSharesOutstanding': {'label': 'Entity Common Stock, Shares Outstanding',
    'description': "Indicate number of shares or other units outstanding of each of registrant's classes of capital or common stock or other ownership interests, if and as stated on cover of related periodic report. Where multiple classes or units exist define each class/interest by adding class of stock items such as Common Class A [Member], Common Class B [Member] or Partnership Interest [Member] onto the Instrument [Domain] of the Entity Listings, Instrument.",
    'units': {'shares': [{'end': '2009-06-27',
       'val': 895816758,
       'accn': '0001193125-09-153165',
       'fy': 2009,
       'fp': 'Q3',
       'form': '10-Q',
       'filed': '2009-07-22',
       'frame': 'CY2009Q2I'},
      {'end': '2009-10-16',
       'val': 900678473,
       'accn': '0001193125-09-214859',
       'fy': 2009,
       'fp': 'FY',
       'form':

In [15]:

# Get Apple's financial data
response_gaap = session.get('"https://data.sec.gov/api/xbrl/companyconcept/CIK0000320193/us-gaap/Revenue.json"')
financial_data_gaap = response_gaap.json()
financial_data_gaap

InvalidSchema: No connection adapters were found for '"https://data.sec.gov/api/xbrl/companyconcept/CIK0000320193/us-gaap/Revenue.json"'